# Географические данные

<h1>Содержание<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Географические-данные" data-toc-modified-id="Географические-данные-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Географические данные</a></span><ul class="toc-item"><li><span><a href="#Как-показать-карту" data-toc-modified-id="Как-показать-карту-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Как показать карту</a></span></li><li><span><a href="#Много-объектов-на-карте" data-toc-modified-id="Много-объектов-на-карте-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Много объектов на карте</a></span></li><li><span><a href="#Собственные-иконки" data-toc-modified-id="Собственные-иконки-1.3"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Собственные иконки</a></span></li><li><span><a href="#Картограммы-(диаграммы-на-картах)" data-toc-modified-id="Картограммы-(диаграммы-на-картах)-1.4"><span class="toc-item-num">1.4&nbsp;&nbsp;</span>Картограммы (диаграммы на картах)</a></span></li></ul></li></ul></div>

## Как показать карту

In [1]:
import folium

In [2]:
moscow_lat, moscow_lng = 55.751244, 37.618423

In [3]:
m = folium.Map(location=[moscow_lat, moscow_lng])
display(m)

In [4]:
display(
    folium.Map(
        location=[moscow_lat, moscow_lng],
        zoom_start=16, tiles='Stamen Terrain'))

In [5]:
bolshoi_theatre_lat, bolshoi_theatre_lng = 55.760082, 37.618668

m = folium.Map(location=[bolshoi_theatre_lat, bolshoi_theatre_lng],
               zoom_start=17)
marker = folium.Marker([bolshoi_theatre_lat, bolshoi_theatre_lng])
marker.add_to(m)
display(m)

In [6]:
place_type = 'Театр'

folium.Marker([55.759700, 37.6207130],
              tooltip=place_type,
              popup='Малый театр').add_to(m)
display(m)

## Много объектов на карте

In [7]:
import pandas as pd

DATA_HOST_URL = 'https://code.s3.yandex.net'

df = pd.read_csv(
    # shopping centers in Moscow
    DATA_HOST_URL + '/datasets/moscow_malls_info.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 786 entries, 0 to 785
Data columns (total 7 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   name      786 non-null    object 
 1   address   786 non-null    object 
 2   hours     685 non-null    object 
 3   lat       786 non-null    float64
 4   lng       786 non-null    float64
 5   rating    786 non-null    float64
 6   district  764 non-null    object 
dtypes: float64(3), object(4)
memory usage: 43.1+ KB


In [8]:
m = folium.Map(location=[55.751244, 37.618423])

def create_marker(row):
    folium.Marker([row['lat'], row['lng']],
                  popup=f"{row['name']} {row['rating']}").add_to(m)

df.apply(create_marker, axis=1)
m

Здесь могут возникнуть проблемы:

Карта может долго отрисовываться, или рендериться (от англ. render, «выводить, отображать»), на слабых по производительности компьютерах или серверах;
Если на карте много точек, при уменьшении масштаба в ней будет сложно ориентироваться.
Из-за высокой нагрузки карта может зависать при передвижении по ней.
Если отобразить на карте несколько тысяч точек, эти проблемы станут особенно заметны. Помогут кластеры — с их помощью можно поместить на карту много маркеров одновременно.

Отметим все торговые центры на карте с помощью кластеров:

In [9]:
m = folium.Map(location=[moscow_lat, moscow_lng])

import folium.plugins

marker_cluster = folium.plugins.MarkerCluster().add_to(m)

def add_to_cluster(row):
    folium.Marker(
        [row['lat'], row['lng']],
        popup=f"{row['name']} {row['rating']}",
    ).add_to(marker_cluster)

df.apply(add_to_cluster, axis=1)
m

## Собственные иконки

In [10]:
m = folium.Map(location=[moscow_lat, moscow_lng])
marker_cluster = folium.plugins.MarkerCluster().add_to(m)

import folium.features
from folium import Marker

icon_url = 'https://img.icons8.com/external-wanicon-flat-wanicon/344/' \
    'external-mall-shop-and-store-wanicon-flat-wanicon.png'

def add_with_icon_to_cluster(row):
    Marker(
        [row['lat'], row['lng']],
        popup=f"{row['name']} {row['rating']}",
        # создавать иконку нужно каждый раз зановоdistrict_poly
        icon=folium.features.CustomIcon(icon_url, icon_size=(30, 30)),
    ).add_to(marker_cluster)

df.apply(add_with_icon_to_cluster, axis=1)
m

## Картограммы (диаграммы на картах)

In [11]:
df['district'].unique()

array(['Северный административный округ',
       'Северо-Восточный административный округ', nan,
       'Северо-Западный административный округ',
       'Восточный административный округ',
       'Западный административный округ',
       'Центральный административный округ',
       'Южный административный округ',
       'Юго-Восточный административный округ',
       'Юго-Западный административный округ'], dtype=object)

In [12]:
rating_df = df.groupby('district', as_index=False)['rating'].agg('median')
rating_df

district  rating
0         Восточный административный округ     4.0
1          Западный административный округ     4.2
2          Северный административный округ     4.2
3  Северо-Восточный административный округ     4.1
4   Северо-Западный административный округ     4.0
5       Центральный административный округ     4.1
6     Юго-Восточный административный округ     4.0
7      Юго-Западный административный округ     4.3
8             Южный административный округ     4.2

Чтобы отобразить округа на карте, folium нужно передать границы каждой области. Для этого можно использовать особый текстовый файл в формате GeoJSON. Файл содержит JSON-описание точек, линий (цепочек точек), полигонов (замкнутых цепочек точек). Каждая точка - это координата в виде "(latitude, longitude)".

Обычно GeoJSON-файлы нужных регионов можно найти в интернете. 

In [13]:
import json

district_boundaries = json.loads('{"type": "FeatureCollection", "geocoding": {"creation_date": "2016-01-09", "generator": {"author": {"name": "Mapzen"}, "package": "fences-builder", "version": "0.1.2"}, "license": "ODbL (see http://www.openstreetmap.org/copyright)"}, "features": [{"id": 1320234, "osm_type": "relation", "type": "Feature", "name": "Восточный административный округ", "properties": {"ref": "ВАО", "name": "Восточный административный округ", "name:be": "Усходняя адміністрацыйная акруга", "name:de": "Östlicher Verwaltungsbezirk", "name:en": "Eastern Administrative Okrug", "name:ru": "Восточный административный округ", "website": "http://www.vao.mos.ru", "boundary": "administrative", "wikipedia": "ru:Восточный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.8756653, 55.825342400000004], [37.876001599999995, 55.8249027], [37.8730967, 55.8237936], [37.8689418, 55.8228697], [37.869206999999996, 55.822363200000005], [37.868322500000005, 55.822211100000004], [37.867472, 55.823703], [37.86851090000001, 55.82391880000001], [37.87046039999999, 55.8242706], [37.871727799999995, 55.8246505], [37.8724412, 55.824851499999994], [37.873601099999995, 55.8251836], [37.874401799999994, 55.8252441], [37.8748787, 55.825267399999994], [37.8756653, 55.825342400000004]]], [[[37.797732300000014, 55.99985], [37.79532840000001, 55.9990248], [37.793020500000004, 56.0011418], [37.792486800000006, 56.0009504], [37.79018290000001, 56.0001243], [37.7887247, 56.0013886], [37.791381200000004, 56.002270100000004], [37.79097720000001, 56.0026548], [37.79033860000001, 56.00251240000001], [37.79001420000001, 56.002850200000005], [37.791075500000005, 56.0032236], [37.79213700000001, 56.003597], [37.79290810000001, 56.0038699], [37.793034600000006, 56.0037881], [37.79353240000001, 56.0037672], [37.79415630000001, 56.003185300000005], [37.797732300000014, 55.99985]]], [[[37.79895800000001, 56.009590100000004], [37.79812700000001, 56.007685099999996], [37.7986646, 56.0068026], [37.79950730000001, 56.006109900000006], [37.797426900000005, 56.0053804], [37.7968617, 56.0046327], [37.7936914, 56.005357800000006], [37.793098500000006, 56.0055271], [37.791304000000004, 56.0071472], [37.791591100000005, 56.0074532], [37.7932241, 56.0080698], [37.79301430000001, 56.00823260000001], [37.795332000000016, 56.00899870000001], [37.7949344, 56.0092902], [37.7979841, 56.00953210000001], [37.79853170000001, 56.0096683], [37.7988895, 56.0096066], [37.79895800000001, 56.009590100000004]]], [[[37.899785200000004, 55.8161364], [37.8999346, 55.8151406], [37.8994626, 55.8145828], [37.897964699999996, 55.813788499999994], [37.8972371, 55.813656599999995], [37.896656300000004, 55.81365039999999], [37.8960238, 55.813732], [37.895435000000006, 55.81376039999999], [37.8943798, 55.813931499999995], [37.8930571, 55.81422599999999], [37.892053700000005, 55.814827399999984], [37.8914232, 55.815043599999996], [37.8892963, 55.81517590000001], [37.88888599999999, 55.8154787], [37.8881524, 55.8156752], [37.887902499999996, 55.815941699999996], [37.886874199999994, 55.816531499999996], [37.8861402, 55.8161663], [37.8853211, 55.816661999999994], [37.8841286, 55.816660799999994], [37.88211890000001, 55.8154707], [37.881639899999996, 55.815015], [37.880831799999996, 55.814580799999995], [37.88084249999999, 55.8143186], [37.879824799999994, 55.81420459999999], [37.879484299999994, 55.813472], [37.87964159999999, 55.81326729999999], [37.8789748, 55.812424899999996], [37.878148100000004, 55.81142919999999], [37.8773566, 55.81146719999999], [37.8741278, 55.810693699999995], [37.8735825, 55.8086963], [37.870080699999995, 55.807760699999996], [37.8711986, 55.8063292], [37.8665868, 55.8042107], [37.8657431, 55.804207999999996], [37.863264699999995, 55.80742109999999], [37.8628232, 55.8073119], [37.861697299999996, 55.8086902], [37.8602718, 55.80857580000001], [37.860033800000004, 55.8084267], [37.86068709999999, 55.807540599999996], [37.85636949999999, 55.80604139999999], [37.8561187, 55.806648499999994], [37.8560108, 55.806588399999995], [37.8521852, 55.8089604], [37.85129959999999, 55.8088336], [37.85069149999999, 55.8085496], [37.85046939999999, 55.8086719], [37.85023739999999, 55.808557], [37.848871499999994, 55.8094232], [37.84980899999999, 55.81046619999999], [37.8453271, 55.8135622], [37.85288299999999, 55.8167206], [37.857320599999994, 55.817911099999996], [37.85726559999999, 55.8183396], [37.8581098, 55.8187889], [37.85754789999999, 55.8195725], [37.8591727, 55.8199786], [37.8594399, 55.8194823], [37.859989799999994, 55.819392], [37.86231860000001, 55.8199379], [37.8622608, 55.82001830000001], [37.8661715, 55.8208519], [37.8662149, 55.82093090000001], [37.86871550000001, 55.8214989], [37.868518400000006, 55.82186399999999], [37.869120900000006, 55.8219754], [37.869128200000006, 55.8219555], [37.872252200000005, 55.8224984], [37.8737977, 55.8200036], [37.87644099999999, 55.8204713], [37.878339100000005, 55.820652800000005], [37.8789454, 55.819896899999996], [37.8797221, 55.819573399999996], [37.880538200000004, 55.8195135], [37.882113800000006, 55.819833599999995], [37.88396769999999, 55.8203394], [37.88427759999999, 55.819960599999995], [37.88511830000001, 55.820598600000004], [37.8879343, 55.82071080000001], [37.8887419, 55.819695599999996], [37.89237250000001, 55.8191777], [37.89235390000001, 55.8190786], [37.8972431, 55.8182319], [37.89894880000001, 55.817437899999994], [37.899785200000004, 55.8161364]]], [[[37.945162700000004, 55.72081180000001], [37.942995800000006, 55.719813], [37.941327099999995, 55.718952400000006], [37.94068139999999, 55.71861930000001], [37.9383672, 55.7174256], [37.9379967, 55.7173827], [37.9365872, 55.7162384], [37.930932500000004, 55.71619280000001], [37.928069900000004, 55.716159000000005], [37.926253800000005, 55.715149700000005], [37.926114600000005, 55.712186800000005], [37.9256924, 55.7119819], [37.924847299999996, 55.71111260000001], [37.9247941, 55.711117300000005], [37.92335530000001, 55.70953930000001], [37.92258, 55.708688900000006], [37.9219165, 55.7079613], [37.920673900000004, 55.707796300000005], [37.9192451, 55.707606399999996], [37.9070118, 55.7069911], [37.9062268, 55.706991900000006], [37.9054419, 55.70699280000001], [37.9013429, 55.7066238], [37.8972438, 55.7062547], [37.89337030000001, 55.70555390000001], [37.8928973, 55.70550620000001], [37.8869711, 55.70521530000001], [37.8854929, 55.7042204], [37.884014699999994, 55.7032255], [37.883870599999995, 55.7032858], [37.883183599999995, 55.702821], [37.882496599999996, 55.70235620000001], [37.882306, 55.702460900000005], [37.8815021, 55.7018524], [37.8805731, 55.7011496], [37.881140099999996, 55.700861599999996], [37.881098699999995, 55.7008451], [37.8794724, 55.7002681], [37.8773882, 55.6988934], [37.8753042, 55.69751850000001], [37.872916200000006, 55.69607860000001], [37.871532200000004, 55.6952975], [37.8684305, 55.6968676], [37.865328500000004, 55.698437600000005], [37.86486489999999, 55.69867490000001], [37.8626911, 55.699787300000004], [37.8600534, 55.70113680000001], [37.8595289, 55.7008246], [37.858951499999996, 55.7011041], [37.85878149999999, 55.70099510000001], [37.858176, 55.7012543], [37.85340899999999, 55.703540200000006], [37.853435399999995, 55.7037885], [37.85234, 55.7041954], [37.8492009, 55.7052667], [37.845551, 55.7064851], [37.8439557, 55.7070257], [37.8423714, 55.7076143], [37.8413708, 55.7079663], [37.837409199999996, 55.7092892], [37.8360239, 55.709776000000005], [37.8339009, 55.710475200000005], [37.827312400000004, 55.7126833], [37.8238797, 55.713846], [37.8207278, 55.7148955], [37.816771499999994, 55.7162257], [37.81358149999999, 55.71731630000001], [37.812093, 55.717820599999996], [37.808573200000005, 55.718999100000005], [37.80480769999999, 55.7202665], [37.80081139999999, 55.72153890000001], [37.79911820000002, 55.72210560000001], [37.79677050000001, 55.72289290000001], [37.793718900000016, 55.72397890000001], [37.79230710000001, 55.7244619], [37.789796, 55.725292900000014], [37.77906290000001, 55.728888700000006], [37.77714280000001, 55.72950600000001], [37.775896700000004, 55.72993910000001], [37.7748882, 55.730387], [37.7741734, 55.730743600000004], [37.773852500000004, 55.730906100000006], [37.76996520000001, 55.73290490000001], [37.7692666, 55.733253600000005], [37.76751900000001, 55.73415430000001], [37.767299200000004, 55.7342686], [37.76713240000001, 55.73435820000001], [37.765891200000006, 55.734963900000004], [37.762636400000005, 55.7365415], [37.76220530000001, 55.736707900000006], [37.7617576, 55.736857], [37.761271300000004, 55.73699280000001], [37.76091120000001, 55.7370686], [37.760543000000006, 55.73713360000001], [37.7599826, 55.7372256], [37.7592284, 55.737363900000005], [37.75854820000001, 55.73745280000001], [37.755363100000004, 55.7378493], [37.7539775, 55.738048000000006], [37.7527664, 55.73825810000001], [37.751621799999995, 55.738499000000004], [37.7504587, 55.73879980000001], [37.74935000000001, 55.73915670000001], [37.74839210000001, 55.73953490000001], [37.7475092, 55.73994570000001], [37.746722600000005, 55.7403678], [37.745944800000004, 55.7408776], [37.7452873, 55.741390100000004], [37.7439671, 55.74253980000001], [37.7430994, 55.743177900000006], [37.74237390000001, 55.7436661], [37.741742300000006, 55.74405230000001], [37.7410175, 55.7444517], [37.7401818, 55.7448321], [37.739341700000004, 55.745177000000005], [37.73841600000001, 55.745485900000006], [37.7374472, 55.74575580000001], [37.73659790000001, 55.74597490000001], [37.736188500000004, 55.746090300000006], [37.726535900000016, 55.748647], [37.725325200000015, 55.7489665], [37.724446300000004, 55.749232400000004], [37.72363280000001, 55.74951550000001], [37.72301500000001, 55.74977260000001], [37.722400500000006, 55.7500624], [37.7218517, 55.75035330000001], [37.72136530000001, 55.750635100000004], [37.72083980000001, 55.7509773], [37.72057250000001, 55.7511608], [37.72030920000001, 55.751355200000006], [37.7197448, 55.7518501], [37.719611900000004, 55.7519793], [37.719168200000006, 55.75241090000001], [37.71871880000001, 55.75294230000001], [37.7183854, 55.753419], [37.718132800000014, 55.753880499999994], [37.71791520000001, 55.7544051], [37.7177565, 55.7549601], [37.71768109999999, 55.755507], [37.7176602, 55.7559645], [37.717713200000006, 55.7564833], [37.717817399999994, 55.7569832], [37.7179697, 55.757493], [37.71817980000001, 55.75801820000001], [37.7184278, 55.758507], [37.7196735, 55.760629200000004], [37.7198555, 55.76094330000001], [37.72024890000001, 55.7616096], [37.720471700000004, 55.76202810000001], [37.72063190000001, 55.7624647], [37.72070510000001, 55.762784], [37.72074490000001, 55.76312290000001], [37.72087330000001, 55.764946300000005], [37.72085310000001, 55.76547030000001], [37.7207817, 55.765883300000006], [37.7206276, 55.76631840000001], [37.720389000000004, 55.76673320000001], [37.720086300000006, 55.76713380000001], [37.719612700000006, 55.767679300000005], [37.7178392, 55.769589200000006], [37.71736739999999, 55.770145500000005], [37.716971300000004, 55.77070090000001], [37.71630270000001, 55.771776300000006], [37.715946200000005, 55.772298000000006], [37.714192700000005, 55.77453270000001], [37.7137476, 55.77511290000002], [37.7136118, 55.77530130000001], [37.7135246, 55.77525590000001], [37.7133277, 55.77547930000001], [37.7126807, 55.77617120000001], [37.710931200000005, 55.77800070000001], [37.71043, 55.778449200000004], [37.70991970000001, 55.7788745], [37.709336500000006, 55.779284499999996], [37.708789800000005, 55.779622700000004], [37.7082977, 55.7799071], [37.7077419, 55.780160800000004], [37.707126800000005, 55.7803837], [37.706092600000005, 55.780737200000004], [37.7052497, 55.7809935], [37.704491399999995, 55.7811858], [37.704302000000006, 55.7812394], [37.7031812, 55.7815238], [37.70252970000001, 55.781654499999995], [37.7018967, 55.7817704], [37.7012436, 55.7818505], [37.7006114, 55.781891099999996], [37.699982600000006, 55.781911900000004], [37.699901200000006, 55.7819144], [37.699517500000006, 55.7819679], [37.69938590000001, 55.7819686], [37.6967864, 55.78201620000001], [37.696335300000015, 55.7819443], [37.692601700000004, 55.781956300000004], [37.692249800000006, 55.78184469999999], [37.6888219, 55.781905], [37.685998100000006, 55.7825234], [37.6826668, 55.783163], [37.67830880000001, 55.7840196], [37.6757476, 55.78453030000001], [37.675093000000004, 55.784683199999996], [37.674579, 55.7847878], [37.674071, 55.7848912], [37.67227870000001, 55.7852207], [37.667289399999994, 55.78612030000001], [37.6638545, 55.786773000000004], [37.66254000000001, 55.7870345], [37.661058800000006, 55.787333800000006], [37.6600296, 55.787523900000004], [37.6555977, 55.788380800000006], [37.651521499999994, 55.7893694], [37.6508167, 55.790755800000014], [37.650451499999996, 55.7916395], [37.6503095, 55.792919300000015], [37.6503663, 55.793392300000015], [37.6504231, 55.7938594], [37.650464799999995, 55.79421220000001], [37.6513037, 55.795943400000006], [37.651334399999996, 55.79641840000001], [37.6511431, 55.796899700000004], [37.650983499999995, 55.797832400000004], [37.65101, 55.798707500000006], [37.651155300000006, 55.79905780000001], [37.6513982, 55.8001096], [37.654530300000005, 55.804100999999996], [37.6578185, 55.8080219], [37.65811860000001, 55.8083605], [37.6600445, 55.81054939999999], [37.66280330000001, 55.813698499999994], [37.66310790000001, 55.814045699999994], [37.6660698, 55.81746989999999], [37.668080800000006, 55.81987709999999], [37.66857560000001, 55.8204479], [37.669246, 55.8215406], [37.669851900000005, 55.8227895], [37.67032270000001, 55.824082], [37.670463399999996, 55.8244238], [37.6706062, 55.8248384], [37.670643, 55.8249165], [37.67095020000001, 55.825686], [37.6712823, 55.826603999999996], [37.671461799999996, 55.827231399999995], [37.6714947, 55.827552000000004], [37.6715246, 55.8282041], [37.6715432, 55.8290195], [37.671500900000005, 55.829474], [37.671274, 55.83088719999999], [37.6710273, 55.8325648], [37.6708873, 55.833602], [37.6707673, 55.8345082], [37.6706272, 55.8356502], [37.6705206, 55.8365488], [37.6703805, 55.8376758], [37.6702104, 55.838739600000004], [37.6707205, 55.838635000000004], [37.6720878, 55.838407399999994], [37.6728491, 55.83833620000001], [37.6735016, 55.83831810000001], [37.6742063, 55.8383472], [37.67496439999999, 55.838450300000005], [37.675689399999996, 55.8386141], [37.676316500000006, 55.838821599999996], [37.6768981, 55.8390943], [37.6773835, 55.8393897], [37.67773820000001, 55.8396759], [37.678009100000004, 55.8399397], [37.67829270000001, 55.840343], [37.678457, 55.840689999999995], [37.67853310000001, 55.8410399], [37.67852870000001, 55.841439099999995], [37.678440300000005, 55.84182339999999], [37.6802576, 55.8424748], [37.6813889, 55.8432125], [37.685362500000004, 55.845290399999996], [37.68584439999999, 55.8455421], [37.6865624, 55.8459342], [37.6866194, 55.8459632], [37.6888242, 55.847167299999995], [37.6888898, 55.847200099999995], [37.6890669, 55.84728859999999], [37.69032010000001, 55.8480054], [37.69021490000001, 55.8481906], [37.6908265, 55.8488919], [37.6922264, 55.8503067], [37.6899704, 55.85122309999999], [37.6918707, 55.852602399999995], [37.69239160000001, 55.8529525], [37.688327900000004, 55.853925999999994], [37.6867679, 55.8545129], [37.6867899, 55.85477339999999], [37.6878597, 55.85549159999999], [37.6879813, 55.8555164], [37.6886034, 55.855284899999994], [37.6894096, 55.8559566], [37.690243, 55.8558958], [37.69059820000001, 55.85608429999999], [37.690747200000004, 55.85617739999999], [37.691630700000005, 55.856029899999996], [37.692521500000005, 55.8561333], [37.69313320000001, 55.8557966], [37.693069200000004, 55.8556987], [37.692895500000006, 55.855567799999996], [37.692634000000005, 55.8555098], [37.69243030000001, 55.855330300000006], [37.69277370000001, 55.855166999999994], [37.694675800000006, 55.85340239999999], [37.6944997, 55.85302459999999], [37.6942892, 55.8525461], [37.694256900000006, 55.85247], [37.694248200000004, 55.85244959999999], [37.69415480000001, 55.852229799999996], [37.693963800000006, 55.85180659999999], [37.69535410000001, 55.8501993], [37.69682290000001, 55.8481609], [37.7035867, 55.848773300000005], [37.70551780000001, 55.84786129999999], [37.7097805, 55.8475429], [37.7118986, 55.8473555], [37.712160100000006, 55.8473548], [37.7123877, 55.8474329], [37.712503100000006, 55.84752749999999], [37.7140751, 55.8469149], [37.7171278, 55.8490573], [37.718019700000006, 55.84935], [37.71937880000001, 55.85004439999999], [37.72010480000001, 55.8505731], [37.719405, 55.85142259999999], [37.721005000000005, 55.8522056], [37.72163930000001, 55.852924099999996], [37.72145630000001, 55.85336449999999], [37.718246300000004, 55.8600081], [37.7179213, 55.8606342], [37.7149391, 55.8606743], [37.71047, 55.860735000000005], [37.700564, 55.8611218], [37.70077280000001, 55.8614562], [37.7019976, 55.86217520000001], [37.702657900000005, 55.8625577], [37.705039600000006, 55.8610008], [37.709321900000006, 55.861007799999996], [37.709115900000015, 55.8625635], [37.708863900000004, 55.8631979], [37.7066693, 55.8641433], [37.7066141, 55.864285599999995], [37.707211900000004, 55.8647584], [37.707835700000004, 55.865265300000004], [37.7079241, 55.86533690000001], [37.707699399999996, 55.86551850000001], [37.70903510000001, 55.8662524], [37.7111427, 55.8674321], [37.71523210000001, 55.8698022], [37.71581330000001, 55.8701542], [37.719053100000004, 55.8722456], [37.72173600000001, 55.872983], [37.7224445, 55.8736321], [37.7236242, 55.87340639999999], [37.723628600000005, 55.873201699999996], [37.72425570000001, 55.873008], [37.726091800000006, 55.8736398], [37.72655540000001, 55.8737993], [37.7270819, 55.8738551], [37.727340100000006, 55.8739219], [37.727549800000006, 55.8739242], [37.7279265, 55.8739005], [37.728060400000004, 55.874004299999996], [37.72832370000001, 55.874214599999995], [37.72854210000001, 55.874259099999996], [37.729479000000005, 55.8743869], [37.72983260000001, 55.87466549999999], [37.7318197, 55.8749452], [37.7310813, 55.87596], [37.7311964, 55.876766499999995], [37.731479, 55.87687939999999], [37.73265790000001, 55.87766489999999], [37.73356230000001, 55.8782167], [37.7342601, 55.8786424], [37.73550520000001, 55.877999499999994], [37.744659, 55.8733247], [37.76849830000001, 55.8608921], [37.777405800000004, 55.85644189999999], [37.78261080000001, 55.8537732], [37.785298000000004, 55.852403699999996], [37.7878982, 55.85107839999999], [37.7895455, 55.8502388], [37.79541040000001, 55.8471925], [37.8022311, 55.843669799999994], [37.807960599999994, 55.8407403], [37.813896099999994, 55.837663899999995], [37.8185855, 55.835295200000004], [37.823348, 55.8327712], [37.8273855, 55.8305991], [37.8297437, 55.830558100000005], [37.83013890000001, 55.8303025], [37.8300501, 55.8297218], [37.83008149999999, 55.829153000000005], [37.83233830000001, 55.8275673], [37.8343899, 55.8259607], [37.836049499999994, 55.8242232], [37.837369499999994, 55.8224896], [37.838094399999996, 55.8209718], [37.8383896, 55.819927199999995], [37.8385906, 55.8193213], [37.8387065, 55.819106399999995], [37.8391745, 55.81626149999999], [37.8398088, 55.815869799999994], [37.84199139999999, 55.815181599999995], [37.8427273, 55.8151177], [37.8433024, 55.81520749999999], [37.8434312, 55.8150863], [37.8435518, 55.8149722], [37.84362339999999, 55.81490439999999], [37.84376159999999, 55.8147738], [37.843043599999994, 55.814365099999996], [37.841448699999994, 55.812894899999996], [37.840632, 55.8124518], [37.8400458, 55.8120784], [37.8397912, 55.8117392], [37.839762, 55.81162469999999], [37.8399519, 55.8090302], [37.840206699999996, 55.80613520000001], [37.840412300000004, 55.80368599999999], [37.8405143, 55.8024712], [37.8409022, 55.798864800000004], [37.841318300000005, 55.79514480000001], [37.8417789, 55.79115650000001], [37.8420251, 55.7889634], [37.8422267, 55.7871679], [37.8426787, 55.7832225], [37.8431377, 55.7792395], [37.84462159999999, 55.77850060000001], [37.8455574, 55.77820830000001], [37.84586149999999, 55.778185400000005], [37.8460519, 55.778171400000005], [37.846381799999996, 55.778199400000005], [37.8484251, 55.778651800000006], [37.85000409999999, 55.77892860000001], [37.850473099999995, 55.77890360000001], [37.850678499999994, 55.77856290000001], [37.85040909999999, 55.77847860000001], [37.849882799999996, 55.778297], [37.849318800000006, 55.7780975], [37.848935100000006, 55.7779667], [37.8486518, 55.77786639999999], [37.8471787, 55.777392500000005], [37.8466903, 55.777253900000005], [37.8457574, 55.7770065], [37.845396, 55.776458700000006], [37.8450368, 55.775979500000005], [37.8438087, 55.77531460000001], [37.8435134, 55.775057800000006], [37.8434007, 55.7747346], [37.8434588, 55.7739617], [37.843565, 55.773852100000006], [37.843505900000004, 55.7736678], [37.843571499999996, 55.77283980000001], [37.843624899999995, 55.77255730000001], [37.8444528, 55.7711374], [37.844526699999996, 55.77113070000001], [37.844590999999994, 55.7710211], [37.844519, 55.771002100000004], [37.8451374, 55.7700365], [37.8455912, 55.769254100000005], [37.8459341, 55.768614500000005], [37.845698, 55.768071000000006], [37.8451879, 55.7679694], [37.8444223, 55.7675971], [37.843828499999994, 55.767279], [37.8436108, 55.76710800000001], [37.843497899999996, 55.766907200000006], [37.8434392, 55.7660805], [37.8433984, 55.76517410000001], [37.8433395, 55.764045700000004], [37.8432587, 55.76240280000001], [37.8434109, 55.76236090000001], [37.8434118, 55.76220060000001], [37.84323439999999, 55.76219490000001], [37.84320139999999, 55.7618465], [37.8431395, 55.7606971], [37.8431601, 55.76046], [37.84311220000001, 55.7596913], [37.84306739999999, 55.758934700000005], [37.843045399999994, 55.758731600000004], [37.842938800000006, 55.756818200000005], [37.842902, 55.75557310000001], [37.842896499999995, 55.755209], [37.84289439999999, 55.7550571], [37.84280639999999, 55.7550236], [37.8427931, 55.7547375], [37.8427824, 55.754507], [37.8427775, 55.754358800000006], [37.8427498, 55.753791], [37.8427086, 55.7537915], [37.8426552, 55.753142100000005], [37.8427249, 55.7528237], [37.8426982, 55.751588999999996], [37.842738000000004, 55.7508055], [37.84271390000001, 55.7494446], [37.842683799999996, 55.749073], [37.8425433, 55.747176100000004], [37.8426549, 55.7467345], [37.8431461, 55.74632530000001], [37.843677899999996, 55.745903000000006], [37.84480439999999, 55.74531490000001], [37.8457065, 55.7448717], [37.84680459999999, 55.7445871], [37.84791739999999, 55.74453530000001], [37.8479957, 55.7444999], [37.8497057, 55.7446206], [37.85142409999999, 55.7447565], [37.8529663, 55.744881199999995], [37.853920599999995, 55.7449497], [37.8566169, 55.7450679], [37.85918739999999, 55.74515500000001], [37.8605434, 55.7452434], [37.863233, 55.74557300000001], [37.864222999999996, 55.745724100000004], [37.864739300000004, 55.7458471], [37.8728499, 55.7474131], [37.879524499999995, 55.7487294], [37.8825409, 55.749339600000006], [37.8832589, 55.7492077], [37.887345399999994, 55.748457], [37.8877105, 55.74857720000001], [37.8882457, 55.7484642], [37.888712000000005, 55.74714290000001], [37.8893337, 55.74547280000001], [37.8900278, 55.7436278], [37.89095330000001, 55.742194600000005], [37.8904033, 55.7420847], [37.890084699999996, 55.7418706], [37.8900854, 55.7416036], [37.885829099999995, 55.74261290000001], [37.88360439999999, 55.7426915], [37.881749899999996, 55.742731000000006], [37.8807532, 55.742504100000005], [37.880106999999995, 55.7422546], [37.8800331, 55.7417465], [37.8780087, 55.737869499999995], [37.8731611, 55.738156900000014], [37.8684891, 55.737289499999996], [37.8665394, 55.7362964], [37.866705100000004, 55.736181800000004], [37.864238, 55.73471680000001], [37.865471, 55.73315850000001], [37.868892200000005, 55.732972900000014], [37.869536000000004, 55.73238620000001], [37.8712339, 55.730838600000006], [37.871570399999996, 55.7308478], [37.873412300000005, 55.7296476], [37.8721668, 55.72770510000001], [37.8702706, 55.726586100000006], [37.8724504, 55.723377000000006], [37.87573810000001, 55.723381200000006], [37.8769962, 55.7216165], [37.8765345, 55.72047090000001], [37.88100449999999, 55.7190992], [37.8824863, 55.71900290000001], [37.8834259, 55.7191594], [37.8861232, 55.719593800000006], [37.886920399999994, 55.7202606], [37.887129099999996, 55.721653], [37.886080799999995, 55.72236970000001], [37.8841562, 55.72339620000001], [37.88547749999999, 55.724191600000005], [37.88744349999999, 55.72376860000001], [37.888902900000005, 55.72378690000001], [37.889850499999994, 55.72370120000001], [37.8906332, 55.72230900000001], [37.892308400000005, 55.723187100000004], [37.898366800000005, 55.723569100000006], [37.8993176, 55.72361910000001], [37.899329800000004, 55.724026900000005], [37.9001848, 55.724343100000006], [37.901823199999995, 55.72441860000001], [37.9024213, 55.72525090000001], [37.9035256, 55.72533440000001], [37.905050700000004, 55.72509970000001], [37.905047599999996, 55.724969900000005], [37.9054413, 55.7249454], [37.906356, 55.72479090000001], [37.9077881, 55.724802700000005], [37.9118339, 55.725744500000005], [37.9138057, 55.726581], [37.915047699999995, 55.726983800000006], [37.915467299999996, 55.7274679], [37.916175300000006, 55.72770980000001], [37.9163955, 55.72816000000001], [37.916927799999996, 55.72835710000001], [37.91738339999999, 55.72945000000001], [37.91796949999999, 55.73052290000001], [37.9180394, 55.7306219], [37.918664899999996, 55.73070380000001], [37.9193266, 55.730704700000004], [37.919978300000004, 55.7308017], [37.9206051, 55.7308776], [37.921162300000006, 55.73085820000001], [37.92212010000001, 55.731013000000004], [37.9228662, 55.731230700000005], [37.9235854, 55.7312255], [37.924044699999996, 55.7310515], [37.9241438, 55.7310019], [37.924241099999996, 55.7308907], [37.9243944, 55.7308455], [37.9244803, 55.730826900000004], [37.924793900000004, 55.7307654], [37.925199600000006, 55.73050990000001], [37.92555180000001, 55.73051780000001], [37.9256164, 55.7304699], [37.9265295, 55.73054200000001], [37.9274801, 55.730226800000004], [37.92802210000001, 55.730003200000006], [37.92835320000001, 55.72954090000001], [37.9284005, 55.729427300000005], [37.92852280000001, 55.72935360000001], [37.928859300000006, 55.729322900000014], [37.9299636, 55.72945270000001], [37.9302418, 55.7298066], [37.9304136, 55.72985810000001], [37.9308738, 55.72975500000001], [37.9313791, 55.72937360000001], [37.9319453, 55.72915620000001], [37.932951700000004, 55.728690500000006], [37.934289699999994, 55.7278764], [37.9349596, 55.72763870000001], [37.9355964, 55.727385700000006], [37.9363364, 55.72713130000001], [37.9376089, 55.726887], [37.9376829, 55.72653370000001], [37.9389668, 55.725578200000015], [37.9397566, 55.72503250000001], [37.9401397, 55.7246854], [37.9404578, 55.72457200000001], [37.94064959999999, 55.72455790000001], [37.9406102, 55.72451630000001], [37.940522300000005, 55.7244924], [37.9408193, 55.724337600000005], [37.941137499999996, 55.72398630000001], [37.941582499999996, 55.7234947], [37.9418102, 55.72317020000001], [37.9422726, 55.72299180000001], [37.9424317, 55.72281000000001], [37.9424025, 55.72276190000001], [37.942481699999995, 55.72269270000001], [37.9424006, 55.72252870000001], [37.942404499999995, 55.7224874], [37.942484699999994, 55.72247920000001], [37.942526900000004, 55.72242860000001], [37.9425043, 55.72238620000001], [37.942470900000004, 55.72238610000001], [37.9426104, 55.72205190000001], [37.942932500000005, 55.7219494], [37.9430304, 55.721926800000006], [37.9430972, 55.72191580000001], [37.9431987, 55.7219266], [37.9432653, 55.72193540000001], [37.9433354, 55.721914000000005], [37.9433693, 55.7218813], [37.9433416, 55.721837], [37.943316, 55.7218115], [37.943302200000005, 55.7217836], [37.9433667, 55.72170500000001], [37.9435135, 55.721512300000015], [37.9435793, 55.7214497], [37.9437046, 55.7214304], [37.94388769999999, 55.72143500000001], [37.9439693, 55.7214419], [37.944005499999996, 55.7214825], [37.944080799999995, 55.721505500000006], [37.944086799999994, 55.721507300000006], [37.944135100000004, 55.7214972], [37.94408119999999, 55.7214255], [37.94406649999999, 55.721397200000006], [37.9443308, 55.72132690000001], [37.9443554, 55.721357100000006], [37.944434599999994, 55.72153510000001], [37.9444793, 55.7215494], [37.944547799999995, 55.721537500000004], [37.944626799999995, 55.721488], [37.9450487, 55.7212219], [37.945650300000004, 55.720838500000006], [37.945162700000004, 55.72081180000001]]]]}}, {"id": 162903, "osm_type": "relation", "type": "Feature", "name": "Северный административный округ", "properties": {"ref": "САО", "name": "Северный административный округ", "name:be": "Паўночная адміністрацыйная акруга", "name:de": "Nördlicher Verwaltungsbezirk", "name:en": "Northern Administrative Okrug", "website": "http://www.sao.mos.ru/", "boundary": "administrative", "wikipedia": "ru:Северный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.4217832, 55.9502361], [37.4207076, 55.9497164], [37.421136800000006, 55.94748149999999], [37.4208886, 55.947199499999996], [37.4192998, 55.946696599999996], [37.4168021, 55.94674], [37.4161889, 55.9465422], [37.415558000000004, 55.9457605], [37.4103667, 55.945258], [37.408578600000006, 55.942771300000004], [37.4082011, 55.941473099999996], [37.408422800000004, 55.9411325], [37.408127300000004, 55.9409418], [37.40821230000001, 55.940694099999995], [37.4074528, 55.939854], [37.4077198, 55.9392932], [37.406663599999995, 55.939028], [37.4071086, 55.9367098], [37.4076939, 55.934986499999994], [37.40762149999999, 55.934809599999994], [37.407668799999996, 55.93469139999999], [37.4094668, 55.9330226], [37.4101679, 55.931913300000005], [37.40986109999999, 55.931406499999994], [37.410188999999995, 55.9306926], [37.4101622, 55.9304426], [37.409427199999996, 55.9296377], [37.407746599999996, 55.9290304], [37.4078184, 55.9288078], [37.408549900000004, 55.92852530000001], [37.410269099999994, 55.9272063], [37.410624799999994, 55.925248], [37.4084134, 55.9241346], [37.396846399999994, 55.92617010000001], [37.3943312, 55.9226576], [37.393778000000005, 55.9215602], [37.393851, 55.921135500000005], [37.39493590000001, 55.9193292], [37.39871300000001, 55.916617699999996], [37.3957806, 55.915497599999995], [37.3952665, 55.9152311], [37.39466649999999, 55.914698099999995], [37.3942619, 55.91448759999999], [37.3900178, 55.912844299999996], [37.389345, 55.9125905], [37.387326699999996, 55.91182909999999], [37.3870521, 55.9117312], [37.386723999999994, 55.91165699999999], [37.386109, 55.9116113], [37.3849908, 55.9115081], [37.3839973, 55.9114283], [37.383677299999995, 55.91140059999999], [37.3830057, 55.9113592], [37.38231630000001, 55.91134759999999], [37.38106479999999, 55.9113985], [37.379231399999995, 55.911491299999994], [37.37835020000001, 55.91148949999999], [37.377708999999996, 55.9114228], [37.376795200000004, 55.911243899999995], [37.372963399999996, 55.909637499999995], [37.36986139999999, 55.90819590000001], [37.36861580000001, 55.909913200000005], [37.3681374, 55.9102257], [37.3657545, 55.9141036], [37.3660258, 55.9153807], [37.3696713, 55.9175133], [37.3688493, 55.9179563], [37.3717351, 55.919643099999995], [37.3769657, 55.9207048], [37.37782299999999, 55.921114300000006], [37.3756398, 55.9217077], [37.37168309999999, 55.9233914], [37.3610349, 55.92805530000001], [37.356462799999996, 55.929954300000006], [37.35172119999999, 55.9277016], [37.3497022, 55.926776100000005], [37.34928649999999, 55.92639380000001], [37.3492233, 55.926038500000004], [37.3437067, 55.9241832], [37.3435925, 55.925422100000006], [37.343613999999995, 55.926109700000005], [37.3435269, 55.9266406], [37.3432582, 55.927089599999995], [37.34141459999999, 55.92891030000001], [37.340609799999996, 55.92995630000001], [37.3398343, 55.93073090000001], [37.3379221, 55.9320225], [37.33668649999999, 55.9326648], [37.335770800000006, 55.932959600000004], [37.333445499999996, 55.9335885], [37.3313205, 55.9338701], [37.334962999999995, 55.9353847], [37.3355374, 55.935188000000004], [37.3363011, 55.9347823], [37.33678, 55.9349949], [37.3364918, 55.9354447], [37.335815200000006, 55.935743900000006], [37.337379, 55.9364081], [37.338208800000004, 55.9363776], [37.3382762, 55.9366921], [37.3386657, 55.937064799999995], [37.3428168, 55.938852100000005], [37.3432683, 55.938957800000004], [37.3495479, 55.9366301], [37.35088109999999, 55.93744769999999], [37.3514523, 55.93722439999999], [37.352138200000006, 55.9377394], [37.352824299999995, 55.93810290000001], [37.3527324, 55.9381478], [37.3534009, 55.938611900000005], [37.3534921, 55.938573700000006], [37.354098699999994, 55.938906900000006], [37.3522537, 55.9396508], [37.3503948, 55.940476], [37.35100859999999, 55.940786599999996], [37.34780129999999, 55.942719100000005], [37.3474532, 55.9429426], [37.34790649999999, 55.9432289], [37.341698199999996, 55.9467499], [37.340527599999994, 55.94626639999999], [37.3385741, 55.9480078], [37.33815580000001, 55.9485636], [37.33851860000001, 55.948859], [37.33794639999999, 55.9493437], [37.337460899999996, 55.949854599999995], [37.336404599999995, 55.9507101], [37.335025900000005, 55.953589099999995], [37.33946769999999, 55.95482759999999], [37.3417992, 55.9559792], [37.3410173, 55.9565621], [37.3415703, 55.956828099999996], [37.3422581, 55.956574399999994], [37.342991399999995, 55.9564282], [37.344570499999996, 55.9564052], [37.346583599999995, 55.956552300000006], [37.3472722, 55.9566503], [37.347928399999994, 55.9567686], [37.3488563, 55.95701149999999], [37.3495832, 55.95728959999999], [37.3501948, 55.9569202], [37.3473268, 55.9553262], [37.346872, 55.955012800000006], [37.3465439, 55.95468899999999], [37.3463701, 55.954319399999996], [37.34633230000001, 55.953801799999994], [37.3464338, 55.953621999999996], [37.3469535, 55.9531035], [37.348819, 55.95189479999999], [37.35038759999999, 55.952475], [37.3521331, 55.951489399999986], [37.3522221, 55.95152149999999], [37.3529704, 55.951256699999995], [37.353492599999996, 55.9511259], [37.354858199999995, 55.95167849999999], [37.3559258, 55.9535018], [37.35797039999999, 55.9531424], [37.3581766, 55.9534769], [37.3582186, 55.95364239999999], [37.3581575, 55.953683899999994], [37.35822039999999, 55.9537079], [37.35811290000001, 55.9539068], [37.35786659999999, 55.95402059999999], [37.35792639999999, 55.95407939999999], [37.35780339999999, 55.95408159999999], [37.35786209999999, 55.9541198], [37.35778039999999, 55.954253699999995], [37.35781349999999, 55.9543558], [37.357707299999994, 55.95448399999999], [37.357960199999994, 55.9545396], [37.3584023, 55.954555], [37.3582973, 55.954620799999994], [37.357948699999994, 55.954662199999994], [37.3579229, 55.954733999999995], [37.3582585, 55.9547167], [37.35865449999999, 55.9547919], [37.358694299999996, 55.9547543], [37.3586111, 55.9547189], [37.3592083, 55.95478349999999], [37.3582748, 55.95528149999999], [37.358211, 55.9556423], [37.359446899999995, 55.9559712], [37.3719719, 55.956138200000005], [37.3764282, 55.955434399999994], [37.3758369, 55.95478309999999], [37.3753774, 55.954582699999996], [37.3752272, 55.954384899999994], [37.375213900000006, 55.95404109999999], [37.37530230000001, 55.9537343], [37.3755478, 55.953549699999996], [37.376344599999996, 55.9531316], [37.376462599999996, 55.952957399999995], [37.37788949999999, 55.952254599999996], [37.3797778, 55.9515999], [37.381161799999994, 55.9510052], [37.381676799999994, 55.95086099999999], [37.382127399999995, 55.95083699999999], [37.3829013, 55.9510149], [37.38325449999999, 55.9511559], [37.3835451, 55.9513092], [37.383667399999986, 55.951541299999995], [37.383587999999996, 55.951723699999995], [37.383371, 55.951873199999994], [37.382866699999994, 55.9524379], [37.3828799, 55.9527209], [37.3833198, 55.952955100000004], [37.38473449999999, 55.953203699999996], [37.38528169999999, 55.9531977], [37.386064899999994, 55.95288539999999], [37.3863653, 55.952861299999995], [37.3872558, 55.9532338], [37.38762059999999, 55.9533299], [37.3881892, 55.9532758], [37.3892192, 55.95308359999999], [37.3895625, 55.9528133], [37.3893479, 55.952555000000004], [37.3893801, 55.9523207], [37.3899058, 55.95208039999999], [37.390259900000004, 55.9519903], [37.391439999999996, 55.952164499999995], [37.391654599999995, 55.9522787], [37.392341300000005, 55.9523147], [37.392523700000005, 55.952297699999995], [37.392791900000006, 55.9522727], [37.393049399999995, 55.9521225], [37.39317810000001, 55.95184019999999], [37.39313520000001, 55.9515939], [37.392985, 55.951287499999985], [37.39203200000001, 55.950832999999996], [37.39188709999999, 55.950731399999995], [37.391742300000004, 55.95050139999999], [37.3916997, 55.95000159999999], [37.391901399999995, 55.949707599999996], [37.3919228, 55.9493712], [37.3924271, 55.948992800000006], [37.3928777, 55.9487705], [37.3931879, 55.948705000000004], [37.3938969, 55.94868639999999], [37.39417590000001, 55.948638300000006], [37.3945943, 55.9487044], [37.395613600000004, 55.9489868], [37.397739200000004, 55.94964339999999], [37.398757100000005, 55.949789599999995], [37.399616800000004, 55.9500038], [37.400550200000005, 55.950063899999996], [37.401344099999996, 55.9503462], [37.40188059999999, 55.9503042], [37.4038439, 55.9508388], [37.4045091, 55.950814799999996], [37.40519580000001, 55.950910900000004], [37.40577590000001, 55.951059799999996], [37.4061946, 55.95123949999999], [37.4064719, 55.95148999999999], [37.40667739999999, 55.9515038], [37.407063599999994, 55.9513536], [37.4073962, 55.95134159999999], [37.4079652, 55.951670199999995], [37.40796399999999, 55.9519787], [37.408232000000005, 55.9524367], [37.4086411, 55.952767599999994], [37.4085646, 55.9529653], [37.4082637, 55.953028499999995], [37.4078199, 55.952919800000004], [37.4074336, 55.953087999999994], [37.407476499999994, 55.9533538], [37.4078349, 55.953470499999995], [37.4081473, 55.9539112], [37.40853320000001, 55.9540089], [37.4090761, 55.95404149999999], [37.4097233, 55.9542052], [37.41024949999999, 55.9541785], [37.410538700000004, 55.953998399999996], [37.4107962, 55.9536501], [37.4107748, 55.9534038], [37.41102149999999, 55.9531936], [37.4113756, 55.953163499999995], [37.4119013, 55.95327759999999], [37.4121667, 55.95349469999999], [37.4120822, 55.95369469999999], [37.41201590000001, 55.953912900000006], [37.4124057, 55.953952], [37.41294739999999, 55.95388399999999], [37.4131366, 55.9537018], [37.4132317, 55.95366709999999], [37.4134013, 55.95372749999999], [37.4133712, 55.9538353], [37.413207199999995, 55.9539421], [37.413164699999996, 55.954112800000004], [37.4132769, 55.954251199999995], [37.41386469999999, 55.954502999999995], [37.414111399999996, 55.954539], [37.41498419999999, 55.9545385], [37.4153238, 55.9544309], [37.415828, 55.9544189], [37.4164181, 55.9543228], [37.4169009, 55.953860299999995], [37.4167903, 55.953582499999996], [37.416836599999996, 55.9534038], [37.4171155, 55.95328969999999], [37.41772709999999, 55.953361699999995], [37.418338600000006, 55.9531996], [37.41851030000001, 55.953271599999994], [37.4188536, 55.95322959999999], [37.4192398, 55.95327759999999], [37.4195999, 55.9532128], [37.419915700000004, 55.95303139999999], [37.420458200000006, 55.952516], [37.42045220000001, 55.9523826], [37.4199432, 55.9520115], [37.419986099999996, 55.95160299999999], [37.4202436, 55.9515309], [37.421059, 55.951578999999995], [37.4215998, 55.9515165], [37.42245810000001, 55.951314599999996], [37.4217832, 55.9502361]]], [[[37.588492300000006, 55.7916718], [37.58832090000001, 55.79115660000001], [37.588179100000005, 55.79073970000001], [37.58803030000001, 55.79023000000001], [37.58786899999999, 55.7897054], [37.5876763, 55.788639], [37.587562999999996, 55.78805690000001], [37.587417099999996, 55.7874755], [37.5869906, 55.785952400000006], [37.586912000000005, 55.785683399999996], [37.5868408, 55.785415500000006], [37.5867925, 55.7851914], [37.5865608, 55.7843862], [37.58644449999999, 55.783981399999995], [37.5863873, 55.783779800000005], [37.586339900000006, 55.7835794], [37.586238900000005, 55.7832467], [37.5861245, 55.7828912], [37.5860669, 55.782700500000004], [37.585958500000004, 55.78237990000001], [37.585846399999994, 55.782059100000005], [37.5856655, 55.7816102], [37.5854437, 55.781015200000006], [37.58519590000001, 55.7804825], [37.58511420000001, 55.780342700000006], [37.58499, 55.78015370000001], [37.5847927, 55.779866399999996], [37.584574499999995, 55.7796766], [37.58406359999999, 55.7792697], [37.5839104, 55.77915550000001], [37.5837773, 55.779063900000004], [37.5834176, 55.77881620000001], [37.5832531, 55.77870540000001], [37.5830726, 55.77859900000001], [37.582664599999994, 55.77836930000001], [37.5825612, 55.778310900000015], [37.58245590000001, 55.778245500000004], [37.5822436, 55.77811160000001], [37.58201820000001, 55.7779681], [37.5818157, 55.7778304], [37.581451699999995, 55.777616200000004], [37.581306999999995, 55.7775371], [37.581095499999996, 55.7774318], [37.5799897, 55.776927], [37.578099900000005, 55.7761477], [37.577459999999995, 55.77594030000001], [37.5767285, 55.77575240000001], [37.575993600000004, 55.775608000000005], [37.57523260000001, 55.77552080000001], [37.57368699999999, 55.7754834], [37.5731175, 55.77547070000001], [37.5710802, 55.77542580000001], [37.56691730000001, 55.774996], [37.5591717, 55.7742227], [37.5555062, 55.7738439], [37.5519166, 55.77340830000001], [37.5496059, 55.773217700000004], [37.5480891, 55.77315130000001], [37.5463871, 55.77310550000001], [37.544433999999995, 55.772989], [37.5433979, 55.772791700000006], [37.541863199999995, 55.77240630000001], [37.540570100000004, 55.7719534], [37.538963300000006, 55.771128600000004], [37.5379231, 55.7703665], [37.5372797, 55.76970500000001], [37.536633200000004, 55.769065100000006], [37.5362433, 55.767379700000006], [37.536061, 55.76610390000001], [37.5347273, 55.76619800000001], [37.534662, 55.766001300000006], [37.534622399999996, 55.76590110000001], [37.5342927, 55.76539250000001], [37.5341492, 55.76510420000001], [37.5338649, 55.764884599999995], [37.53357520000001, 55.764711000000005], [37.53311250000001, 55.764356500000005], [37.5322807, 55.763480900000005], [37.532118900000015, 55.76337100000001], [37.531822, 55.763223200000006], [37.5288475, 55.76197510000001], [37.52834000000001, 55.76175800000001], [37.5268841, 55.76113520000001], [37.52677870000001, 55.7610847], [37.5264245, 55.760923700000006], [37.52561230000001, 55.7604868], [37.5250671, 55.76010800000001], [37.524388, 55.7598784], [37.5242852, 55.7598459], [37.52256220000001, 55.7616884], [37.5219435, 55.761509000000004], [37.5214748, 55.76201990000001], [37.521232700000006, 55.762271000000005], [37.5208286, 55.76271430000001], [37.52051660000001, 55.763041], [37.520135900000014, 55.763439600000005], [37.519849699999995, 55.76373630000001], [37.5195731, 55.764022800000006], [37.5187374, 55.764904300000005], [37.5179168, 55.76577080000001], [37.5171018, 55.7666244], [37.5163263, 55.7674284], [37.5159631, 55.767810600000004], [37.5155606, 55.76823260000001], [37.515241599999996, 55.76856910000001], [37.5150741, 55.768744500000004], [37.514926599999995, 55.76889890000001], [37.5147929, 55.769041300000005], [37.514664999999994, 55.769177600000006], [37.514308, 55.76955800000001], [37.5140063, 55.769874200000004], [37.513846599999994, 55.7700395], [37.5136763, 55.77021580000001], [37.5133405, 55.7705612], [37.51317280000001, 55.77073860000001], [37.512802900000004, 55.7711244], [37.5125247, 55.7714167], [37.512122700000006, 55.7718391], [37.51188839999999, 55.77208590000001], [37.5117056, 55.7722795], [37.511275399999995, 55.77275980000001], [37.5109932, 55.7730656], [37.51055230000001, 55.7735211], [37.51025, 55.773828200000004], [37.51004, 55.7740431], [37.5096911, 55.774396], [37.50943290000001, 55.77466149999999], [37.5092005, 55.7748795], [37.5086447, 55.7754461], [37.50807530000001, 55.77605560000001], [37.5077413, 55.776431200000005], [37.5074439, 55.7768213], [37.507051499999996, 55.7774334], [37.506981399999994, 55.7775711], [37.5068526, 55.7778633], [37.5066488, 55.778409], [37.5062857, 55.78032210000001], [37.505761, 55.7826699], [37.505233700000005, 55.7848542], [37.50488969999999, 55.7866344], [37.5043917, 55.788578400000006], [37.504044199999996, 55.79044530000001], [37.5038924, 55.79112070000001], [37.50324739999999, 55.7938611], [37.50257580000001, 55.794982100000006], [37.50055530000001, 55.79734260000001], [37.4995576, 55.79859400000001], [37.498478000000006, 55.79981890000001], [37.49614270000001, 55.8024742], [37.493174, 55.8059574], [37.490987, 55.8084988], [37.48941, 55.8103134], [37.4885824, 55.81126879999999], [37.48789789999999, 55.812102100000004], [37.48765959999999, 55.8124387], [37.487361899999996, 55.8129907], [37.48722399999999, 55.813278399999994], [37.4871006, 55.8136659], [37.48702779999999, 55.8139517], [37.4869086, 55.81502439999999], [37.48684419999999, 55.8153461], [37.4867584, 55.8161493], [37.486724599999995, 55.81687049999999], [37.4867197, 55.8171743], [37.486701, 55.81742749999999], [37.486803599999995, 55.81793449999999], [37.48706959999999, 55.8188513], [37.4875492, 55.81986709999999], [37.488042, 55.8206297], [37.4889712, 55.821681999999996], [37.4898587, 55.822439300000006], [37.4902612, 55.8227664], [37.490720200000005, 55.8230964], [37.4919622, 55.8238104], [37.492648100000004, 55.8242031], [37.493365700000005, 55.8244783], [37.49332820000001, 55.824519], [37.4910751, 55.8272718], [37.4909498, 55.8272398], [37.4906968, 55.827172700000006], [37.490292800000006, 55.827064699999994], [37.489792900000005, 55.826931], [37.488426999999994, 55.8265657], [37.4871593, 55.826484699999995], [37.486376, 55.826478800000004], [37.4859625, 55.8264992], [37.4856033, 55.826517], [37.48428489999999, 55.8267077], [37.4835307, 55.826837399999995], [37.4828335, 55.826914800000004], [37.4813937, 55.8270137], [37.4803853, 55.8270233], [37.4788291, 55.8266538], [37.4784938, 55.8265742], [37.4782013, 55.8266146], [37.4779908, 55.8267936], [37.476299399999995, 55.828231900000006], [37.4762377, 55.8282843], [37.4757717, 55.8286851], [37.4744188, 55.8298286], [37.47446779999999, 55.8300036], [37.4783235, 55.8304707], [37.479122700000005, 55.830748], [37.478983, 55.8315541], [37.478549900000004, 55.8319632], [37.4778166, 55.832852800000005], [37.4762079, 55.8342859], [37.474223499999994, 55.8359672], [37.472178500000005, 55.8371823], [37.471677799999995, 55.837785499999995], [37.471778900000004, 55.8385544], [37.4720609, 55.8393886], [37.4725865, 55.8403538], [37.47251230000001, 55.840982999999994], [37.4722678, 55.8417749], [37.471515600000004, 55.8423979], [37.4703495, 55.842725900000005], [37.469885399999995, 55.8431779], [37.468845300000005, 55.8435381], [37.4680678, 55.8446782], [37.466711700000005, 55.8456326], [37.46537980000001, 55.8462341], [37.464462499999996, 55.847118200000004], [37.4639345, 55.84768559999999], [37.4634933, 55.8481997], [37.4636035, 55.849086299999996], [37.4628942, 55.8500763], [37.4613263, 55.85104499999999], [37.4610061, 55.85180669999999], [37.460847199999996, 55.85300399999999], [37.4601813, 55.8541059], [37.459825599999995, 55.855296599999996], [37.459445699999996, 55.8563209], [37.458821099999994, 55.85763849999999], [37.4582562, 55.8585639], [37.4577068, 55.85983739999999], [37.45660139999999, 55.8608586], [37.456082599999995, 55.86188479999999], [37.4559372, 55.8628426], [37.455090999999996, 55.864689299999995], [37.454721899999996, 55.86613630000001], [37.45454939999999, 55.8671416], [37.454602699999995, 55.8684899], [37.4539735, 55.870116], [37.4528921, 55.8700626], [37.4514503, 55.870264799999994], [37.44893870000001, 55.871357399999994], [37.44762239999999, 55.8719788], [37.4449403, 55.873419], [37.4426198, 55.874410999999995], [37.440133200000005, 55.875852300000005], [37.4387242, 55.8765343], [37.437978300000005, 55.8772161], [37.4378402, 55.878146], [37.437785, 55.878564499999996], [37.436483499999994, 55.8795786], [37.437495, 55.879893599999996], [37.43812230000001, 55.88008609999999], [37.44047449999999, 55.88082159999999], [37.4406998, 55.880939999999995], [37.4408781, 55.8810357], [37.4410737, 55.88114159999999], [37.4412022, 55.881225799999996], [37.4413518, 55.8813548], [37.44145399999999, 55.881472699999996], [37.4415135, 55.8815703], [37.441583699999995, 55.881692199999996], [37.4416353, 55.88180049999999], [37.44169719999999, 55.8819253], [37.441762, 55.88211280000001], [37.44182759999999, 55.88228149999999], [37.44188239999999, 55.882426499999994], [37.4419324, 55.8825748], [37.441977699999995, 55.8827631], [37.441986199999995, 55.8828932], [37.4419742, 55.883096099999996], [37.44198399999999, 55.883263299999996], [37.4419429, 55.8833399], [37.4418526, 55.883507599999994], [37.44174759999999, 55.88362109999999], [37.4416519, 55.88372139999999], [37.441535300000005, 55.883838999999995], [37.442418800000006, 55.8841651], [37.442531300000006, 55.88408339999999], [37.4426364, 55.8840123], [37.4428091, 55.8838782], [37.442962300000005, 55.883770399999996], [37.442914300000005, 55.883749699999996], [37.4437042, 55.883247999999995], [37.4438177, 55.8831924], [37.443964099999995, 55.8831423], [37.44428149999999, 55.88308299999999], [37.4445742, 55.883041999999996], [37.444933, 55.883017699999996], [37.44514890000001, 55.883003599999995], [37.4454056, 55.88298399999999], [37.4457174, 55.8829554], [37.446087299999995, 55.8829247], [37.4469285, 55.88286449999999], [37.4472149, 55.882840699999996], [37.447465599999994, 55.8828166], [37.4477311, 55.8827967], [37.447990499999996, 55.882788], [37.44833830000001, 55.882773900000004], [37.448729, 55.8827743], [37.450274099999994, 55.88286169999999], [37.45459739999999, 55.8830325], [37.4555653, 55.88320339999999], [37.4598799, 55.883204899999996], [37.46283210000001, 55.883217099999996], [37.4647226, 55.883459599999995], [37.467316600000004, 55.8837927], [37.4713061, 55.88469919999999], [37.473696999999994, 55.8852992], [37.4759345, 55.88586449999999], [37.47993820000001, 55.8873168], [37.4801488, 55.887410499999994], [37.4803402, 55.88749419999999], [37.480532100000005, 55.88758099999999], [37.48080409999999, 55.887704799999995], [37.481052399999996, 55.88780699999999], [37.4812358, 55.887886399999985], [37.481476199999996, 55.887997199999994], [37.48169719999999, 55.8880942], [37.4819137, 55.8881854], [37.4820901, 55.88826709999999], [37.4823164, 55.8883802], [37.482409499999996, 55.8884393], [37.4825261, 55.888528300000004], [37.4826398, 55.888633], [37.482741399999995, 55.8887586], [37.4828355, 55.888901], [37.4829315, 55.8890603], [37.4830325, 55.889221899999995], [37.4831236, 55.889376399999996], [37.4832561, 55.8895802], [37.4833469, 55.88972759999999], [37.4834287, 55.88987459999999], [37.4835006, 55.8900304], [37.4835239, 55.8902048], [37.4835633, 55.890412600000005], [37.48358459999999, 55.890593800000005], [37.4835978, 55.8906504], [37.4839947, 55.8906501], [37.4840598, 55.8904809], [37.4841168, 55.890325600000004], [37.4841657, 55.8901473], [37.4842308, 55.889987299999994], [37.484279699999995, 55.88985939999999], [37.484398999999996, 55.8897826], [37.48446399999999, 55.8895728], [37.48456349999999, 55.8893952], [37.484617699999994, 55.889226699999995], [37.48462149999999, 55.889164699999995], [37.484748499999995, 55.8889296], [37.48484939999999, 55.888803599999996], [37.4850252, 55.8886568], [37.4852756, 55.8885565], [37.485508100000004, 55.888497199999996], [37.4857232, 55.8884302], [37.48593530000001, 55.888398800000004], [37.4924417, 55.8908262], [37.4928601, 55.890982300000005], [37.49298830000001, 55.891116000000004], [37.4930934, 55.8912802], [37.493217900000005, 55.891437499999995], [37.4933245, 55.8915897], [37.4934104, 55.8917347], [37.4934966, 55.8918738], [37.4936267, 55.8920669], [37.493749, 55.8922469], [37.4938678, 55.892380800000005], [37.493999, 55.892493300000005], [37.49413320000001, 55.8925847], [37.494345300000006, 55.892676800000004], [37.4946009, 55.892759600000005], [37.4948148, 55.8928065], [37.49513950000001, 55.8928174], [37.495509500000004, 55.8927625], [37.49578830000001, 55.89271080000001], [37.496035000000006, 55.892603300000005], [37.4962542, 55.8924795], [37.49851120000001, 55.893472900000006], [37.50281830000001, 55.895365600000005], [37.5069433, 55.897175600000004], [37.5072164, 55.8972972], [37.51764729999999, 55.901994499999994], [37.5199439, 55.90297290000001], [37.522847399999996, 55.9042337], [37.5244518, 55.9049172], [37.5260016, 55.905487699999995], [37.527025900000005, 55.90579590000001], [37.527937800000004, 55.906015000000004], [37.5294685, 55.906328800000004], [37.5318958, 55.906827899999996], [37.533818600000004, 55.9071717], [37.5370259, 55.9075556], [37.5368567, 55.907063699999995], [37.5376117, 55.905475300000006], [37.5378582, 55.9050619], [37.5380601, 55.9047557], [37.538279100000004, 55.904464999999995], [37.5386925, 55.9039985], [37.5392272, 55.903499599999996], [37.5399434, 55.90288439999999], [37.5405773, 55.902430800000005], [37.541169599999996, 55.9020266], [37.54166459999999, 55.901731], [37.542371, 55.901367799999996], [37.542885399999996, 55.9011424], [37.5441185, 55.900665599999996], [37.5519785, 55.8977748], [37.5528556, 55.89746099999999], [37.5590425, 55.89523380000001], [37.5622276, 55.8940409], [37.563069, 55.893697599999996], [37.564058100000004, 55.8932732], [37.5647478, 55.892842], [37.56537050000001, 55.8923855], [37.565896800000004, 55.8919341], [37.56635860000001, 55.8914168], [37.56675520000001, 55.8908373], [37.5670561, 55.8901632], [37.56719890000001, 55.8892787], [37.5674047, 55.8873023], [37.5674995, 55.884548099999996], [37.567675300000005, 55.882644299999995], [37.56816210000001, 55.8782823], [37.56829090000001, 55.8775903], [37.5684672, 55.876988399999995], [37.56928739999999, 55.8749889], [37.56999880000001, 55.8733055], [37.5704746, 55.8721766], [37.571371, 55.8701818], [37.57261820000001, 55.8671064], [37.5731862, 55.8657867], [37.573917900000005, 55.8640117], [37.574328, 55.863002200000004], [37.5746003, 55.86211690000001], [37.57468139999999, 55.8611375], [37.574631499999995, 55.860457], [37.574546399999996, 55.859893099999994], [37.5743515, 55.859217699999995], [37.5741499, 55.85860159999999], [37.573442, 55.85687339999999], [37.572785200000006, 55.855241199999995], [37.5727074, 55.854734699999995], [37.5726431, 55.8541581], [37.572678200000006, 55.853206199999995], [37.572759000000005, 55.8523622], [37.57290580000001, 55.851419799999995], [37.5730897, 55.85062439999999], [37.5733094, 55.849840199999996], [37.573671, 55.848794], [37.5737717, 55.8484763], [37.5738961, 55.848099], [37.57444139999999, 55.8465657], [37.5749493, 55.8450937], [37.575397900000006, 55.8439287], [37.57561810000001, 55.84358399999999], [37.5760178, 55.8430943], [37.577661199999994, 55.8414303], [37.5779697, 55.84102119999999], [37.57821810000001, 55.8406209], [37.578493900000005, 55.840036], [37.578672600000004, 55.8394438], [37.57871920000001, 55.839032200000005], [37.578739500000005, 55.8386144], [37.5786411, 55.8379066], [37.57854820000001, 55.83758769999999], [37.578371100000005, 55.83714139999999], [37.57815370000001, 55.8367858], [37.5778195, 55.836296499999996], [37.577447899999996, 55.8358898], [37.576818800000005, 55.835345800000006], [37.5762939, 55.834949699999996], [37.57611060000001, 55.8348039], [37.5759673, 55.83469739999999], [37.5750831, 55.8339784], [37.574442499999996, 55.8333046], [37.5741456, 55.832856], [37.5738908, 55.832395000000005], [37.573761499999996, 55.8320855], [37.5736501, 55.831718900000006], [37.573571300000005, 55.83132139999999], [37.573575600000005, 55.830584099999996], [37.5736451, 55.829131000000004], [37.573948200000004, 55.82279690000001], [37.5740221, 55.82239280000001], [37.5741424, 55.8219591], [37.5743079, 55.821533], [37.574553200000004, 55.821116100000005], [37.5756899, 55.819594499999994], [37.577535700000006, 55.817124799999995], [37.5778185, 55.81664059999999], [37.578055400000004, 55.8160549], [37.5786805, 55.813138900000006], [37.578831300000004, 55.81262139999999], [37.5790441, 55.8121915], [37.5791446, 55.8120186], [37.5793077, 55.81180769999999], [37.5796069, 55.81147839999999], [37.5804261, 55.810852399999995], [37.5810542, 55.810506499999995], [37.5836423, 55.809306], [37.584401899999996, 55.8088932], [37.5847301, 55.808682399999995], [37.5843356, 55.808685399999995], [37.58313690000001, 55.808621499999994], [37.5806522, 55.80828739999999], [37.581196999999996, 55.8073742], [37.581784299999995, 55.806425499999996], [37.582339600000005, 55.8055211], [37.5828408, 55.8037217], [37.5831873, 55.802378000000004], [37.5835067, 55.801021799999994], [37.5837205, 55.799932100000014], [37.5839686, 55.79849430000001], [37.5841136, 55.7972084], [37.5842021, 55.79626230000001], [37.5841863, 55.79585260000001], [37.5842913, 55.79550180000001], [37.5843177, 55.79532260000001], [37.584388399999995, 55.79508290000001], [37.584424799999994, 55.79499560000001], [37.5844709, 55.794903100000006], [37.584531399999996, 55.794808700000004], [37.5845992, 55.7947215], [37.5846713, 55.794637300000005], [37.5847379, 55.79456820000001], [37.5848158, 55.794498600000004], [37.5850046, 55.7943695], [37.58573320000001, 55.79396030000001], [37.586530100000004, 55.793437600000004], [37.5877997, 55.79263660000001], [37.588229, 55.792363400000006], [37.588633300000005, 55.79205660000001], [37.588492300000006, 55.7916718]]]]}}, {"id": 1304596, "osm_type": "relation", "type": "Feature", "name": "Юго-Западный административный округ", "properties": {"ref": "ЮЗАО", "name": "Юго-Западный административный округ", "name:be": "Паўднёва-заходняя адміністрацыйная акруга", "name:de": "Südwestlicher Verwaltungsbezirk", "name:en": "South-Western Administrative Okrug", "name:ru": "Юго-Западный административный округ", "website": "http://www.uzao.mos.ru/", "boundary": "administrative", "wikipedia": "ru:Юго-Западный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.6183837, 55.6845037], [37.616996300000004, 55.6847717], [37.61519860000001, 55.6847313], [37.6142067, 55.684587699999994], [37.613156100000005, 55.6843777], [37.612596100000005, 55.6842769], [37.6120809, 55.6841842], [37.6113806, 55.6840735], [37.6106538, 55.6839671], [37.609910600000006, 55.683881199999995], [37.6093449, 55.68386649999999], [37.6090242, 55.6838718], [37.6086084, 55.683886699999995], [37.60812070000001, 55.683945200000004], [37.607615900000006, 55.6840609], [37.607168, 55.684196], [37.606749, 55.6843561], [37.6064314, 55.6845105], [37.6060048, 55.684750300000005], [37.60571300000001, 55.6849572], [37.60547630000001, 55.685186900000005], [37.6052717, 55.6854176], [37.60502280000001, 55.6857954], [37.6049491, 55.6860546], [37.6049148, 55.6863256], [37.604931900000004, 55.6866554], [37.604983399999995, 55.6869795], [37.605085, 55.6873154], [37.605216600000006, 55.6877218], [37.60529030000001, 55.688074300000004], [37.605285300000006, 55.6884461], [37.6052442, 55.688807], [37.60517420000001, 55.6890097], [37.60510120000001, 55.689150100000006], [37.6047416, 55.689564399999995], [37.6044927, 55.6897973], [37.604015000000004, 55.6900694], [37.60351320000001, 55.69034680000001], [37.60373810000001, 55.69052490000001], [37.6037863, 55.6906298], [37.603272000000004, 55.69085530000001], [37.602605600000004, 55.6912174], [37.601975700000004, 55.69153670000001], [37.6016161, 55.6915807], [37.601308, 55.691781], [37.600685, 55.692202400000006], [37.600070900000006, 55.69270810000001], [37.5996, 55.693104100000006], [37.59922230000001, 55.693454800000005], [37.59896260000001, 55.693665700000004], [37.5980616, 55.6943974], [37.597557200000004, 55.694848], [37.59710230000001, 55.69523500000001], [37.59673320000001, 55.69557360000001], [37.59625260000001, 55.69607190000001], [37.5956174, 55.69677810000001], [37.594905000000004, 55.697614900000005], [37.59397810000001, 55.698698400000005], [37.59295670000001, 55.699873800000006], [37.5909671, 55.70219330000001], [37.58984099999999, 55.703506000000004], [37.5893432, 55.704081599999995], [37.5890212, 55.7044431], [37.58845590000001, 55.705077800000005], [37.5880849, 55.705490000000005], [37.587819999999994, 55.7057835], [37.5875028, 55.70611410000001], [37.58731290000001, 55.7063416], [37.5874732, 55.7064275], [37.587697299999995, 55.70655620000001], [37.588709, 55.7071405], [37.5853646, 55.7088144], [37.58422699999999, 55.70951360000001], [37.5834012, 55.710042300000005], [37.582139600000005, 55.7109925], [37.5816353, 55.711348], [37.5794176, 55.71295560000001], [37.5776083, 55.7142058], [37.574928, 55.713117700000005], [37.569610100000006, 55.7116173], [37.565400600000004, 55.7107574], [37.5609954, 55.710337800000005], [37.5592321, 55.7102802], [37.55702469999999, 55.70861480000001], [37.55414939999999, 55.70653060000001], [37.546313000000005, 55.700746300000006], [37.536571200000004, 55.69356320000001], [37.535747300000004, 55.69309880000001], [37.530053300000006, 55.689929], [37.51166239999999, 55.679730600000006], [37.5121291, 55.679442800000004], [37.514263699999994, 55.678286], [37.5188513, 55.676134100000006], [37.5236985, 55.673846999999995], [37.524002700000004, 55.67372030000001], [37.52413820000001, 55.6736653], [37.520093700000004, 55.670884599999994], [37.5089576, 55.663380800000006], [37.506542800000005, 55.6617784], [37.501653399999995, 55.6585246], [37.4956144, 55.6556312], [37.4826333, 55.649537], [37.4824662, 55.649460499999996], [37.4782007, 55.6475145], [37.4637211, 55.6407043], [37.455718700000006, 55.6370488], [37.4560027, 55.636875], [37.4562889, 55.63699530000001], [37.45659439999999, 55.637125100000006], [37.456882799999995, 55.6372406], [37.45700759999999, 55.6372686], [37.457111499999996, 55.6372918], [37.457323599999995, 55.6373377], [37.457521199999995, 55.6373642], [37.45778119999999, 55.6373824], [37.4579587, 55.637385], [37.458152500000004, 55.637376200000006], [37.4584737, 55.6373417], [37.4588143, 55.6373061], [37.4591305, 55.6372796], [37.4594533, 55.6372449], [37.45983139999999, 55.6372088], [37.4602096, 55.63717280000001], [37.4604068, 55.637143300000005], [37.4606117, 55.637094], [37.460782300000005, 55.6370638], [37.461896599999996, 55.63611540000001], [37.46203630000001, 55.63612230000001], [37.46210280000001, 55.63595280000001], [37.4620887, 55.63595190000001], [37.463872200000004, 55.6344335], [37.463774, 55.634352400000004], [37.463765200000005, 55.63434230000001], [37.4637679, 55.63433070000001], [37.464482499999995, 55.633695800000005], [37.464666599999994, 55.633757], [37.465973700000006, 55.63313900000001], [37.466833, 55.63236570000001], [37.4674921, 55.6313616], [37.469392400000004, 55.629715300000015], [37.473729, 55.62599920000001], [37.4776022, 55.6226745], [37.481533, 55.619308100000005], [37.4854513, 55.6161843], [37.48620699999999, 55.6155944], [37.487522, 55.61448169999999], [37.48769359999999, 55.614354399999996], [37.4888953, 55.613275900000005], [37.4888054, 55.613030300000005], [37.488887899999995, 55.612884099999995], [37.488972600000004, 55.6127042], [37.4890191, 55.6124443], [37.489039999999996, 55.612242], [37.4890492, 55.612065300000005], [37.489052900000004, 55.61189439999999], [37.489060099999996, 55.6117667], [37.489069699999995, 55.61172439999999], [37.489062999999994, 55.61170739999999], [37.489066199999996, 55.61148149999999], [37.489022999999996, 55.6113146], [37.4890793, 55.611216399999996], [37.4891568, 55.610718500000004], [37.488875, 55.6100771], [37.4888279, 55.6099819], [37.488775200000006, 55.6098379], [37.4886365, 55.609614], [37.488512500000006, 55.609384], [37.488430300000005, 55.6092648], [37.488398700000005, 55.609219700000004], [37.4883961, 55.609216], [37.4883074, 55.609089499999996], [37.4881406, 55.6088536], [37.4880311, 55.6086858], [37.48784199999999, 55.608390400000005], [37.488333100000006, 55.608273000000004], [37.4887893, 55.608164], [37.4890365, 55.608591800000006], [37.4891684, 55.60876820000001], [37.4893115, 55.60894890000001], [37.489405, 55.60910380000001], [37.489495399999996, 55.60925030000001], [37.489634099999996, 55.60937800000001], [37.4897449, 55.60947590000001], [37.4897741, 55.609500800000006], [37.48984539999999, 55.609611], [37.4899498, 55.609675800000005], [37.4899682, 55.609661599999995], [37.490212400000004, 55.6098469], [37.490445300000005, 55.6099616], [37.4906984, 55.6100624], [37.4909461, 55.6101744], [37.491179, 55.610100300000006], [37.49133500000001, 55.6100001], [37.4913611, 55.609978000000005], [37.4913686, 55.6099821], [37.49151330000001, 55.60992890000001], [37.4917073, 55.6097679], [37.491919800000005, 55.609584399999996], [37.49218820000001, 55.609351100000005], [37.49239830000001, 55.60911500000001], [37.49251960000001, 55.60899580000001], [37.49262530000001, 55.608893300000005], [37.49274690000001, 55.608771600000004], [37.49292520000001, 55.6086866], [37.493098100000005, 55.608631800000005], [37.493361300000004, 55.6086212], [37.493706, 55.6086255], [37.4940943, 55.608574600000004], [37.494097499999995, 55.60857360000001], [37.497522700000005, 55.6056014], [37.4982498, 55.604971], [37.501483099999994, 55.602206100000004], [37.5015361, 55.60216090000001], [37.5021825, 55.6016081], [37.502520700000005, 55.601348300000005], [37.50346699999999, 55.600621499999995], [37.50655270000001, 55.5982494], [37.50871530000001, 55.59717270000001], [37.5111936, 55.59593790000001], [37.5115487, 55.59576090000001], [37.51187939999999, 55.59559610000001], [37.5180898, 55.5936478], [37.5262872, 55.5916203], [37.5262906, 55.591619200000004], [37.52630530000001, 55.5916072], [37.52648, 55.5914813], [37.5265776, 55.5914002], [37.5266986, 55.5912998], [37.52685880000001, 55.5911601], [37.526885, 55.591139000000005], [37.527011800000004, 55.5909946], [37.527359800000006, 55.590466], [37.52741290000001, 55.590362000000006], [37.5274736, 55.59019370000001], [37.5274787, 55.59003250000001], [37.527417, 55.58986699999999], [37.5272405, 55.589663099999996], [37.52771380000001, 55.5895463], [37.5278016, 55.5895866], [37.5279049, 55.5896069], [37.52813770000001, 55.5895696], [37.52837880000001, 55.589508800000004], [37.528802400000004, 55.58947], [37.529079100000004, 55.5895265], [37.5292541, 55.589608], [37.52933520000001, 55.5896791], [37.529822200000005, 55.59030220000001], [37.5300407, 55.59053490000001], [37.53015690000001, 55.5906626], [37.5302736, 55.5906944], [37.5304243, 55.590695800000006], [37.53871790000001, 55.5887076], [37.5472703, 55.586662999999994], [37.5471978, 55.5866009], [37.5470557, 55.58648109999999], [37.5458313, 55.585694499999995], [37.545675800000005, 55.5855826], [37.54575210000001, 55.585531], [37.545773000000004, 55.585498900000005], [37.545765700000004, 55.5854396], [37.5457646, 55.5854285], [37.5457645, 55.5854233], [37.5457645, 55.585418100000005], [37.5457616, 55.5854077], [37.545754900000006, 55.5853946], [37.54571990000001, 55.5853547], [37.545686399999994, 55.58533020000001], [37.5456455, 55.585302600000006], [37.54561520000001, 55.585283499999996], [37.5455873, 55.5852662], [37.5455604, 55.5852472], [37.545539600000005, 55.5852282], [37.5455267, 55.5852146], [37.5455045, 55.5851946], [37.5454785, 55.585162700000005], [37.5454513, 55.5851274], [37.545436900000006, 55.5851047], [37.545433100000004, 55.585089399999994], [37.545430800000005, 55.5850791], [37.5454304, 55.585075700000004], [37.5454306, 55.585063], [37.54543530000001, 55.58505220000001], [37.545441399999994, 55.585042900000005], [37.5454466, 55.5850385], [37.5454575, 55.585031300000004], [37.545466499999996, 55.5850249], [37.54551670000001, 55.5850176], [37.54553690000001, 55.585014], [37.54553690000001, 55.585005900000006], [37.545524300000004, 55.5850049], [37.54551480000001, 55.5850031], [37.5454966, 55.5849998], [37.5454798, 55.584996], [37.54545890000001, 55.5849923], [37.545441499999995, 55.584984199999994], [37.5454271, 55.5849761], [37.5454207, 55.5849652], [37.5454144, 55.5849516], [37.545419100000004, 55.5849398], [37.5454254, 55.5849365], [37.545435100000006, 55.584921599999994], [37.5454457, 55.5849082], [37.545462300000004, 55.5848952], [37.545781399999996, 55.58484429999999], [37.5458237, 55.58484409999999], [37.545880399999994, 55.58484059999999], [37.545916000000005, 55.58482539999999], [37.5459485, 55.5847902], [37.545969, 55.5847347], [37.546013800000004, 55.58469159999999], [37.546082, 55.58464709999999], [37.5461145, 55.5846185], [37.546143900000004, 55.584584799999995], [37.5461651, 55.5845201], [37.546216900000005, 55.5843427], [37.546235800000005, 55.584260199999996], [37.5462422, 55.584207899999996], [37.5462361, 55.5841289], [37.5462508, 55.58411220000001], [37.5463097, 55.58409639999999], [37.5464525, 55.584080199999995], [37.546644799999996, 55.584056], [37.546829699999996, 55.5840171], [37.546986399999994, 55.5839672], [37.5471218, 55.583930800000005], [37.5472791, 55.583894799999996], [37.5473603, 55.5838511], [37.547413399999996, 55.5838088], [37.54746169999999, 55.5837852], [37.5475239, 55.583771399999996], [37.5475737, 55.5837573], [37.5476198, 55.5837401], [37.547641299999995, 55.583702900000006], [37.5476627, 55.58364439999999], [37.54768399999999, 55.5836141], [37.5478263, 55.5835072], [37.547993399999996, 55.5833942], [37.54807890000001, 55.583351900000004], [37.548182100000005, 55.5833095], [37.5482426, 55.5832733], [37.54829590000001, 55.583245], [37.54834230000001, 55.5832288], [37.548399200000006, 55.5832147], [37.5484669, 55.5832167], [37.54853810000001, 55.5832287], [37.548602200000005, 55.5832408], [37.548709800000005, 55.583248999999995], [37.548728600000004, 55.5832059], [37.54873490000001, 55.583187499999994], [37.54875620000001, 55.58317520000001], [37.5487635, 55.583165900000004], [37.5487675, 55.583151900000004], [37.5487666, 55.583118000000006], [37.548760900000005, 55.583081099999994], [37.548767, 55.583060999999994], [37.548784399999995, 55.5830392], [37.5488008, 55.58302449999999], [37.5488394, 55.5829973], [37.5488756, 55.5829745], [37.548898, 55.5829631], [37.548942100000005, 55.5829437], [37.548959700000005, 55.582938000000006], [37.5489694, 55.5829378], [37.5489854, 55.5829432], [37.5490034, 55.5829594], [37.5490134, 55.582972600000005], [37.5490402, 55.5829817], [37.5490564, 55.5829856], [37.5490852, 55.5829884], [37.5490982, 55.5829877], [37.5491213, 55.5829828], [37.549141399999996, 55.5829742], [37.5491754, 55.5829504], [37.549208300000004, 55.5829212], [37.5492273, 55.582902000000004], [37.5492562, 55.582866599999996], [37.549269599999995, 55.582844699999995], [37.5492748, 55.5828318], [37.5492793, 55.5828078], [37.549278, 55.5827839], [37.5492748, 55.582772600000006], [37.5492659, 55.582758000000005], [37.549252100000004, 55.5827467], [37.549233300000004, 55.582733700000006], [37.5492273, 55.582726300000004], [37.5492249, 55.582714], [37.549229, 55.5826892], [37.549235, 55.5826781], [37.5492549, 55.582660399999995], [37.549282999999996, 55.582646499999996], [37.5493264, 55.582629499999996], [37.549348300000005, 55.582619900000005], [37.5493887, 55.5825964], [37.549406999999995, 55.5825811], [37.549432200000005, 55.582555500000005], [37.5494651, 55.582508600000004], [37.549492300000004, 55.5824524], [37.549506900000004, 55.58241290000001], [37.549525, 55.58234], [37.5495278, 55.58230220000001], [37.5495261, 55.582286999999994], [37.549519800000006, 55.5822685], [37.549514800000004, 55.5822613], [37.5495012, 55.582250200000004], [37.5494926, 55.5822465], [37.5494726, 55.5822419], [37.549451, 55.5822406], [37.5494118, 55.5822441], [37.549392600000004, 55.582249], [37.54937090000001, 55.5822622], [37.549330100000006, 55.582291], [37.5492911, 55.5823204], [37.5492737, 55.58233590000001], [37.549240999999995, 55.5823774], [37.549202300000005, 55.5824194], [37.549161, 55.5824624], [37.5491276, 55.5824981], [37.549117100000004, 55.582508700000005], [37.549109800000004, 55.58251310000001], [37.5490943, 55.5825175], [37.5490712, 55.582517800000005], [37.549055700000004, 55.58251590000001], [37.5490292, 55.582509], [37.549016200000004, 55.582503300000006], [37.5490005, 55.582489499999994], [37.548996900000006, 55.582481699999995], [37.5489966, 55.5824649], [37.5490031, 55.582447599999995], [37.5490252, 55.58241520000001], [37.5490478, 55.5823881], [37.5490881, 55.5823468], [37.549148800000005, 55.5822926], [37.5491895, 55.5822621], [37.549254499999996, 55.5822231], [37.5492911, 55.5822054], [37.549350600000004, 55.5821825], [37.5494736, 55.5821454], [37.5495079, 55.582129900000005], [37.549522700000004, 55.5821206], [37.54953530000001, 55.58211000000001], [37.5495554, 55.5820858], [37.549570100000004, 55.5820601], [37.5495904, 55.5820068], [37.549606, 55.58196409999999], [37.5496092, 55.58194459999999], [37.5496068, 55.5819243], [37.5496031, 55.5819135], [37.5495811, 55.581877199999994], [37.5495431, 55.581824899999994], [37.549528, 55.5817993], [37.5495174, 55.5817639], [37.5495176, 55.581742], [37.549520300000005, 55.5817281], [37.549530100000005, 55.581701499999994], [37.549575100000006, 55.581624299999994], [37.5495832, 55.58160439999999], [37.5495924, 55.5815649], [37.549615100000004, 55.581486899999994], [37.5496313, 55.5814363], [37.5496452, 55.5814151], [37.5496663, 55.58139739999999], [37.549721, 55.5813679], [37.5497767, 55.581340499999996], [37.5498038, 55.5813306], [37.5498299, 55.5813248], [37.5498602, 55.5813191], [37.5498718, 55.581315000000004], [37.54988459999999, 55.5813057], [37.5499001, 55.5812923], [37.54991210000001, 55.58128779999999], [37.549925300000005, 55.58128539999999], [37.5499492, 55.5812823], [37.5499624, 55.581278999999995], [37.5499825, 55.58126949999999], [37.54999230000001, 55.581261999999995], [37.55002139999999, 55.58122739999999], [37.5500629, 55.5811612], [37.55008779999999, 55.5811238], [37.5501306, 55.58106779999999], [37.5501863, 55.5810023], [37.55020699999999, 55.5809773], [37.5502239, 55.5809524], [37.5502268, 55.5809422], [37.5502043, 55.5809226], [37.5502192, 55.580929499999996], [37.550204799999996, 55.5809166], [37.55020139999999, 55.580906999999996], [37.55020439999999, 55.580893599999996], [37.5502093, 55.5808852], [37.550226499999994, 55.580864899999995], [37.55026049999999, 55.580834599999996], [37.550280199999996, 55.5808201], [37.5503249, 55.5807941], [37.5503385, 55.5807891], [37.550363399999995, 55.5807823], [37.5504049, 55.5807772], [37.5504227, 55.580772700000004], [37.5504391, 55.580764099999996], [37.5504343, 55.580733], [37.550461299999995, 55.580738200000006], [37.550463699999995, 55.580724], [37.5504621, 55.5807173], [37.5504584, 55.5807111], [37.550446699999995, 55.5806999], [37.5504222, 55.5806797], [37.550418900000004, 55.580669099999994], [37.550425399999995, 55.5806593], [37.5504325, 55.5806547], [37.5504483, 55.5806489], [37.5504708, 55.5806452], [37.55048459999999, 55.58064439999999], [37.5505177, 55.5806456], [37.550537, 55.580647799999994], [37.5505699, 55.5806533], [37.5505807, 55.5806567], [37.550602399999995, 55.58066039999999], [37.55062349999999, 55.5806602], [37.5506373, 55.580658], [37.55066479999999, 55.580649699999995], [37.550685099999995, 55.5806403], [37.5507043, 55.5806003], [37.5508332, 55.5804999], [37.550868699999995, 55.580476], [37.5509419, 55.580433], [37.551014599999995, 55.5803966], [37.5511392, 55.580341399999995], [37.5511832, 55.5803213], [37.551028599999995, 55.580279399999995], [37.5479348, 55.578997], [37.5457465, 55.57835730000001], [37.5442561, 55.57851550000001], [37.542937800000004, 55.578436200000006], [37.542478300000006, 55.5785204], [37.5419061, 55.578553500000005], [37.5409175, 55.5788372], [37.540792200000006, 55.5790545], [37.5410749, 55.5791878], [37.541027899999996, 55.5792324], [37.54051520000001, 55.5793042], [37.53879260000001, 55.579540900000005], [37.538655000000006, 55.579559800000006], [37.5368507, 55.57728899999999], [37.539297499999996, 55.5767215], [37.53930090000001, 55.576720300000005], [37.538729100000005, 55.5759206], [37.539948100000004, 55.5760443], [37.5399515, 55.5760432], [37.5395076, 55.57440149999999], [37.539546200000004, 55.57332590000001], [37.539546800000004, 55.573263], [37.5379704, 55.5731965], [37.53768939999999, 55.5731846], [37.53691560000001, 55.57315200000001], [37.536888, 55.5730962], [37.5372403, 55.5723867], [37.53805800000001, 55.57229830000001], [37.53890870000001, 55.5722064], [37.53891220000001, 55.5722054], [37.540324399999996, 55.5716706], [37.5406908, 55.5711273], [37.54368349999999, 55.57075270000001], [37.543686799999996, 55.5707516], [37.5445136, 55.57022], [37.5461206, 55.56993890000001], [37.5469531, 55.5704487], [37.5475043, 55.5704006], [37.5475078, 55.5703996], [37.5488828, 55.569937900000006], [37.54788959999999, 55.56892330000001], [37.5501395, 55.56831650000001], [37.553498999999995, 55.567624499999994], [37.5537716, 55.5660436], [37.5534532, 55.5649232], [37.553162, 55.5640597], [37.552511300000006, 55.563652100000006], [37.5517397, 55.56351830000001], [37.5505919, 55.5636035], [37.55049399999999, 55.56331560000001], [37.550358700000004, 55.56292870000001], [37.5520167, 55.561845999999996], [37.55480349999999, 55.5614779], [37.55446659999999, 55.5602646], [37.5541992, 55.5593015], [37.5529687, 55.556226499999994], [37.5523735, 55.55522], [37.552147399999996, 55.55486899999999], [37.55188089999999, 55.554788599999995], [37.55140719999999, 55.5546429], [37.5495264, 55.55414739999999], [37.5494658, 55.554131399999996], [37.549067599999994, 55.5531996], [37.5488225, 55.5526259], [37.544878, 55.55202], [37.5365076, 55.5536721], [37.529188100000006, 55.5552455], [37.52857900000001, 55.55486469999999], [37.52535250000001, 55.553438], [37.523307100000004, 55.5525497], [37.5216115, 55.5518187], [37.52137260000001, 55.5517156], [37.5202693, 55.55123999999999], [37.5181868, 55.5503233], [37.517978, 55.5502155], [37.514496099999995, 55.548505000000006], [37.511115000000004, 55.544985999999994], [37.507767599999994, 55.5429454], [37.507505, 55.5428807], [37.500665, 55.5413068], [37.494799900000004, 55.539977300000004], [37.4936293, 55.539687199999996], [37.493449399999996, 55.5396458], [37.4910287, 55.539433], [37.488767499999994, 55.5396281], [37.488677599999995, 55.539675200000005], [37.48786549999999, 55.5397681], [37.48780059999999, 55.5398365], [37.487739999999995, 55.5398689], [37.4877559, 55.5399736], [37.48774349999999, 55.5399745], [37.4877481, 55.540086699999996], [37.48748039999999, 55.540092], [37.48746729999999, 55.5399085], [37.486175100000004, 55.539793], [37.485735000000005, 55.5396913], [37.4851037, 55.5395247], [37.4841155, 55.5392638], [37.482198600000004, 55.538811800000005], [37.482150600000004, 55.5388472], [37.4776169, 55.5377852], [37.4776149, 55.5377867], [37.476310600000005, 55.537481199999995], [37.47631200000001, 55.537479499999996], [37.476294499999995, 55.5374754], [37.476193300000006, 55.5374537], [37.475516500000005, 55.5372951], [37.475709, 55.5353874], [37.475712400000006, 55.5353885], [37.475753000000005, 55.5349964], [37.4757624, 55.5347785], [37.475165000000004, 55.534114900000006], [37.4749516, 55.5334932], [37.47503390000001, 55.532905400000004], [37.475157700000004, 55.5326672], [37.475351100000005, 55.53238270000001], [37.4759296, 55.5318567], [37.4759686, 55.53113260000001], [37.4759918, 55.530899399999996], [37.4761043, 55.529768700000005], [37.4761216, 55.5295964], [37.4761012, 55.529029900000005], [37.476162, 55.527865399999996], [37.4762491, 55.5266243], [37.4762798, 55.52656030000001], [37.47633570000001, 55.52653480000001], [37.476359, 55.52650010000001], [37.4763536, 55.526442], [37.476378800000006, 55.5264205], [37.4764798, 55.52639920000001], [37.47655230000001, 55.52639920000001], [37.476612, 55.526422600000004], [37.4766607, 55.526434], [37.4767068, 55.5264304], [37.4767803, 55.526417], [37.4768403, 55.526400800000005], [37.4768738, 55.526383900000006], [37.4769175, 55.5263471], [37.47706149999999, 55.526282200000004], [37.4771636, 55.52624], [37.4772689, 55.52621590000001], [37.4773365, 55.526174700000006], [37.477388999999995, 55.52615630000001], [37.477494799999995, 55.526143600000005], [37.477612, 55.52614220000001], [37.477690499999994, 55.52615220000001], [37.4777546, 55.52615210000001], [37.477822599999996, 55.526139500000006], [37.4778725, 55.52613040000001], [37.477921099999996, 55.526126100000006], [37.478030000000004, 55.52615360000001], [37.47817020000001, 55.52616210000001], [37.47821020000001, 55.526169], [37.478242900000005, 55.5261806], [37.478253300000006, 55.52619560000001], [37.4782485, 55.52621070000001], [37.478228300000005, 55.52623830000001], [37.4782234, 55.526260900000004], [37.4782402, 55.5262856], [37.4782803, 55.526314000000006], [37.4783479, 55.526348000000006], [37.478387, 55.5263715], [37.478415500000004, 55.5264091], [37.4784555, 55.5264247], [37.478508000000005, 55.5264404], [37.4785405, 55.5264574], [37.47857570000001, 55.52649290000001], [37.4786081, 55.52650570000001], [37.478650900000005, 55.526507300000006], [37.4788043, 55.52650680000001], [37.4789075, 55.52651670000001], [37.478945200000005, 55.52651360000001], [37.4790113, 55.5264943], [37.4791013, 55.52645890000001], [37.479144, 55.5264248], [37.479164, 55.526397900000006], [37.4791764, 55.526359500000005], [37.479194, 55.52634530000001], [37.479266499999994, 55.52632690000001], [37.4793516, 55.52631250000001], [37.4794369, 55.5263015], [37.4795296, 55.52629], [37.4795821, 55.526283], [37.479689799999996, 55.526251800000004], [37.479734900000004, 55.5262418], [37.4797999, 55.5262376], [37.4798951, 55.5262377], [37.4799652, 55.5262334], [37.48004039999999, 55.526222100000005], [37.4801361, 55.5262061], [37.480173, 55.526205000000004], [37.480201799999996, 55.5262079], [37.4802381, 55.52621920000001], [37.48027149999999, 55.5262315], [37.4803012, 55.5262413], [37.4803482, 55.5262476], [37.480415900000004, 55.5262448], [37.4804759, 55.526256200000006], [37.4805335, 55.52627890000001], [37.480603599999995, 55.526303000000006], [37.4806536, 55.52633000000001], [37.4807011, 55.52636830000001], [37.4807462, 55.52641380000001], [37.480801299999996, 55.52645210000001], [37.480976399999996, 55.526514600000006], [37.4810558, 55.52653610000001], [37.481124599999994, 55.52653920000001], [37.481184299999995, 55.5265472], [37.481239499999994, 55.5265685], [37.4812922, 55.52659380000001], [37.481399499999995, 55.526619600000004], [37.4814721, 55.5266424], [37.4815722, 55.526686399999996], [37.481674999999996, 55.5267418], [37.48176759999999, 55.5268042], [37.481850099999996, 55.526875200000006], [37.48188259999999, 55.526905000000006], [37.4819326, 55.526943200000005], [37.4819903, 55.526973100000006], [37.4820355, 55.526988700000004], [37.482087899999996, 55.526994300000005], [37.482163, 55.526993000000004], [37.4822532, 55.526988800000005], [37.48237280000001, 55.526974800000005], [37.4824166, 55.526971200000006], [37.482455800000004, 55.526974900000006], [37.482521399999996, 55.5269898], [37.482606499999996, 55.52701830000001], [37.482798900000006, 55.5270938], [37.4828993, 55.527137200000006], [37.482939300000005, 55.52715890000001], [37.4829647, 55.5271865], [37.4829693, 55.527219], [37.4829672, 55.5272518], [37.482952600000004, 55.527284699999996], [37.482933200000005, 55.52731230000001], [37.4828927, 55.5273477], [37.482820499999995, 55.5274592], [37.4828052, 55.52750880000001], [37.482798700000004, 55.52755830000001], [37.4827986, 55.5276178], [37.4828051, 55.5276809], [37.4827942, 55.5277714], [37.482796300000004, 55.5278148], [37.4828291, 55.5279448], [37.482876999999995, 55.52803510000001], [37.4829098, 55.52807850000001], [37.4829906, 55.52813060000001], [37.4831068, 55.52821510000001], [37.4831618, 55.52826290000001], [37.4831655, 55.52827370000001], [37.4831625, 55.5282836], [37.483108200000004, 55.52832680000001], [37.483097599999994, 55.52834490000001], [37.4830953, 55.52839070000001], [37.4830933, 55.52843030000001], [37.483097599999994, 55.52852820000001], [37.48311530000001, 55.5286047], [37.483143399999996, 55.528627300000004], [37.4832089, 55.52863970000001], [37.4833072, 55.528640800000005], [37.483388, 55.528640900000006], [37.483429799999996, 55.5286496], [37.4834953, 55.5286806], [37.483659599999996, 55.52872180000001], [37.483787799999995, 55.52876220000001], [37.48389639999999, 55.52879420000001], [37.4839909, 55.5288296], [37.4840793, 55.5288684], [37.4841578, 55.5289094], [37.484234099999995, 55.52894020000001], [37.484375, 55.52899500000001], [37.484521699999995, 55.5290418], [37.484638399999994, 55.529065800000005], [37.48486759999999, 55.529140000000005], [37.48495, 55.5291696], [37.4849943, 55.529194700000005], [37.48510890000001, 55.52927230000001], [37.4851511, 55.52931560000001], [37.4852195, 55.5294217], [37.485267699999994, 55.5294891], [37.48530590000001, 55.529529000000004], [37.485356100000004, 55.529565500000004], [37.4854807, 55.5296237], [37.485551300000004, 55.5296431], [37.485672, 55.5296637], [37.4857866, 55.5296773], [37.4859433, 55.52970020000001], [37.4863233, 55.529769800000004], [37.4864341, 55.529785800000006], [37.4865265, 55.529794900000006], [37.486602999999995, 55.5298007], [37.4866653, 55.5298007], [37.4867639, 55.5297904], [37.4868323, 55.529779000000005], [37.4869026, 55.529759600000006], [37.486962999999996, 55.52973570000001], [37.4870253, 55.52970260000001], [37.487179399999995, 55.529596000000005], [37.487218999999996, 55.5295843], [37.48726639999999, 55.529587], [37.4873187, 55.52959230000001], [37.4873793, 55.5296011], [37.4874357, 55.52961830000001], [37.48748809999999, 55.529631300000005], [37.487562399999995, 55.5296434], [37.48762669999999, 55.529644499999996], [37.48768899999999, 55.52963990000001], [37.48779149999999, 55.5296217], [37.4878521, 55.5296046], [37.487892099999996, 55.5295875], [37.4879386, 55.52955330000001], [37.4880331, 55.529494], [37.488075200000004, 55.5294735], [37.4881296, 55.529459700000004], [37.4881838, 55.52945520000001], [37.488232100000005, 55.5294575], [37.4883045, 55.52947], [37.4883849, 55.529489399999996], [37.4886302, 55.52957270000001], [37.488710700000006, 55.529608100000004], [37.4887449, 55.52963200000001], [37.488759, 55.529652600000006], [37.4887649, 55.5296811], [37.488780999999996, 55.52971880000001], [37.4888393, 55.5297678], [37.48895, 55.5298454], [37.489040499999994, 55.5299046], [37.4891571, 55.5299606], [37.489219399999996, 55.5299834], [37.489277699999995, 55.529993700000006], [37.4893642, 55.5299971], [37.4894306, 55.5299904], [37.489478999999996, 55.529979100000006], [37.4894998, 55.529959500000004], [37.489484299999994, 55.52993320000001], [37.48946169999999, 55.52991170000001], [37.4894181, 55.5298851], [37.4893838, 55.529856200000005], [37.4893778, 55.5298247], [37.4893851, 55.5297841], [37.489363, 55.529695800000006], [37.48936739999999, 55.52967280000001], [37.4893942, 55.5296491], [37.4895575, 55.5295794], [37.4895919, 55.52957180000001], [37.4896354, 55.52957430000001], [37.48967139999999, 55.52959820000001], [37.4897201, 55.529627], [37.489747699999995, 55.52963290000001], [37.489825599999996, 55.529625300000006], [37.489909499999996, 55.529603200000004], [37.48998439999999, 55.52955910000001], [37.4900803, 55.5294785], [37.49017620000001, 55.529425], [37.490230100000005, 55.52938], [37.4902945, 55.52933080000001], [37.490330400000005, 55.52931980000001], [37.490430700000005, 55.52931050000001], [37.490484599999995, 55.52931550000001], [37.49052210000001, 55.529329100000005], [37.490585, 55.52933420000001], [37.490688399999996, 55.529322400000005], [37.490730400000004, 55.52931300000001], [37.49075130000001, 55.52930290000001], [37.490760300000005, 55.529290100000004], [37.490746900000005, 55.52925690000001], [37.490743900000005, 55.529239200000006], [37.490757300000006, 55.5292204], [37.4907917, 55.529200900000006], [37.4908562, 55.52917890000001], [37.4909416, 55.529166200000006], [37.4910793, 55.52915600000001], [37.49112290000001, 55.52914330000001], [37.4912171, 55.529099], [37.4912756, 55.529071900000005], [37.4913296, 55.529060900000005], [37.4914613, 55.529047399999996], [37.491669599999994, 55.52901590000001], [37.49171890000001, 55.529004900000004], [37.4917548, 55.528994700000005], [37.491778800000006, 55.52899210000001], [37.491798300000006, 55.528999000000006], [37.4919481, 55.52909230000001], [37.4920004, 55.52911700000001], [37.492029, 55.529125500000006], [37.49215170000001, 55.52915180000001], [37.4922295, 55.52916200000001], [37.4922671, 55.529159500000006], [37.4922971, 55.52915180000001], [37.49231660000001, 55.52913730000001], [37.49231650000001, 55.529114400000005], [37.492295600000006, 55.529061], [37.492298500000004, 55.52901260000001], [37.492327, 55.52896330000001], [37.492344900000006, 55.52894980000001], [37.492382400000004, 55.52893780000001], [37.4924978, 55.528917500000006], [37.492547200000004, 55.52890480000001], [37.49256820000001, 55.52889210000001], [37.49257570000001, 55.528865700000004], [37.49257290000001, 55.52883990000001], [37.4925246, 55.5288004], [37.49250680000001, 55.52878330000001], [37.49250980000001, 55.5287647], [37.49256520000001, 55.52871630000001], [37.49261310000001, 55.5286892], [37.492650600000005, 55.52867890000001], [37.492694, 55.52867560000001], [37.49278830000001, 55.5286849], [37.492896200000004, 55.5286917], [37.49294870000001, 55.5286892], [37.49299190000001, 55.5286747], [37.4930114, 55.52865520000001], [37.4930266, 55.52859490000001], [37.493043, 55.52857630000001], [37.4930685, 55.528564300000006], [37.49309230000001, 55.528561], [37.49312230000001, 55.5285644], [37.49317330000001, 55.52858560000001], [37.493317100000006, 55.528653500000004], [37.49335010000001, 55.5286637], [37.493419, 55.5286646], [37.49350870000001, 55.528653500000004], [37.493556600000005, 55.5286374], [37.4936391, 55.528564300000006], [37.493691399999996, 55.52853130000001], [37.4937273, 55.52851770000001], [37.4938711, 55.5284795], [37.4939671, 55.52846], [37.494018000000004, 55.5284414], [37.494050900000005, 55.52841080000001], [37.494046499999996, 55.52838870000001], [37.4940344, 55.52837840000001], [37.4939881, 55.52835720000001], [37.493953700000006, 55.52833940000001], [37.4939071, 55.528294800000005], [37.4938938, 55.528272400000006], [37.4938967, 55.5282436], [37.4939297, 55.528216400000005], [37.4939942, 55.52817730000001], [37.494023999999996, 55.52814330000001], [37.4940585, 55.528118700000014], [37.4940916, 55.52810680000001], [37.494118400000005, 55.52810520000001], [37.494144, 55.52810860000001], [37.4941635, 55.528120400000006], [37.4942024, 55.52815950000001], [37.494227599999995, 55.528169600000005], [37.4942773, 55.528171400000005], [37.494328100000004, 55.52816030000001], [37.494379, 55.52813730000001], [37.494403, 55.52811100000001], [37.4944284, 55.52805590000001], [37.4944554, 55.5280245], [37.49457830000001, 55.527935400000004], [37.4946067, 55.5279116], [37.4946202, 55.5278921], [37.494621699999996, 55.5278691], [37.4946067, 55.527849599999996], [37.4945842, 55.5278326], [37.494557300000004, 55.5278165], [37.4945438, 55.5277995], [37.494551300000005, 55.5277655], [37.4945619, 55.527734200000005], [37.494599300000004, 55.5276917], [37.4947071, 55.5276085], [37.494746, 55.52757290000001], [37.494779, 55.5275449], [37.494803, 55.52753210000001], [37.494831399999995, 55.527528700000005], [37.494852300000005, 55.52753390000001], [37.4948689, 55.52755330000001], [37.4948899, 55.52757630000001], [37.4949318, 55.52759580000001], [37.495000600000004, 55.5276068], [37.4950696, 55.5276034], [37.49513990000001, 55.5275848], [37.49533160000001, 55.52751690000001], [37.4953841, 55.5275024], [37.495426, 55.527497399999994], [37.495512900000016, 55.527498200000004], [37.495628200000006, 55.527498200000004], [37.495721, 55.5274812], [37.495776500000005, 55.5274633], [37.4958678, 55.527415000000005], [37.49596520000001, 55.527384399999995], [37.4960206, 55.5273776], [37.4960835, 55.5273836], [37.4961644, 55.5273971], [37.496219800000006, 55.527399700000004], [37.49627230000001, 55.5273896], [37.496360700000004, 55.527350500000004], [37.4966452, 55.5272241], [37.496703600000004, 55.5272062], [37.496759100000006, 55.5271994], [37.4968205, 55.5272079], [37.496962700000005, 55.5272512], [37.497115400000006, 55.5272987], [37.4972142, 55.52731920000001], [37.4972607, 55.52731990000001], [37.497311700000004, 55.52730890000001], [37.49735210000001, 55.5272885], [37.4973624, 55.52726139999999], [37.497353600000004, 55.527222300000005], [37.49731920000001, 55.5271866], [37.4973071, 55.5271637], [37.497316100000006, 55.5271375], [37.4973865, 55.5270771], [37.4974165, 55.52705], [37.4974659, 55.527024499999996], [37.497488399999995, 55.527010100000005], [37.4975019, 55.5269855], [37.4975018, 55.5268819], [37.4975094, 55.5268446], [37.4975213, 55.5268284], [37.4975663, 55.5268037], [37.497635300000006, 55.526780800000004], [37.49771890000001, 55.526765600000004], [37.49775210000001, 55.526763900000006], [37.497785, 55.5267715], [37.497796900000004, 55.5267818], [37.4977968, 55.526831], [37.4978179, 55.5268666], [37.4978584, 55.52690820000001], [37.4978838, 55.5269244], [37.4979047, 55.5269294], [37.4979257, 55.52692690000001], [37.497952600000005, 55.5269014], [37.4979736, 55.5268777], [37.4980035, 55.52686739999999], [37.4980679, 55.5268564], [37.498120400000005, 55.5268471], [37.49815630000001, 55.5268344], [37.4981774, 55.5268285], [37.4982074, 55.526825800000005], [37.498239600000005, 55.526825200000005], [37.498265800000006, 55.526833200000006], [37.498273700000006, 55.5268515], [37.4982677, 55.5268881], [37.498279800000006, 55.5269075], [37.498318200000014, 55.52692220000001], [37.49835840000001, 55.5269245], [37.498414600000004, 55.526917700000006], [37.49846290000001, 55.526904], [37.49851510000001, 55.5268801], [37.49857540000001, 55.526845800000004], [37.4986297, 55.526808100000004], [37.4986679, 55.526788800000006], [37.498724300000006, 55.526779600000005], [37.49881680000001, 55.526774], [37.4989676, 55.5267694], [37.49907830000001, 55.52675230000001], [37.4991204, 55.52675120000001], [37.49916880000001, 55.5267545], [37.499214900000005, 55.5267648], [37.4992672, 55.526782000000004], [37.4993276, 55.526805800000005], [37.499390000000005, 55.526835600000005], [37.4994704, 55.526863999999996], [37.4996092, 55.5269075], [37.499757900000006, 55.5269611], [37.49994890000001, 55.527026], [37.500232600000004, 55.527131000000004], [37.5005425, 55.527239200000004], [37.500944399999995, 55.5273774], [37.501037499999995, 55.5274048], [37.5011515, 55.527446999999995], [37.5013024, 55.52751310000001], [37.501457099999996, 55.52757590000001], [37.5015927, 55.527614], [37.5017429, 55.527655800000005], [37.50186149999999, 55.5276819], [37.5019197, 55.527684199999996], [37.5020471, 55.5276659], [37.50213630000001, 55.527660499999996], [37.502203300000005, 55.52765230000001], [37.502275000000004, 55.5276349], [37.5022977, 55.5276079], [37.5022869, 55.527568200000005], [37.502275700000006, 55.527499399999996], [37.5022748, 55.5274549], [37.5022736, 55.5273934], [37.5022734, 55.527368300000006], [37.5022761, 55.52735330000001], [37.5022947, 55.5273211], [37.502306600000004, 55.527287099999995], [37.502306700000005, 55.527253800000004], [37.5022882, 55.527212500000005], [37.5022294, 55.527111500000004], [37.5022238, 55.5270756], [37.502231300000005, 55.5270505], [37.502242300000006, 55.527034300000004], [37.5022607, 55.52701810000001], [37.5022819, 55.5270077], [37.50231410000001, 55.5270004], [37.502365600000005, 55.526990500000004], [37.50239870000001, 55.5269847], [37.502503000000004, 55.526954700000005], [37.502551800000006, 55.5269344], [37.5025794, 55.526914000000005], [37.502588700000004, 55.526895800000005], [37.5025868, 55.526878100000005], [37.5025684, 55.5268546], [37.5025435, 55.526834300000004], [37.50251510000001, 55.52681280000001], [37.502487599999995, 55.52678590000001], [37.5024775, 55.52675310000001], [37.5024796, 55.52671860000001], [37.5024995, 55.5266936], [37.502531700000006, 55.52667530000001], [37.50257130000001, 55.5266597], [37.5026036, 55.526655500000004], [37.5026366, 55.5266535], [37.502676, 55.526659200000005], [37.50271580000001, 55.5266717], [37.5027811, 55.5266936], [37.50288449999999, 55.52673730000001], [37.5029406, 55.5267685], [37.502971, 55.52678890000001], [37.5029894, 55.52681290000001], [37.5029976, 55.5268364], [37.502998600000005, 55.5268573], [37.502998700000006, 55.52688439999999], [37.503002200000005, 55.526906800000006], [37.503019800000004, 55.5269314], [37.503039, 55.52694230000001], [37.503069499999995, 55.5269471], [37.503109, 55.5269485], [37.5031514, 55.526946], [37.503179900000006, 55.5269465], [37.5032266, 55.526958500000006], [37.503255100000004, 55.52696530000001], [37.5032873, 55.5269678], [37.503317700000004, 55.526962100000006], [37.5033407, 55.5269496], [37.50335820000001, 55.52693230000001], [37.5033684, 55.52691250000001], [37.503375600000005, 55.5268896], [37.503385800000004, 55.5268734], [37.5033949, 55.526863999999996], [37.5034134, 55.5268541], [37.5034337, 55.526852500000004], [37.503463999999994, 55.5268536], [37.5034898, 55.526857], [37.50351830000001, 55.526863999999996], [37.503565200000004, 55.5268812], [37.5036002, 55.5268943], [37.5036269, 55.526897399999996], [37.5036527, 55.526896300000004], [37.503672900000005, 55.526892700000005], [37.5036868, 55.526886999999995], [37.5037025, 55.5268687], [37.5037097, 55.5268441], [37.5037116, 55.526819100000004], [37.5037144, 55.5268024], [37.5037213, 55.526774800000005], [37.5037443, 55.52674030000001], [37.503752600000006, 55.526730400000005], [37.5037775, 55.5267247], [37.5037986, 55.5267211], [37.5038299, 55.526723600000004], [37.5038493, 55.5267278], [37.5038732, 55.526734600000005], [37.50388699999999, 55.5267471], [37.503906300000004, 55.5267664], [37.50393580000001, 55.5268014], [37.5039606, 55.526822200000005], [37.5040002, 55.5268499], [37.5040461, 55.5268603], [37.5040803, 55.526863999999996], [37.504128200000004, 55.52685880000001], [37.5042377, 55.526836800000005], [37.5043269, 55.526810700000006], [37.5044259, 55.52677860000001], [37.5044506, 55.5267655], [37.5044681, 55.526754600000004], [37.50448109999999, 55.5267416], [37.504483799999996, 55.526721800000004], [37.5044791, 55.52670500000001], [37.5044663, 55.52667580000001], [37.504440499999994, 55.5266346], [37.504417499999995, 55.526597300000006], [37.5044156, 55.52657330000001], [37.504421099999995, 55.526549800000005], [37.5044332, 55.52653360000001], [37.504449599999994, 55.5265174], [37.504462499999995, 55.5264955], [37.5044736, 55.5264705], [37.5044902, 55.52641830000001], [37.5044957, 55.5264095], [37.50453, 55.52641570000001], [37.5047686, 55.5264773], [37.5049972, 55.5265405], [37.5054486, 55.526704900000006], [37.5056018, 55.526751000000004], [37.50573510000001, 55.526771600000004], [37.505993200000006, 55.52681030000001], [37.506205200000004, 55.526834300000004], [37.5063446, 55.5268542], [37.5064623, 55.526881599999996], [37.5066387, 55.5269794], [37.5067542, 55.5269495], [37.5068085, 55.5269666], [37.5068319, 55.526986900000004], [37.506833, 55.527025900000005], [37.5068286, 55.527059], [37.506844699999995, 55.527086399999995], [37.5068809, 55.52710580000001], [37.506933100000005, 55.527117100000005], [37.506987499999994, 55.52711820000001], [37.507044699999994, 55.52711230000001], [37.507078, 55.52710220000001], [37.507096, 55.5270852], [37.50711290000001, 55.5270447], [37.507122100000004, 55.5270087], [37.507138000000005, 55.526989], [37.5071663, 55.52697680000001], [37.50720739999999, 55.5269665], [37.50726149999999, 55.526964], [37.507304, 55.526967], [37.507330800000005, 55.5269775], [37.5073378, 55.526990000000005], [37.5073335, 55.5270054], [37.5073013, 55.527030100000005], [37.507283099999995, 55.527051], [37.5072852, 55.527076], [37.5073012, 55.5271011], [37.5073298, 55.5271145], [37.507367499999994, 55.52711600000001], [37.5073969, 55.52711020000001], [37.5074167, 55.52709230000001], [37.507439999999995, 55.527027], [37.507466799999996, 55.52699210000001], [37.5075305, 55.5269476], [37.5075787, 55.526924300000005], [37.5076269, 55.52690830000001], [37.507660599999994, 55.526904300000005], [37.507697199999996, 55.526903700000005], [37.5077657, 55.526907200000004], [37.507829099999995, 55.526903700000005], [37.5078902, 55.5268901], [37.5079325, 55.5268832], [37.507964799999996, 55.5268855], [37.507984799999996, 55.5268912], [37.507996999999996, 55.5269014], [37.5080049, 55.52692210000001], [37.508009200000004, 55.527003300000004], [37.5080212, 55.52703270000001], [37.508037200000004, 55.5270544], [37.5080634, 55.5270725], [37.5081016, 55.527083999999995], [37.50815580000001, 55.5270885], [37.508200300000006, 55.5270867], [37.508254, 55.5270797], [37.508381, 55.5270555], [37.508411200000005, 55.527044], [37.508430800000006, 55.527028300000005], [37.50843330000001, 55.52701090000001], [37.508425300000006, 55.5269995], [37.508403200000004, 55.526976700000006], [37.5083971, 55.526960800000005], [37.508404, 55.5269436], [37.508423300000004, 55.5269266], [37.5084977, 55.5268696], [37.50853790000001, 55.526841], [37.508564, 55.5268342], [37.50859220000001, 55.52683530000001], [37.5086184, 55.5268421], [37.5086406, 55.526857], [37.5086826, 55.526904], [37.508716500000006, 55.5269174], [37.508753600000006, 55.526923200000006], [37.5088696, 55.5269242], [37.508944, 55.5269174], [37.5089964, 55.52690260000001], [37.50905, 55.5268784], [37.5091091, 55.5268506], [37.509191300000005, 55.5268045], [37.5092498, 55.526777100000004], [37.509294, 55.5267634], [37.50935030000001, 55.52675310000001], [37.5094146, 55.52675430000001], [37.509471, 55.52675930000001], [37.50951320000001, 55.52677020000001], [37.5095473, 55.5267861], [37.5095892, 55.5268208], [37.5096179, 55.52685230000001], [37.5096721, 55.5268991], [37.50971270000001, 55.526922400000004], [37.5097617, 55.52693560000001], [37.5098048, 55.52693790000001], [37.5098512, 55.5269345], [37.5099272, 55.52692220000001], [37.510028, 55.526895700000004], [37.5100903, 55.526869399999995], [37.510112500000005, 55.5268488], [37.510112500000005, 55.526828300000005], [37.510108100000004, 55.5268144], [37.510090399999996, 55.526802], [37.5100457, 55.526785100000005], [37.5099616, 55.52675990000001], [37.509933600000004, 55.526745000000005], [37.5099134, 55.526726800000006], [37.5099054, 55.5267074], [37.5099061, 55.5266843], [37.509921399999996, 55.526656200000005], [37.5099495, 55.52663210000001], [37.509981599999996, 55.526616100000005], [37.5100239, 55.5266024], [37.5100607, 55.5266], [37.5101004, 55.5266076], [37.5102029, 55.52663210000001], [37.5102379, 55.52663590000001], [37.51026709999999, 55.5266298], [37.51028939999999, 55.526616100000005], [37.5103174, 55.526591], [37.510388, 55.52651120000001], [37.5104161, 55.52649290000001], [37.5104543, 55.526481499999996], [37.5104908, 55.526478100000006], [37.51055220000001, 55.526478100000006], [37.51064769999999, 55.5264955], [37.5107016, 55.5264998], [37.510843099999995, 55.526503000000005], [37.510960399999995, 55.526507], [37.51104149999999, 55.52651120000001], [37.5111038, 55.526506600000005], [37.511172200000004, 55.526494], [37.511268599999994, 55.52647230000001], [37.5113511, 55.526458700000006], [37.5114738, 55.5264449], [37.5116689, 55.5264335], [37.511825599999995, 55.5264164], [37.51198659999999, 55.526392400000006], [37.5121294, 55.526367300000004], [37.512213700000004, 55.526347900000005], [37.5123045, 55.526327], [37.5123604, 55.5263246], [37.5123947, 55.52632880000001], [37.512425, 55.526337600000005], [37.5124652, 55.52635690000001], [37.512509800000004, 55.526380800000005], [37.512561399999996, 55.52639390000001], [37.51261, 55.526400300000006], [37.5126784, 55.5264015], [37.512742700000004, 55.52639920000001], [37.5128031, 55.526391100000005], [37.51286939999999, 55.52637290000001], [37.5129419, 55.5263444], [37.512992000000004, 55.5263295], [37.51304449999999, 55.52631820000001], [37.5130957, 55.526315300000014], [37.5131375, 55.5263214], [37.51315890000001, 55.526336400000005], [37.5131831, 55.52637970000001], [37.5132033, 55.526390000000006], [37.5132255, 55.52639570000001], [37.5132556, 55.52639570000001], [37.513362, 55.526374000000004], [37.513446599999995, 55.526366100000004], [37.5134767, 55.52635580000001], [37.5134925, 55.526341200000005], [37.5134687, 55.52631360000001], [37.513434499999995, 55.5262884], [37.513426499999994, 55.526270200000006], [37.513434399999994, 55.5262462], [37.513460599999995, 55.5262314], [37.5135007, 55.52622], [37.513555000000004, 55.5262085], [37.513649599999994, 55.526199500000004], [37.5137702, 55.5261891], [37.513822499999996, 55.5261891], [37.51386469999999, 55.52619250000001], [37.51391520000001, 55.5262005], [37.5139632, 55.52621090000001], [37.51404169999999, 55.526231100000004], [37.51408849999999, 55.526239700000005], [37.5141301, 55.526245], [37.5141904, 55.5262494], [37.514263299999996, 55.52625520000001], [37.51428909999999, 55.52625520000001], [37.5143092, 55.5262546], [37.5143238, 55.52625260000001], [37.51436759999999, 55.52623930000001], [37.5143887, 55.5262285], [37.5144258, 55.5262164], [37.514446899999996, 55.526206300000005], [37.5144762, 55.5261885], [37.51448489999999, 55.526183200000006], [37.514490599999995, 55.52617970000001], [37.5145232, 55.52617520000001], [37.5145701, 55.5261675], [37.514603699999995, 55.526161800000004], [37.51462839999999, 55.5261605], [37.51467769999999, 55.526163100000005], [37.514703499999996, 55.526165000000006], [37.5147259, 55.52617020000001], [37.5147506, 55.52617630000001], [37.5147752, 55.526179600000006], [37.5147953, 55.526180200000006], [37.51480419999999, 55.526179600000006], [37.51482439999999, 55.52617510000001], [37.51484449999999, 55.52616880000001], [37.51486699999999, 55.5261605], [37.51489839999999, 55.526147800000004], [37.5149319, 55.526137000000006], [37.5149565, 55.52613320000001], [37.5149979, 55.52613070000001], [37.5150316, 55.52612810000001], [37.515064499999994, 55.526128500000006], [37.51513190000001, 55.52612980000001], [37.5152211, 55.526117400000004], [37.5152537, 55.52610390000001], [37.5152629, 55.5260912], [37.515269399999994, 55.526077300000004], [37.5152651, 55.5260264], [37.515264499999994, 55.526011700000005], [37.515271, 55.525997800000006], [37.5152963, 55.52597490000001], [37.5153045, 55.525962500000006], [37.515320700000004, 55.525947900000006], [37.515342800000006, 55.52593880000001], [37.5154081, 55.52591770000001], [37.515484199999996, 55.5258942], [37.515519600000005, 55.525882200000005], [37.5155416, 55.52587810000001], [37.5155736, 55.5258774], [37.5156147, 55.52587520000001], [37.5156776, 55.5258634], [37.515756200000006, 55.525851700000004], [37.5158002, 55.525851], [37.51583, 55.525854800000005], [37.516003999999995, 55.52587690000001], [37.5160651, 55.525882900000006], [37.5161062, 55.5258816], [37.516193200000004, 55.525879100000004], [37.516256999999996, 55.5258837], [37.5162927, 55.525882300000006], [37.516317900000004, 55.5258741], [37.5163442, 55.525866900000004], [37.516388, 55.5258637], [37.5164399, 55.5258601], [37.5164955, 55.525857200000004], [37.5165608, 55.52585590000001], [37.516615, 55.52585220000001], [37.516645499999996, 55.5258485], [37.516664799999994, 55.5258445], [37.51668749999999, 55.525841], [37.5167068, 55.525828000000004], [37.5167164, 55.52581330000001], [37.516712600000005, 55.52579800000001], [37.5166939, 55.525781900000005], [37.516643099999996, 55.52575990000001], [37.5165961, 55.52573920000001], [37.516572800000006, 55.52572610000001], [37.5165673, 55.52571150000001], [37.51657290000001, 55.525699700000004], [37.5165985, 55.5256884], [37.51664439999999, 55.52567500000001], [37.5166986, 55.525661], [37.516741399999994, 55.52565800000001], [37.516764599999995, 55.5256617], [37.51680939999999, 55.5256818], [37.516841199999995, 55.525689], [37.5168742, 55.5256864], [37.5169036, 55.525671], [37.5169354, 55.52565630000001], [37.516972100000004, 55.5256476], [37.517030999999996, 55.5256416], [37.517098, 55.525631600000004], [37.5171547, 55.52561420000001], [37.5171912, 55.52559680000001], [37.51722769999999, 55.52557870000001], [37.51724419999999, 55.52555870000001], [37.517257099999995, 55.52553660000001], [37.517272399999996, 55.52551260000001], [37.51728439999999, 55.525494800000004], [37.5173003, 55.5254813], [37.517316, 55.525472400000005], [37.517333900000004, 55.525471800000005], [37.5173502, 55.52547990000001], [37.5173986, 55.52550080000001], [37.51744959999999, 55.525507600000005], [37.5175033, 55.525504600000005], [37.5175486, 55.525488], [37.5176531, 55.5254236], [37.517680199999994, 55.525401200000005], [37.517711, 55.525381100000004], [37.5177562, 55.52536220000001], [37.517785399999994, 55.52535550000001], [37.517822699999996, 55.52534530000001], [37.5178539, 55.5253444], [37.51788319999999, 55.52535050000001], [37.517901599999995, 55.52536090000001], [37.517920999999994, 55.52537980000001], [37.517932200000004, 55.525406100000005], [37.5179419, 55.52543070000001], [37.5179587, 55.525447], [37.5179922, 55.52545980000001], [37.5180401, 55.52547880000001], [37.5180655, 55.52549020000001], [37.5180829, 55.5254974], [37.518097399999995, 55.525499800000006], [37.518114100000005, 55.525497], [37.5181442, 55.5254862], [37.518208300000005, 55.5254604], [37.5182885, 55.5254235], [37.5183741, 55.525386600000004], [37.5184222, 55.525365400000005], [37.5184418, 55.52535730000001], [37.5184597, 55.52535870000001], [37.5184764, 55.52536830000001], [37.518506, 55.52539020000001], [37.5185267, 55.52541120000001], [37.518549300000004, 55.52542630000001], [37.51859090000001, 55.525434800000006], [37.51864, 55.52543670000001], [37.518665399999996, 55.52542890000001], [37.518677, 55.52540990000001], [37.518675300000005, 55.525366000000005], [37.518665399999996, 55.52532130000001], [37.5186685, 55.52529580000001], [37.5186856, 55.5252696], [37.518706, 55.52524590000001], [37.518720300000005, 55.525223600000004], [37.5187298, 55.525211500000005], [37.5187434, 55.525207800000004], [37.5187566, 55.52521070000001], [37.518782200000004, 55.52521850000001], [37.5188134, 55.52521910000001], [37.518857, 55.5252035], [37.518928200000005, 55.525187900000006], [37.5189775, 55.525172800000014], [37.519038300000005, 55.52515010000001], [37.5190739, 55.525140400000005], [37.5191072, 55.52514480000001], [37.519145200000004, 55.52516890000001], [37.5191773, 55.525206700000005], [37.5191915, 55.5252411], [37.5191797, 55.5252764], [37.5191621, 55.525312800000016], [37.5191597, 55.525352800000014], [37.519169399999996, 55.52540280000001], [37.51919, 55.52543500000001], [37.5192178, 55.52546590000001], [37.51924699999999, 55.525480900000005], [37.5192966, 55.52549390000001], [37.5193412, 55.52550020000001], [37.5193687, 55.525496700000005], [37.519386, 55.5254896], [37.5193948, 55.52547890000001], [37.5194019, 55.5254614], [37.5194089, 55.52535690000001], [37.519403399999995, 55.52530280000001], [37.5194226, 55.525236400000004], [37.5194306, 55.525200600000005], [37.519394399999996, 55.5250819], [37.5193984, 55.5250295], [37.51940139999999, 55.524994], [37.5194125, 55.5249884], [37.5194305, 55.5249838], [37.519446699999996, 55.52497520000001], [37.5194731, 55.5249584], [37.5194929, 55.524945], [37.5195913, 55.524844699999996], [37.519643599999995, 55.524786399999996], [37.519649699999995, 55.5247636], [37.519649599999994, 55.5247424], [37.51964939999999, 55.5247371], [37.5196456, 55.5247044], [37.5196555, 55.5246655], [37.51968159999999, 55.5246176], [37.519711900000004, 55.5245834], [37.5197461, 55.5245571], [37.519758100000004, 55.5245435], [37.5197661, 55.5245275], [37.5197862, 55.524516000000006], [37.519876599999996, 55.524459], [37.5198888, 55.524445300000004], [37.5199008, 55.524425900000004], [37.519926999999996, 55.5243461], [37.519933, 55.5243278], [37.5199571, 55.5242947], [37.5200274, 55.5242298], [37.5200716, 55.5241841], [37.520093700000004, 55.52415210000001], [37.52010390000001, 55.52412590000001], [37.52010580000001, 55.5241065], [37.520093800000005, 55.5240347], [37.5200975, 55.524002700000004], [37.520107800000005, 55.52397870000001], [37.52012570000001, 55.523957], [37.520168000000005, 55.523936600000006], [37.520193400000004, 55.5239015], [37.52020220000001, 55.5238681], [37.520209900000005, 55.523799700000005], [37.5202854, 55.5228892], [37.52011020000001, 55.522479800000006], [37.5222995, 55.52185], [37.522809900000006, 55.5216342], [37.527498200000004, 55.52119290000001], [37.52957910000001, 55.52054520000001], [37.532650800000006, 55.5187602], [37.5351234, 55.517961799999995], [37.5354891, 55.5175473], [37.536170600000005, 55.5167777], [37.5363244, 55.516332600000005], [37.536197, 55.5159975], [37.53661, 55.5156562], [37.5371663, 55.5154632], [37.5380897, 55.5150395], [37.5390366, 55.5141324], [37.538985800000006, 55.51404469999999], [37.53957210000001, 55.513681899999995], [37.539554, 55.513592], [37.5399265, 55.513508], [37.53915290000001, 55.51215810000001], [37.53845220000001, 55.5121297], [37.53815580000001, 55.5120016], [37.5370991, 55.51144119999999], [37.5364012, 55.511172300000005], [37.5356831, 55.5095485], [37.53533380000001, 55.5090822], [37.5350534, 55.50833210000001], [37.5344489, 55.5083034], [37.5342083, 55.508349100000004], [37.5322541, 55.508286399999996], [37.5302887, 55.50816220000001], [37.5302201, 55.5075852], [37.5300411, 55.50637820000001], [37.52975910000001, 55.503909900000004], [37.532593600000006, 55.50283820000001], [37.5339637, 55.50571220000001], [37.535679200000004, 55.5055945], [37.5397977, 55.5044757], [37.541038900000004, 55.5039219], [37.5417683, 55.5037892], [37.542333600000006, 55.5045612], [37.5437549, 55.504455300000004], [37.5465718, 55.5042452], [37.5466981, 55.5046502], [37.547660699999994, 55.5045601], [37.548104800000004, 55.50593690000001], [37.551311399999996, 55.505636900000006], [37.5525736, 55.50551920000001], [37.5537453, 55.5092104], [37.553963599999996, 55.5096659], [37.553646699999994, 55.5097295], [37.553133800000005, 55.509862399999996], [37.550112000000006, 55.5106451], [37.5468991, 55.5119938], [37.5470252, 55.5127237], [37.55082779999999, 55.5126535], [37.5513256, 55.5126443], [37.551588599999995, 55.512662], [37.5529884, 55.512852300000006], [37.5547883, 55.513096999999995], [37.5547592, 55.5131714], [37.55494439999999, 55.5132163], [37.554936399999995, 55.5132333], [37.5550473, 55.5132584], [37.5550662, 55.5132396], [37.5552658, 55.51328169999999], [37.555302600000005, 55.5132232], [37.556145900000004, 55.5134339], [37.556343, 55.5135005], [37.55813920000001, 55.5139508], [37.558618800000005, 55.514202399999995], [37.560639900000005, 55.5152413], [37.560962800000006, 55.515198000000005], [37.5614402, 55.5156796], [37.562974200000006, 55.516981599999994], [37.5640867, 55.518475900000006], [37.5640992, 55.5184948], [37.564778800000006, 55.518411], [37.5653604, 55.520436700000005], [37.566875100000004, 55.5202911], [37.56617890000001, 55.51708059999999], [37.5676921, 55.51668399999999], [37.570521, 55.5167892], [37.57428649999999, 55.517009099999996], [37.5771272, 55.5172033], [37.571814499999995, 55.5000538], [37.572177, 55.4991416], [37.5730576, 55.4990491], [37.57308, 55.4989873], [37.573106900000006, 55.498928400000004], [37.573129300000005, 55.4988835], [37.57315800000001, 55.498838000000006], [37.5731894, 55.49879320000001], [37.5732235, 55.498749800000006], [37.573281099999996, 55.4986818], [37.57331610000001, 55.498647], [37.5733618, 55.498606], [37.5734043, 55.49856630000001], [37.5734432, 55.49853330000001], [37.5734908, 55.498492000000006], [37.573598700000005, 55.498420100000004], [37.5737043, 55.498355300000014], [37.5738432, 55.4982881], [37.574044099999995, 55.49821330000001], [37.5741935, 55.498145400000006], [37.5773412, 55.4968142], [37.578435500000005, 55.49631830000001], [37.578531100000006, 55.4962811], [37.5786269, 55.496252500000004], [37.57871680000001, 55.496230600000004], [37.57883590000001, 55.496211200000005], [37.57895280000001, 55.4962012], [37.5790462, 55.496197900000006], [37.5791419, 55.49619880000001], [37.579198600000005, 55.4961964], [37.5792662, 55.49619010000001], [37.579296, 55.4961861], [37.579908, 55.49593130000001], [37.584023499999994, 55.494275], [37.591337300000006, 55.4913076], [37.5912209, 55.492409300000006], [37.590276100000004, 55.49339210000001], [37.5924965, 55.4942239], [37.5936678, 55.49305210000001], [37.593855500000004, 55.49301330000001], [37.5952875, 55.49317500000001], [37.5970032, 55.494233200000004], [37.5986834, 55.49502210000001], [37.6002296, 55.495748000000006], [37.600004, 55.4968287], [37.6027811, 55.49811180000001], [37.604145200000005, 55.498705400000006], [37.6041006, 55.4990632], [37.602554600000005, 55.5004511], [37.602991200000005, 55.5010354], [37.6045412, 55.502416800000006], [37.598892500000005, 55.504376], [37.5966517, 55.5054216], [37.5977492, 55.50613210000001], [37.598594000000006, 55.5076213], [37.59871800000001, 55.508132300000014], [37.5978066, 55.5086481], [37.5931864, 55.511495599999996], [37.59263580000001, 55.5116108], [37.59266890000001, 55.51188989999999], [37.5918282, 55.5124933], [37.590551100000006, 55.5134097], [37.589715000000005, 55.514009699999995], [37.5886984, 55.515529300000004], [37.5858048, 55.517129399999995], [37.5855231, 55.5179973], [37.5822493, 55.519739900000005], [37.5791255, 55.5213491], [37.57850390000001, 55.5216793], [37.579936700000005, 55.526237900000005], [37.5799626, 55.5265644], [37.5799692, 55.5266346], [37.580322100000004, 55.527760300000004], [37.58072, 55.527717200000005], [37.58221230000001, 55.5316397], [37.582522100000006, 55.532673], [37.5836358, 55.53651250000001], [37.583915100000006, 55.537199300000005], [37.5833174, 55.53786159999999], [37.58461749999999, 55.5420618], [37.5845248, 55.5420603], [37.5852261, 55.5445906], [37.585445, 55.545342100000006], [37.5855304, 55.54555210000001], [37.5856555, 55.54575380000001], [37.5858393, 55.546266599999996], [37.58593270000001, 55.5462619], [37.5871455, 55.550223599999995], [37.587488799999996, 55.5513459], [37.587913900000004, 55.5522403], [37.58811890000001, 55.55273280000001], [37.5882062, 55.55369099999999], [37.58930290000001, 55.557199499999996], [37.589453999999996, 55.55768299999999], [37.59334520000001, 55.560245800000004], [37.5961804, 55.561756], [37.59883820000001, 55.56271080000001], [37.6003671, 55.563108500000006], [37.6008769, 55.5632833], [37.60213860000001, 55.5638907], [37.603576700000005, 55.5645916], [37.6022876, 55.56637270000001], [37.598397000000006, 55.5666055], [37.597467599999995, 55.5668718], [37.59755320000001, 55.5678882], [37.59719630000001, 55.5690831], [37.594987499999995, 55.5717837], [37.5940996, 55.57293380000001], [37.59370080000001, 55.573542], [37.59283010000001, 55.574664799999994], [37.59252530000001, 55.57503560000001], [37.5922404, 55.57539990000001], [37.59209810000001, 55.57555290000001], [37.5918517, 55.5757746], [37.5915216, 55.576076], [37.591207499999996, 55.576253900000005], [37.590093100000004, 55.5768957], [37.58666439999999, 55.5777032], [37.578140100000006, 55.57973220000001], [37.57293990000001, 55.5809669], [37.5735811, 55.5814983], [37.573742900000006, 55.5816952], [37.5738298, 55.581876099999995], [37.573827099999995, 55.58203580000001], [37.5736777, 55.5822096], [37.5755047, 55.5839241], [37.5774788, 55.5863496], [37.577476499999996, 55.58698939999999], [37.5770668, 55.5872209], [37.5770597, 55.58744419999999], [37.5767866, 55.58786659999999], [37.576920900000005, 55.5880716], [37.5772147, 55.58868939999999], [37.57748709999999, 55.588717200000005], [37.577621699999995, 55.5892199], [37.5768643, 55.589314900000005], [37.576980999999996, 55.589872], [37.576924399999996, 55.5902534], [37.576998700000004, 55.5908576], [37.5771505, 55.5912501], [37.5771426, 55.5916951], [37.577412300000006, 55.59207890000001], [37.5775263, 55.59241270000001], [37.577868699999996, 55.593164], [37.577913200000005, 55.593625700000004], [37.57817850000001, 55.594213], [37.5783666, 55.594821399999994], [37.5785865, 55.595223600000004], [37.578974, 55.59591340000001], [37.5802368, 55.59581330000001], [37.5801979, 55.596898700000004], [37.580571, 55.5977608], [37.576663399999994, 55.5978687], [37.5764301, 55.59815500000001], [37.5764883, 55.59865370000001], [37.576714700000004, 55.5992866], [37.5770423, 55.59952280000001], [37.577511300000005, 55.600030100000005], [37.577673399999995, 55.600169900000004], [37.5788794, 55.600852100000004], [37.5792964, 55.6010331], [37.5817703, 55.6034936], [37.5815337, 55.6043463], [37.5778221, 55.604366399999996], [37.57576220000001, 55.6062573], [37.574899599999995, 55.606596], [37.5742126, 55.6066376], [37.5739863, 55.6066513], [37.573616, 55.60595000000001], [37.57186769999999, 55.605988700000005], [37.571298999999996, 55.60671790000001], [37.570140300000006, 55.607154200000004], [37.5698955, 55.607243], [37.56990630000001, 55.607370200000005], [37.5699656, 55.6075292], [37.5698498, 55.60755820000001], [37.569884099999996, 55.6077178], [37.56979830000001, 55.608069300000004], [37.56991630000001, 55.6084693], [37.570954300000004, 55.60851320000001], [37.571705300000005, 55.60837990000001], [37.5719867, 55.60830930000001], [37.5732883, 55.60830890000001], [37.5736164, 55.60836080000001], [37.5742438, 55.60869230000001], [37.5746859, 55.60881690000001], [37.57557560000001, 55.610983499999996], [37.575678100000005, 55.6117933], [37.575710400000006, 55.612282900000004], [37.5752291, 55.6126364], [37.5746262, 55.6132284], [37.577527399999994, 55.6143282], [37.577792, 55.6145257], [37.5780867, 55.614758], [37.577693399999994, 55.6148622], [37.5759344, 55.6155066], [37.5784625, 55.61875630000001], [37.5794247, 55.619691399999994], [37.5804221, 55.6193292], [37.5804987, 55.6193862], [37.579517100000004, 55.6198313], [37.5788852, 55.620094900000005], [37.577894799999996, 55.619345], [37.5775513, 55.6192541], [37.5773218, 55.6192619], [37.5769766, 55.61930830000001], [37.5756784, 55.6196779], [37.5749918, 55.6198233], [37.574745, 55.6200474], [37.575056200000006, 55.620544200000005], [37.5755604, 55.621022800000006], [37.5759467, 55.6214226], [37.576397300000004, 55.62175580000001], [37.576920900000005, 55.62196290000001], [37.5779349, 55.621739600000005], [37.57807890000001, 55.621908000000005], [37.578588800000006, 55.621768800000005], [37.578842800000004, 55.621745100000005], [37.57830800000001, 55.62205200000001], [37.578381300000004, 55.62221390000001], [37.57871480000001, 55.62223630000001], [37.57888, 55.62211900000001], [37.57917090000001, 55.62210940000001], [37.57966749999999, 55.62193860000001], [37.5796707, 55.621847599999995], [37.5799079, 55.621742100000006], [37.58011200000001, 55.621701300000005], [37.5802913, 55.621781399999996], [37.58053520000001, 55.621788900000006], [37.581258399999996, 55.622229100000006], [37.58263290000001, 55.6232446], [37.582219200000004, 55.623327700000004], [37.5816589, 55.62291940000001], [37.581544099999995, 55.62303620000001], [37.58182789999999, 55.623246300000005], [37.581881399999986, 55.623353400000006], [37.5817208, 55.623388000000006], [37.58192639999999, 55.62363620000001], [37.5817786, 55.6238466], [37.5813932, 55.6240714], [37.58198649999999, 55.6242456], [37.582354200000005, 55.62436230000001], [37.5820298, 55.6245849], [37.5824208, 55.624802700000004], [37.5827831, 55.62516510000001], [37.582885399999995, 55.62540390000001], [37.5832427, 55.626231100000005], [37.58344739999999, 55.6262846], [37.5836354, 55.626329000000005], [37.583816399999996, 55.626912300000015], [37.584044199999994, 55.6268863], [37.5842063, 55.62669330000001], [37.5843505, 55.6266836], [37.5846823, 55.62770390000001], [37.58462779999999, 55.627740300000006], [37.584348999999996, 55.627641499999996], [37.584191399999995, 55.6275846], [37.5840258, 55.62777890000001], [37.5840882, 55.627995000000006], [37.58444749999999, 55.62800080000001], [37.584740499999995, 55.62792520000001], [37.584917, 55.62834550000001], [37.5850272, 55.62872300000001], [37.5848357, 55.6287675], [37.5846721, 55.628476400000004], [37.5843505, 55.62856280000001], [37.58422149999999, 55.62843480000001], [37.5841307, 55.628674600000004], [37.584588499999995, 55.628969100000006], [37.585146800000004, 55.629200600000004], [37.585284099999996, 55.629399400000004], [37.585259900000004, 55.62953970000001], [37.585395600000005, 55.62979620000001], [37.58551030000001, 55.6300194], [37.5857961, 55.630621399999995], [37.5858754, 55.6308714], [37.585982900000005, 55.631173000000004], [37.5858037, 55.6314207], [37.5852426, 55.63148639999999], [37.583819999999996, 55.631472800000004], [37.5772657, 55.63267690000001], [37.577405999999996, 55.634360300000004], [37.5775701, 55.634454], [37.57778139999999, 55.634698900000004], [37.57813870000001, 55.63473880000001], [37.578797900000005, 55.63535800000001], [37.579058, 55.63540520000001], [37.5792056, 55.63555300000001], [37.579140800000005, 55.63565930000001], [37.5792798, 55.635780700000005], [37.5801576, 55.635563600000005], [37.580594399999995, 55.63591100000001], [37.579844599999994, 55.636022600000004], [37.580319700000004, 55.6365675], [37.5805256, 55.6365884], [37.580621799999996, 55.6367698], [37.5808298, 55.6368147], [37.5811043, 55.6372784], [37.5816659, 55.6372003], [37.58166549999999, 55.6372043], [37.5822546, 55.638467], [37.581907099999995, 55.638691300000005], [37.581490699999996, 55.638960000000004], [37.58144769999999, 55.6394871], [37.5816209, 55.63947530000001], [37.582056800000004, 55.6395444], [37.58215530000001, 55.63965230000001], [37.582119500000005, 55.63973490000001], [37.5820025, 55.6398242], [37.5816158, 55.63996530000001], [37.58126179999999, 55.6408951], [37.5819231, 55.6409], [37.5819117, 55.6409906], [37.5820011, 55.6412222], [37.5807067, 55.64233320000001], [37.5792904, 55.6428012], [37.579362200000006, 55.643615200000006], [37.5800031, 55.6438219], [37.5800959, 55.6448098], [37.5801147, 55.644940999999996], [37.5804124, 55.6449225], [37.5804286, 55.64511100000001], [37.5803884, 55.64532620000001], [37.5826673, 55.6446348], [37.5865867, 55.643434], [37.589415300000006, 55.642579000000005], [37.5902236, 55.642397200000005], [37.5916832, 55.642188600000004], [37.59451310000001, 55.6419632], [37.5948165, 55.6419459], [37.605729200000006, 55.6413276], [37.6056462, 55.643340300000006], [37.605593500000005, 55.6444793], [37.605580700000004, 55.6448207], [37.605586200000005, 55.6452014], [37.60558880000001, 55.64537980000001], [37.605590600000006, 55.6454994], [37.60559220000001, 55.645611800000005], [37.60561930000001, 55.6473858], [37.6055871, 55.6486206], [37.60557670000001, 55.649021], [37.605533400000006, 55.6510713], [37.605504700000004, 55.652922800000006], [37.60550280000001, 55.653044099999995], [37.60550070000001, 55.6533743], [37.605495700000006, 55.653627699999994], [37.6054878, 55.65373220000001], [37.6054648, 55.6547905], [37.6054449, 55.6560591], [37.60544530000001, 55.65622139999999], [37.60544590000001, 55.6564483], [37.605467399999995, 55.6565272], [37.605492000000005, 55.656584699999996], [37.6056662, 55.6568109], [37.6058668, 55.6570306], [37.60691530000001, 55.6579233], [37.60805820000001, 55.6588985], [37.60811510000001, 55.6589479], [37.60995990000001, 55.6604497], [37.6102368, 55.6606778], [37.6104101, 55.660807], [37.61053530000001, 55.6609004], [37.6113748, 55.661598100000006], [37.6128693, 55.66287630000001], [37.613016800000004, 55.6630024], [37.6131638, 55.66312810000001], [37.6133979, 55.66333180000001], [37.613496999999995, 55.663414200000005], [37.6135718, 55.663479300000006], [37.60764639999999, 55.6640831], [37.60771280000001, 55.6642794], [37.60811620000001, 55.664473], [37.6090918, 55.66512020000001], [37.6096956, 55.6652215], [37.61064399999999, 55.6649643], [37.6109239, 55.6652964], [37.6110019, 55.66538890000001], [37.6111031, 55.66550900000001], [37.6116352, 55.66612870000001], [37.610690999999996, 55.66655420000001], [37.6068545, 55.66828290000001], [37.6062794, 55.6688637], [37.60610280000001, 55.6703905], [37.6062279, 55.6716954], [37.60565280000001, 55.672063300000005], [37.605896300000005, 55.67243510000001], [37.6058243, 55.672829300000004], [37.60597270000001, 55.673095100000005], [37.606053700000004, 55.673245], [37.606914800000006, 55.6738731], [37.6072286, 55.6741797], [37.6073744, 55.6744852], [37.60737830000001, 55.6746682], [37.6077372, 55.674711800000004], [37.608101600000005, 55.674955100000005], [37.608379400000004, 55.675234], [37.60859020000001, 55.67533620000001], [37.608593000000006, 55.6754577], [37.6084809, 55.675678600000005], [37.60853360000001, 55.6758092], [37.608779600000005, 55.6760004], [37.60895530000001, 55.6763047], [37.609122600000006, 55.6764084], [37.6092478, 55.67647830000001], [37.6094397, 55.676615500000004], [37.609933500000004, 55.67673570000001], [37.6100305, 55.6768254], [37.6101849, 55.676965800000005], [37.6104768, 55.677072300000006], [37.6108973, 55.67714], [37.6112922, 55.6772175], [37.6114229, 55.677319100000005], [37.6115213, 55.677520300000005], [37.611544499999994, 55.6779144], [37.6115062, 55.67809890000001], [37.6114759, 55.678329500000004], [37.6117107, 55.678605600000004], [37.612013100000006, 55.678810500000004], [37.6123594, 55.6789646], [37.6126655, 55.6792742], [37.613223399999995, 55.6796517], [37.61377830000001, 55.679985800000004], [37.61414739999999, 55.6803811], [37.6144722, 55.6804385], [37.614681299999994, 55.68055030000001], [37.614920999999995, 55.680925900000005], [37.6147009, 55.681598300000005], [37.6149408, 55.6817682], [37.61531600000001, 55.68188959999999], [37.6158819, 55.681882599999994], [37.616035600000004, 55.681913900000005], [37.6162201, 55.68214270000001], [37.6167813, 55.68285530000001], [37.617340999999996, 55.683327], [37.618334100000006, 55.683672200000004], [37.6190041, 55.6843165], [37.6183837, 55.6845037]]]]}}, {"id": 1278703, "osm_type": "relation", "type": "Feature", "name": "Юго-Восточный административный округ", "properties": {"ref": "ЮВАО", "name": "Юго-Восточный административный округ", "name:be": "Паўднёва-усходняя адміністрацыйная акруга", "name:de": "Südöstlicher Verwaltungsbezirk", "name:en": "South-Eastern Administrative Okrug", "website": "http://www.uvao.mos.ru/", "boundary": "administrative", "wikipedia": "ru:Юго-Восточный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.967427699999995, 55.716249], [37.967316700000005, 55.7160403], [37.9650216, 55.715439800000006], [37.9606662, 55.7147541], [37.9598592, 55.7140911], [37.966706300000006, 55.7104986], [37.9667697, 55.7102269], [37.965972400000005, 55.7099606], [37.96435090000001, 55.70938830000001], [37.964192800000006, 55.7091974], [37.953097899999996, 55.7112623], [37.949666799999996, 55.7113411], [37.94736699999999, 55.70867200000001], [37.954199599999995, 55.706734000000004], [37.9543952, 55.70693820000001], [37.9579107, 55.70594010000001], [37.959744799999996, 55.7045084], [37.9582197, 55.70293980000001], [37.95895, 55.70259680000001], [37.957045199999996, 55.7008597], [37.956037699999996, 55.7011036], [37.9565608, 55.7016689], [37.956628599999995, 55.7020674], [37.956507499999994, 55.702206600000004], [37.9562135, 55.702351500000006], [37.956138700000004, 55.70250610000001], [37.95575590000001, 55.70273160000001], [37.9555062, 55.702796400000004], [37.95485639999999, 55.702809800000004], [37.9546132, 55.702875000000006], [37.954208599999994, 55.70277520000001], [37.9540752, 55.7026285], [37.9536922, 55.7024254], [37.9532962, 55.70207560000001], [37.953209199999996, 55.701687099999994], [37.9530529, 55.70157820000001], [37.9529261, 55.701329], [37.9531626, 55.701193800000006], [37.953257099999995, 55.7007217], [37.953352200000005, 55.7005831], [37.952983399999994, 55.7005685], [37.952813, 55.700615000000006], [37.9521706, 55.700602], [37.95209439999999, 55.700568200000006], [37.95166619999999, 55.7006292], [37.95148519999999, 55.700536400000004], [37.95132649999999, 55.7005594], [37.950999499999995, 55.7004655], [37.9509425, 55.7004011], [37.9503087, 55.70025580000001], [37.950080299999996, 55.700071200000004], [37.9499099, 55.7000291], [37.9495221, 55.700054800000004], [37.9494124, 55.7000074], [37.948995700000005, 55.700114000000006], [37.9486365, 55.70013910000001], [37.948304300000004, 55.7000774], [37.9477538, 55.7002236], [37.9471979, 55.700248200000004], [37.94686139999999, 55.700162000000006], [37.9466456, 55.6999944], [37.946677599999994, 55.6998692], [37.9463699, 55.69951570000001], [37.9453045, 55.699127600000004], [37.945232600000004, 55.69898220000001], [37.9453431, 55.69855500000001], [37.945603999999996, 55.6981644], [37.94553870000001, 55.698089800000005], [37.9452039, 55.6979775], [37.9448393, 55.697767], [37.9446343, 55.697548000000005], [37.94456709999999, 55.6973666], [37.94460359999999, 55.697206800000004], [37.944789799999995, 55.69699390000001], [37.9450608, 55.696856200000006], [37.9462308, 55.69667270000001], [37.94644709999999, 55.69641610000001], [37.946673, 55.69636220000001], [37.9470592, 55.69637840000001], [37.9472191, 55.69630220000001], [37.9477931, 55.69591450000001], [37.94789759999999, 55.69561090000001], [37.948272, 55.695424900000006], [37.94830230000001, 55.69525890000001], [37.9484764, 55.69512790000001], [37.9488772, 55.69507820000001], [37.9497773, 55.69524210000001], [37.95005999999999, 55.69539980000001], [37.9502173, 55.69555790000001], [37.9503613, 55.695857700000005], [37.950876699999995, 55.696186600000004], [37.955612300000006, 55.69451310000001], [37.953929499999994, 55.69272600000001], [37.9563543, 55.69274290000001], [37.9575785, 55.6938492], [37.9602039, 55.69277400000001], [37.95898439999999, 55.691030000000005], [37.95788009999999, 55.6894508], [37.9581243, 55.689399800000004], [37.9591458, 55.6895692], [37.9594026, 55.6894821], [37.959426199999996, 55.6894272], [37.9596251, 55.68933520000001], [37.9599999, 55.6892733], [37.960732500000006, 55.6892341], [37.96118439999999, 55.6890271], [37.961238300000005, 55.688968700000004], [37.9609437, 55.6884701], [37.960962, 55.68831380000001], [37.9611673, 55.688081399999994], [37.961618200000004, 55.6877957], [37.962224, 55.687629199999996], [37.962621399999996, 55.6875993], [37.962822300000006, 55.6875095], [37.9634548, 55.6873656], [37.9635777, 55.687194], [37.9635704, 55.687042399999996], [37.9632405, 55.6866712], [37.9632451, 55.68655880000001], [37.9635973, 55.686441099999996], [37.9642493, 55.6864319], [37.9645395, 55.6863771], [37.96471580000001, 55.6862738], [37.9647713, 55.686174300000005], [37.96477, 55.6860602], [37.9642362, 55.686003], [37.963535400000005, 55.686001], [37.9632055, 55.685938500000006], [37.9629045, 55.6857406], [37.962873200000004, 55.6856636], [37.96283890000001, 55.685484699999996], [37.9629849, 55.68503580000001], [37.9632861, 55.684896699999996], [37.963798600000004, 55.68451830000001], [37.963738000000006, 55.684343999999996], [37.9635695, 55.68426939999999], [37.9635462, 55.684181599999995], [37.963553700000006, 55.684045], [37.9636633, 55.6839601], [37.9634995, 55.683639], [37.9634911, 55.683351300000005], [37.9632684, 55.683021499999995], [37.9630378, 55.682816300000006], [37.9630657, 55.682317700000006], [37.963281599999995, 55.68186109999999], [37.9634623, 55.681765999999996], [37.9635879, 55.681575800000005], [37.9635042, 55.6811248], [37.9633796, 55.680907], [37.963605900000005, 55.68053990000001], [37.96435030000001, 55.680052700000005], [37.9644024, 55.6798146], [37.9642771, 55.679602900000006], [37.963263399999995, 55.67891840000001], [37.9626295, 55.67821310000001], [37.96212270000001, 55.6779499], [37.9618591, 55.677714200000004], [37.961779, 55.6774869], [37.961877099999995, 55.676960300000005], [37.961355600000005, 55.67563690000001], [37.9614452, 55.675379400000004], [37.96173890000001, 55.675131500000006], [37.9626019, 55.6748992], [37.9634687, 55.67442449999999], [37.963796300000006, 55.6739042], [37.963377900000005, 55.673656], [37.960042, 55.6740081], [37.95086599999999, 55.675022600000005], [37.9496509, 55.675161700000004], [37.9486257, 55.67550230000001], [37.9355974, 55.675777100000005], [37.932014800000005, 55.67591120000001], [37.93160439999999, 55.675964300000004], [37.92811110000001, 55.6760237], [37.9271265, 55.67595240000001], [37.9204717, 55.676143], [37.920472800000006, 55.6764408], [37.918936300000006, 55.6805384], [37.9184757, 55.6807639], [37.9161091, 55.6812027], [37.915475, 55.6812321], [37.9137928, 55.681538], [37.914306399999994, 55.682998100000006], [37.9132908, 55.68331680000001], [37.9167144, 55.6859461], [37.9172582, 55.68626739999999], [37.9173348, 55.6869866], [37.91737739999999, 55.6870638], [37.9177251, 55.687694199999996], [37.9186031, 55.68826], [37.9224346, 55.688808300000005], [37.92319270000001, 55.689271399999996], [37.9234006, 55.68955280000001], [37.9244196, 55.690763200000006], [37.924679499999996, 55.69094330000001], [37.9248141, 55.691036700000005], [37.925996600000005, 55.692378800000014], [37.9264882, 55.69263130000001], [37.9275831, 55.69397980000001], [37.927405, 55.6940575], [37.927508700000004, 55.69417270000001], [37.927868, 55.6945885], [37.927911200000004, 55.6946384], [37.92825280000001, 55.694999300000006], [37.92856820000001, 55.69512730000001], [37.9358711, 55.696811000000004], [37.939126, 55.69649870000001], [37.939876999999996, 55.696504000000004], [37.939755500000004, 55.6966076], [37.9398067, 55.69801460000001], [37.92705290000001, 55.698215300000015], [37.9266095, 55.698221100000005], [37.926068, 55.6978943], [37.9248433, 55.69697970000001], [37.9193762, 55.69935210000001], [37.91893830000001, 55.69942520000001], [37.9151667, 55.6970473], [37.9134366, 55.6978652], [37.913464899999994, 55.70217040000001], [37.912205900000004, 55.70296990000001], [37.9122407, 55.7034207], [37.9113772, 55.704776700000004], [37.909273, 55.7049441], [37.9078057, 55.7046341], [37.907246799999996, 55.704613200000004], [37.9061276, 55.706258500000004], [37.9070118, 55.7069911], [37.9192451, 55.707606399999996], [37.920673900000004, 55.707796300000005], [37.9219165, 55.7079613], [37.92258, 55.708688900000006], [37.92335530000001, 55.70953930000001], [37.9247941, 55.711117300000005], [37.924847299999996, 55.71111260000001], [37.9256924, 55.7119819], [37.926114600000005, 55.712186800000005], [37.926253800000005, 55.715149700000005], [37.928069900000004, 55.716159000000005], [37.930932500000004, 55.71619280000001], [37.9365872, 55.7162384], [37.9379967, 55.7173827], [37.9383672, 55.7174256], [37.94068139999999, 55.71861930000001], [37.941327099999995, 55.718952400000006], [37.942995800000006, 55.719813], [37.945162700000004, 55.72081180000001], [37.945650300000004, 55.720838500000006], [37.9474751, 55.7200604], [37.948040999999996, 55.72025030000001], [37.94831990000001, 55.720178900000015], [37.9494082, 55.72005230000001], [37.94982339999999, 55.720004], [37.9505098, 55.72003030000001], [37.955512600000006, 55.72022200000001], [37.9584742, 55.7176168], [37.962053000000004, 55.717164499999996], [37.967427699999995, 55.716249]]], [[[37.864792, 55.6873501], [37.8634002, 55.685017200000004], [37.8610154, 55.6809535], [37.860477499999995, 55.67988939999999], [37.860178600000005, 55.67935010000001], [37.859529699999996, 55.67816230000001], [37.859420199999995, 55.677962], [37.85885639999999, 55.6770986], [37.8573105, 55.6759867], [37.8569422, 55.67573900000001], [37.85688819999999, 55.675701000000004], [37.849693699999996, 55.6790621], [37.847561299999995, 55.6799978], [37.8457176, 55.6807778], [37.8433949, 55.6817314], [37.840255, 55.6829504], [37.8380612, 55.6838112], [37.8368553, 55.684258], [37.835848999999996, 55.684569599999996], [37.835376100000005, 55.68462149999999], [37.834657799999995, 55.68464349999999], [37.833380399999996, 55.6843898], [37.832767399999994, 55.684032200000004], [37.8325244, 55.6836508], [37.832474399999995, 55.683418200000006], [37.832463999999995, 55.6830379], [37.832785, 55.6822247], [37.8333821, 55.6809055], [37.8337391, 55.6800461], [37.8340993, 55.679107], [37.834347699999995, 55.67840890000001], [37.8345286, 55.67789], [37.834704099999996, 55.677323], [37.8348148, 55.6770314], [37.834929499999994, 55.67675510000001], [37.8350401, 55.6764706], [37.8351344, 55.67617190000001], [37.835245, 55.6758838], [37.8354598, 55.67531930000001], [37.8355601, 55.67503130000001], [37.8356564, 55.6747384], [37.835914700000004, 55.674061599999995], [37.8360739, 55.673594200000004], [37.836344399999994, 55.67293090000001], [37.8366582, 55.67209820000001], [37.8370572, 55.6709608], [37.8376038, 55.669511500000006], [37.8377967, 55.668900400000005], [37.8380608, 55.66824930000001], [37.8384642, 55.6671314], [37.83891890000001, 55.66590550000001], [37.839338600000005, 55.664739100000006], [37.839484299999995, 55.6643455], [37.8395998, 55.6640071], [37.8397197, 55.663526600000004], [37.8398439, 55.66305090000001], [37.8399432, 55.66256560000001], [37.8400337, 55.66210720000001], [37.8400733, 55.6615911], [37.840109399999996, 55.661106100000005], [37.840141599999995, 55.659827299999996], [37.840109399999996, 55.659206399999995], [37.840043099999995, 55.658558400000004], [37.840133, 55.6582724], [37.840741099999995, 55.658149], [37.8412502, 55.65810580000001], [37.84162659999999, 55.6578452], [37.841599099999996, 55.65728489999999], [37.8413901, 55.656702900000006], [37.84128859999999, 55.656420399999995], [37.840962, 55.65555930000001], [37.841039499999994, 55.65550530000001], [37.841265899999996, 55.6553475], [37.8411397, 55.6551916], [37.839514, 55.6555235], [37.8392609, 55.65551520000001], [37.8390998, 55.6554662], [37.8388958, 55.655244499999995], [37.838368700000004, 55.6542421], [37.837718200000005, 55.653279999999995], [37.8372124, 55.6526179], [37.836990300000004, 55.652364399999996], [37.836288599999996, 55.6515041], [37.8360608, 55.651221299999996], [37.8357811, 55.6509417], [37.83511630000001, 55.650242399999996], [37.83489719999999, 55.6500593], [37.834056499999996, 55.6494506], [37.832093900000004, 55.6480497], [37.8308518, 55.64724759999999], [37.829615800000006, 55.6464618], [37.828872200000006, 55.646016700000004], [37.8284407, 55.6456765], [37.8279951, 55.64536820000001], [37.827678, 55.645225200000006], [37.8273401, 55.6450855], [37.8248319, 55.643390700000005], [37.82473290000001, 55.64331250000001], [37.8226572, 55.6416176], [37.822540100000005, 55.6415104], [37.82255910000001, 55.64148399999999], [37.822656300000006, 55.6413679], [37.8229284, 55.641243599999996], [37.823152500000006, 55.641137], [37.8233449, 55.641030300000004], [37.8235374, 55.6409146], [37.8237455, 55.640816900000004], [37.823937900000004, 55.64071010000001], [37.8241147, 55.640585300000005], [37.824163999999996, 55.6404868], [37.824182, 55.6403611], [37.82415230000001, 55.640235200000006], [37.8240118, 55.6400908], [37.823823499999996, 55.63995500000001], [37.8236354, 55.63981030000001], [37.823510600000006, 55.6396749], [37.822929, 55.6393215], [37.822580300000006, 55.6392836], [37.82237520000001, 55.6392017], [37.82213810000001, 55.639137600000005], [37.821916200000004, 55.6391094], [37.8217579, 55.6390816], [37.8214713, 55.63912500000001], [37.82124749999999, 55.639213600000005], [37.8210556, 55.6392934], [37.8208956, 55.6393644], [37.82071990000001, 55.639426300000004], [37.820377, 55.639426900000004], [37.8189777, 55.63930800000001], [37.8185441, 55.6392663], [37.818332000000005, 55.6392096], [37.818116700000004, 55.639092500000004], [37.81740779999999, 55.63861820000001], [37.816965999999994, 55.63833540000001], [37.8139268, 55.6363605], [37.8103408, 55.6340315], [37.8086639, 55.63291100000001], [37.80835830000001, 55.632584900000005], [37.808391, 55.632529600000005], [37.8074738, 55.631930700000005], [37.8073572, 55.631962900000005], [37.8061648, 55.631260999999995], [37.8047141, 55.6303446], [37.801967999999995, 55.62854020000001], [37.8013526, 55.628128900000014], [37.80064739999999, 55.627693900000004], [37.8006022, 55.6274596], [37.799743400000004, 55.62691710000001], [37.7958476, 55.6242264], [37.793561000000004, 55.62295970000001], [37.792532000000016, 55.62371470000001], [37.78975560000001, 55.62575170000001], [37.786708600000004, 55.63025820000001], [37.78503490000001, 55.633262300000005], [37.784262399999996, 55.63832500000001], [37.783833200000004, 55.6425879], [37.78550690000001, 55.645106600000005], [37.785335300000014, 55.6473346], [37.783446999999995, 55.6485454], [37.77979920000001, 55.64873910000001], [37.76691910000001, 55.645621], [37.76619500000001, 55.6454457], [37.7495868, 55.640626], [37.7453811, 55.6398994], [37.72950240000001, 55.6408925], [37.72903410000001, 55.6408512], [37.726469800000004, 55.6406196], [37.7132784, 55.6394575], [37.69941680000001, 55.642121800000005], [37.694481499999995, 55.6432843], [37.69290610000001, 55.6438288], [37.6889454, 55.6452218], [37.6780449, 55.649944], [37.6745688, 55.651759999999996], [37.672594700000005, 55.653212800000006], [37.6716505, 55.6543508], [37.6715218, 55.655779300000006], [37.6716027, 55.6563638], [37.67238210000001, 55.661982800000004], [37.6732404, 55.66510550000001], [37.67504280000001, 55.6676469], [37.67813270000001, 55.66905080000001], [37.6824243, 55.6706239], [37.6874025, 55.6711564], [37.6907475, 55.6732397], [37.692702300000015, 55.673779], [37.697347, 55.6750645], [37.7003414, 55.6758865], [37.7047617, 55.6773626], [37.7072419, 55.678800200000005], [37.7079299, 55.679100700000006], [37.71195, 55.681319800000004], [37.71237920000001, 55.6846586], [37.712121700000004, 55.688456800000004], [37.70757270000001, 55.693270500000004], [37.694783900000004, 55.69535060000001], [37.68851320000001, 55.69657880000001], [37.684650999999995, 55.69737090000001], [37.679011300000006, 55.69819170000001], [37.674485499999996, 55.69850850000001], [37.67293380000001, 55.69967690000001], [37.670954800000004, 55.700500700000006], [37.6672891, 55.7007415], [37.66735290000001, 55.7012704], [37.6675631, 55.70313900000001], [37.667811, 55.7052824], [37.667430100000004, 55.7065679], [37.6672947, 55.706948100000005], [37.66635590000001, 55.70979500000001], [37.6662648, 55.710097499999996], [37.66612570000001, 55.7104932], [37.6658801, 55.7112054], [37.665012800000014, 55.714052900000006], [37.663946700000004, 55.7174169], [37.6636775, 55.71813200000001], [37.6636206, 55.718452600000006], [37.6635834, 55.719007], [37.663652500000005, 55.7208691], [37.6636425, 55.7219491], [37.6636574, 55.72249930000001], [37.6636784, 55.723068000000005], [37.663675500000004, 55.7245641], [37.663639200000006, 55.7248896], [37.6635975, 55.72522120000001], [37.663410600000006, 55.72600380000001], [37.66312670000001, 55.726758300000014], [37.6630915, 55.726862800000006], [37.66271850000001, 55.7276605], [37.662228600000006, 55.728444700000004], [37.6607618, 55.730601], [37.660690300000006, 55.7307034], [37.6608171, 55.73073430000001], [37.66133510000001, 55.7308446], [37.66301510000001, 55.73117680000001], [37.66339880000001, 55.731250800000005], [37.6636607, 55.7312948], [37.6640891, 55.731389300000004], [37.6644263, 55.7314673], [37.66581080000001, 55.7316354], [37.666240200000004, 55.73153570000001], [37.6668226, 55.73121590000001], [37.6674635, 55.7308639], [37.6676873, 55.7305484], [37.66770390000001, 55.73047820000001], [37.66777080000001, 55.73035470000001], [37.6679637, 55.730037900000006], [37.66817960000001, 55.72970110000001], [37.66867880000001, 55.7288811], [37.669585600000005, 55.727361300000005], [37.669667, 55.7272243], [37.67010030000001, 55.72653770000001], [37.670509700000004, 55.725921500000005], [37.6705808, 55.725825500000006], [37.67071890000001, 55.7258475], [37.6708026, 55.72586220000001], [37.671748900000004, 55.7260477], [37.67221220000001, 55.72614820000001], [37.67256690000001, 55.72622520000001], [37.673768700000004, 55.726485800000006], [37.6775679, 55.72730620000001], [37.678073000000005, 55.72751610000001], [37.67837890000001, 55.727779600000005], [37.67861510000001, 55.7279895], [37.678747900000005, 55.728105700000015], [37.67886, 55.72820370000001], [37.678918300000014, 55.7282645], [37.680567499999995, 55.7276885], [37.680555500000004, 55.72777530000001], [37.6805216, 55.728064800000006], [37.6805072, 55.72815110000001], [37.6804742, 55.72835710000001], [37.6804669, 55.7284045], [37.6815705, 55.72847200000001], [37.681441799999995, 55.72903990000001], [37.6832978, 55.72907010000001], [37.6841025, 55.729583600000005], [37.6840596, 55.73003070000001], [37.6858384, 55.73011320000001], [37.685826999999996, 55.730182500000005], [37.68543290000001, 55.73257670000001], [37.6853636, 55.73299800000001], [37.6856019, 55.73293960000001], [37.686898, 55.732446800000005], [37.68819880000001, 55.73177280000001], [37.69094320000001, 55.73017890000001], [37.69215770000001, 55.72954030000001], [37.6926416, 55.72937180000001], [37.693037200000006, 55.7292916], [37.69331020000001, 55.729277], [37.69360270000001, 55.729290000000006], [37.69370010000001, 55.729302900000015], [37.69395500000001, 55.729526500000006], [37.69450870000001, 55.7302994], [37.69512710000001, 55.7311849], [37.69573590000002, 55.7319971], [37.69610260000001, 55.732470500000005], [37.696606100000004, 55.733125400000006], [37.697067399999995, 55.7337244], [37.69717000000001, 55.733857900000004], [37.69831150000001, 55.73534890000001], [37.698350800000014, 55.73540030000001], [37.69840620000001, 55.73547260000001], [37.698479500000005, 55.7356204], [37.69886220000001, 55.73643620000001], [37.69929030000001, 55.736383800000006], [37.69983530000001, 55.73631690000001], [37.699487399999995, 55.736743100000005], [37.6979194, 55.7395896], [37.6970804, 55.74079090000001], [37.69615690000001, 55.741702700000005], [37.6952841, 55.74231980000001], [37.69370290000001, 55.74317550000001], [37.69230360000001, 55.7438365], [37.692340400000006, 55.7438692], [37.689943, 55.744998200000005], [37.686945900000005, 55.746362600000005], [37.6859699, 55.746770600000005], [37.68487439999999, 55.7473079], [37.6847776, 55.747293], [37.683947399999994, 55.7476928], [37.6832039, 55.7480005], [37.6824447, 55.74827020000001], [37.6815405, 55.74852980000001], [37.6806622, 55.74875000000001], [37.679814900000004, 55.748932300000014], [37.67835980000001, 55.74919290000001], [37.677623499999996, 55.74931890000001], [37.6766426, 55.7494807], [37.6759854, 55.7495862], [37.673106100000005, 55.750050200000004], [37.67232620000001, 55.7502072], [37.671679499999996, 55.7503617], [37.6710524, 55.750556200000005], [37.67053080000001, 55.750748800000004], [37.671075200000004, 55.751153800000004], [37.671852200000004, 55.7518008], [37.672549700000005, 55.7523878], [37.673020300000005, 55.753170700000005], [37.6730467, 55.75369439999999], [37.672941, 55.75400139999999], [37.67270580000001, 55.7544162], [37.6722576, 55.755084499999995], [37.671684899999995, 55.75611620000001], [37.6713575, 55.7566258], [37.67075620000001, 55.7579228], [37.670960900000004, 55.758348000000005], [37.671331200000004, 55.758676200000004], [37.67230010000001, 55.759162700000005], [37.673015400000004, 55.75932890000001], [37.673911700000005, 55.7593699], [37.675127, 55.759311100000005], [37.6764911, 55.759201499999996], [37.679468, 55.7590578], [37.6802155, 55.7590725], [37.680948, 55.7591418], [37.681802499999996, 55.75931230000001], [37.682588, 55.75953560000001], [37.684159300000005, 55.760274100000004], [37.68539030000001, 55.761525600000006], [37.686008300000005, 55.762201600000004], [37.68575080000001, 55.76355380000001], [37.6858452, 55.7639835], [37.68611990000001, 55.76431190000001], [37.68728719999999, 55.76570260000001], [37.68843890000001, 55.76713170000001], [37.6890397, 55.76777390000001], [37.69037860000001, 55.7684836], [37.692198900000015, 55.7694899], [37.69231950000001, 55.76939800000001], [37.69236720000001, 55.76937880000001], [37.69243470000001, 55.76935170000001], [37.692606000000005, 55.769265100000005], [37.6928606, 55.76914020000001], [37.694085, 55.76846930000001], [37.695415300000015, 55.76772090000001], [37.696590500000006, 55.7670617], [37.6968795, 55.766892000000006], [37.69692010000001, 55.76687510000001], [37.6970297, 55.7668304], [37.6970687, 55.766813600000006], [37.6972212, 55.76679530000001], [37.69730260000001, 55.76679330000001], [37.69737560000001, 55.76680220000001], [37.6974858, 55.766837300000006], [37.69754330000001, 55.766878500000004], [37.6976467, 55.76695310000001], [37.69793310000001, 55.76713320000001], [37.6979777, 55.76716090000001], [37.69873640000001, 55.76763230000001], [37.6988894, 55.76773270000001], [37.69894800000001, 55.76777080000001], [37.69919050000001, 55.7679217], [37.69937420000001, 55.768041600000004], [37.7003574, 55.7686994], [37.701798600000004, 55.76958930000001], [37.70251850000001, 55.770029], [37.7027714, 55.77013280000001], [37.703093200000005, 55.770244399999996], [37.7034741, 55.77037120000001], [37.703801399999996, 55.7704617], [37.703946200000004, 55.7704979], [37.7043485, 55.7706065], [37.7046489, 55.7707272], [37.70472590000001, 55.7707746], [37.7048206, 55.77083290000001], [37.705147800000006, 55.7710984], [37.7052894, 55.7711876], [37.70541600000001, 55.77126739999999], [37.7056843, 55.77141220000001], [37.706606900000004, 55.7718407], [37.70737290000001, 55.77221960000001], [37.707638, 55.77233900000001], [37.70833500000001, 55.772685800000005], [37.70897190000001, 55.77300280000001], [37.709551600000005, 55.7732912], [37.7096495, 55.77333990000001], [37.70973270000001, 55.773381300000004], [37.7098662, 55.7734477], [37.710088999999996, 55.773566], [37.7102438, 55.773638000000005], [37.710335400000005, 55.7736842], [37.7104472, 55.7737405], [37.7110554, 55.774064499999994], [37.7116592, 55.7743497], [37.7117867, 55.774418700000005], [37.71188139999999, 55.7744652], [37.712019000000005, 55.77453290000001], [37.7124975, 55.774770000000004], [37.71291320000001, 55.774976], [37.713183300000004, 55.775106400000006], [37.7135246, 55.77525590000001], [37.7136118, 55.77530130000001], [37.7137476, 55.77511290000002], [37.714192700000005, 55.77453270000001], [37.715946200000005, 55.772298000000006], [37.71630270000001, 55.771776300000006], [37.716971300000004, 55.77070090000001], [37.71736739999999, 55.770145500000005], [37.7178392, 55.769589200000006], [37.719612700000006, 55.767679300000005], [37.720086300000006, 55.76713380000001], [37.720389000000004, 55.76673320000001], [37.7206276, 55.76631840000001], [37.7207817, 55.765883300000006], [37.72085310000001, 55.76547030000001], [37.72087330000001, 55.764946300000005], [37.72074490000001, 55.76312290000001], [37.72070510000001, 55.762784], [37.72063190000001, 55.7624647], [37.720471700000004, 55.76202810000001], [37.72024890000001, 55.7616096], [37.7198555, 55.76094330000001], [37.7196735, 55.760629200000004], [37.7184278, 55.758507], [37.71817980000001, 55.75801820000001], [37.7179697, 55.757493], [37.717817399999994, 55.7569832], [37.717713200000006, 55.7564833], [37.7176602, 55.7559645], [37.71768109999999, 55.755507], [37.7177565, 55.7549601], [37.71791520000001, 55.7544051], [37.718132800000014, 55.753880499999994], [37.7183854, 55.753419], [37.71871880000001, 55.75294230000001], [37.719168200000006, 55.75241090000001], [37.719611900000004, 55.7519793], [37.7197448, 55.7518501], [37.72030920000001, 55.751355200000006], [37.72057250000001, 55.7511608], [37.72083980000001, 55.7509773], [37.72136530000001, 55.750635100000004], [37.7218517, 55.75035330000001], [37.722400500000006, 55.7500624], [37.72301500000001, 55.74977260000001], [37.72363280000001, 55.74951550000001], [37.724446300000004, 55.749232400000004], [37.725325200000015, 55.7489665], [37.726535900000016, 55.748647], [37.736188500000004, 55.746090300000006], [37.73659790000001, 55.74597490000001], [37.7374472, 55.74575580000001], [37.73841600000001, 55.745485900000006], [37.739341700000004, 55.745177000000005], [37.7401818, 55.7448321], [37.7410175, 55.7444517], [37.741742300000006, 55.74405230000001], [37.74237390000001, 55.7436661], [37.7430994, 55.743177900000006], [37.7439671, 55.74253980000001], [37.7452873, 55.741390100000004], [37.745944800000004, 55.7408776], [37.746722600000005, 55.7403678], [37.7475092, 55.73994570000001], [37.74839210000001, 55.73953490000001], [37.74935000000001, 55.73915670000001], [37.7504587, 55.73879980000001], [37.751621799999995, 55.738499000000004], [37.7527664, 55.73825810000001], [37.7539775, 55.738048000000006], [37.755363100000004, 55.7378493], [37.75854820000001, 55.73745280000001], [37.7592284, 55.737363900000005], [37.7599826, 55.7372256], [37.760543000000006, 55.73713360000001], [37.76091120000001, 55.7370686], [37.761271300000004, 55.73699280000001], [37.7617576, 55.736857], [37.76220530000001, 55.736707900000006], [37.762636400000005, 55.7365415], [37.765891200000006, 55.734963900000004], [37.76713240000001, 55.73435820000001], [37.767299200000004, 55.7342686], [37.76751900000001, 55.73415430000001], [37.7692666, 55.733253600000005], [37.76996520000001, 55.73290490000001], [37.773852500000004, 55.730906100000006], [37.7741734, 55.730743600000004], [37.7748882, 55.730387], [37.775896700000004, 55.72993910000001], [37.77714280000001, 55.72950600000001], [37.77906290000001, 55.728888700000006], [37.789796, 55.725292900000014], [37.79230710000001, 55.7244619], [37.793718900000016, 55.72397890000001], [37.79677050000001, 55.72289290000001], [37.79911820000002, 55.72210560000001], [37.80081139999999, 55.72153890000001], [37.80480769999999, 55.7202665], [37.808573200000005, 55.718999100000005], [37.812093, 55.717820599999996], [37.81358149999999, 55.71731630000001], [37.816771499999994, 55.7162257], [37.8207278, 55.7148955], [37.8238797, 55.713846], [37.827312400000004, 55.7126833], [37.8339009, 55.710475200000005], [37.8360239, 55.709776000000005], [37.837409199999996, 55.7092892], [37.8413708, 55.7079663], [37.8423714, 55.7076143], [37.8439557, 55.7070257], [37.845551, 55.7064851], [37.8492009, 55.7052667], [37.85234, 55.7041954], [37.853435399999995, 55.7037885], [37.85340899999999, 55.703540200000006], [37.858176, 55.7012543], [37.8573155, 55.7006976], [37.857373599999995, 55.700623300000004], [37.857921299999994, 55.700362600000005], [37.85840699999999, 55.7001245], [37.8565458, 55.69899350000001], [37.85616649999999, 55.698764800000006], [37.858739, 55.697365600000005], [37.8603248, 55.6962697], [37.860812200000005, 55.69590660000001], [37.8640933, 55.693688300000005], [37.8638317, 55.69353910000001], [37.860812800000005, 55.6917604], [37.8607269, 55.6916828], [37.8605004, 55.6914784], [37.8604091, 55.69139560000001], [37.860005300000005, 55.69103090000001], [37.8601871, 55.69093020000001], [37.862316400000005, 55.6897602], [37.8639217, 55.688771700000004], [37.8647451, 55.688264399999994], [37.8647491, 55.688180800000005], [37.8647708, 55.6873542], [37.864792, 55.6873501]]]]}}, {"id": 1282181, "osm_type": "relation", "type": "Feature", "name": "Южный административный округ", "properties": {"ref": "ЮАО", "name": "Южный административный округ", "name:be": "Паўднёвая адміністрацыйная акруга", "name:de": "Südlicher Verwaltungsbezirk", "name:en": "Southern Administrative Okrug", "website": "http://www.uao.mos.ru/", "boundary": "administrative", "wikipedia": "ru:Южный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.792532000000016, 55.62371470000001], [37.78975560000001, 55.62575170000001], [37.786708600000004, 55.63025820000001], [37.78503490000001, 55.633262300000005], [37.784262399999996, 55.63832500000001], [37.783833200000004, 55.6425879], [37.78550690000001, 55.645106600000005], [37.785335300000014, 55.6473346], [37.783446999999995, 55.6485454], [37.77979920000001, 55.64873910000001], [37.76691910000001, 55.645621], [37.76619500000001, 55.6454457], [37.7495868, 55.640626], [37.7453811, 55.6398994], [37.72950240000001, 55.6408925], [37.72903410000001, 55.6408512], [37.726469800000004, 55.6406196], [37.7132784, 55.6394575], [37.69941680000001, 55.642121800000005], [37.694481499999995, 55.6432843], [37.69290610000001, 55.6438288], [37.6889454, 55.6452218], [37.6780449, 55.649944], [37.6745688, 55.651759999999996], [37.672594700000005, 55.653212800000006], [37.6716505, 55.6543508], [37.6715218, 55.655779300000006], [37.6716027, 55.6563638], [37.67238210000001, 55.661982800000004], [37.6732404, 55.66510550000001], [37.67504280000001, 55.6676469], [37.67813270000001, 55.66905080000001], [37.6824243, 55.6706239], [37.6874025, 55.6711564], [37.6907475, 55.6732397], [37.692702300000015, 55.673779], [37.697347, 55.6750645], [37.7003414, 55.6758865], [37.7047617, 55.6773626], [37.7072419, 55.678800200000005], [37.7079299, 55.679100700000006], [37.71195, 55.681319800000004], [37.71237920000001, 55.6846586], [37.712121700000004, 55.688456800000004], [37.70757270000001, 55.693270500000004], [37.694783900000004, 55.69535060000001], [37.68851320000001, 55.69657880000001], [37.684650999999995, 55.69737090000001], [37.679011300000006, 55.69819170000001], [37.674485499999996, 55.69850850000001], [37.67293380000001, 55.69967690000001], [37.670954800000004, 55.700500700000006], [37.6672891, 55.7007415], [37.66735290000001, 55.7012704], [37.6675631, 55.70313900000001], [37.667811, 55.7052824], [37.667430100000004, 55.7065679], [37.6672947, 55.706948100000005], [37.66635590000001, 55.70979500000001], [37.6662648, 55.710097499999996], [37.66612570000001, 55.7104932], [37.6658801, 55.7112054], [37.665012800000014, 55.714052900000006], [37.663946700000004, 55.7174169], [37.6636775, 55.71813200000001], [37.6636206, 55.718452600000006], [37.6635834, 55.719007], [37.663652500000005, 55.7208691], [37.6636425, 55.7219491], [37.6636574, 55.72249930000001], [37.6636784, 55.723068000000005], [37.663675500000004, 55.7245641], [37.663639200000006, 55.7248896], [37.6635975, 55.72522120000001], [37.663410600000006, 55.72600380000001], [37.66312670000001, 55.726758300000014], [37.663009900000006, 55.726751400000005], [37.662852400000006, 55.72673860000001], [37.662717400000005, 55.72672990000001], [37.66239570000001, 55.72670730000001], [37.661988900000004, 55.7266879], [37.6597685, 55.72657820000001], [37.6567176, 55.72637240000001], [37.6562105, 55.7270994], [37.6557668, 55.7276237], [37.6542108, 55.7288214], [37.6522347, 55.728043400000004], [37.6520679, 55.72817180000001], [37.651752200000004, 55.728134300000015], [37.651651199999996, 55.728132600000016], [37.6515535, 55.72814420000001], [37.6511208, 55.72825560000001], [37.6509263, 55.728283600000005], [37.650780399999995, 55.72830460000001], [37.650731900000004, 55.72831700000001], [37.6505231, 55.72837040000001], [37.6503761, 55.72840790000001], [37.6502165, 55.72844870000001], [37.650022, 55.72849840000001], [37.64996, 55.72851420000001], [37.649865, 55.72853850000001], [37.649106700000004, 55.72873220000002], [37.64877880000001, 55.72881600000001], [37.6482494, 55.72895120000001], [37.6479661, 55.729023600000005], [37.6470763, 55.72925090000001], [37.6463847, 55.7294276], [37.646034900000004, 55.729516900000014], [37.6459446, 55.72939970000001], [37.645574200000006, 55.728914900000014], [37.644943, 55.72807680000001], [37.6449111, 55.72801190000001], [37.6448981, 55.7279684], [37.6448798, 55.7278566], [37.64451830000001, 55.7260664], [37.6444388, 55.72567260000001], [37.6443775, 55.72536870000001], [37.6441042, 55.72401500000001], [37.6440761, 55.72387590000001], [37.644066699999996, 55.723828100000006], [37.6440595, 55.72379130000001], [37.64404639999999, 55.72372620000001], [37.6440315, 55.723651600000004], [37.643992100000006, 55.72347570000001], [37.6438198, 55.72262430000001], [37.6437679, 55.72242590000001], [37.64316530000001, 55.72234610000001], [37.64191280000001, 55.72219840000001], [37.641760999999995, 55.72219840000001], [37.6416361, 55.72223860000001], [37.6412598, 55.72246260000001], [37.64072290000001, 55.722670400000005], [37.63995370000001, 55.722897800000005], [37.6398024, 55.722932600000014], [37.639084399999994, 55.72308890000001], [37.6385974, 55.723187100000004], [37.63837270000001, 55.7232216], [37.63815350000001, 55.7232654], [37.637219200000004, 55.72343790000001], [37.636664499999995, 55.723529500000005], [37.6364613, 55.72352930000001], [37.6364114, 55.72337620000001], [37.6364024, 55.72335390000001], [37.636136500000006, 55.72267810000001], [37.63610830000001, 55.72261550000001], [37.635839000000004, 55.72201610000001], [37.63575020000001, 55.72203430000001], [37.6343872, 55.722313800000016], [37.63403230000001, 55.72238660000001], [37.63371530000001, 55.72245410000001], [37.6330891, 55.722584100000006], [37.63153530000001, 55.72218010000001], [37.6314058, 55.72214960000001], [37.631122100000006, 55.722081900000006], [37.63022290000001, 55.7218748], [37.629723000000006, 55.7217654], [37.627892800000005, 55.721364900000005], [37.627627499999996, 55.72133660000001], [37.627199000000005, 55.7212947], [37.626797200000006, 55.721267], [37.62559670000001, 55.7211775], [37.62391430000001, 55.7210145], [37.62381980000001, 55.721004900000004], [37.6235694, 55.72098280000001], [37.62272500000001, 55.72090790000001], [37.62239780000001, 55.720877], [37.6219824, 55.72083510000001], [37.6178953, 55.720296000000005], [37.61777, 55.720280100000004], [37.6175459, 55.72026], [37.617407799999995, 55.7202476], [37.6169636, 55.720207900000005], [37.6156714, 55.720098400000005], [37.615568, 55.72009010000001], [37.61503890000001, 55.72056320000001], [37.6144134, 55.72099570000001], [37.6141718, 55.7210897], [37.6122072, 55.721256800000006], [37.6120046, 55.721274], [37.6111437, 55.7213465], [37.6103207, 55.72141570000001], [37.61017390000001, 55.721428100000004], [37.6100526, 55.72113380000001], [37.609765100000004, 55.72039470000001], [37.609403, 55.7194792], [37.609048200000004, 55.719545200000006], [37.607267099999994, 55.719884199999996], [37.6067042, 55.719990900000006], [37.605387300000004, 55.7202515], [37.605262200000006, 55.72027550000001], [37.60514580000001, 55.7202975], [37.6034349, 55.7206447], [37.602273600000004, 55.720885800000005], [37.6018149, 55.720981], [37.6014907, 55.72104830000001], [37.6014387, 55.7210617], [37.6007004, 55.721256800000006], [37.600469, 55.72131120000001], [37.600379700000005, 55.72134880000001], [37.59812810000001, 55.7198467], [37.5974937, 55.72014180000001], [37.597236800000005, 55.7199632], [37.5968554, 55.720130300000015], [37.5968012, 55.72009310000001], [37.59599300000001, 55.71955590000001], [37.59565690000001, 55.719356600000005], [37.5940838, 55.71832520000001], [37.592564900000006, 55.719146], [37.59261850000001, 55.719405900000005], [37.59297260000001, 55.71957510000001], [37.592818400000006, 55.7196453], [37.592747300000006, 55.7196718], [37.59271460000001, 55.719685999999996], [37.592228500000004, 55.7194285], [37.592132700000015, 55.7188278], [37.5914295, 55.7183866], [37.5913879, 55.71835490000001], [37.59079510000001, 55.717873], [37.590788800000006, 55.7178124], [37.5916661, 55.717458900000004], [37.592504700000006, 55.7170205], [37.5924676, 55.7170011], [37.592544200000006, 55.7169547], [37.59257730000001, 55.716972000000005], [37.592671300000006, 55.7168706], [37.591905700000005, 55.716379100000005], [37.5917207, 55.7164483], [37.5906915, 55.7156866], [37.590503700000006, 55.715745600000005], [37.589951, 55.71533520000001], [37.5879827, 55.7139395], [37.5884454, 55.713762800000005], [37.587912300000006, 55.7133267], [37.587873699999996, 55.7132951], [37.58833610000001, 55.713095900000006], [37.585594, 55.711090999999996], [37.5854794, 55.7111405], [37.5854288, 55.7111634], [37.5853472, 55.7111972], [37.585232000000005, 55.7112481], [37.5852018, 55.7112269], [37.585171, 55.711204099999996], [37.5851014, 55.7112334], [37.583925300000004, 55.7110138], [37.582786399999996, 55.7112279], [37.582266999999995, 55.7110349], [37.582139600000005, 55.7109925], [37.5834012, 55.710042300000005], [37.58422699999999, 55.70951360000001], [37.5853646, 55.7088144], [37.588709, 55.7071405], [37.587697299999995, 55.70655620000001], [37.5874732, 55.7064275], [37.58731290000001, 55.7063416], [37.5875028, 55.70611410000001], [37.587819999999994, 55.7057835], [37.5880849, 55.705490000000005], [37.58845590000001, 55.705077800000005], [37.5890212, 55.7044431], [37.5893432, 55.704081599999995], [37.58984099999999, 55.703506000000004], [37.5909671, 55.70219330000001], [37.59295670000001, 55.699873800000006], [37.59397810000001, 55.698698400000005], [37.594905000000004, 55.697614900000005], [37.5956174, 55.69677810000001], [37.59625260000001, 55.69607190000001], [37.59673320000001, 55.69557360000001], [37.59710230000001, 55.69523500000001], [37.597557200000004, 55.694848], [37.5980616, 55.6943974], [37.59896260000001, 55.693665700000004], [37.59922230000001, 55.693454800000005], [37.5996, 55.693104100000006], [37.600070900000006, 55.69270810000001], [37.600685, 55.692202400000006], [37.601308, 55.691781], [37.6016161, 55.6915807], [37.601975700000004, 55.69153670000001], [37.602605600000004, 55.6912174], [37.603272000000004, 55.69085530000001], [37.6037863, 55.6906298], [37.60373810000001, 55.69052490000001], [37.60351320000001, 55.69034680000001], [37.604015000000004, 55.6900694], [37.6044927, 55.6897973], [37.6047416, 55.689564399999995], [37.60510120000001, 55.689150100000006], [37.60517420000001, 55.6890097], [37.6052442, 55.688807], [37.605285300000006, 55.6884461], [37.60529030000001, 55.688074300000004], [37.605216600000006, 55.6877218], [37.605085, 55.6873154], [37.604983399999995, 55.6869795], [37.604931900000004, 55.6866554], [37.6049148, 55.6863256], [37.6049491, 55.6860546], [37.60502280000001, 55.6857954], [37.6052717, 55.6854176], [37.60547630000001, 55.685186900000005], [37.60571300000001, 55.6849572], [37.6060048, 55.684750300000005], [37.6064314, 55.6845105], [37.606749, 55.6843561], [37.607168, 55.684196], [37.607615900000006, 55.6840609], [37.60812070000001, 55.683945200000004], [37.6086084, 55.683886699999995], [37.6090242, 55.6838718], [37.6093449, 55.68386649999999], [37.609910600000006, 55.683881199999995], [37.6106538, 55.6839671], [37.6113806, 55.6840735], [37.6120809, 55.6841842], [37.612596100000005, 55.6842769], [37.613156100000005, 55.6843777], [37.6142067, 55.684587699999994], [37.61519860000001, 55.6847313], [37.616996300000004, 55.6847717], [37.6183837, 55.6845037], [37.6190041, 55.6843165], [37.618334100000006, 55.683672200000004], [37.617340999999996, 55.683327], [37.6167813, 55.68285530000001], [37.6162201, 55.68214270000001], [37.616035600000004, 55.681913900000005], [37.6158819, 55.681882599999994], [37.61531600000001, 55.68188959999999], [37.6149408, 55.6817682], [37.6147009, 55.681598300000005], [37.614920999999995, 55.680925900000005], [37.614681299999994, 55.68055030000001], [37.6144722, 55.6804385], [37.61414739999999, 55.6803811], [37.61377830000001, 55.679985800000004], [37.613223399999995, 55.6796517], [37.6126655, 55.6792742], [37.6123594, 55.6789646], [37.612013100000006, 55.678810500000004], [37.6117107, 55.678605600000004], [37.6114759, 55.678329500000004], [37.6115062, 55.67809890000001], [37.611544499999994, 55.6779144], [37.6115213, 55.677520300000005], [37.6114229, 55.677319100000005], [37.6112922, 55.6772175], [37.6108973, 55.67714], [37.6104768, 55.677072300000006], [37.6101849, 55.676965800000005], [37.6100305, 55.6768254], [37.609933500000004, 55.67673570000001], [37.6094397, 55.676615500000004], [37.6092478, 55.67647830000001], [37.609122600000006, 55.6764084], [37.60895530000001, 55.6763047], [37.608779600000005, 55.6760004], [37.60853360000001, 55.6758092], [37.6084809, 55.675678600000005], [37.608593000000006, 55.6754577], [37.60859020000001, 55.67533620000001], [37.608379400000004, 55.675234], [37.608101600000005, 55.674955100000005], [37.6077372, 55.674711800000004], [37.60737830000001, 55.6746682], [37.6073744, 55.6744852], [37.6072286, 55.6741797], [37.606914800000006, 55.6738731], [37.606053700000004, 55.673245], [37.60597270000001, 55.673095100000005], [37.6058243, 55.672829300000004], [37.605896300000005, 55.67243510000001], [37.60565280000001, 55.672063300000005], [37.6062279, 55.6716954], [37.60610280000001, 55.6703905], [37.6062794, 55.6688637], [37.6068545, 55.66828290000001], [37.610690999999996, 55.66655420000001], [37.6116352, 55.66612870000001], [37.6111031, 55.66550900000001], [37.6110019, 55.66538890000001], [37.6109239, 55.6652964], [37.61064399999999, 55.6649643], [37.6096956, 55.6652215], [37.6090918, 55.66512020000001], [37.60811620000001, 55.664473], [37.60771280000001, 55.6642794], [37.60764639999999, 55.6640831], [37.6135718, 55.663479300000006], [37.613496999999995, 55.663414200000005], [37.6133979, 55.66333180000001], [37.6131638, 55.66312810000001], [37.613016800000004, 55.6630024], [37.6128693, 55.66287630000001], [37.6113748, 55.661598100000006], [37.61053530000001, 55.6609004], [37.6104101, 55.660807], [37.6102368, 55.6606778], [37.60995990000001, 55.6604497], [37.60811510000001, 55.6589479], [37.60805820000001, 55.6588985], [37.60691530000001, 55.6579233], [37.6058668, 55.6570306], [37.6056662, 55.6568109], [37.605492000000005, 55.656584699999996], [37.605467399999995, 55.6565272], [37.60544590000001, 55.6564483], [37.60544530000001, 55.65622139999999], [37.6054449, 55.6560591], [37.6054648, 55.6547905], [37.6054878, 55.65373220000001], [37.605495700000006, 55.653627699999994], [37.60550070000001, 55.6533743], [37.60550280000001, 55.653044099999995], [37.605504700000004, 55.652922800000006], [37.605533400000006, 55.6510713], [37.60557670000001, 55.649021], [37.6055871, 55.6486206], [37.60561930000001, 55.6473858], [37.60559220000001, 55.645611800000005], [37.605590600000006, 55.6454994], [37.60558880000001, 55.64537980000001], [37.605586200000005, 55.6452014], [37.605580700000004, 55.6448207], [37.605593500000005, 55.6444793], [37.6056462, 55.643340300000006], [37.605729200000006, 55.6413276], [37.5948165, 55.6419459], [37.59451310000001, 55.6419632], [37.5916832, 55.642188600000004], [37.5902236, 55.642397200000005], [37.589415300000006, 55.642579000000005], [37.5865867, 55.643434], [37.5826673, 55.6446348], [37.5803884, 55.64532620000001], [37.5804286, 55.64511100000001], [37.5804124, 55.6449225], [37.5801147, 55.644940999999996], [37.5800959, 55.6448098], [37.5800031, 55.6438219], [37.579362200000006, 55.643615200000006], [37.5792904, 55.6428012], [37.5807067, 55.64233320000001], [37.5820011, 55.6412222], [37.5819117, 55.6409906], [37.5819231, 55.6409], [37.58126179999999, 55.6408951], [37.5816158, 55.63996530000001], [37.5820025, 55.6398242], [37.582119500000005, 55.63973490000001], [37.58215530000001, 55.63965230000001], [37.582056800000004, 55.6395444], [37.5816209, 55.63947530000001], [37.58144769999999, 55.6394871], [37.581490699999996, 55.638960000000004], [37.581907099999995, 55.638691300000005], [37.5822546, 55.638467], [37.58166549999999, 55.6372043], [37.5816659, 55.6372003], [37.5811043, 55.6372784], [37.5808298, 55.6368147], [37.580621799999996, 55.6367698], [37.5805256, 55.6365884], [37.580319700000004, 55.6365675], [37.579844599999994, 55.636022600000004], [37.580594399999995, 55.63591100000001], [37.5801576, 55.635563600000005], [37.5792798, 55.635780700000005], [37.579140800000005, 55.63565930000001], [37.5792056, 55.63555300000001], [37.579058, 55.63540520000001], [37.578797900000005, 55.63535800000001], [37.57813870000001, 55.63473880000001], [37.57778139999999, 55.634698900000004], [37.5775701, 55.634454], [37.577405999999996, 55.634360300000004], [37.5772657, 55.63267690000001], [37.583819999999996, 55.631472800000004], [37.5852426, 55.63148639999999], [37.5858037, 55.6314207], [37.585982900000005, 55.631173000000004], [37.5858754, 55.6308714], [37.5857961, 55.630621399999995], [37.58551030000001, 55.6300194], [37.585395600000005, 55.62979620000001], [37.585259900000004, 55.62953970000001], [37.585284099999996, 55.629399400000004], [37.585146800000004, 55.629200600000004], [37.584588499999995, 55.628969100000006], [37.5841307, 55.628674600000004], [37.58422149999999, 55.62843480000001], [37.5843505, 55.62856280000001], [37.5846721, 55.628476400000004], [37.5848357, 55.6287675], [37.5850272, 55.62872300000001], [37.584917, 55.62834550000001], [37.584740499999995, 55.62792520000001], [37.58444749999999, 55.62800080000001], [37.5840882, 55.627995000000006], [37.5840258, 55.62777890000001], [37.584191399999995, 55.6275846], [37.584348999999996, 55.627641499999996], [37.58462779999999, 55.627740300000006], [37.5846823, 55.62770390000001], [37.5843505, 55.6266836], [37.5842063, 55.62669330000001], [37.584044199999994, 55.6268863], [37.583816399999996, 55.626912300000015], [37.5836354, 55.626329000000005], [37.58344739999999, 55.6262846], [37.5832427, 55.626231100000005], [37.582885399999995, 55.62540390000001], [37.5827831, 55.62516510000001], [37.5824208, 55.624802700000004], [37.5820298, 55.6245849], [37.582354200000005, 55.62436230000001], [37.58198649999999, 55.6242456], [37.5813932, 55.6240714], [37.5817786, 55.6238466], [37.58192639999999, 55.62363620000001], [37.5817208, 55.623388000000006], [37.581881399999986, 55.623353400000006], [37.58182789999999, 55.623246300000005], [37.581544099999995, 55.62303620000001], [37.5816589, 55.62291940000001], [37.582219200000004, 55.623327700000004], [37.58263290000001, 55.6232446], [37.581258399999996, 55.622229100000006], [37.58053520000001, 55.621788900000006], [37.5802913, 55.621781399999996], [37.58011200000001, 55.621701300000005], [37.5799079, 55.621742100000006], [37.5796707, 55.621847599999995], [37.57966749999999, 55.62193860000001], [37.57917090000001, 55.62210940000001], [37.57888, 55.62211900000001], [37.57871480000001, 55.62223630000001], [37.578381300000004, 55.62221390000001], [37.57830800000001, 55.62205200000001], [37.578842800000004, 55.621745100000005], [37.578588800000006, 55.621768800000005], [37.57807890000001, 55.621908000000005], [37.5779349, 55.621739600000005], [37.576920900000005, 55.62196290000001], [37.576397300000004, 55.62175580000001], [37.5759467, 55.6214226], [37.5755604, 55.621022800000006], [37.575056200000006, 55.620544200000005], [37.574745, 55.6200474], [37.5749918, 55.6198233], [37.5756784, 55.6196779], [37.5769766, 55.61930830000001], [37.5773218, 55.6192619], [37.5775513, 55.6192541], [37.577894799999996, 55.619345], [37.5788852, 55.620094900000005], [37.579517100000004, 55.6198313], [37.5804987, 55.6193862], [37.5804221, 55.6193292], [37.5794247, 55.619691399999994], [37.5784625, 55.61875630000001], [37.5759344, 55.6155066], [37.577693399999994, 55.6148622], [37.5780867, 55.614758], [37.577792, 55.6145257], [37.577527399999994, 55.6143282], [37.5746262, 55.6132284], [37.5752291, 55.6126364], [37.575710400000006, 55.612282900000004], [37.575678100000005, 55.6117933], [37.57557560000001, 55.610983499999996], [37.5746859, 55.60881690000001], [37.5742438, 55.60869230000001], [37.5736164, 55.60836080000001], [37.5732883, 55.60830890000001], [37.5719867, 55.60830930000001], [37.571705300000005, 55.60837990000001], [37.570954300000004, 55.60851320000001], [37.56991630000001, 55.6084693], [37.56979830000001, 55.608069300000004], [37.569884099999996, 55.6077178], [37.5698498, 55.60755820000001], [37.5699656, 55.6075292], [37.56990630000001, 55.607370200000005], [37.5698955, 55.607243], [37.570140300000006, 55.607154200000004], [37.571298999999996, 55.60671790000001], [37.57186769999999, 55.605988700000005], [37.573616, 55.60595000000001], [37.5739863, 55.6066513], [37.5742126, 55.6066376], [37.574899599999995, 55.606596], [37.57576220000001, 55.6062573], [37.5778221, 55.604366399999996], [37.5815337, 55.6043463], [37.5817703, 55.6034936], [37.5792964, 55.6010331], [37.5788794, 55.600852100000004], [37.577673399999995, 55.600169900000004], [37.577511300000005, 55.600030100000005], [37.5770423, 55.59952280000001], [37.576714700000004, 55.5992866], [37.5764883, 55.59865370000001], [37.5764301, 55.59815500000001], [37.576663399999994, 55.5978687], [37.580571, 55.5977608], [37.5801979, 55.596898700000004], [37.5802368, 55.59581330000001], [37.578974, 55.59591340000001], [37.5785865, 55.595223600000004], [37.5783666, 55.594821399999994], [37.57817850000001, 55.594213], [37.577913200000005, 55.593625700000004], [37.577868699999996, 55.593164], [37.5775263, 55.59241270000001], [37.577412300000006, 55.59207890000001], [37.5771426, 55.5916951], [37.5771505, 55.5912501], [37.576998700000004, 55.5908576], [37.576924399999996, 55.5902534], [37.576980999999996, 55.589872], [37.5768643, 55.589314900000005], [37.577621699999995, 55.5892199], [37.57748709999999, 55.588717200000005], [37.5772147, 55.58868939999999], [37.576920900000005, 55.5880716], [37.5767866, 55.58786659999999], [37.5770597, 55.58744419999999], [37.5770668, 55.5872209], [37.577476499999996, 55.58698939999999], [37.5774788, 55.5863496], [37.5755047, 55.5839241], [37.5736777, 55.5822096], [37.573827099999995, 55.58203580000001], [37.5738298, 55.581876099999995], [37.573742900000006, 55.5816952], [37.5735811, 55.5814983], [37.57293990000001, 55.5809669], [37.578140100000006, 55.57973220000001], [37.58666439999999, 55.5777032], [37.590093100000004, 55.5768957], [37.591207499999996, 55.576253900000005], [37.5915216, 55.576076], [37.5918517, 55.5757746], [37.59209810000001, 55.57555290000001], [37.5922404, 55.57539990000001], [37.59252530000001, 55.57503560000001], [37.59283010000001, 55.574664799999994], [37.59370080000001, 55.573542], [37.5940996, 55.57293380000001], [37.594987499999995, 55.5717837], [37.59719630000001, 55.5690831], [37.59755320000001, 55.5678882], [37.597467599999995, 55.5668718], [37.598397000000006, 55.5666055], [37.6022876, 55.56637270000001], [37.6016747, 55.5672282], [37.6010966, 55.568416000000006], [37.600977, 55.5690878], [37.6008505, 55.5696672], [37.6006201, 55.5701806], [37.6005971, 55.570570200000006], [37.6005631, 55.57073530000001], [37.6002004, 55.5707011], [37.59995850000001, 55.571007599999994], [37.5994672, 55.5714282], [37.598512100000015, 55.572186900000005], [37.59838080000001, 55.57235590000001], [37.598277200000005, 55.57252090000001], [37.59819430000001, 55.5726662], [37.598152800000015, 55.572756600000005], [37.59809090000001, 55.5728823], [37.5979456, 55.5732936], [37.597858900000006, 55.57351290000001], [37.5978043, 55.573733600000004], [37.597788, 55.57378], [37.5977935, 55.573810800000004], [37.597804599999996, 55.5738788], [37.5978592, 55.5739406], [37.5979576, 55.5740332], [37.598319900000014, 55.57431510000001], [37.5984891, 55.5744262], [37.5994047, 55.5749003], [37.60032030000001, 55.5753745], [37.60319090000001, 55.575234800000004], [37.603685, 55.57521080000001], [37.603833, 55.575100500000005], [37.603959800000005, 55.574967199999996], [37.6040493, 55.5748439], [37.6041802, 55.574759], [37.6040773, 55.5744822], [37.60411230000001, 55.5744262], [37.604162900000006, 55.5744194], [37.6044518, 55.5745826], [37.6044256, 55.5745996], [37.6047305, 55.5747623], [37.6050414, 55.5748937], [37.6054915, 55.575045800000005], [37.6055416, 55.5750574], [37.6064867, 55.575003900000006], [37.611092, 55.5747441], [37.613125200000006, 55.5746309], [37.6178512, 55.5743618], [37.623308400000006, 55.5740243], [37.62843010000001, 55.573723300000005], [37.62850310000001, 55.5737578], [37.630783300000004, 55.573623999999995], [37.63073280000001, 55.5735881], [37.632929700000005, 55.5734593], [37.6329014, 55.5735341], [37.635040200000006, 55.5734491], [37.63503190000001, 55.573336000000005], [37.637766, 55.573175500000005], [37.6424402, 55.572906], [37.6456679, 55.57271270000001], [37.6496649, 55.572478800000006], [37.650003399999996, 55.572419800000006], [37.650235, 55.57233830000001], [37.6503512, 55.5722851], [37.650483099999995, 55.572163], [37.650558800000006, 55.5720054], [37.650533200000005, 55.5719236], [37.650491099999996, 55.571831599999996], [37.6507517, 55.5717346], [37.6508588, 55.5718381], [37.6509785, 55.5719198], [37.65113230000001, 55.5719649], [37.65126849999999, 55.571978800000004], [37.651564799999996, 55.5719909], [37.65178949999999, 55.572002000000005], [37.6522806, 55.5720045], [37.6526468, 55.5720043], [37.6528297, 55.571999399999996], [37.653162800000004, 55.572076100000004], [37.65389699999999, 55.572285], [37.6545428, 55.5722495], [37.655794, 55.572180800000005], [37.65686749999999, 55.572121800000005], [37.6590501, 55.5719243], [37.663428700000004, 55.5716593], [37.66435630000001, 55.571622999999995], [37.66637480000001, 55.57166759999999], [37.6707236, 55.5716683], [37.6760494, 55.5720884], [37.6807341, 55.572917800000006], [37.6830843, 55.5736685], [37.6845672, 55.5740546], [37.6849026, 55.5740905], [37.68518230000001, 55.574120300000004], [37.685544300000004, 55.574108900000006], [37.6858456, 55.5740918], [37.6864906, 55.5740027], [37.6869447, 55.5739271], [37.6873881, 55.5738591], [37.687684899999994, 55.573804599999995], [37.688151000000005, 55.573716700000006], [37.688405100000004, 55.5736596], [37.68875230000001, 55.573579], [37.68915530000001, 55.5734796], [37.6894472, 55.5733804], [37.6896364, 55.573294], [37.6899396, 55.573185200000005], [37.690270600000005, 55.573015700000006], [37.69043330000001, 55.572925100000006], [37.69050580000001, 55.572835600000005], [37.6906464, 55.5726667], [37.690779500000005, 55.5724784], [37.6909246, 55.57231910000001], [37.691745600000004, 55.5728184], [37.691720600000004, 55.5729498], [37.691653200000005, 55.5731273], [37.6916004, 55.573235800000006], [37.691585100000005, 55.573404399999994], [37.69155380000001, 55.5735887], [37.69151840000001, 55.5736788], [37.6914795, 55.5737856], [37.691445, 55.5739206], [37.691408200000005, 55.5741024], [37.6913641, 55.5742621], [37.691369900000005, 55.5744408], [37.691378400000005, 55.5746385], [37.69137990000001, 55.574784799999996], [37.6914206, 55.574943], [37.691468900000004, 55.5750967], [37.6915071, 55.575321200000005], [37.69155930000001, 55.57549590000001], [37.6916011, 55.5756505], [37.6916376, 55.575812500000005], [37.6916838, 55.57599290000001], [37.691762100000005, 55.5761893], [37.691788700000004, 55.576407399999994], [37.69191210000001, 55.5766055], [37.6920914, 55.576752500000005], [37.69223780000001, 55.5768748], [37.69256430000001, 55.5771246], [37.6926914, 55.577159800000004], [37.69643630000001, 55.5785494], [37.69905210000001, 55.57955320000001], [37.699400700000005, 55.5796826], [37.7002971, 55.57999280000001], [37.701058200000006, 55.580272900000004], [37.700929, 55.580395900000006], [37.7032964, 55.5812799], [37.703425900000006, 55.5811787], [37.704748, 55.581656499999994], [37.704644099999996, 55.581748], [37.70621930000001, 55.58233380000001], [37.7075249, 55.5828219], [37.7082445, 55.5830899], [37.710109900000006, 55.58377], [37.711380399999996, 55.5842369], [37.7129495, 55.584802999999994], [37.715551000000005, 55.585741399999996], [37.71599810000001, 55.585893399999996], [37.7161644, 55.586000399999996], [37.719658100000004, 55.5873263], [37.724051, 55.58913330000001], [37.72450370000001, 55.589313100000005], [37.725271400000004, 55.5896181], [37.72634890000001, 55.5900666], [37.72697320000001, 55.590082300000006], [37.72837000000001, 55.589933900000005], [37.72886080000001, 55.5898756], [37.73025230000001, 55.589712500000005], [37.73043690000001, 55.5896722], [37.73063380000001, 55.5895625], [37.7308441, 55.58946769999999], [37.7311442, 55.589309], [37.731278700000004, 55.5892202], [37.7315406, 55.589100300000005], [37.73217350000001, 55.5887973], [37.732804200000004, 55.5891672], [37.73257380000001, 55.589318500000005], [37.73241380000001, 55.589446599999995], [37.73232470000001, 55.5895438], [37.73224220000001, 55.5896419], [37.73213920000001, 55.5897707], [37.732040600000005, 55.5899349], [37.731996, 55.590076800000006], [37.731990700000004, 55.5902632], [37.7319946, 55.59035810000001], [37.731999300000005, 55.5904545], [37.73201420000001, 55.59058530000001], [37.732041800000005, 55.59070990000001], [37.73209860000001, 55.5909144], [37.73216590000001, 55.591102400000004], [37.73223630000001, 55.5912954], [37.73231450000001, 55.59151020000001], [37.73239850000001, 55.591725100000005], [37.732470000000006, 55.59192530000001], [37.73254590000001, 55.59213380000001], [37.7326278, 55.59232430000001], [37.73279620000001, 55.592485200000006], [37.732986700000005, 55.59270080000001], [37.733154600000006, 55.59285280000001], [37.73695020000001, 55.5944435], [37.7411801, 55.596214200000006], [37.74670510000001, 55.598527600000004], [37.7484849, 55.599273700000005], [37.750726300000004, 55.60021330000001], [37.753831399999996, 55.601597399999996], [37.7572893, 55.603425], [37.761089, 55.60551980000001], [37.76227110000001, 55.6061494], [37.7622817, 55.606248900000004], [37.76302810000001, 55.6066095], [37.76505190000001, 55.6077506], [37.766723000000006, 55.6086402], [37.771305500000004, 55.61127439999999], [37.7762494, 55.6140048], [37.780129800000005, 55.6161594], [37.7802524, 55.61610230000001], [37.780725600000004, 55.6163472], [37.7817868, 55.6169076], [37.7820417, 55.61692], [37.782321, 55.6169277], [37.78260890000001, 55.6169218], [37.782723600000004, 55.6169232], [37.7829478, 55.6169111], [37.78331190000001, 55.6168889], [37.7835445, 55.6168749], [37.784748, 55.6168317], [37.785053100000006, 55.6168196], [37.7853895, 55.616807699999995], [37.785768700000006, 55.616797], [37.7862832, 55.616773200000004], [37.786726, 55.616702800000006], [37.78691330000001, 55.6166025], [37.7871217, 55.61684759999999], [37.7871692, 55.6169034], [37.7869697, 55.6170019], [37.786704, 55.6171366], [37.786526900000005, 55.6172308], [37.786248, 55.617286199999995], [37.7860638, 55.61732], [37.7857604, 55.617336], [37.78543990000001, 55.6173478], [37.785170400000005, 55.6173716], [37.7848989, 55.6173901], [37.7846347, 55.617412], [37.784335500000005, 55.617454599999995], [37.7841219, 55.617538100000004], [37.78394290000001, 55.6176209], [37.783773800000006, 55.6177673], [37.78372590000001, 55.6179092], [37.783745800000005, 55.618011100000004], [37.7837977, 55.61811010000001], [37.7838571, 55.61819070000001], [37.7839764, 55.618256], [37.784844799999995, 55.61873610000001], [37.7849689, 55.6186662], [37.7868251, 55.6196597], [37.78835610000001, 55.62037810000001], [37.7882885, 55.6204411], [37.791992400000005, 55.62230690000001], [37.79212720000001, 55.62216920000001], [37.793561000000004, 55.62295970000001], [37.792532000000016, 55.62371470000001]]]]}}, {"id": 1252558, "osm_type": "relation", "type": "Feature", "name": "Северо-Восточный административный округ", "properties": {"ref": "СВАО", "name": "Северо-Восточный административный округ", "name:be": "Паўночна-усходняя адміністрацыйная акруга", "name:de": "Nordöstlicher Verwaltungsbezirk", "name:en": "North-Eastern Administrative Okrug", "website": "http://www.svao.mos.ru/", "boundary": "administrative", "wikipedia": "ru:Северо-Восточный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.73356230000001, 55.8782167], [37.73265790000001, 55.87766489999999], [37.731479, 55.87687939999999], [37.7311964, 55.876766499999995], [37.7310813, 55.87596], [37.7318197, 55.8749452], [37.72983260000001, 55.87466549999999], [37.729479000000005, 55.8743869], [37.72854210000001, 55.874259099999996], [37.72832370000001, 55.874214599999995], [37.728060400000004, 55.874004299999996], [37.7279265, 55.8739005], [37.727549800000006, 55.8739242], [37.727340100000006, 55.8739219], [37.7270819, 55.8738551], [37.72655540000001, 55.8737993], [37.726091800000006, 55.8736398], [37.72425570000001, 55.873008], [37.723628600000005, 55.873201699999996], [37.7236242, 55.87340639999999], [37.7224445, 55.8736321], [37.72173600000001, 55.872983], [37.719053100000004, 55.8722456], [37.71581330000001, 55.8701542], [37.71523210000001, 55.8698022], [37.7111427, 55.8674321], [37.70903510000001, 55.8662524], [37.707699399999996, 55.86551850000001], [37.7079241, 55.86533690000001], [37.707835700000004, 55.865265300000004], [37.707211900000004, 55.8647584], [37.7066141, 55.864285599999995], [37.7066693, 55.8641433], [37.708863900000004, 55.8631979], [37.709115900000015, 55.8625635], [37.709321900000006, 55.861007799999996], [37.705039600000006, 55.8610008], [37.702657900000005, 55.8625577], [37.7019976, 55.86217520000001], [37.70077280000001, 55.8614562], [37.700564, 55.8611218], [37.71047, 55.860735000000005], [37.7149391, 55.8606743], [37.7179213, 55.8606342], [37.718246300000004, 55.8600081], [37.72145630000001, 55.85336449999999], [37.72163930000001, 55.852924099999996], [37.721005000000005, 55.8522056], [37.719405, 55.85142259999999], [37.72010480000001, 55.8505731], [37.71937880000001, 55.85004439999999], [37.718019700000006, 55.84935], [37.7171278, 55.8490573], [37.7140751, 55.8469149], [37.712503100000006, 55.84752749999999], [37.7123877, 55.8474329], [37.712160100000006, 55.8473548], [37.7118986, 55.8473555], [37.7097805, 55.8475429], [37.70551780000001, 55.84786129999999], [37.7035867, 55.848773300000005], [37.69682290000001, 55.8481609], [37.69535410000001, 55.8501993], [37.693963800000006, 55.85180659999999], [37.69415480000001, 55.852229799999996], [37.694248200000004, 55.85244959999999], [37.694256900000006, 55.85247], [37.6942892, 55.8525461], [37.6944997, 55.85302459999999], [37.694675800000006, 55.85340239999999], [37.69277370000001, 55.855166999999994], [37.69243030000001, 55.855330300000006], [37.692634000000005, 55.8555098], [37.692895500000006, 55.855567799999996], [37.693069200000004, 55.8556987], [37.69313320000001, 55.8557966], [37.692521500000005, 55.8561333], [37.691630700000005, 55.856029899999996], [37.690747200000004, 55.85617739999999], [37.69059820000001, 55.85608429999999], [37.690243, 55.8558958], [37.6894096, 55.8559566], [37.6886034, 55.855284899999994], [37.6879813, 55.8555164], [37.6878597, 55.85549159999999], [37.6867899, 55.85477339999999], [37.6867679, 55.8545129], [37.688327900000004, 55.853925999999994], [37.69239160000001, 55.8529525], [37.6918707, 55.852602399999995], [37.6899704, 55.85122309999999], [37.6922264, 55.8503067], [37.6908265, 55.8488919], [37.69021490000001, 55.8481906], [37.69032010000001, 55.8480054], [37.6890669, 55.84728859999999], [37.6888898, 55.847200099999995], [37.6888242, 55.847167299999995], [37.6866194, 55.8459632], [37.6865624, 55.8459342], [37.68584439999999, 55.8455421], [37.685362500000004, 55.845290399999996], [37.6813889, 55.8432125], [37.6802576, 55.8424748], [37.678440300000005, 55.84182339999999], [37.67852870000001, 55.841439099999995], [37.67853310000001, 55.8410399], [37.678457, 55.840689999999995], [37.67829270000001, 55.840343], [37.678009100000004, 55.8399397], [37.67773820000001, 55.8396759], [37.6773835, 55.8393897], [37.6768981, 55.8390943], [37.676316500000006, 55.838821599999996], [37.675689399999996, 55.8386141], [37.67496439999999, 55.838450300000005], [37.6742063, 55.8383472], [37.6735016, 55.83831810000001], [37.6728491, 55.83833620000001], [37.6720878, 55.838407399999994], [37.6707205, 55.838635000000004], [37.6702104, 55.838739600000004], [37.6703805, 55.8376758], [37.6705206, 55.8365488], [37.6706272, 55.8356502], [37.6707673, 55.8345082], [37.6708873, 55.833602], [37.6710273, 55.8325648], [37.671274, 55.83088719999999], [37.671500900000005, 55.829474], [37.6715432, 55.8290195], [37.6715246, 55.8282041], [37.6714947, 55.827552000000004], [37.671461799999996, 55.827231399999995], [37.6712823, 55.826603999999996], [37.67095020000001, 55.825686], [37.670643, 55.8249165], [37.6706062, 55.8248384], [37.670463399999996, 55.8244238], [37.67032270000001, 55.824082], [37.669851900000005, 55.8227895], [37.669246, 55.8215406], [37.66857560000001, 55.8204479], [37.668080800000006, 55.81987709999999], [37.6660698, 55.81746989999999], [37.66310790000001, 55.814045699999994], [37.66280330000001, 55.813698499999994], [37.6600445, 55.81054939999999], [37.65811860000001, 55.8083605], [37.6578185, 55.8080219], [37.654530300000005, 55.804100999999996], [37.6513982, 55.8001096], [37.651155300000006, 55.79905780000001], [37.65101, 55.798707500000006], [37.650983499999995, 55.797832400000004], [37.6511431, 55.796899700000004], [37.651334399999996, 55.79641840000001], [37.6513037, 55.795943400000006], [37.650464799999995, 55.79421220000001], [37.6504231, 55.7938594], [37.6503663, 55.793392300000015], [37.6503095, 55.792919300000015], [37.650451499999996, 55.7916395], [37.6508167, 55.790755800000014], [37.651521499999994, 55.7893694], [37.6501467, 55.789723800000004], [37.64875630000001, 55.79010730000001], [37.6482278, 55.79023810000001], [37.6477311, 55.79038070000001], [37.6469971, 55.7906046], [37.646295200000004, 55.7908878], [37.645527300000005, 55.7912685], [37.64292330000001, 55.793004700000004], [37.640458900000006, 55.79459870000001], [37.638266, 55.795663100000006], [37.6364991, 55.79638870000001], [37.63531980000001, 55.796974000000006], [37.634998, 55.79713380000001], [37.634956, 55.79693970000001], [37.634751800000004, 55.79602220000001], [37.6344484, 55.79461210000001], [37.6344313, 55.7944611], [37.634432100000005, 55.79430000000001], [37.634464699999995, 55.79380230000001], [37.634505600000004, 55.79330620000001], [37.634604599999996, 55.792280700000006], [37.6346377, 55.79189230000001], [37.6340869, 55.7918661], [37.6337764, 55.79185280000001], [37.6335945, 55.7918471], [37.633413600000004, 55.791842900000006], [37.63315130000001, 55.7918425], [37.6328831, 55.7918449], [37.6326466, 55.79185210000001], [37.6324314, 55.7918625], [37.63188939999999, 55.791901100000004], [37.631536700000005, 55.791937000000004], [37.63131310000001, 55.791965700000006], [37.6310795, 55.79200050000001], [37.6306134, 55.79207950000001], [37.63012510000001, 55.79216920000001], [37.62987580000001, 55.79221500000001], [37.629735300000014, 55.79224080000001], [37.62894070000001, 55.79238070000001], [37.62851900000001, 55.79245010000001], [37.62822820000001, 55.7924844], [37.6279594, 55.79250780000001], [37.6246204, 55.7926871], [37.6234441, 55.79274670000001], [37.62236330000001, 55.792797500000006], [37.6213642, 55.79285510000001], [37.619374300000004, 55.79298870000001], [37.61815790000001, 55.79305690000001], [37.617580399999994, 55.7930834], [37.616990200000004, 55.79310570000001], [37.6166833, 55.79311160000001], [37.6163716, 55.793115600000014], [37.6163097, 55.79311600000001], [37.616311, 55.79290340000001], [37.616344399999996, 55.79247000000001], [37.6163542, 55.79230060000001], [37.6164115, 55.79157790000001], [37.6164237, 55.791376500000005], [37.6164262, 55.79133370000001], [37.6164298, 55.79127390000001], [37.616533000000004, 55.789810100000004], [37.6165649, 55.789371300000006], [37.6166213, 55.78861260000001], [37.6166325, 55.788527], [37.6166343, 55.78851360000001], [37.6166361, 55.78850020000001], [37.6166499, 55.7884091], [37.616684799999994, 55.7880673], [37.616700300000005, 55.7878527], [37.6167078, 55.7877945], [37.61675520000001, 55.787261699999995], [37.6167978, 55.7868239], [37.6168202, 55.7864317], [37.616722200000005, 55.7861473], [37.6162701, 55.785381900000004], [37.6162242, 55.7853044], [37.61613390000001, 55.78514990000001], [37.6159444, 55.7848298], [37.6155734, 55.784303900000005], [37.6155275, 55.784075200000004], [37.6155076, 55.7839673], [37.6154776, 55.78388339999999], [37.6152868, 55.783498900000005], [37.6152688, 55.783385100000004], [37.6152667, 55.7832852], [37.615300100000006, 55.7830486], [37.615351700000005, 55.7828366], [37.6152184, 55.7830401], [37.615005000000004, 55.783376700000005], [37.614961099999995, 55.783416200000005], [37.614910200000004, 55.783449399999995], [37.6148355, 55.7834787], [37.614765399999996, 55.783491399999996], [37.614695499999996, 55.7834993], [37.61462949999999, 55.783500000000004], [37.613235100000004, 55.7834256], [37.613147, 55.7834164], [37.6130598, 55.783394], [37.6129804, 55.78335570000001], [37.61293690000001, 55.78330230000001], [37.61281, 55.7829856], [37.6127668, 55.78290630000001], [37.612705600000005, 55.782825900000006], [37.612555400000005, 55.782651800000004], [37.6124492, 55.78254810000001], [37.61231500000001, 55.7825885], [37.611903, 55.78270580000001], [37.61142739999999, 55.7828621], [37.611385399999996, 55.78287580000001], [37.6112969, 55.782904800000004], [37.6109298, 55.7830249], [37.6103666, 55.783196800000006], [37.6097476, 55.783393700000005], [37.609339500000004, 55.7835245], [37.608057800000005, 55.7839618], [37.6079072, 55.784013200000004], [37.6072718, 55.7842317], [37.607109900000005, 55.784282], [37.606794, 55.7843893], [37.6067541, 55.7844048], [37.6066316, 55.7844525], [37.60631820000001, 55.784570800000004], [37.6060018, 55.7846903], [37.6056833, 55.784825399999995], [37.6047906, 55.785237800000004], [37.6046803, 55.785288800000004], [37.6045342, 55.785327], [37.6043485, 55.78533710000001], [37.603876, 55.78531810000001], [37.603725700000005, 55.78530790000001], [37.6035816, 55.785300500000005], [37.6028575, 55.785251200000005], [37.6026849, 55.78523870000001], [37.602225100000005, 55.7852054], [37.602021300000004, 55.785191100000006], [37.6018463, 55.785179500000005], [37.601719900000006, 55.78516890000001], [37.6017035, 55.78521320000001], [37.60168709999999, 55.7852602], [37.6016381, 55.78539000000001], [37.601525900000006, 55.785696200000004], [37.60115580000001, 55.78657230000001], [37.6010966, 55.786711200000006], [37.6008506, 55.787317300000005], [37.600748700000004, 55.7875937], [37.600682, 55.787815900000005], [37.6006105, 55.78802830000001], [37.600416100000004, 55.7886055], [37.60037080000001, 55.788740000000004], [37.600162100000006, 55.7893978], [37.600139000000006, 55.7894771], [37.59990280000001, 55.79030930000001], [37.5998997, 55.79032080000001], [37.5997644, 55.790821300000005], [37.59951720000001, 55.791617200000005], [37.59934520000001, 55.79227500000001], [37.59931390000001, 55.79240480000001], [37.59929580000001, 55.7924817], [37.598291100000004, 55.79239600000001], [37.5972547, 55.79230770000001], [37.5963844, 55.7922464], [37.59613820000001, 55.79223300000001], [37.5958899, 55.79222570000001], [37.595656700000006, 55.79223300000001], [37.59541270000001, 55.792248400000005], [37.5944086, 55.79233170000001], [37.5934651, 55.792421100000006], [37.593311400000005, 55.79242910000001], [37.59278290000001, 55.79243490000001], [37.59223930000001, 55.79243700000001], [37.591731300000006, 55.79243910000001], [37.59017600000001, 55.79243650000001], [37.589969499999995, 55.792432900000016], [37.589934, 55.79243330000001], [37.589762300000004, 55.79242610000001], [37.5894238, 55.792407100000005], [37.5893281, 55.79240670000001], [37.589244199999996, 55.79241170000001], [37.5891654, 55.79242060000001], [37.5889044, 55.79246320000001], [37.58828439999999, 55.79256250000001], [37.5882178, 55.792573800000014], [37.5881801, 55.79258670000001], [37.58815220000001, 55.79259900000001], [37.5881215, 55.79261650000001], [37.5877997, 55.79263660000001], [37.586530100000004, 55.793437600000004], [37.58573320000001, 55.79396030000001], [37.5850046, 55.7943695], [37.5848158, 55.794498600000004], [37.5847379, 55.79456820000001], [37.5846713, 55.794637300000005], [37.5845992, 55.7947215], [37.584531399999996, 55.794808700000004], [37.5844709, 55.794903100000006], [37.584424799999994, 55.79499560000001], [37.584388399999995, 55.79508290000001], [37.5843177, 55.79532260000001], [37.5842913, 55.79550180000001], [37.5841863, 55.79585260000001], [37.5842021, 55.79626230000001], [37.5841136, 55.7972084], [37.5839686, 55.79849430000001], [37.5837205, 55.799932100000014], [37.5835067, 55.801021799999994], [37.5831873, 55.802378000000004], [37.5828408, 55.8037217], [37.582339600000005, 55.8055211], [37.581784299999995, 55.806425499999996], [37.581196999999996, 55.8073742], [37.5806522, 55.80828739999999], [37.58313690000001, 55.808621499999994], [37.5843356, 55.808685399999995], [37.5847301, 55.808682399999995], [37.584401899999996, 55.8088932], [37.5836423, 55.809306], [37.5810542, 55.810506499999995], [37.5804261, 55.810852399999995], [37.5796069, 55.81147839999999], [37.5793077, 55.81180769999999], [37.5791446, 55.8120186], [37.5790441, 55.8121915], [37.578831300000004, 55.81262139999999], [37.5786805, 55.813138900000006], [37.578055400000004, 55.8160549], [37.5778185, 55.81664059999999], [37.577535700000006, 55.817124799999995], [37.5756899, 55.819594499999994], [37.574553200000004, 55.821116100000005], [37.5743079, 55.821533], [37.5741424, 55.8219591], [37.5740221, 55.82239280000001], [37.573948200000004, 55.82279690000001], [37.5736451, 55.829131000000004], [37.573575600000005, 55.830584099999996], [37.573571300000005, 55.83132139999999], [37.5736501, 55.831718900000006], [37.573761499999996, 55.8320855], [37.5738908, 55.832395000000005], [37.5741456, 55.832856], [37.574442499999996, 55.8333046], [37.5750831, 55.8339784], [37.5759673, 55.83469739999999], [37.57611060000001, 55.8348039], [37.5762939, 55.834949699999996], [37.576818800000005, 55.835345800000006], [37.577447899999996, 55.8358898], [37.5778195, 55.836296499999996], [37.57815370000001, 55.8367858], [37.578371100000005, 55.83714139999999], [37.57854820000001, 55.83758769999999], [37.5786411, 55.8379066], [37.578739500000005, 55.8386144], [37.57871920000001, 55.839032200000005], [37.578672600000004, 55.8394438], [37.578493900000005, 55.840036], [37.57821810000001, 55.8406209], [37.5779697, 55.84102119999999], [37.577661199999994, 55.8414303], [37.5760178, 55.8430943], [37.57561810000001, 55.84358399999999], [37.575397900000006, 55.8439287], [37.5749493, 55.8450937], [37.57444139999999, 55.8465657], [37.5738961, 55.848099], [37.5737717, 55.8484763], [37.573671, 55.848794], [37.5733094, 55.849840199999996], [37.5730897, 55.85062439999999], [37.57290580000001, 55.851419799999995], [37.572759000000005, 55.8523622], [37.572678200000006, 55.853206199999995], [37.5726431, 55.8541581], [37.5727074, 55.854734699999995], [37.572785200000006, 55.855241199999995], [37.573442, 55.85687339999999], [37.5741499, 55.85860159999999], [37.5743515, 55.859217699999995], [37.574546399999996, 55.859893099999994], [37.574631499999995, 55.860457], [37.57468139999999, 55.8611375], [37.5746003, 55.86211690000001], [37.574328, 55.863002200000004], [37.573917900000005, 55.8640117], [37.5731862, 55.8657867], [37.57261820000001, 55.8671064], [37.571371, 55.8701818], [37.5704746, 55.8721766], [37.56999880000001, 55.8733055], [37.56928739999999, 55.8749889], [37.5684672, 55.876988399999995], [37.56829090000001, 55.8775903], [37.56816210000001, 55.8782823], [37.567675300000005, 55.882644299999995], [37.5674995, 55.884548099999996], [37.5674047, 55.8873023], [37.56719890000001, 55.8892787], [37.5670561, 55.8901632], [37.56675520000001, 55.8908373], [37.56635860000001, 55.8914168], [37.565896800000004, 55.8919341], [37.56537050000001, 55.8923855], [37.5647478, 55.892842], [37.564058100000004, 55.8932732], [37.563069, 55.893697599999996], [37.5622276, 55.8940409], [37.5590425, 55.89523380000001], [37.5528556, 55.89746099999999], [37.5519785, 55.8977748], [37.5441185, 55.900665599999996], [37.542885399999996, 55.9011424], [37.542371, 55.901367799999996], [37.54166459999999, 55.901731], [37.541169599999996, 55.9020266], [37.5405773, 55.902430800000005], [37.5399434, 55.90288439999999], [37.5392272, 55.903499599999996], [37.5386925, 55.9039985], [37.538279100000004, 55.904464999999995], [37.5380601, 55.9047557], [37.5378582, 55.9050619], [37.5376117, 55.905475300000006], [37.5368567, 55.907063699999995], [37.5370259, 55.9075556], [37.536270900000005, 55.908790800000006], [37.528307000000005, 55.9248134], [37.528101400000004, 55.9252075], [37.527755400000004, 55.92535910000001], [37.5268072, 55.927309300000005], [37.523529, 55.9336424], [37.5210238, 55.938548700000005], [37.520220800000004, 55.9401099], [37.52031950000001, 55.9402018], [37.52025280000001, 55.9403257], [37.519479499999996, 55.9417633], [37.5200417, 55.94184549999999], [37.5237684, 55.94239030000001], [37.5238991, 55.942660399999994], [37.52691430000001, 55.942985], [37.53417230000001, 55.943848599999995], [37.5360043, 55.943938700000004], [37.537116600000004, 55.944070499999995], [37.5376334, 55.944126], [37.5409136, 55.94406119999999], [37.5417652, 55.9439141], [37.5424717, 55.944065499999994], [37.53691330000001, 55.952764499999994], [37.5390466, 55.9531979], [37.540653, 55.953648799999996], [37.5408131, 55.9538551], [37.5420171, 55.9541197], [37.54384939999999, 55.95452699999999], [37.5457473, 55.9551202], [37.5466366, 55.9553455], [37.546618200000005, 55.955505200000005], [37.54789409999999, 55.955686799999995], [37.5482976, 55.9558026], [37.5488594, 55.95470759999999], [37.54941290000001, 55.9545393], [37.549617, 55.954222599999994], [37.55051830000001, 55.9526258], [37.5503268, 55.9522293], [37.5502021, 55.951952999999996], [37.550650999999995, 55.95126929999999], [37.5519657, 55.95129719999999], [37.55192949999999, 55.952138500000004], [37.55167399999999, 55.952238900000005], [37.55176599999999, 55.95348489999999], [37.5525685, 55.95348099999999], [37.552446499999995, 55.9537402], [37.5532001, 55.9539409], [37.555104, 55.9539953], [37.555069399999994, 55.953080299999996], [37.5550637, 55.9516182], [37.557342999999996, 55.9523479], [37.56671980000001, 55.9552772], [37.571685499999994, 55.956865699999994], [37.574200999999995, 55.957698799999996], [37.574387599999994, 55.957658699999996], [37.5753675, 55.9573057], [37.5748503, 55.9563512], [37.57853830000001, 55.9557662], [37.5808138, 55.9541628], [37.5792489, 55.95384749999999], [37.579550700000006, 55.95340709999999], [37.5801616, 55.952195700000004], [37.580156800000005, 55.95188509999999], [37.579534800000005, 55.9496421], [37.5697747, 55.95064709999999], [37.5696869, 55.9506429], [37.568211100000006, 55.950597099999996], [37.567972700000006, 55.950834799999996], [37.56321590000001, 55.9513348], [37.56259310000001, 55.951251199999994], [37.5628807, 55.9480561], [37.563784399999996, 55.9454516], [37.564157900000005, 55.9439378], [37.5643073, 55.942744499999996], [37.564562900000006, 55.9413331], [37.5676136, 55.9411198], [37.5701637, 55.941315100000004], [37.569950600000006, 55.936691399999994], [37.569301100000004, 55.9368658], [37.56773570000001, 55.93671260000001], [37.5662687, 55.936715500000005], [37.565668300000006, 55.933589399999995], [37.5649601, 55.933516600000004], [37.560705500000005, 55.93251500000001], [37.560816200000005, 55.9315662], [37.5609235, 55.9304284], [37.5610379, 55.928822600000004], [37.56095630000001, 55.92803210000001], [37.560808, 55.9273604], [37.560565600000004, 55.926258100000005], [37.5597221, 55.92313520000001], [37.5591492, 55.9211079], [37.55873280000001, 55.9202518], [37.558572500000004, 55.9195801], [37.557997699999994, 55.9167899], [37.557365399999995, 55.914561299999995], [37.5564311, 55.9115799], [37.5559505, 55.9095555], [37.570536700000005, 55.9110169], [37.5741491, 55.9112732], [37.5786006, 55.911434299999996], [37.580350800000005, 55.911291799999994], [37.581026699999995, 55.91118749999999], [37.5838922, 55.9109577], [37.5873513, 55.9103686], [37.588278700000004, 55.911597199999996], [37.58871270000001, 55.9119308], [37.589514300000005, 55.9121479], [37.5898758, 55.9123897], [37.590250600000005, 55.9129617], [37.59073530000001, 55.9136561], [37.590976700000006, 55.91362409999999], [37.5912017, 55.9135942], [37.591058600000004, 55.9132926], [37.59075490000001, 55.9124546], [37.59051130000001, 55.9120901], [37.59037860000001, 55.911839799999996], [37.590393600000006, 55.911531599999996], [37.59050330000001, 55.91129159999999], [37.591076900000004, 55.9107422], [37.59265930000001, 55.9093427], [37.593152900000014, 55.9089479], [37.5949836, 55.9084548], [37.5976623, 55.90768939999999], [37.59912920000001, 55.907277199999996], [37.60925290000001, 55.904560499999995], [37.6156066, 55.9029267], [37.617512500000004, 55.9024203], [37.6195224, 55.9019203], [37.621348700000006, 55.9015146], [37.62555400000001, 55.90068649999999], [37.62751680000001, 55.900313100000005], [37.6292697, 55.899928900000006], [37.6294645, 55.8999335], [37.6306942, 55.899702000000005], [37.63372280000001, 55.899198500000004], [37.637352500000006, 55.8986084], [37.638924900000006, 55.898425100000004], [37.64437230000001, 55.89768459999999], [37.6522572, 55.896778700000006], [37.660422200000006, 55.896061599999996], [37.66263830000001, 55.8958853], [37.668920500000006, 55.895639300000006], [37.66955570000001, 55.89577580000001], [37.6715262, 55.8969207], [37.67182439999999, 55.8972197], [37.6718998, 55.8977344], [37.67261320000001, 55.897806599999996], [37.67272520000001, 55.8974226], [37.672976500000004, 55.89708439999999], [37.6730617, 55.8970422], [37.6741004, 55.896581], [37.674455900000005, 55.8964348], [37.67631860000001, 55.8954547], [37.676838200000006, 55.89531070000001], [37.68221270000001, 55.89511400000001], [37.685245200000004, 55.8950826], [37.688906200000005, 55.8950449], [37.694288, 55.8948748], [37.69872010000001, 55.894336], [37.7030517, 55.8934116], [37.7064346, 55.8922584], [37.707188300000006, 55.89233110000001], [37.7073434, 55.892259100000004], [37.7075862, 55.8921464], [37.7075818, 55.8917661], [37.7112059, 55.8901495], [37.719269399999995, 55.886128], [37.7197072, 55.885910200000005], [37.7202076, 55.885661199999994], [37.721481, 55.8850379], [37.724362400000004, 55.883801899999995], [37.72752380000001, 55.8839511], [37.7300654, 55.885015300000006], [37.73155510000001, 55.8856186], [37.732099500000004, 55.88531580000001], [37.731259200000004, 55.88477399999999], [37.730879300000005, 55.8843958], [37.7303817, 55.8840119], [37.73019300000001, 55.8837839], [37.7300042, 55.8835561], [37.7296648, 55.8830907], [37.72956030000001, 55.8829032], [37.72945330000001, 55.8826173], [37.72923020000001, 55.8820433], [37.7294495, 55.881568699999995], [37.72970170000001, 55.881057199999994], [37.73037500000001, 55.880606699999994], [37.732369600000006, 55.879523], [37.7342601, 55.8786424], [37.73356230000001, 55.8782167]]]]}}, {"id": 2162196, "osm_type": "relation", "type": "Feature", "name": "Центральный административный округ", "properties": {"ref": "ЦАО", "name": "Центральный административный округ", "name:be": "Цэнтральная адміністрацыйная акруга", "name:de": "Zentraler Verwaltungsbezirk", "name:en": "Central Administrative Okrug", "name:ru": "Центральный административный округ", "boundary": "administrative", "wikipedia": "ru:Центральный административный округ Москвы", "omkte:code": "0100", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU", "contact:website": "http://cao.mos.ru/"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.7133277, 55.77547930000001], [37.7126807, 55.77617120000001], [37.710931200000005, 55.77800070000001], [37.71043, 55.778449200000004], [37.70991970000001, 55.7788745], [37.709336500000006, 55.779284499999996], [37.708789800000005, 55.779622700000004], [37.7082977, 55.7799071], [37.7077419, 55.780160800000004], [37.707126800000005, 55.7803837], [37.706092600000005, 55.780737200000004], [37.7052497, 55.7809935], [37.704491399999995, 55.7811858], [37.704302000000006, 55.7812394], [37.7031812, 55.7815238], [37.70252970000001, 55.781654499999995], [37.7018967, 55.7817704], [37.7012436, 55.7818505], [37.7006114, 55.781891099999996], [37.699982600000006, 55.781911900000004], [37.699901200000006, 55.7819144], [37.699517500000006, 55.7819679], [37.69938590000001, 55.7819686], [37.6967864, 55.78201620000001], [37.696335300000015, 55.7819443], [37.692601700000004, 55.781956300000004], [37.692249800000006, 55.78184469999999], [37.6888219, 55.781905], [37.685998100000006, 55.7825234], [37.6826668, 55.783163], [37.67830880000001, 55.7840196], [37.6757476, 55.78453030000001], [37.675093000000004, 55.784683199999996], [37.674579, 55.7847878], [37.674071, 55.7848912], [37.67227870000001, 55.7852207], [37.667289399999994, 55.78612030000001], [37.6638545, 55.786773000000004], [37.66254000000001, 55.7870345], [37.661058800000006, 55.787333800000006], [37.6600296, 55.787523900000004], [37.6555977, 55.788380800000006], [37.651521499999994, 55.7893694], [37.6501467, 55.789723800000004], [37.64875630000001, 55.79010730000001], [37.6482278, 55.79023810000001], [37.6477311, 55.79038070000001], [37.6469971, 55.7906046], [37.646295200000004, 55.7908878], [37.645527300000005, 55.7912685], [37.64292330000001, 55.793004700000004], [37.640458900000006, 55.79459870000001], [37.638266, 55.795663100000006], [37.6364991, 55.79638870000001], [37.63531980000001, 55.796974000000006], [37.634998, 55.79713380000001], [37.634956, 55.79693970000001], [37.634751800000004, 55.79602220000001], [37.6344484, 55.79461210000001], [37.6344313, 55.7944611], [37.634432100000005, 55.79430000000001], [37.634464699999995, 55.79380230000001], [37.634505600000004, 55.79330620000001], [37.634604599999996, 55.792280700000006], [37.6346377, 55.79189230000001], [37.6340869, 55.7918661], [37.6337764, 55.79185280000001], [37.6335945, 55.7918471], [37.633413600000004, 55.791842900000006], [37.63315130000001, 55.7918425], [37.6328831, 55.7918449], [37.6326466, 55.79185210000001], [37.6324314, 55.7918625], [37.63188939999999, 55.791901100000004], [37.631536700000005, 55.791937000000004], [37.63131310000001, 55.791965700000006], [37.6310795, 55.79200050000001], [37.6306134, 55.79207950000001], [37.63012510000001, 55.79216920000001], [37.62987580000001, 55.79221500000001], [37.629735300000014, 55.79224080000001], [37.62894070000001, 55.79238070000001], [37.62851900000001, 55.79245010000001], [37.62822820000001, 55.7924844], [37.6279594, 55.79250780000001], [37.6246204, 55.7926871], [37.6234441, 55.79274670000001], [37.62236330000001, 55.792797500000006], [37.6213642, 55.79285510000001], [37.619374300000004, 55.79298870000001], [37.61815790000001, 55.79305690000001], [37.617580399999994, 55.7930834], [37.616990200000004, 55.79310570000001], [37.6166833, 55.79311160000001], [37.6163716, 55.793115600000014], [37.6163097, 55.79311600000001], [37.616311, 55.79290340000001], [37.616344399999996, 55.79247000000001], [37.6163542, 55.79230060000001], [37.6164115, 55.79157790000001], [37.6164237, 55.791376500000005], [37.6164262, 55.79133370000001], [37.6164298, 55.79127390000001], [37.616533000000004, 55.789810100000004], [37.6165649, 55.789371300000006], [37.6166213, 55.78861260000001], [37.6166325, 55.788527], [37.6166343, 55.78851360000001], [37.6166361, 55.78850020000001], [37.6166499, 55.7884091], [37.616684799999994, 55.7880673], [37.616700300000005, 55.7878527], [37.6167078, 55.7877945], [37.61675520000001, 55.787261699999995], [37.6167978, 55.7868239], [37.6168202, 55.7864317], [37.616722200000005, 55.7861473], [37.6162701, 55.785381900000004], [37.6162242, 55.7853044], [37.61613390000001, 55.78514990000001], [37.6159444, 55.7848298], [37.6155734, 55.784303900000005], [37.6155275, 55.784075200000004], [37.6155076, 55.7839673], [37.6154776, 55.78388339999999], [37.6152868, 55.783498900000005], [37.6152688, 55.783385100000004], [37.6152667, 55.7832852], [37.615300100000006, 55.7830486], [37.615351700000005, 55.7828366], [37.6152184, 55.7830401], [37.615005000000004, 55.783376700000005], [37.614961099999995, 55.783416200000005], [37.614910200000004, 55.783449399999995], [37.6148355, 55.7834787], [37.614765399999996, 55.783491399999996], [37.614695499999996, 55.7834993], [37.61462949999999, 55.783500000000004], [37.613235100000004, 55.7834256], [37.613147, 55.7834164], [37.6130598, 55.783394], [37.6129804, 55.78335570000001], [37.61293690000001, 55.78330230000001], [37.61281, 55.7829856], [37.6127668, 55.78290630000001], [37.612705600000005, 55.782825900000006], [37.612555400000005, 55.782651800000004], [37.6124492, 55.78254810000001], [37.61231500000001, 55.7825885], [37.611903, 55.78270580000001], [37.61142739999999, 55.7828621], [37.611385399999996, 55.78287580000001], [37.6112969, 55.782904800000004], [37.6109298, 55.7830249], [37.6103666, 55.783196800000006], [37.6097476, 55.783393700000005], [37.609339500000004, 55.7835245], [37.608057800000005, 55.7839618], [37.6079072, 55.784013200000004], [37.6072718, 55.7842317], [37.607109900000005, 55.784282], [37.606794, 55.7843893], [37.6067541, 55.7844048], [37.6066316, 55.7844525], [37.60631820000001, 55.784570800000004], [37.6060018, 55.7846903], [37.6056833, 55.784825399999995], [37.6047906, 55.785237800000004], [37.6046803, 55.785288800000004], [37.6045342, 55.785327], [37.6043485, 55.78533710000001], [37.603876, 55.78531810000001], [37.603725700000005, 55.78530790000001], [37.6035816, 55.785300500000005], [37.6028575, 55.785251200000005], [37.6026849, 55.78523870000001], [37.602225100000005, 55.7852054], [37.602021300000004, 55.785191100000006], [37.6018463, 55.785179500000005], [37.601719900000006, 55.78516890000001], [37.6017035, 55.78521320000001], [37.60168709999999, 55.7852602], [37.6016381, 55.78539000000001], [37.601525900000006, 55.785696200000004], [37.60115580000001, 55.78657230000001], [37.6010966, 55.786711200000006], [37.6008506, 55.787317300000005], [37.600748700000004, 55.7875937], [37.600682, 55.787815900000005], [37.6006105, 55.78802830000001], [37.600416100000004, 55.7886055], [37.60037080000001, 55.788740000000004], [37.600162100000006, 55.7893978], [37.600139000000006, 55.7894771], [37.59990280000001, 55.79030930000001], [37.5998997, 55.79032080000001], [37.5997644, 55.790821300000005], [37.59951720000001, 55.791617200000005], [37.59934520000001, 55.79227500000001], [37.59931390000001, 55.79240480000001], [37.59929580000001, 55.7924817], [37.598291100000004, 55.79239600000001], [37.5972547, 55.79230770000001], [37.5963844, 55.7922464], [37.59613820000001, 55.79223300000001], [37.5958899, 55.79222570000001], [37.595656700000006, 55.79223300000001], [37.59541270000001, 55.792248400000005], [37.5944086, 55.79233170000001], [37.5934651, 55.792421100000006], [37.593311400000005, 55.79242910000001], [37.59278290000001, 55.79243490000001], [37.59223930000001, 55.79243700000001], [37.591731300000006, 55.79243910000001], [37.59017600000001, 55.79243650000001], [37.589969499999995, 55.792432900000016], [37.589934, 55.79243330000001], [37.589762300000004, 55.79242610000001], [37.5894238, 55.792407100000005], [37.5893281, 55.79240670000001], [37.589244199999996, 55.79241170000001], [37.5891654, 55.79242060000001], [37.5889044, 55.79246320000001], [37.58828439999999, 55.79256250000001], [37.5882178, 55.792573800000014], [37.5881801, 55.79258670000001], [37.58815220000001, 55.79259900000001], [37.5881215, 55.79261650000001], [37.5877997, 55.79263660000001], [37.588229, 55.792363400000006], [37.588633300000005, 55.79205660000001], [37.588492300000006, 55.7916718], [37.58832090000001, 55.79115660000001], [37.588179100000005, 55.79073970000001], [37.58803030000001, 55.79023000000001], [37.58786899999999, 55.7897054], [37.5876763, 55.788639], [37.587562999999996, 55.78805690000001], [37.587417099999996, 55.7874755], [37.5869906, 55.785952400000006], [37.586912000000005, 55.785683399999996], [37.5868408, 55.785415500000006], [37.5867925, 55.7851914], [37.5865608, 55.7843862], [37.58644449999999, 55.783981399999995], [37.5863873, 55.783779800000005], [37.586339900000006, 55.7835794], [37.586238900000005, 55.7832467], [37.5861245, 55.7828912], [37.5860669, 55.782700500000004], [37.585958500000004, 55.78237990000001], [37.585846399999994, 55.782059100000005], [37.5856655, 55.7816102], [37.5854437, 55.781015200000006], [37.58519590000001, 55.7804825], [37.58511420000001, 55.780342700000006], [37.58499, 55.78015370000001], [37.5847927, 55.779866399999996], [37.584574499999995, 55.7796766], [37.58406359999999, 55.7792697], [37.5839104, 55.77915550000001], [37.5837773, 55.779063900000004], [37.5834176, 55.77881620000001], [37.5832531, 55.77870540000001], [37.5830726, 55.77859900000001], [37.582664599999994, 55.77836930000001], [37.5825612, 55.778310900000015], [37.58245590000001, 55.778245500000004], [37.5822436, 55.77811160000001], [37.58201820000001, 55.7779681], [37.5818157, 55.7778304], [37.581451699999995, 55.777616200000004], [37.581306999999995, 55.7775371], [37.581095499999996, 55.7774318], [37.5799897, 55.776927], [37.578099900000005, 55.7761477], [37.577459999999995, 55.77594030000001], [37.5767285, 55.77575240000001], [37.575993600000004, 55.775608000000005], [37.57523260000001, 55.77552080000001], [37.57368699999999, 55.7754834], [37.5731175, 55.77547070000001], [37.5710802, 55.77542580000001], [37.56691730000001, 55.774996], [37.5591717, 55.7742227], [37.5555062, 55.7738439], [37.5519166, 55.77340830000001], [37.5496059, 55.773217700000004], [37.5480891, 55.77315130000001], [37.5463871, 55.77310550000001], [37.544433999999995, 55.772989], [37.5433979, 55.772791700000006], [37.541863199999995, 55.77240630000001], [37.540570100000004, 55.7719534], [37.538963300000006, 55.771128600000004], [37.5379231, 55.7703665], [37.5372797, 55.76970500000001], [37.536633200000004, 55.769065100000006], [37.5362433, 55.767379700000006], [37.536061, 55.76610390000001], [37.5347273, 55.76619800000001], [37.534662, 55.766001300000006], [37.534622399999996, 55.76590110000001], [37.5342927, 55.76539250000001], [37.5341492, 55.76510420000001], [37.5338649, 55.764884599999995], [37.53357520000001, 55.764711000000005], [37.53311250000001, 55.764356500000005], [37.5322807, 55.763480900000005], [37.532118900000015, 55.76337100000001], [37.531822, 55.763223200000006], [37.5288475, 55.76197510000001], [37.52834000000001, 55.76175800000001], [37.5268841, 55.76113520000001], [37.52677870000001, 55.7610847], [37.5264245, 55.760923700000006], [37.52561230000001, 55.7604868], [37.5250671, 55.76010800000001], [37.524388, 55.7598784], [37.5242852, 55.7598459], [37.52256220000001, 55.7616884], [37.5219435, 55.761509000000004], [37.521830900000005, 55.7614838], [37.5218019, 55.761462800000004], [37.521731100000004, 55.761439800000005], [37.5216603, 55.761416700000005], [37.5215895, 55.761393700000006], [37.52151860000001, 55.76137060000001], [37.5211675, 55.7612401], [37.52097290000001, 55.76112270000001], [37.5203849, 55.7608975], [37.5199265, 55.76072190000001], [37.5192742, 55.760470100000006], [37.5166317, 55.7594597], [37.5156656, 55.759089599999996], [37.5139298, 55.7584219], [37.5145394, 55.7580891], [37.516299, 55.7568334], [37.5176723, 55.7546358], [37.5181443, 55.753210900000006], [37.518502700000006, 55.7525846], [37.5202286, 55.750022200000004], [37.52036030000001, 55.7498517], [37.5220496, 55.747583399999996], [37.52252080000001, 55.7472106], [37.5236375, 55.746327300000004], [37.52556870000001, 55.74533690000001], [37.527972000000005, 55.744612200000006], [37.5324042, 55.744396300000005], [37.5367267, 55.7446364], [37.5403745, 55.7454577], [37.543550200000006, 55.7465205], [37.549043399999995, 55.748984300000004], [37.554535200000004, 55.751436399999996], [37.557561699999994, 55.7523904], [37.56017830000001, 55.7530784], [37.5640208, 55.7535974], [37.5678832, 55.75335580000001], [37.570801499999995, 55.752727900000004], [37.572059900000006, 55.752019700000005], [37.5730331, 55.751472], [37.5740201, 55.75033690000001], [37.5744922, 55.7488635], [37.5744493, 55.746327300000004], [37.574133800000006, 55.745453600000005], [37.573891399999994, 55.744708900000006], [37.5730331, 55.7436943], [37.56832670000001, 55.73855250000001], [37.56575030000001, 55.736401], [37.563632600000005, 55.735095400000006], [37.559062499999996, 55.733068700000004], [37.553034499999995, 55.729946600000005], [37.5488288, 55.728424200000006], [37.5477856, 55.72806810000001], [37.545220300000004, 55.72719130000001], [37.5449026, 55.72705570000001], [37.5430747, 55.72556630000001], [37.54186349999999, 55.724039600000005], [37.54118149999999, 55.722055800000014], [37.541081199999994, 55.72012510000001], [37.5418853, 55.7175946], [37.543330700000006, 55.715617200000004], [37.5459418, 55.71368699999999], [37.54851590000001, 55.712262800000005], [37.552896999999994, 55.710972600000005], [37.5568729, 55.710342600000004], [37.5592321, 55.7102802], [37.5609954, 55.710337800000005], [37.565400600000004, 55.7107574], [37.569610100000006, 55.7116173], [37.574928, 55.713117700000005], [37.5776083, 55.7142058], [37.5794176, 55.71295560000001], [37.5816353, 55.711348], [37.582139600000005, 55.7109925], [37.582266999999995, 55.7110349], [37.582786399999996, 55.7112279], [37.583925300000004, 55.7110138], [37.5851014, 55.7112334], [37.585171, 55.711204099999996], [37.5852018, 55.7112269], [37.585232000000005, 55.7112481], [37.5853472, 55.7111972], [37.5854288, 55.7111634], [37.5854794, 55.7111405], [37.585594, 55.711090999999996], [37.58833610000001, 55.713095900000006], [37.587873699999996, 55.7132951], [37.587912300000006, 55.7133267], [37.5884454, 55.713762800000005], [37.5879827, 55.7139395], [37.589951, 55.71533520000001], [37.590503700000006, 55.715745600000005], [37.5906915, 55.7156866], [37.5917207, 55.7164483], [37.591905700000005, 55.716379100000005], [37.592671300000006, 55.7168706], [37.59257730000001, 55.716972000000005], [37.592544200000006, 55.7169547], [37.5924676, 55.7170011], [37.592504700000006, 55.7170205], [37.5916661, 55.717458900000004], [37.590788800000006, 55.7178124], [37.59079510000001, 55.717873], [37.5913879, 55.71835490000001], [37.5914295, 55.7183866], [37.592132700000015, 55.7188278], [37.592228500000004, 55.7194285], [37.59271460000001, 55.719685999999996], [37.592747300000006, 55.7196718], [37.592818400000006, 55.7196453], [37.59297260000001, 55.71957510000001], [37.59261850000001, 55.719405900000005], [37.592564900000006, 55.719146], [37.5940838, 55.71832520000001], [37.59565690000001, 55.719356600000005], [37.59599300000001, 55.71955590000001], [37.5968012, 55.72009310000001], [37.5968554, 55.720130300000015], [37.597236800000005, 55.7199632], [37.5974937, 55.72014180000001], [37.59812810000001, 55.7198467], [37.600379700000005, 55.72134880000001], [37.600469, 55.72131120000001], [37.6007004, 55.721256800000006], [37.6014387, 55.7210617], [37.6014907, 55.72104830000001], [37.6018149, 55.720981], [37.602273600000004, 55.720885800000005], [37.6034349, 55.7206447], [37.60514580000001, 55.7202975], [37.605262200000006, 55.72027550000001], [37.605387300000004, 55.7202515], [37.6067042, 55.719990900000006], [37.607267099999994, 55.719884199999996], [37.609048200000004, 55.719545200000006], [37.609403, 55.7194792], [37.609765100000004, 55.72039470000001], [37.6100526, 55.72113380000001], [37.61017390000001, 55.721428100000004], [37.6103207, 55.72141570000001], [37.6111437, 55.7213465], [37.6120046, 55.721274], [37.6122072, 55.721256800000006], [37.6141718, 55.7210897], [37.6144134, 55.72099570000001], [37.61503890000001, 55.72056320000001], [37.615568, 55.72009010000001], [37.6156714, 55.720098400000005], [37.6169636, 55.720207900000005], [37.617407799999995, 55.7202476], [37.6175459, 55.72026], [37.61777, 55.720280100000004], [37.6178953, 55.720296000000005], [37.6219824, 55.72083510000001], [37.62239780000001, 55.720877], [37.62272500000001, 55.72090790000001], [37.6235694, 55.72098280000001], [37.62381980000001, 55.721004900000004], [37.62391430000001, 55.7210145], [37.62559670000001, 55.7211775], [37.626797200000006, 55.721267], [37.627199000000005, 55.7212947], [37.627627499999996, 55.72133660000001], [37.627892800000005, 55.721364900000005], [37.629723000000006, 55.7217654], [37.63022290000001, 55.7218748], [37.631122100000006, 55.722081900000006], [37.6314058, 55.72214960000001], [37.63153530000001, 55.72218010000001], [37.6330891, 55.722584100000006], [37.63371530000001, 55.72245410000001], [37.63403230000001, 55.72238660000001], [37.6343872, 55.722313800000016], [37.63575020000001, 55.72203430000001], [37.635839000000004, 55.72201610000001], [37.63610830000001, 55.72261550000001], [37.636136500000006, 55.72267810000001], [37.6364024, 55.72335390000001], [37.6364114, 55.72337620000001], [37.6364613, 55.72352930000001], [37.636664499999995, 55.723529500000005], [37.637219200000004, 55.72343790000001], [37.63815350000001, 55.7232654], [37.63837270000001, 55.7232216], [37.6385974, 55.723187100000004], [37.639084399999994, 55.72308890000001], [37.6398024, 55.722932600000014], [37.63995370000001, 55.722897800000005], [37.64072290000001, 55.722670400000005], [37.6412598, 55.72246260000001], [37.6416361, 55.72223860000001], [37.641760999999995, 55.72219840000001], [37.64191280000001, 55.72219840000001], [37.64316530000001, 55.72234610000001], [37.6437679, 55.72242590000001], [37.6438198, 55.72262430000001], [37.643992100000006, 55.72347570000001], [37.6440315, 55.723651600000004], [37.64404639999999, 55.72372620000001], [37.6440595, 55.72379130000001], [37.644066699999996, 55.723828100000006], [37.6440761, 55.72387590000001], [37.6441042, 55.72401500000001], [37.6443775, 55.72536870000001], [37.6444388, 55.72567260000001], [37.64451830000001, 55.7260664], [37.6448798, 55.7278566], [37.6448981, 55.7279684], [37.6449111, 55.72801190000001], [37.644943, 55.72807680000001], [37.645574200000006, 55.728914900000014], [37.6459446, 55.72939970000001], [37.646034900000004, 55.729516900000014], [37.6463847, 55.7294276], [37.6470763, 55.72925090000001], [37.6479661, 55.729023600000005], [37.6482494, 55.72895120000001], [37.64877880000001, 55.72881600000001], [37.649106700000004, 55.72873220000002], [37.649865, 55.72853850000001], [37.64996, 55.72851420000001], [37.650022, 55.72849840000001], [37.6502165, 55.72844870000001], [37.6503761, 55.72840790000001], [37.6505231, 55.72837040000001], [37.650731900000004, 55.72831700000001], [37.650780399999995, 55.72830460000001], [37.6509263, 55.728283600000005], [37.6511208, 55.72825560000001], [37.6515535, 55.72814420000001], [37.651651199999996, 55.728132600000016], [37.651752200000004, 55.728134300000015], [37.6520679, 55.72817180000001], [37.6522347, 55.728043400000004], [37.6542108, 55.7288214], [37.6557668, 55.7276237], [37.6562105, 55.7270994], [37.6567176, 55.72637240000001], [37.6597685, 55.72657820000001], [37.661988900000004, 55.7266879], [37.66239570000001, 55.72670730000001], [37.662717400000005, 55.72672990000001], [37.662852400000006, 55.72673860000001], [37.663009900000006, 55.726751400000005], [37.66312670000001, 55.726758300000014], [37.6630915, 55.726862800000006], [37.66271850000001, 55.7276605], [37.662228600000006, 55.728444700000004], [37.6607618, 55.730601], [37.660690300000006, 55.7307034], [37.6608171, 55.73073430000001], [37.66133510000001, 55.7308446], [37.66301510000001, 55.73117680000001], [37.66339880000001, 55.731250800000005], [37.6636607, 55.7312948], [37.6640891, 55.731389300000004], [37.6644263, 55.7314673], [37.66581080000001, 55.7316354], [37.666240200000004, 55.73153570000001], [37.6668226, 55.73121590000001], [37.6674635, 55.7308639], [37.6676873, 55.7305484], [37.66770390000001, 55.73047820000001], [37.66777080000001, 55.73035470000001], [37.6679637, 55.730037900000006], [37.66817960000001, 55.72970110000001], [37.66867880000001, 55.7288811], [37.669585600000005, 55.727361300000005], [37.669667, 55.7272243], [37.67010030000001, 55.72653770000001], [37.670509700000004, 55.725921500000005], [37.6705808, 55.725825500000006], [37.67071890000001, 55.7258475], [37.6708026, 55.72586220000001], [37.671748900000004, 55.7260477], [37.67221220000001, 55.72614820000001], [37.67256690000001, 55.72622520000001], [37.673768700000004, 55.726485800000006], [37.6775679, 55.72730620000001], [37.678073000000005, 55.72751610000001], [37.67837890000001, 55.727779600000005], [37.67861510000001, 55.7279895], [37.678747900000005, 55.728105700000015], [37.67886, 55.72820370000001], [37.678918300000014, 55.7282645], [37.680567499999995, 55.7276885], [37.680555500000004, 55.72777530000001], [37.6805216, 55.728064800000006], [37.6805072, 55.72815110000001], [37.6804742, 55.72835710000001], [37.6804669, 55.7284045], [37.6815705, 55.72847200000001], [37.681441799999995, 55.72903990000001], [37.6832978, 55.72907010000001], [37.6841025, 55.729583600000005], [37.6840596, 55.73003070000001], [37.6858384, 55.73011320000001], [37.685826999999996, 55.730182500000005], [37.68543290000001, 55.73257670000001], [37.6853636, 55.73299800000001], [37.6856019, 55.73293960000001], [37.686898, 55.732446800000005], [37.68819880000001, 55.73177280000001], [37.69094320000001, 55.73017890000001], [37.69215770000001, 55.72954030000001], [37.6926416, 55.72937180000001], [37.693037200000006, 55.7292916], [37.69331020000001, 55.729277], [37.69360270000001, 55.729290000000006], [37.69370010000001, 55.729302900000015], [37.69395500000001, 55.729526500000006], [37.69450870000001, 55.7302994], [37.69512710000001, 55.7311849], [37.69573590000002, 55.7319971], [37.69610260000001, 55.732470500000005], [37.696606100000004, 55.733125400000006], [37.697067399999995, 55.7337244], [37.69717000000001, 55.733857900000004], [37.69831150000001, 55.73534890000001], [37.698350800000014, 55.73540030000001], [37.69840620000001, 55.73547260000001], [37.698479500000005, 55.7356204], [37.69886220000001, 55.73643620000001], [37.69929030000001, 55.736383800000006], [37.69983530000001, 55.73631690000001], [37.699487399999995, 55.736743100000005], [37.6979194, 55.7395896], [37.6970804, 55.74079090000001], [37.69615690000001, 55.741702700000005], [37.6952841, 55.74231980000001], [37.69370290000001, 55.74317550000001], [37.69230360000001, 55.7438365], [37.692340400000006, 55.7438692], [37.689943, 55.744998200000005], [37.686945900000005, 55.746362600000005], [37.6859699, 55.746770600000005], [37.68487439999999, 55.7473079], [37.6847776, 55.747293], [37.683947399999994, 55.7476928], [37.6832039, 55.7480005], [37.6824447, 55.74827020000001], [37.6815405, 55.74852980000001], [37.6806622, 55.74875000000001], [37.679814900000004, 55.748932300000014], [37.67835980000001, 55.74919290000001], [37.677623499999996, 55.74931890000001], [37.6766426, 55.7494807], [37.6759854, 55.7495862], [37.673106100000005, 55.750050200000004], [37.67232620000001, 55.7502072], [37.671679499999996, 55.7503617], [37.6710524, 55.750556200000005], [37.67053080000001, 55.750748800000004], [37.671075200000004, 55.751153800000004], [37.671852200000004, 55.7518008], [37.672549700000005, 55.7523878], [37.673020300000005, 55.753170700000005], [37.6730467, 55.75369439999999], [37.672941, 55.75400139999999], [37.67270580000001, 55.7544162], [37.6722576, 55.755084499999995], [37.671684899999995, 55.75611620000001], [37.6713575, 55.7566258], [37.67075620000001, 55.7579228], [37.670960900000004, 55.758348000000005], [37.671331200000004, 55.758676200000004], [37.67230010000001, 55.759162700000005], [37.673015400000004, 55.75932890000001], [37.673911700000005, 55.7593699], [37.675127, 55.759311100000005], [37.6764911, 55.759201499999996], [37.679468, 55.7590578], [37.6802155, 55.7590725], [37.680948, 55.7591418], [37.681802499999996, 55.75931230000001], [37.682588, 55.75953560000001], [37.684159300000005, 55.760274100000004], [37.68539030000001, 55.761525600000006], [37.686008300000005, 55.762201600000004], [37.68575080000001, 55.76355380000001], [37.6858452, 55.7639835], [37.68611990000001, 55.76431190000001], [37.68728719999999, 55.76570260000001], [37.68843890000001, 55.76713170000001], [37.6890397, 55.76777390000001], [37.69037860000001, 55.7684836], [37.692198900000015, 55.7694899], [37.69231950000001, 55.76939800000001], [37.69236720000001, 55.76937880000001], [37.69243470000001, 55.76935170000001], [37.692606000000005, 55.769265100000005], [37.6928606, 55.76914020000001], [37.694085, 55.76846930000001], [37.695415300000015, 55.76772090000001], [37.696590500000006, 55.7670617], [37.6968795, 55.766892000000006], [37.69692010000001, 55.76687510000001], [37.6970297, 55.7668304], [37.6970687, 55.766813600000006], [37.6972212, 55.76679530000001], [37.69730260000001, 55.76679330000001], [37.69737560000001, 55.76680220000001], [37.6974858, 55.766837300000006], [37.69754330000001, 55.766878500000004], [37.6976467, 55.76695310000001], [37.69793310000001, 55.76713320000001], [37.6979777, 55.76716090000001], [37.69873640000001, 55.76763230000001], [37.6988894, 55.76773270000001], [37.69894800000001, 55.76777080000001], [37.69919050000001, 55.7679217], [37.69937420000001, 55.768041600000004], [37.7003574, 55.7686994], [37.701798600000004, 55.76958930000001], [37.70251850000001, 55.770029], [37.7027714, 55.77013280000001], [37.703093200000005, 55.770244399999996], [37.7034741, 55.77037120000001], [37.703801399999996, 55.7704617], [37.703946200000004, 55.7704979], [37.7043485, 55.7706065], [37.7046489, 55.7707272], [37.70472590000001, 55.7707746], [37.7048206, 55.77083290000001], [37.705147800000006, 55.7710984], [37.7052894, 55.7711876], [37.70541600000001, 55.77126739999999], [37.7056843, 55.77141220000001], [37.706606900000004, 55.7718407], [37.70737290000001, 55.77221960000001], [37.707638, 55.77233900000001], [37.70833500000001, 55.772685800000005], [37.70897190000001, 55.77300280000001], [37.709551600000005, 55.7732912], [37.7096495, 55.77333990000001], [37.70973270000001, 55.773381300000004], [37.7098662, 55.7734477], [37.710088999999996, 55.773566], [37.7102438, 55.773638000000005], [37.710335400000005, 55.7736842], [37.7104472, 55.7737405], [37.7110554, 55.774064499999994], [37.7116592, 55.7743497], [37.7117867, 55.774418700000005], [37.71188139999999, 55.7744652], [37.712019000000005, 55.77453290000001], [37.7124975, 55.774770000000004], [37.71291320000001, 55.774976], [37.713183300000004, 55.775106400000006], [37.7135246, 55.77525590000001], [37.7133277, 55.77547930000001]]]]}}, {"id": 446092, "osm_type": "relation", "type": "Feature", "name": "Северо-Западный административный округ", "properties": {"ref": "СЗАО", "name": "Северо-Западный административный округ", "name:be": "Паўночна-заходняя адміністрацыйная акруга", "name:de": "Nordwestlicher Verwaltungsbezirk", "name:en": "North-Western Administrative Okrug", "boundary": "administrative", "wikipedia": "ru:Северо-Западный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU", "contact:website": "http://www.szao.mos.ru/"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.521830900000005, 55.7614838], [37.5218019, 55.761462800000004], [37.521731100000004, 55.761439800000005], [37.5216603, 55.761416700000005], [37.5215895, 55.761393700000006], [37.52151860000001, 55.76137060000001], [37.5211675, 55.7612401], [37.52097290000001, 55.76112270000001], [37.5203849, 55.7608975], [37.5199265, 55.76072190000001], [37.5192742, 55.760470100000006], [37.5166317, 55.7594597], [37.5156656, 55.759089599999996], [37.5139298, 55.7584219], [37.51166409999999, 55.7596587], [37.505827599999996, 55.7617836], [37.5042827, 55.762532100000016], [37.50295230000001, 55.763401300000005], [37.50106399999999, 55.7643671], [37.49814580000001, 55.76550190000001], [37.49751620000001, 55.7656864], [37.4960858, 55.76610540000001], [37.492051800000006, 55.767360800000006], [37.489715800000006, 55.767959600000005], [37.487180599999995, 55.76819410000001], [37.4845108, 55.76817000000001], [37.481918900000004, 55.76797690000001], [37.4800361, 55.76771280000001], [37.4794184, 55.7675454], [37.4788659, 55.7673434], [37.4784216, 55.7670545], [37.4780555, 55.76669230000001], [37.47708699999999, 55.76552560000001], [37.476388, 55.764510400000006], [37.476173100000004, 55.76299090000001], [37.476173100000004, 55.76171120000001], [37.476773900000005, 55.75690590000001], [37.476731, 55.7559641], [37.4765165, 55.75458749999999], [37.476173100000004, 55.752293200000004], [37.4757869, 55.7512305], [37.475143200000005, 55.749878], [37.4741561, 55.74850120000001], [37.472782800000004, 55.7472693], [37.4710233, 55.74610990000001], [37.4673755, 55.7440325], [37.4648006, 55.7428971], [37.4617965, 55.741858300000004], [37.459135700000004, 55.7412061], [37.45531630000001, 55.740602100000004], [37.4525268, 55.740602100000004], [37.4492652, 55.741133600000005], [37.446518600000005, 55.741858300000004], [37.4444587, 55.7426072], [37.44248459999999, 55.743573500000004], [37.439738000000006, 55.74521610000001], [37.4373777, 55.7464239], [37.436690999999996, 55.74710030000001], [37.4363477, 55.7478732], [37.4366052, 55.74871860000001], [37.436979, 55.749251900000004], [37.437376300000004, 55.7496855], [37.439221599999996, 55.75053090000001], [37.442182800000005, 55.7513038], [37.4455712, 55.752098800000006], [37.4488347, 55.7528978], [37.453083299999996, 55.753887999999996], [37.455443599999995, 55.75478149999999], [37.4576323, 55.75582], [37.45960639999999, 55.7571482], [37.461838, 55.7588385], [37.463425900000004, 55.76019070000001], [37.4645205, 55.762383400000004], [37.4645693, 55.76269580000001], [37.464584599999995, 55.76279400000001], [37.4646628, 55.76329530000001], [37.464561499999995, 55.76430680000001], [37.4642718, 55.765227900000006], [37.463990100000004, 55.76577130000001], [37.46293970000001, 55.76695050000001], [37.46037890000001, 55.76907570000001], [37.4552656, 55.7741771], [37.45303, 55.775693700000005], [37.45064309999999, 55.7768688], [37.449683799999995, 55.77714], [37.448829399999994, 55.7772765], [37.44811970000001, 55.777308000000005], [37.4473534, 55.7772534], [37.4454867, 55.7768773], [37.443640099999996, 55.776332300000014], [37.439357900000005, 55.775217600000005], [37.4362176, 55.7744065], [37.4341209, 55.7741996], [37.4307464, 55.774173000000005], [37.428843300000004, 55.7742825], [37.4256268, 55.7745234], [37.4210255, 55.7749416], [37.4169486, 55.77532780000001], [37.41429169999999, 55.77543550000001], [37.412185, 55.77552090000001], [37.4100321, 55.775665000000004], [37.4085801, 55.77576220000001], [37.4001204, 55.771272200000006], [37.3997447, 55.7712515], [37.3982596, 55.77117690000001], [37.397342200000004, 55.771095900000006], [37.394868499999994, 55.771203], [37.390933600000004, 55.7710465], [37.386765999999994, 55.7708554], [37.383374499999995, 55.7716755], [37.380406099999995, 55.771578100000006], [37.37108049999999, 55.770896300000004], [37.3702608, 55.77136230000001], [37.37026159999999, 55.773026900000005], [37.3688853, 55.77303830000001], [37.368919600000005, 55.77393620000001], [37.3689417, 55.7748313], [37.3689624, 55.77573010000001], [37.368967399999995, 55.7766275], [37.368988300000005, 55.7775255], [37.368993100000004, 55.778423700000005], [37.3689692, 55.779323600000005], [37.3689945, 55.7802212], [37.3690717, 55.78272590000001], [37.369199300000005, 55.7835235], [37.369275300000005, 55.783832700000005], [37.369347499999996, 55.784399900000004], [37.36935530000001, 55.7844458], [37.36941290000001, 55.784844899999996], [37.370091599999995, 55.7863746], [37.37048969999999, 55.787415300000006], [37.3706009, 55.7876924], [37.370622, 55.7877908], [37.3706192, 55.78791880000001], [37.37060099999999, 55.78819190000001], [37.3705437, 55.78832260000001], [37.3704513, 55.788433600000005], [37.3703118, 55.7885664], [37.370051499999995, 55.788777100000004], [37.3698721, 55.78891050000001], [37.36917390000001, 55.7894487], [37.3687664, 55.78973520000001], [37.36835620000001, 55.7899745], [37.36726469999999, 55.790358900000015], [37.36784439999999, 55.791361], [37.3680686, 55.791324800000005], [37.3683071, 55.7912815], [37.368581, 55.7912416], [37.3688535, 55.791251100000004], [37.369193100000004, 55.7912839], [37.3694903, 55.79130000000001], [37.3698347, 55.791318900000014], [37.370150800000005, 55.79134520000001], [37.3704322, 55.79137310000001], [37.3707554, 55.791408700000005], [37.3710367, 55.791450600000005], [37.37126129999999, 55.7914878], [37.371541099999995, 55.7915274], [37.371854199999994, 55.7915714], [37.372152400000004, 55.7916076], [37.3724795, 55.791659], [37.3727668, 55.79171180000001], [37.3729604, 55.791765100000006], [37.373180999999995, 55.791828200000005], [37.37342149999999, 55.791904], [37.373602, 55.79197070000001], [37.373866899999996, 55.79206370000001], [37.37402339999999, 55.792142300000016], [37.3742282, 55.79224130000001], [37.37448119999999, 55.79236350000001], [37.3752637, 55.79316240000001], [37.376020999999994, 55.79395260000001], [37.3767784, 55.79474290000001], [37.3777139, 55.79572000000001], [37.380231599999995, 55.79834790000001], [37.381726099999995, 55.79991800000001], [37.38180639999999, 55.7998945], [37.382317900000004, 55.8004493], [37.382370800000004, 55.8005066], [37.382756300000004, 55.800924499999994], [37.382885099999996, 55.801122], [37.3830393, 55.801297299999995], [37.38353, 55.8018128], [37.384479299999995, 55.8030063], [37.38447539999999, 55.8030104], [37.384653799999995, 55.8032365], [37.3859537, 55.8051878], [37.386785499999995, 55.8069524], [37.386708, 55.8069658], [37.3865231, 55.807001899999996], [37.386306999999995, 55.807062699999996], [37.386179999999996, 55.8071079], [37.386044299999995, 55.807220599999994], [37.3859825, 55.807309399999994], [37.3859492, 55.80744459999999], [37.3859926, 55.807585399999994], [37.3860223, 55.80776099999999], [37.3860597, 55.8079233], [37.386092999999995, 55.8080807], [37.386134399999996, 55.8082315], [37.386175900000005, 55.808411], [37.3862228, 55.80857], [37.3862501, 55.8087495], [37.38616939999999, 55.8087962], [37.3860556, 55.8088709], [37.385845599999996, 55.8088987], [37.38561, 55.808928200000004], [37.384948099999995, 55.8090119], [37.3850513, 55.8093072], [37.3851849, 55.809296399999994], [37.38528759999999, 55.8092925], [37.38535590000001, 55.80929], [37.3854506, 55.80928639999999], [37.3857106, 55.809279399999994], [37.385722200000004, 55.8092829], [37.3861685, 55.8098155], [37.3865342, 55.809870399999994], [37.386669999999995, 55.80986909999999], [37.38688479999999, 55.80985449999999], [37.387224999999994, 55.8098226], [37.387559599999996, 55.8097886], [37.38789049999999, 55.8097622], [37.389138700000004, 55.813671199999995], [37.39011120000001, 55.816749099999996], [37.3901437, 55.81684359999999], [37.3910795, 55.81980849999999], [37.3922545, 55.82351370000001], [37.392985700000004, 55.826775600000005], [37.3930197, 55.826918500000005], [37.393696, 55.8291697], [37.39391870000001, 55.829862], [37.3937807, 55.8298621], [37.3937442, 55.8298768], [37.393705700000005, 55.8298791], [37.3936526, 55.8298756], [37.3935881, 55.8298767], [37.3935435, 55.829884699999994], [37.393500800000005, 55.8298937], [37.3933145, 55.829903800000004], [37.3932252, 55.829900300000006], [37.393130000000006, 55.8299048], [37.393050900000006, 55.829918500000005], [37.392931100000006, 55.8299434], [37.3928076, 55.8299616], [37.39271240000001, 55.8299774], [37.392625200000005, 55.829978600000004], [37.392554200000006, 55.829976200000004], [37.3925015, 55.8299796], [37.392371700000005, 55.8300057], [37.3922704, 55.8300022], [37.3921872, 55.8299976], [37.39213670000001, 55.8299997], [37.392090100000004, 55.8300054], [37.3920292, 55.83002139999999], [37.3919562, 55.8300292], [37.39188949999999, 55.8300429], [37.3918202, 55.8300485], [37.3916786, 55.830049599999995], [37.391573, 55.8300541], [37.3913035, 55.830059399999996], [37.39111510000001, 55.830073], [37.390979200000004, 55.83008769999999], [37.390934, 55.83008769999999], [37.39089, 55.83008759999999], [37.3906164, 55.830101], [37.3905657, 55.83011820000001], [37.3904765, 55.8301432], [37.3903894, 55.8301597], [37.39031020000001, 55.8301636], [37.390117700000005, 55.8301862], [37.389965499999995, 55.8302009], [37.38983999999999, 55.830214399999996], [37.3897791, 55.8302178], [37.3897366, 55.8302053], [37.389679799999996, 55.8301915], [37.3895987, 55.830188], [37.38941439999999, 55.8301912], [37.3891856, 55.8302002], [37.388986599999996, 55.830211399999996], [37.3889492, 55.830216], [37.3888955, 55.8302227], [37.3888326, 55.8302397], [37.388739300000005, 55.83026699999999], [37.3886116, 55.8302932], [37.38846149999999, 55.8303216], [37.3883217, 55.8303465], [37.3881772, 55.8303777], [37.3880743, 55.8304], [37.3879263, 55.8304181], [37.3875168, 55.83048149999999], [37.38740719999999, 55.8304963], [37.3873525, 55.830493999999995], [37.3873201, 55.83048699999999], [37.38727139999999, 55.830489299999996], [37.38720649999999, 55.8305007], [37.3871092, 55.830524499999996], [37.3870382, 55.8305312], [37.38698959999999, 55.8305267], [37.3869086, 55.83051520000001], [37.38684169999999, 55.8305095], [37.38680299999999, 55.83051390000001], [37.3867301, 55.8305344], [37.38668349999999, 55.830534300000004], [37.38664099999999, 55.8305263], [37.3865905, 55.8305286], [37.3865516, 55.8305468], [37.386523399999994, 55.8305525], [37.38648059999999, 55.8305524], [37.3864159, 55.830548900000004], [37.38622949999999, 55.830573900000005], [37.386002399999995, 55.8306125], [37.385692, 55.8306395], [37.3854286, 55.8306599], [37.3853273, 55.830664299999995], [37.385025399999996, 55.8306823], [37.384745599999995, 55.8306888], [37.3845349, 55.8306852], [37.384405099999995, 55.830696499999995], [37.384318900000004, 55.83068599999999], [37.38421459999999, 55.8306952], [37.3841438, 55.8306883], [37.38405649999999, 55.830682499999995], [37.3839511, 55.83068469999999], [37.383797099999995, 55.83068339999999], [37.3837119, 55.83068899999999], [37.3836227, 55.8307004], [37.383499199999996, 55.830707], [37.38338759999999, 55.8307115], [37.3833655, 55.8307116], [37.3833269, 55.8307047], [37.383267999999994, 55.8307091], [37.3832336, 55.830708], [37.383172900000005, 55.8306931], [37.3829398, 55.8306951], [37.3827232, 55.830669799999995], [37.3825773, 55.8306651], [37.3824597, 55.8306582], [37.3823786, 55.8306586], [37.38226699999999, 55.8306591], [37.3820562, 55.83065439999999], [37.38196119999999, 55.8306554], [37.38185369999999, 55.830647299999995], [37.38170769999999, 55.8306541], [37.38162869999999, 55.83067449999999], [37.3815659, 55.830680099999995], [37.38148469999999, 55.83068469999999], [37.3813551, 55.83066049999999], [37.38129429999999, 55.830651399999994], [37.3812153, 55.83066149999999], [37.3811768, 55.8306639], [37.3811505, 55.8306557], [37.3811119, 55.8306421], [37.3809682, 55.8306168], [37.38078169999999, 55.8306006], [37.3807068, 55.830590300000004], [37.3806198, 55.8305697], [37.38056699999999, 55.8305685], [37.380526399999994, 55.8305741], [37.380483899999994, 55.8305775], [37.380435399999996, 55.8305775], [37.380352300000006, 55.8305625], [37.38028549999999, 55.830556800000004], [37.3801901, 55.830553300000005], [37.3801436, 55.830545300000004], [37.38008759999999, 55.8305355], [37.3799375, 55.830666099999995], [37.37596, 55.82971390000001], [37.3731062, 55.8290306], [37.36891610000001, 55.8280237], [37.367281299999995, 55.82740139999999], [37.365873, 55.826481099999995], [37.3635376, 55.8243612], [37.3626071, 55.8231668], [37.362157200000006, 55.822036700000005], [37.3603401, 55.8224401], [37.359778399999996, 55.822498800000005], [37.358924699999996, 55.822887699999995], [37.35758429999999, 55.82519030000001], [37.35688259999999, 55.8265268], [37.3563561, 55.8266578], [37.35606149999999, 55.8266241], [37.35604429999999, 55.8266314], [37.3540129, 55.8263994], [37.354017999999996, 55.826390200000006], [37.353997799999995, 55.8263879], [37.35423399999999, 55.8260018], [37.35460409999999, 55.825337000000005], [37.35492469999999, 55.824895399999996], [37.3563725, 55.8226601], [37.354296899999994, 55.822374700000005], [37.354146199999995, 55.82235510000001], [37.354605899999996, 55.821760399999995], [37.352312100000006, 55.82128449999999], [37.34973, 55.822027399999996], [37.3491556, 55.82222530000001], [37.3501037, 55.823059900000004], [37.35129109999999, 55.8241247], [37.35158859999999, 55.8243916], [37.350966299999996, 55.8245869], [37.3497145, 55.826373700000005], [37.3491006, 55.82657570000001], [37.3480391, 55.8264068], [37.3453344, 55.8260746], [37.345129, 55.8259601], [37.34482349999999, 55.826066999999995], [37.34469849999999, 55.82627], [37.34799399999999, 55.828514500000004], [37.3485673, 55.8290754], [37.3486509, 55.83071520000001], [37.34813580000001, 55.8310258], [37.3483297, 55.8314157], [37.348727399999994, 55.8322154], [37.34766679999999, 55.8324008], [37.3444563, 55.832962], [37.3439355, 55.8330958], [37.3418339, 55.8341519], [37.342195200000006, 55.8344188], [37.3422458, 55.8343991], [37.342387099999996, 55.834402499999996], [37.343629799999995, 55.8354112], [37.344025699999996, 55.835722800000006], [37.344111399999996, 55.835822900000004], [37.3450013, 55.8364662], [37.344960699999994, 55.8364942], [37.344976599999995, 55.8365196], [37.344735, 55.836651499999995], [37.344700499999995, 55.8366757], [37.34454169999999, 55.8367571], [37.3430569, 55.83756749999999], [37.3431003, 55.8375947], [37.342708800000004, 55.8377731], [37.342231399999996, 55.838018000000005], [37.3413531, 55.838511800000006], [37.340409799999996, 55.839012200000006], [37.340502, 55.8393234], [37.340782499999996, 55.8402701], [37.341026199999995, 55.840282499999994], [37.34104439999999, 55.84028339999999], [37.3449221, 55.8404798], [37.3457808, 55.8404782], [37.346962399999995, 55.840477299999996], [37.347365999999994, 55.840441899999995], [37.3484957, 55.8424367], [37.3492301, 55.84386399999999], [37.3467717, 55.84425399999999], [37.3428857, 55.84483999999999], [37.3384462, 55.8450384], [37.335042900000005, 55.8452412], [37.333003999999995, 55.845284899999996], [37.332920300000005, 55.8452958], [37.332861199999996, 55.8453665], [37.3328449, 55.845423499999995], [37.3328406, 55.8454588], [37.332846499999995, 55.8454863], [37.3328502, 55.8455764], [37.3327972, 55.8456573], [37.332726, 55.845710800000006], [37.3326365, 55.8457575], [37.332585800000004, 55.8457779], [37.33251280000001, 55.8457904], [37.3324519, 55.8458052], [37.332413300000006, 55.8458062], [37.3323607, 55.845800399999995], [37.332306, 55.8457764], [37.33221280000001, 55.845758000000004], [37.3321419, 55.8457705], [37.332095, 55.8458012], [37.3320685, 55.84584449999999], [37.3320561, 55.8459073], [37.3320437, 55.8459483], [37.3320456, 55.8459825], [37.332061499999995, 55.8460578], [37.3320996, 55.8461411], [37.3321076, 55.846195900000005], [37.3320912, 55.8462222], [37.3320687, 55.84626539999999], [37.3320767, 55.846299599999995], [37.332101, 55.846315700000005], [37.332224599999996, 55.8463432], [37.332266999999995, 55.8463661], [37.33231520000001, 55.846426599999994], [37.3323416, 55.8464563], [37.332384, 55.84648599999999], [37.3324254, 55.846515700000005], [37.3324366, 55.8465335], [37.3324638, 55.84655], [37.3324852, 55.846557499999996], [37.3325277, 55.8465621], [37.332549900000004, 55.8465701], [37.3325611, 55.846575800000004], [37.332564, 55.846585], [37.332562, 55.846606099999995], [37.332566, 55.8466152], [37.3325802, 55.846621999999996], [37.3325984, 55.84662779999999], [37.3326186, 55.84662949999999], [37.3326591, 55.8466307], [37.3326734, 55.8466336], [37.3327574, 55.8466713], [37.3327776, 55.846683899999995], [37.3328028, 55.846701599999996], [37.3328262, 55.846710200000004], [37.3328403, 55.8467113], [37.3328525, 55.8467096], [37.33288099999999, 55.84669769999999], [37.332903200000004, 55.8466921], [37.3329378, 55.846688099999994], [37.33295290000001, 55.846688099999994], [37.332967, 55.8466921], [37.3330085, 55.8467081], [37.3330268, 55.846711], [37.3330401, 55.846711], [37.3330725, 55.8467066], [37.33308159999999, 55.8467066], [37.3330997, 55.8467185], [37.3331048, 55.8467288], [37.3331037, 55.846744799999996], [37.33308639999999, 55.8467761], [37.3330863, 55.846783699999996], [37.3330963, 55.8467921], [37.333110600000005, 55.846799499999996], [37.33313690000001, 55.84680639999999], [37.333168300000004, 55.8468127], [37.3331774, 55.8468167], [37.333180399999996, 55.846820799999996], [37.333181399999994, 55.84682709999999], [37.33318739999999, 55.8468373], [37.333237, 55.8468721], [37.333239999999996, 55.846877799999994], [37.3332338, 55.8469029], [37.333229599999996, 55.8469377], [37.3332346, 55.846952], [37.3332427, 55.8469628], [37.3332437, 55.8469748], [37.333249599999995, 55.84698449999999], [37.3332619, 55.8469902], [37.333273999999996, 55.8469909], [37.3332932, 55.846988499999995], [37.333318600000005, 55.84698399999999], [37.333342900000005, 55.846982999999994], [37.33338139999999, 55.8469859], [37.3333996, 55.8469858], [37.3334301, 55.8469928], [37.3334482, 55.8470002], [37.33346349999999, 55.847008699999996], [37.3334756, 55.847019599999996], [37.33348159999999, 55.847031099999995], [37.33348159999999, 55.84704299999999], [37.3334785, 55.8470527], [37.3334683, 55.84706119999999], [37.333445, 55.8470726], [37.333429699999996, 55.84708169999999], [37.3334256, 55.84708969999999], [37.333424699999995, 55.84709539999999], [37.3334347, 55.8471115], [37.3334326, 55.8471194], [37.3334101, 55.8471438], [37.3334101, 55.847148999999995], [37.3334132, 55.8471536], [37.333423399999994, 55.8471558], [37.333443599999995, 55.847156999999996], [37.333467899999995, 55.8471542], [37.3335085, 55.8471451], [37.333556200000004, 55.8471298], [37.3335886, 55.847122999999996], [37.333614, 55.8471219], [37.3336354, 55.847123599999996], [37.33366169999999, 55.84712939999999], [37.3337071, 55.847147699999994], [37.3337435, 55.84716939999999], [37.3337497, 55.8471785], [37.3337536, 55.84720709999999], [37.3337627, 55.8472173], [37.333778900000006, 55.847228199999996], [37.333794, 55.8472356], [37.3338324, 55.84724769999999], [37.3338628, 55.84727099999999], [37.333891099999995, 55.84729739999999], [37.3339021, 55.8473037], [37.33397, 55.847312800000005], [37.334005499999996, 55.8473163], [37.3340208, 55.8473192], [37.3340339, 55.8473232], [37.33404399999999, 55.8473283], [37.3340581, 55.847345499999996], [37.3340753, 55.8473547], [37.33407939999999, 55.84736039999999], [37.334081299999994, 55.8473718], [37.334095399999995, 55.8473929], [37.3341025, 55.84740659999999], [37.3341024, 55.84741459999999], [37.33407999999999, 55.84744189999999], [37.33406469999999, 55.84744759999999], [37.334015, 55.84746119999999], [37.3339643, 55.84746399999999], [37.333947099999996, 55.847467399999985], [37.33393280000001, 55.84747419999999], [37.3339268, 55.8474788], [37.3339268, 55.84748559999999], [37.333936800000004, 55.8475033], [37.3339519, 55.84752039999999], [37.333963, 55.8475301], [37.33398739999999, 55.8475422], [37.3339934, 55.847546799999996], [37.333994399999995, 55.847553], [37.333992300000006, 55.84756839999999], [37.3339852, 55.847584299999994], [37.333982999999996, 55.847598], [37.3339961, 55.84762429999999], [37.3339961, 55.8476352], [37.333998, 55.84764259999999], [37.334007199999995, 55.84764309999999], [37.334024299999996, 55.84764149999999], [37.33404769999999, 55.84763399999999], [37.3340549, 55.84763459999999], [37.3340599, 55.8476381], [37.334067899999994, 55.84765339999999], [37.3340789, 55.84768709999999], [37.33408899999999, 55.8477026], [37.3341093, 55.847716999999996], [37.3341284, 55.847727799999994], [37.3341508, 55.847733999999996], [37.334199399999996, 55.8477421], [37.334244999999996, 55.84774839999999], [37.33428339999999, 55.8477525], [37.334323, 55.8477519], [37.334369599999995, 55.8477457], [37.3344549, 55.8477253], [37.334480299999996, 55.847723099999996], [37.3345239, 55.847723699999996], [37.3345431, 55.84772139999999], [37.3345502, 55.847718], [37.3345554, 55.8477106], [37.33456459999999, 55.84769119999999], [37.3345788, 55.847679199999995], [37.334593999999996, 55.847672499999994], [37.3346123, 55.84766959999999], [37.33462449999999, 55.84766959999999], [37.3346549, 55.847673099999994], [37.334673099999996, 55.84767139999999], [37.334688299999996, 55.84766629999999], [37.3347059, 55.84766409999999], [37.33476339999999, 55.84766319999999], [37.334783599999994, 55.84765939999999], [37.3347959, 55.847655599999996], [37.3348059, 55.847654999999996], [37.334817199999996, 55.847658499999994], [37.334829199999994, 55.84766699999999], [37.334834099999995, 55.8477025], [37.3348381, 55.847706499999994], [37.33484939999999, 55.8477093], [37.33486149999999, 55.8477087], [37.334891899999995, 55.8477008], [37.3349051, 55.84769849999999], [37.334944699999994, 55.84768609999999], [37.3349721, 55.84768319999999], [37.3350097, 55.84768269999999], [37.335039, 55.847679899999996], [37.33505830000001, 55.84767469999999], [37.3350775, 55.84766569999999], [37.3350898, 55.847662299999996], [37.335106100000004, 55.847662299999996], [37.33513130000001, 55.84766629999999], [37.33515570000001, 55.847673199999996], [37.335219300000006, 55.847703499999994], [37.3352285, 55.8477058], [37.3352355, 55.84770639999999], [37.3352507, 55.847704699999994], [37.3352661, 55.84769959999999], [37.3352803, 55.8476922], [37.3352965, 55.84769109999999], [37.335320700000004, 55.84769159999999], [37.3353401, 55.847695099999996], [37.33535620000001, 55.8477009], [37.3353693, 55.8477106], [37.3353805, 55.84772139999999], [37.3353855, 55.8477317], [37.335387399999995, 55.84776359999999], [37.3353974, 55.8477762], [37.335407599999996, 55.847782499999994], [37.3354319, 55.8477927], [37.3354511, 55.84780939999999], [37.3354622, 55.8478157], [37.335480499999996, 55.847818499999995], [37.3354987, 55.84781739999999], [37.33553930000001, 55.847794099999994], [37.335558600000006, 55.8477901], [37.33557890000001, 55.84778949999999], [37.3356032, 55.847792999999996], [37.3356195, 55.8477987], [37.335629499999996, 55.847804999999994], [37.3356366, 55.84782099999999], [37.3356354, 55.847832399999994], [37.335630300000005, 55.847842699999994], [37.335622300000004, 55.847850699999995], [37.3356131, 55.8478569], [37.3355978, 55.84786259999999], [37.3355897, 55.84787159999999], [37.3355867, 55.84788189999999], [37.3355887, 55.84789099999999], [37.3355977, 55.84789969999999], [37.33561280000001, 55.8479105], [37.335635100000005, 55.8479202], [37.335666499999995, 55.847931599999995], [37.3356746, 55.8479391], [37.335681599999994, 55.847951599999995], [37.33568459999999, 55.84796649999999], [37.3356886, 55.8479773], [37.3356957, 55.84798539999999], [37.33571380000001, 55.8479956], [37.335731200000005, 55.8480025], [37.33575230000001, 55.8480093], [37.3357665, 55.848015700000005], [37.335776700000004, 55.8480242], [37.3357898, 55.8480288], [37.335806999999996, 55.8480306], [37.3358263, 55.8480306], [37.33584749999999, 55.8480249], [37.3358801, 55.8480135], [37.3358921, 55.8480113], [37.3359084, 55.8480124], [37.3359206, 55.8480165], [37.335940900000004, 55.8480273], [37.3359621, 55.8480364], [37.3359843, 55.8480428], [37.3360107, 55.8480479], [37.3360432, 55.8480502], [37.336065399999995, 55.8480543], [37.3360886, 55.8480623], [37.336111900000006, 55.8480731], [37.3361261, 55.8480754], [37.33613820000001, 55.8480749], [37.3361495, 55.8480709], [37.336180999999996, 55.848055], [37.336209399999994, 55.8480448], [37.336232800000005, 55.84804139999999], [37.336258, 55.8480408], [37.33628349999999, 55.8480443], [37.336310700000006, 55.8480506], [37.336325900000006, 55.848049399999994], [37.3363635, 55.848040999999995], [37.336413300000004, 55.8480268], [37.33644159999999, 55.84802], [37.33646399999999, 55.84801830000001], [37.3364913, 55.848013200000004], [37.3365452, 55.8480002], [37.3365635, 55.847997299999996], [37.3365765, 55.847997299999996], [37.3366029, 55.848001399999994], [37.3366709, 55.848002], [37.3367013, 55.8480061], [37.3367235, 55.8480112], [37.3367499, 55.8480198], [37.3367731, 55.8480307], [37.3367853, 55.8480393], [37.336795200000005, 55.848049499999995], [37.336797399999995, 55.848057], [37.336838900000004, 55.8480781], [37.336847899999995, 55.848087299999996], [37.336849799999996, 55.8480969], [37.3368377, 55.848114], [37.3368335, 55.8481254], [37.33684159999999, 55.84813230000001], [37.33688409999999, 55.8481426], [37.336918600000004, 55.8481472], [37.3369612, 55.8481484], [37.33702399999999, 55.8481394], [37.33705439999999, 55.848137200000004], [37.337080799999995, 55.8481406], [37.337155700000004, 55.8481635], [37.3371679, 55.8481715], [37.3371699, 55.8481784], [37.3371637, 55.8481897], [37.3371536, 55.848203399999996], [37.3371555, 55.848223999999995], [37.3371596, 55.8482378], [37.3371778, 55.8482548], [37.3371756, 55.848268399999995], [37.3371633, 55.848277599999996], [37.3371228, 55.8482935], [37.3371166, 55.848302700000005], [37.3371104, 55.8483242], [37.337094199999996, 55.84833330000001], [37.337072, 55.848339100000004], [37.3370293, 55.8483401], [37.3370049, 55.8483446], [37.3369826, 55.8483594], [37.336974399999995, 55.848370900000006], [37.336972300000006, 55.848384599999996], [37.3369763, 55.8484097], [37.336972200000005, 55.8484199], [37.336958, 55.8484256], [37.3369256, 55.8484313], [37.3369195, 55.8484369], [37.3369164, 55.848445], [37.336919300000005, 55.848464299999996], [37.33692739999999, 55.8484769], [37.336941499999995, 55.848487799999994], [37.3369608, 55.848493399999995], [37.33700639999999, 55.848494099999996], [37.337023499999994, 55.8484924], [37.3371049, 55.84846399999999], [37.3371262, 55.848460599999996], [37.337146499999996, 55.8484607], [37.337164599999994, 55.848464099999994], [37.3371778, 55.848471599999996], [37.3371828, 55.848479999999995], [37.3371908, 55.8485006], [37.337199999999996, 55.848508], [37.3372111, 55.84851030000001], [37.33724759999999, 55.848508700000004], [37.337260799999996, 55.8485104], [37.3372779, 55.848519], [37.337292, 55.84853210000001], [37.3372981, 55.848542900000005], [37.337306, 55.848582900000004], [37.337302, 55.8485971], [37.33728669999999, 55.8486171], [37.33726939999999, 55.8486336], [37.33726119999999, 55.8486524], [37.3372509, 55.8486923], [37.337249699999994, 55.848718000000005], [37.3372537, 55.84873220000001], [37.3372658, 55.848746], [37.3373255, 55.848786], [37.3373284, 55.848792800000005], [37.3373335, 55.8487991], [37.3373538, 55.8488036], [37.337372, 55.848805399999996], [37.3374197, 55.8488049], [37.33744099999999, 55.848809499999994], [37.3374551, 55.8488169], [37.337478399999995, 55.8488397], [37.33748949999999, 55.8488438], [37.3375078, 55.848845], [37.3375342, 55.848844899999996], [37.3375482, 55.8488507], [37.3375543, 55.848865499999995], [37.33756449999999, 55.848867899999995], [37.3375766, 55.848866699999995], [37.33760099999999, 55.848856399999995], [37.3376172, 55.848855300000004], [37.337629299999996, 55.8488599], [37.33763739999999, 55.848867899999995], [37.33763939999999, 55.84888169999999], [37.337653499999995, 55.8488908], [37.337665599999994, 55.8488908], [37.337692, 55.8488851], [37.3377083, 55.8488852], [37.3377225, 55.848888599999995], [37.3377386, 55.848895399999996], [37.3377508, 55.8489091], [37.337773, 55.848914900000004], [37.337805499999995, 55.8489195], [37.3378782, 55.848963999999995], [37.3379107, 55.848972100000005], [37.337928999999995, 55.848971], [37.3379513, 55.848966399999995], [37.3379999, 55.8489517], [37.3380813, 55.848905], [37.33811180000001, 55.8488959], [37.338152400000006, 55.8488937], [37.3381868, 55.8489006], [37.3382292, 55.848913200000005], [37.3382535, 55.8489235], [37.3382698, 55.8489406], [37.3382777, 55.84896], [37.3382735, 55.848981699999996], [37.338259300000004, 55.8490033], [37.3382572, 55.8490147], [37.3382653, 55.849027299999996], [37.33828749999999, 55.8490502], [37.3383017, 55.849073], [37.338311600000004, 55.8491027], [37.338313600000006, 55.849122], [37.3382993, 55.8491437], [37.338272800000006, 55.8491573], [37.338222, 55.849174399999995], [37.3381816, 55.8491823], [37.338157200000005, 55.849178900000005], [37.338126900000006, 55.8491697], [37.338108600000005, 55.8491697], [37.33809230000001, 55.8491766], [37.3380761, 55.8491901], [37.3380618, 55.8492209], [37.3380495, 55.849227799999994], [37.3380292, 55.8492386], [37.338018000000005, 55.8492489], [37.3380078, 55.8492722], [37.337996399999994, 55.8492768], [37.3379632, 55.8492727], [37.3379489, 55.849275], [37.3379438, 55.849280699999994], [37.3379347, 55.849307499999995], [37.33792759999999, 55.849312000000005], [37.3379154, 55.8493137], [37.3379012, 55.849312000000005], [37.33788099999999, 55.8492983], [37.33786679999999, 55.8492926], [37.33785459999999, 55.849294799999996], [37.337840299999996, 55.849302200000004], [37.3378333, 55.8493147], [37.337828099999996, 55.8493342], [37.337827999999995, 55.84935290000001], [37.3378199, 55.8493626], [37.33780459999999, 55.849367199999996], [37.337784299999996, 55.849367199999996], [37.33776399999999, 55.84936139999999], [37.3377509, 55.849352800000005], [37.337735800000004, 55.8493505], [37.3377225, 55.8493517], [37.337711399999996, 55.84936139999999], [37.3377082, 55.84937], [37.3377082, 55.849382399999996], [37.337718300000006, 55.8493916], [37.3377376, 55.8494025], [37.3377386, 55.84940699999999], [37.3377334, 55.8494093], [37.3377031, 55.8494155], [37.33768679999999, 55.849420699999996], [37.33768169999999, 55.8494258], [37.33768369999999, 55.8494343], [37.337706999999995, 55.849448599999995], [37.337711, 55.8494549], [37.33771, 55.8494628], [37.337699699999995, 55.849468599999994], [37.33768049999999, 55.849472], [37.337644999999995, 55.84946909999999], [37.3376339, 55.8494713], [37.3376258, 55.849475399999996], [37.3376196, 55.849483799999994], [37.337616499999996, 55.84951290000001], [37.3376113, 55.8495209], [37.3375972, 55.849529399999994], [37.3375707, 55.8495392], [37.3375626, 55.8495448], [37.33756149999999, 55.849554499999996], [37.33756759999999, 55.8495693], [37.33756339999999, 55.8495762], [37.337555300000005, 55.8495802], [37.3375238, 55.8495807], [37.3375148, 55.849584699999994], [37.3375118, 55.8495898], [37.3375146, 55.849600099999996], [37.3375238, 55.8496081], [37.3375591, 55.849629199999995], [37.337567199999995, 55.849636], [37.3375713, 55.8496429], [37.3375751, 55.849703399999996], [37.3375791, 55.8497142], [37.337587199999994, 55.8497228], [37.3376033, 55.8497343], [37.337622599999996, 55.8497456], [37.337628499999994, 55.8497554], [37.33762839999999, 55.849807799999994], [37.33763439999999, 55.84982659999999], [37.33764359999999, 55.8498363], [37.337656599999995, 55.84984439999999], [37.3376709, 55.84984779999999], [37.337681999999994, 55.84984779999999], [37.337693099999996, 55.84984609999999], [37.337706399999995, 55.84984039999999], [37.3377145, 55.849828499999994], [37.337721499999994, 55.8498233], [37.3377419, 55.8498154], [37.3377632, 55.8498123], [37.3377967, 55.8498132], [37.337830999999994, 55.849819499999995], [37.33788369999999, 55.8498367], [37.337937399999994, 55.849857799999995], [37.338008300000006, 55.849890499999994], [37.338052700000006, 55.8499156], [37.3380619, 55.8499236], [37.3380649, 55.8499299], [37.3380658, 55.8499367], [37.338076, 55.849944099999995], [37.338104300000005, 55.849962399999995], [37.338148800000006, 55.84998699999999], [37.338168, 55.8499905], [37.3382248, 55.849987999999996], [37.338243, 55.849987199999994], [37.338263399999995, 55.8499883], [37.338286499999995, 55.84999439999999], [37.3383078, 55.85000449999999], [37.338325100000006, 55.850014599999994], [37.3383411, 55.8500329], [37.33835130000001, 55.85004039999999], [37.3383685, 55.85004719999999], [37.338396800000005, 55.8500507], [37.3384334, 55.8500507], [37.3384525, 55.8500558], [37.338472900000006, 55.850063899999995], [37.3384819, 55.850071299999996], [37.3384881, 55.85008039999999], [37.338491, 55.85009409999999], [37.3384868, 55.8501112], [37.338492800000004, 55.8501187], [37.338506100000004, 55.8501238], [37.33853250000001, 55.8501283], [37.338553600000004, 55.8501468], [37.3385638, 55.8501502], [37.3385881, 55.850149099999996], [37.3386024, 55.850151399999994], [37.3386125, 55.850156], [37.3386145, 55.8501628], [37.338608300000004, 55.850176499999996], [37.338610300000006, 55.8501925], [37.33862439999999, 55.85020739999999], [37.3386466, 55.85022099999999], [37.338682999999996, 55.85023139999999], [37.3386972, 55.850237099999994], [37.3387074, 55.850246199999994], [37.3387072, 55.850262199999996], [37.338701, 55.85028159999999], [37.3387011, 55.8503021], [37.338709, 55.8503192], [37.338735400000004, 55.8503421], [37.3387535, 55.850353399999996], [37.33881220000001, 55.8503729], [37.3388687, 55.8504021], [37.338933700000005, 55.85042099999999], [37.3389661, 55.8504393], [37.3389841, 55.85046099999999], [37.3390767, 55.85064129999999], [37.3390928, 55.850675599999995], [37.3391171, 55.8507029], [37.3391736, 55.850752], [37.339266599999995, 55.850814899999996], [37.33937590000001, 55.85086639999999], [37.339473, 55.8509098], [37.339563999999996, 55.8509522], [37.33969749999999, 55.85101739999999], [37.3397764, 55.85105959999999], [37.339847199999994, 55.851105399999994], [37.3398957, 55.851141899999995], [37.33993, 55.8511739], [37.3399481, 55.851197799999994], [37.339958300000006, 55.85122859999999], [37.3399825, 55.85125609999999], [37.340006699999996, 55.85127549999999], [37.34004109999999, 55.85128809999999], [37.3401099, 55.8513166], [37.3401693, 55.85134409999999], [37.340209099999996, 55.851369299999995], [37.34024339999999, 55.851398999999994], [37.340265499999994, 55.85142179999999], [37.3402959, 55.85144809999999], [37.3403424, 55.851473299999995], [37.3403829, 55.851492699999994], [37.340421299999996, 55.8515167], [37.34044349999999, 55.851538399999995], [37.34046169999999, 55.8515703], [37.3405018, 55.85167979999999], [37.340542, 55.85175639999999], [37.3405701, 55.851817999999994], [37.3406022, 55.8519321], [37.3406099, 55.85198799999999], [37.340607899999995, 55.8520199], [37.3405607, 55.8521213], [37.340560599999996, 55.8521579], [37.34056449999999, 55.852203499999995], [37.3405926, 55.852257099999996], [37.3406289, 55.8523039], [37.340701599999996, 55.852385], [37.3407622, 55.852433], [37.34086539999999, 55.852483299999996], [37.3409038, 55.8525142], [37.34093, 55.8525449], [37.3409421, 55.852575800000004], [37.340945999999995, 55.852614499999994], [37.340941799999996, 55.852649899999996], [37.3409356, 55.852675], [37.3409091, 55.852704599999996], [37.340876699999995, 55.8527263], [37.34082179999999, 55.85274439999999], [37.3407487, 55.8527591], [37.340673699999996, 55.8527716], [37.3406331, 55.8527807], [37.340588399999994, 55.852797699999996], [37.3405437, 55.85282039999999], [37.3404889, 55.852860299999996], [37.3404562, 55.8529024], [37.340419399999995, 55.85296749999999], [37.340405, 55.853007299999994], [37.3404008, 55.85304609999999], [37.3403986, 55.85309049999999], [37.3403905, 55.8531225], [37.3403719, 55.85316699999999], [37.3403637, 55.8532137], [37.34036759999999, 55.85326499999999], [37.3403652, 55.8533186], [37.340361099999996, 55.85336759999999], [37.3403487, 55.853408699999996], [37.3403221, 55.8534703], [37.3403037, 55.85350439999999], [37.340283299999996, 55.8535363], [37.340272999999996, 55.853571699999996], [37.3402543, 55.85366409999999], [37.340239999999994, 55.8537108], [37.340227799999994, 55.8537302], [37.3401178, 55.85384179999999], [37.34008719999999, 55.85388059999999], [37.3400688, 55.8539251], [37.3400482, 55.853981999999995], [37.3400338, 55.85404809999999], [37.3400368, 55.854136499999996], [37.3400365, 55.85422349999999], [37.3400199, 55.85430139999999], [37.3400196, 55.8543701], [37.3399949, 55.854434299999994], [37.33991290000001, 55.854535], [37.3398392, 55.854608299999995], [37.3397408, 55.854745599999994], [37.33968339999999, 55.85483249999999], [37.33960139999999, 55.85494699999999], [37.3395683, 55.8550708], [37.3395515, 55.8551761], [37.3395754, 55.8553365], [37.33968739999999, 55.855506999999996], [37.3400536, 55.8557238], [37.3402152, 55.85584449999999], [37.3402903, 55.85600149999999], [37.340280099999994, 55.8560989], [37.3402251, 55.8561907], [37.340085499999994, 55.8563939], [37.340070399999995, 55.85647469999999], [37.3401147, 55.8565305], [37.3401937, 55.856580599999994], [37.3402926, 55.856655999999994], [37.3403516, 55.8567452], [37.3403511, 55.85685939999999], [37.3403459, 55.856967999999995], [37.34029099999999, 55.85704869999999], [37.34028049999999, 55.85718239999999], [37.3403443, 55.857322599999996], [37.3404132, 55.85747779999999], [37.3404913, 55.857709099999994], [37.340604299999995, 55.85795159999999], [37.3406337, 55.858049099999995], [37.340697799999994, 55.85813280000001], [37.3408163, 55.8582193], [37.341013999999994, 55.8583421], [37.341265899999996, 55.858529], [37.341355, 55.8585737], [37.341453599999994, 55.8586909], [37.341482899999995, 55.8587828], [37.341447399999986, 55.858966499999994], [37.341471799999994, 55.859066899999995], [37.3415062, 55.859158900000004], [37.34160979999999, 55.8592398], [37.34168399999999, 55.8593207], [37.341723099999996, 55.85942939999999], [37.34174739999999, 55.8595547], [37.3417568, 55.859668899999996], [37.34178139999999, 55.8597051], [37.341825899999996, 55.85974699999999], [37.3418357, 55.859777699999995], [37.3419189, 55.8600006], [37.3420073, 55.86019290000001], [37.342022300000004, 55.8602068], [37.3421607, 55.8602573], [37.3422398, 55.860287899999996], [37.342333800000006, 55.860352000000006], [37.342476999999995, 55.860444199999996], [37.342565900000004, 55.860516700000005], [37.342618, 55.8605943], [37.3451935, 55.8613095], [37.3465853, 55.8622364], [37.3458799, 55.8629437], [37.3464132, 55.86306149999999], [37.346479499999994, 55.863129], [37.3470589, 55.8631837], [37.34783449999999, 55.8634304], [37.3493919, 55.863528200000005], [37.349819, 55.863798800000005], [37.35789079999999, 55.864264899999995], [37.3591142, 55.8650687], [37.3594751, 55.86551500000001], [37.359867399999985, 55.865856900000004], [37.3601466, 55.8660568], [37.3617292, 55.867113700000004], [37.36232220000001, 55.8675032], [37.362346, 55.867519800000004], [37.36238, 55.867522900000004], [37.362424, 55.8675293], [37.3624924, 55.8675233], [37.362579800000006, 55.8675243], [37.362613800000005, 55.867529499999996], [37.362649499999996, 55.8675489], [37.3627271, 55.86758739999999], [37.36277220000001, 55.8676198], [37.3628063, 55.8676399], [37.362822200000004, 55.86764709999999], [37.362835800000006, 55.86764779999999], [37.3628516, 55.86764099999999], [37.362856, 55.8676321], [37.362863999999995, 55.867592800000004], [37.3628518, 55.8675578], [37.3628177, 55.8675097], [37.3628085, 55.867464299999995], [37.36281580000001, 55.8674483], [37.3628335, 55.8674399], [37.3628755, 55.8674328], [37.3629547, 55.8674347], [37.3630249, 55.8674313], [37.3630498, 55.86742649999999], [37.3630592, 55.8674121], [37.3630717, 55.867376300000004], [37.3630784, 55.86736139999999], [37.3630951, 55.8673562], [37.363154200000004, 55.8673518], [37.363232100000005, 55.8673493], [37.3632532, 55.8673411], [37.3632772, 55.8673257], [37.363355000000006, 55.867318000000004], [37.363435800000005, 55.867318000000004], [37.3634965, 55.8673251], [37.363541399999995, 55.867345300000004], [37.3635771, 55.8673786], [37.3635847, 55.867400399999994], [37.363561399999995, 55.867423099999996], [37.363535000000006, 55.867446699999995], [37.3635316, 55.8674659], [37.363558100000006, 55.86748779999999], [37.3635813, 55.8675184], [37.36359530000001, 55.8675341], [37.3636185, 55.8675413], [37.363641799999996, 55.8675325], [37.3636948, 55.8674993], [37.3637448, 55.867478399999996], [37.363806999999994, 55.8674688], [37.3638521, 55.8674453], [37.363881799999994, 55.8674349], [37.3639144, 55.867433999999996], [37.3639409, 55.867446199999996], [37.3639391, 55.8674829], [37.3639406, 55.8675171], [37.3639575, 55.867553], [37.3639825, 55.8675792], [37.3640367, 55.8675967], [37.3641004, 55.8676169], [37.3641517, 55.8676309], [37.3642171, 55.867630999999996], [37.36429639999999, 55.86762139999999], [37.3643555, 55.867604899999996], [37.3644008, 55.8675735], [37.364432, 55.867544599999995], [37.3644483, 55.8675401], [37.3644708, 55.8675412], [37.3645082, 55.8675623], [37.3645485, 55.8675754], [37.364598300000004, 55.8675668], [37.3646451, 55.8675456], [37.364705900000004, 55.8675065], [37.364743399999995, 55.867457699999996], [37.364788499999996, 55.867427899999996], [37.3648384, 55.8674053], [37.36488359999999, 55.867398300000005], [37.3649318, 55.867401799999996], [37.36498139999999, 55.867416], [37.36503280000001, 55.8674378], [37.3650824, 55.8674633], [37.36511960000001, 55.8674973], [37.3651677, 55.867546399999995], [37.365217300000005, 55.867578800000004], [37.36523880000001, 55.8676059], [37.3652372, 55.867628599999996], [37.365209300000004, 55.867650399999995], [37.36516090000001, 55.867698499999996], [37.36512810000001, 55.86774739999999], [37.3651046, 55.8677971], [37.365103000000005, 55.8678313], [37.365121300000006, 55.8678592], [37.36515880000001, 55.86788549999999], [37.365205200000005, 55.8678988], [37.3652514, 55.8678987], [37.365304800000004, 55.86789099999999], [37.365351700000005, 55.8678586], [37.3654062, 55.867819399999995], [37.3654468, 55.867801899999996], [37.3654827, 55.86779739999999], [37.3655044, 55.8677991], [37.36551670000001, 55.867803699999996], [37.36553530000001, 55.867833399999995], [37.365558500000006, 55.8678763], [37.365578600000006, 55.867906999999995], [37.365600300000004, 55.8679236], [37.365619900000006, 55.8679268], [37.3656438, 55.8679236], [37.3656797, 55.8679088], [37.3657094, 55.867880899999996], [37.365739000000005, 55.86786169999999], [37.3657636, 55.8678568], [37.365780900000004, 55.8678582], [37.365805800000004, 55.86786439999999], [37.365819800000004, 55.86788539999999], [37.3658257, 55.8679422], [37.3658366, 55.8679667], [37.36586139999999, 55.86798339999999], [37.36591270000001, 55.867985999999995], [37.3660621, 55.8679801], [37.3661055, 55.867969599999995], [37.3661242, 55.8679479], [37.366152400000004, 55.867912000000004], [37.3661807, 55.86788839999999], [37.3662116, 55.86787439999999], [37.3662428, 55.8678727], [37.366288, 55.8678789], [37.36631890000001, 55.86788149999999], [37.3663394, 55.86787639999999], [37.366350000000004, 55.86786059999999], [37.36635330000001, 55.86784049999999], [37.366384399999994, 55.8678318], [37.366436, 55.8678222], [37.3664778, 55.8678222], [37.36651210000001, 55.8678355], [37.36653990000001, 55.867856599999996], [37.366600399999996, 55.8679019], [37.366664099999994, 55.8679492], [37.3667091, 55.8679913], [37.3667463, 55.86801830000001], [37.3667945, 55.868026300000004], [37.366844099999994, 55.868028100000004], [37.366876999999995, 55.868018500000005], [37.3668973, 55.86798709999999], [37.3669037, 55.867932], [37.366907, 55.86786739999999], [37.366925800000004, 55.867837599999994], [37.3669585, 55.8678228], [37.367012800000005, 55.8678203], [37.3670736, 55.86782469999999], [37.367162300000004, 55.8678169], [37.36722449999999, 55.867809099999995], [37.3672931, 55.8677856], [37.3673366, 55.8677822], [37.367364599999995, 55.8677935], [37.3673692, 55.8678057], [37.3673411, 55.8678259], [37.3672943, 55.867865099999996], [37.367290999999994, 55.8679027], [37.3672755, 55.8679306], [37.36726739999999, 55.8679726], [37.3672798, 55.867998], [37.367315600000005, 55.86801380000001], [37.3673514, 55.868019000000004], [37.3673949, 55.8680043], [37.36746049999999, 55.86796759999999], [37.3675211, 55.8679335], [37.367541599999996, 55.8679047], [37.3675384, 55.867874199999996], [37.3675137, 55.8678523], [37.367485699999996, 55.8678199], [37.3674906, 55.8677823], [37.367525, 55.8677482], [37.3675592, 55.8677238], [37.3675853, 55.8677219], [37.3676058, 55.8677256], [37.3676508, 55.867732600000004], [37.3676992, 55.867732000000004], [37.367748999999996, 55.8677021], [37.3677927, 55.8676689], [37.367825499999995, 55.8676193], [37.3678397, 55.867583399999994], [37.3678568, 55.8675786], [37.3678755, 55.8675799], [37.36791890000001, 55.8675852], [37.3679919, 55.867607099999994], [37.368018500000005, 55.867611499999995], [37.368057300000004, 55.867602], [37.36812270000001, 55.8675933], [37.368191, 55.8675829], [37.36825, 55.8675768], [37.368286, 55.867586499999994], [37.368317000000005, 55.867606599999995], [37.3683544, 55.86762409999999], [37.368411800000004, 55.8676268], [37.3684755, 55.867628599999996], [37.368517600000004, 55.8676305], [37.36855500000001, 55.8676428], [37.368576600000004, 55.86766109999999], [37.368588900000006, 55.8676829], [37.36859210000001, 55.8677179], [37.36859810000001, 55.8677485], [37.3686277, 55.8677756], [37.368678900000006, 55.867795], [37.368727, 55.867811599999996], [37.36878290000001, 55.867821199999995], [37.3688406, 55.867821299999996], [37.36891680000001, 55.8678135], [37.3690225, 55.8677979], [37.3691284, 55.8677902], [37.369185900000005, 55.8677954], [37.3692386, 55.8677947], [37.369301, 55.8677859], [37.36935230000001, 55.8677738], [37.3693805, 55.867758900000005], [37.369379, 55.8677301], [37.3693541, 55.867699599999995], [37.369309200000004, 55.867654099999996], [37.3692859, 55.8676208], [37.3692799, 55.8675972], [37.3693, 55.867580499999995], [37.369356200000006, 55.867560499999996], [37.369402900000004, 55.8675458], [37.369457399999995, 55.8675466], [37.3695024, 55.8675625], [37.3695226, 55.8675773], [37.3695443, 55.8675949], [37.369566, 55.867608], [37.3695892, 55.867611499999995], [37.369617399999996, 55.867609699999996], [37.3696593, 55.8676002], [37.3697216, 55.867585399999996], [37.3697574, 55.8675855], [37.3697852, 55.8675881], [37.3698039, 55.8675933], [37.3698118, 55.867608999999995], [37.3698193, 55.8676388], [37.3698318, 55.8676598], [37.3698598, 55.867672999999996], [37.36988759999999, 55.867682599999995], [37.3699235, 55.86768429999999], [37.3699515, 55.8676739], [37.3699686, 55.8676548], [37.3699748, 55.8676119], [37.3699813, 55.867563], [37.3699907, 55.8675367], [37.3699925, 55.8675025], [37.369989499999996, 55.867468599999995], [37.3699943, 55.867438], [37.3700239, 55.8674134], [37.3700567, 55.8673899], [37.37008149999999, 55.8673725], [37.3701097, 55.8673542], [37.3701438, 55.867349], [37.3702029, 55.867349], [37.370274599999995, 55.8673465], [37.370357, 55.867341399999994], [37.370406499999994, 55.86733530000001], [37.370515600000004, 55.867319200000004], [37.370617599999996, 55.8673116], [37.3706581, 55.8673173], [37.370688799999996, 55.8673285], [37.37073530000001, 55.8673628], [37.370784199999996, 55.8673936], [37.3708233, 55.8674169], [37.3708532, 55.867423599999995], [37.3709406, 55.8674281], [37.370981099999995, 55.8674459], [37.3710321, 55.86746709999999], [37.371075499999996, 55.86747449999999], [37.371133, 55.867470999999995], [37.371189199999996, 55.8674548], [37.37124659999999, 55.86742459999999], [37.371260799999995, 55.8674086], [37.37128499999999, 55.867366499999996], [37.3713325, 55.8673402], [37.371367299999996, 55.867336], [37.3713988, 55.867342300000004], [37.371453499999994, 55.867350300000005], [37.37149709999999, 55.8673465], [37.3715171, 55.86734439999999], [37.371540499999995, 55.867353], [37.3715562, 55.8673713], [37.3715432, 55.8673912], [37.371524799999996, 55.867409099999996], [37.3715154, 55.867443099999996], [37.3715451, 55.8674586], [37.371601299999995, 55.86746169999999], [37.3716599, 55.867460799999996], [37.37169239999999, 55.86748099999999], [37.371710300000004, 55.8674928], [37.3717365, 55.8675038], [37.3717688, 55.867507499999995], [37.3717953, 55.8675154], [37.37183709999999, 55.86753830000001], [37.37186899999999, 55.8675515], [37.3719055, 55.867552800000006], [37.3719708, 55.8675395], [37.3719999, 55.8675443], [37.3720501, 55.8675747], [37.372099, 55.867595800000004], [37.372162100000004, 55.8676177], [37.372207599999996, 55.8676378], [37.3722542, 55.86766139999999], [37.3722924, 55.86768739999999], [37.372314300000006, 55.867686199999994], [37.372338000000006, 55.867674599999994], [37.372355000000006, 55.86764899999999], [37.372410200000004, 55.8676173], [37.372519000000004, 55.867572300000006], [37.372542, 55.867555900000006], [37.372548200000004, 55.8675305], [37.37251390000001, 55.86751530000001], [37.372464699999995, 55.8675056], [37.372392500000004, 55.86749439999999], [37.37235830000001, 55.86748349999999], [37.3723534, 55.867469699999994], [37.3723795, 55.8674505], [37.372449499999995, 55.8673984], [37.372463999999994, 55.867377], [37.372478900000004, 55.86733220000001], [37.37251220000001, 55.8672956], [37.372542900000006, 55.867274099999996], [37.3725734, 55.867260599999994], [37.372616300000004, 55.867237599999996], [37.3726796, 55.8672185], [37.3727416, 55.8672057], [37.3727878, 55.8672007], [37.372829599999996, 55.8671967], [37.372865399999995, 55.8671986], [37.3729045, 55.8672056], [37.372976900000005, 55.8672126], [37.3730087, 55.867200499999996], [37.3730324, 55.867181599999995], [37.3730889, 55.8671554], [37.3731226, 55.8671531], [37.373145300000004, 55.867160999999996], [37.3731981, 55.8671797], [37.3732233, 55.8671852], [37.373253399999996, 55.8671832], [37.373290399999995, 55.867181599999995], [37.373321, 55.8671873], [37.3733618, 55.8672028], [37.3733861, 55.867200499999996], [37.3734238, 55.86719], [37.3734511, 55.867190300000004], [37.373487299999994, 55.8671942], [37.373567099999995, 55.8671947], [37.373606099999996, 55.867202], [37.373644999999996, 55.867235900000004], [37.37366239999999, 55.86724159999999], [37.3737054, 55.86724649999999], [37.3737337, 55.8672589], [37.3737408, 55.867282499999995], [37.3737311, 55.8672992], [37.373705, 55.867315600000005], [37.3736317, 55.8673402], [37.3736092, 55.867354], [37.3736186, 55.8673732], [37.37365739999999, 55.8673943], [37.373689899999995, 55.8673976], [37.373725900000004, 55.86740339999999], [37.3737535, 55.8674199], [37.37378449999999, 55.8674524], [37.3738102, 55.86746479999999], [37.3738558, 55.86746749999999], [37.373901399999994, 55.8674539], [37.3739291, 55.8674512], [37.3739516, 55.8674587], [37.373964099999995, 55.867492399999996], [37.374001699999994, 55.8675098], [37.3740185, 55.8675154], [37.3740527, 55.867537399999996], [37.374049199999995, 55.8675776], [37.3740591, 55.8675941], [37.374083799999994, 55.8675997], [37.3741711, 55.8675873], [37.3741989, 55.867591499999996], [37.374224999999996, 55.867606699999996], [37.37426189999999, 55.867641299999995], [37.37428749999999, 55.86767939999999], [37.37428859999999, 55.867722900000004], [37.374298399999994, 55.867755300000006], [37.3743154, 55.8677755], [37.374324099999995, 55.8677801], [37.374354499999995, 55.8677869], [37.3744358, 55.867781699999995], [37.374462099999995, 55.8677857], [37.374493599999994, 55.8677948], [37.3745426, 55.8678142], [37.374589099999994, 55.8678281], [37.374626199999994, 55.867827999999996], [37.374654099999994, 55.8678188], [37.374714399999995, 55.8677833], [37.3747371, 55.8677777], [37.3747626, 55.8677764], [37.3747982, 55.867791], [37.374818499999996, 55.8677998], [37.374837899999996, 55.867808999999994], [37.374870699999995, 55.8678139], [37.374924099999994, 55.8678173], [37.374969799999995, 55.8678229], [37.37498769999999, 55.86782639999999], [37.3750279, 55.867847899999994], [37.3750768, 55.867878999999995], [37.3751145, 55.8679007], [37.3751419, 55.8679061], [37.375210800000005, 55.8679013], [37.3752431, 55.867886199999994], [37.375261099999996, 55.8678743], [37.375285999999996, 55.867837699999995], [37.3752985, 55.8678306], [37.375325200000006, 55.8678302], [37.375376800000005, 55.8678351], [37.3754027, 55.867849799999995], [37.3754288, 55.867866199999995], [37.3754579, 55.8678682], [37.3754738, 55.86786139999999], [37.3755134, 55.8678325], [37.3755493, 55.86782349999999], [37.3755698, 55.867829099999994], [37.3756912, 55.8678555], [37.3757462, 55.86787759999999], [37.3757852, 55.8679032], [37.375804499999994, 55.8679481], [37.3758062, 55.867974499999995], [37.3758032, 55.8680004], [37.3758088, 55.8680225], [37.3758381, 55.86803200000001], [37.3759442, 55.868025100000004], [37.3759699, 55.868019100000005], [37.376024199999996, 55.8679986], [37.376058300000004, 55.8679951], [37.3760779, 55.8679986], [37.3760972, 55.868019700000005], [37.376117300000004, 55.8680287], [37.3761608, 55.8680317], [37.3762112, 55.8680272], [37.3762382, 55.868016600000004], [37.3762781, 55.8679962], [37.376297699999995, 55.8679989], [37.376338600000004, 55.8680195], [37.3763493, 55.868035400000004], [37.3763469, 55.8680693], [37.3763609, 55.8680904], [37.376424199999995, 55.86811980000001], [37.3764682, 55.86811930000001], [37.3765237, 55.86811260000001], [37.3765417, 55.868122400000004], [37.3765608, 55.86815560000001], [37.3765802, 55.86817570000001], [37.376602999999996, 55.8681812], [37.37662749999999, 55.868174], [37.3766483, 55.86816290000001], [37.3766731, 55.86816030000001], [37.37668839999999, 55.868161900000004], [37.3767384, 55.8682001], [37.376749499999995, 55.868208900000006], [37.376764099999995, 55.8682336], [37.376755800000005, 55.86825090000001], [37.3767395, 55.8682693], [37.3767346, 55.8682885], [37.376754, 55.868308600000006], [37.3767785, 55.86831880000001], [37.3768068, 55.8683216], [37.376841899999995, 55.86830870000001], [37.37687939999999, 55.8682855], [37.376941599999995, 55.8682455], [37.3769757, 55.868231], [37.3769951, 55.8682281], [37.3770196, 55.8682256], [37.377046699999994, 55.86823290000001], [37.3771091, 55.8682641], [37.3771578, 55.8682889], [37.377195300000004, 55.868293300000005], [37.3772957, 55.868285300000004], [37.3773548, 55.8682854], [37.377374399999994, 55.868295100000005], [37.377416499999995, 55.86833580000001], [37.377460199999994, 55.8683606], [37.377488899999996, 55.868361900000004], [37.3775238, 55.868354100000005], [37.37756139999999, 55.86834230000001], [37.3775907, 55.868328700000006], [37.377613499999995, 55.868305500000005], [37.3776149, 55.8682681], [37.377626199999995, 55.8682484], [37.37764419999999, 55.868239200000005], [37.377658999999994, 55.8682342], [37.37768699999999, 55.868222100000004], [37.3777048, 55.8682076], [37.37770139999999, 55.8681977], [37.377663299999995, 55.86817330000001], [37.3776539, 55.868160800000005], [37.377655, 55.868149], [37.377670499999994, 55.86813270000001], [37.37769449999999, 55.868121200000004], [37.3777402, 55.868108500000005], [37.37778159999999, 55.86810200000001], [37.3778593, 55.8680896], [37.37788609999999, 55.86808], [37.377902999999996, 55.8680571], [37.3779101, 55.8680372], [37.377925999999995, 55.868018600000006], [37.3779439, 55.868008100000004], [37.3779703, 55.8680037], [37.377988699999996, 55.8680046], [37.378013, 55.868008200000006], [37.3780316, 55.868018400000004], [37.3780554, 55.868052000000006], [37.3780762, 55.8680688], [37.37811570000001, 55.86807280000001], [37.3781466, 55.868070100000004], [37.378207399999994, 55.868048800000004], [37.3782407, 55.8680395], [37.378284799999996, 55.86803880000001], [37.3783195, 55.868042900000006], [37.378348, 55.8680524], [37.378362900000006, 55.868061], [37.3783716, 55.8680979], [37.3784002, 55.86812200000001], [37.3784347, 55.8681375], [37.3784718, 55.8681442], [37.3784999, 55.868143], [37.3785297, 55.86813980000001], [37.3785515, 55.86813210000001], [37.3785687, 55.86812320000001], [37.3785767, 55.86811600000001], [37.3785848, 55.8681064], [37.378593900000006, 55.868090300000006], [37.3786043, 55.8680775], [37.3786116, 55.8680698], [37.3786237, 55.868064], [37.3786364, 55.868061399999995], [37.3786501, 55.86805820000001], [37.3786649, 55.86805830000001], [37.3786868, 55.8680609], [37.3786906, 55.8680545], [37.378679999999996, 55.868011700000004], [37.3786686, 55.8680015], [37.378652200000005, 55.868000900000006], [37.378586399999996, 55.8680218], [37.378561399999995, 55.868025700000004], [37.378544399999996, 55.8680276], [37.37851810000001, 55.8680141], [37.3784762, 55.8679979], [37.3784566, 55.8679743], [37.378454399999995, 55.86796399999999], [37.378459, 55.8679423], [37.3784773, 55.8679282], [37.37851860000001, 55.8679166], [37.3786164, 55.8679117], [37.3787145, 55.867903999999996], [37.3788198, 55.867885599999994], [37.3788561, 55.867875999999995], [37.378872, 55.86786709999999], [37.37888699999999, 55.8678539], [37.37888349999999, 55.8678312], [37.3788698, 55.8678209], [37.37884739999999, 55.8678141], [37.378724, 55.8677952], [37.3786669, 55.8677798], [37.37861, 55.8677591], [37.3786009, 55.867747599999994], [37.3786079, 55.8677386], [37.3786238, 55.8677345], [37.3788883, 55.867715200000006], [37.3789295, 55.867698], [37.3789684, 55.867671099999995], [37.378995800000006, 55.8676288], [37.3790142, 55.8675904], [37.3790332, 55.8675655], [37.3793318, 55.867402399999996], [37.3794062, 55.8673525], [37.3794086, 55.867330300000006], [37.3794002, 55.867316], [37.3793768, 55.867296399999994], [37.3793042, 55.8672937], [37.3792206, 55.867293999999994], [37.3792167, 55.867285599999995], [37.3792493, 55.8672249], [37.3792372, 55.867178900000006], [37.3792652, 55.8671652], [37.379293399999995, 55.867155600000004], [37.3793217, 55.867144599999996], [37.379339, 55.8671272], [37.37931890000001, 55.8670954], [37.3792881, 55.867079499999996], [37.37926949999999, 55.867053999999996], [37.379273999999995, 55.8670351], [37.379290999999995, 55.8670209], [37.3793238, 55.8669856], [37.3793166, 55.8669574], [37.379305300000006, 55.8669384], [37.3792621, 55.8669205], [37.379201099999996, 55.8668923], [37.379150300000006, 55.866878], [37.379105200000005, 55.866871599999996], [37.37906759999999, 55.8668725], [37.3790543, 55.866879499999996], [37.379059999999996, 55.8668922], [37.3790937, 55.8669032], [37.379147399999994, 55.8669208], [37.379172100000005, 55.86693880000001], [37.3791981, 55.86695890000001], [37.379212, 55.866978], [37.3792092, 55.8669954], [37.379195100000004, 55.8670081], [37.37915520000001, 55.8670179], [37.379113100000005, 55.8670318], [37.3790792, 55.8670381], [37.3790537, 55.867041699999994], [37.3790143, 55.8670332], [37.3789862, 55.8670221], [37.3789468, 55.867004699999995], [37.3789242, 55.8669888], [37.37891570000001, 55.8669696], [37.3789017, 55.8669666], [37.3788565, 55.86697290000001], [37.3787293, 55.866990200000004], [37.3786927, 55.8669965], [37.37866739999999, 55.8669996], [37.3786334, 55.866998], [37.378610800000004, 55.8669932], [37.378584399999994, 55.866978100000004], [37.3785941, 55.866959900000005], [37.378613900000005, 55.8669536], [37.378642, 55.8669472], [37.378664699999995, 55.866936100000004], [37.3786719, 55.8669201], [37.3787061, 55.8668911], [37.3787055, 55.866884199999994], [37.378694499999995, 55.8668762], [37.3786787, 55.8668772], [37.3786376, 55.8668833], [37.3785284, 55.8669249], [37.3784957, 55.8669238], [37.3784612, 55.8669238], [37.3784185, 55.8669306], [37.378359800000005, 55.8669249], [37.378333500000004, 55.86691690000001], [37.37833630000001, 55.8669056], [37.378345200000005, 55.866884799999994], [37.3783673, 55.8668724], [37.378451399999996, 55.8668378], [37.3784482, 55.8668085], [37.378435100000004, 55.8667961], [37.37843530000001, 55.8667573], [37.3784212, 55.866718500000005], [37.3784031, 55.8666911], [37.3783687, 55.866665999999995], [37.37833630000001, 55.866647699999994], [37.378322100000005, 55.8666317], [37.378319100000006, 55.86661230000001], [37.378326300000005, 55.8665804], [37.378320800000004, 55.8665706], [37.37830830000001, 55.866565], [37.37828459999999, 55.866561399999995], [37.378264099999996, 55.86657030000001], [37.378243399999995, 55.866602300000004], [37.37823230000001, 55.866621699999996], [37.3782013, 55.866648], [37.3781895, 55.866648399999995], [37.378162700000004, 55.8666368], [37.37813580000001, 55.8666155], [37.37811070000001, 55.8666003], [37.378068, 55.8665887], [37.3780316, 55.8665772], [37.3780191, 55.866572700000006], [37.3780111, 55.8665572], [37.3780224, 55.8665425], [37.3780493, 55.866535400000004], [37.3780887, 55.866531], [37.3781235, 55.866525700000004], [37.378155400000004, 55.86651520000001], [37.3781868, 55.8664947], [37.378207399999994, 55.8664686], [37.3782334, 55.8664479], [37.3782254, 55.8664092], [37.3782297, 55.866359], [37.3782717, 55.866280399999994], [37.37825230000001, 55.8662655], [37.378219900000005, 55.866235800000005], [37.3782037, 55.8662164], [37.3782038, 55.8662016], [37.3782241, 55.866190200000005], [37.378325700000005, 55.866156000000004], [37.378348, 55.8661424], [37.37835210000001, 55.8661207], [37.3783515, 55.86608939999999], [37.378333600000005, 55.8660587], [37.3783096, 55.8660426], [37.3782278, 55.8660204], [37.378161399999996, 55.8660115], [37.3780731, 55.8660016], [37.37801280000001, 55.866002200000004], [37.37798449999999, 55.8659918], [37.377945, 55.86597580000001], [37.3779136, 55.8659535], [37.3779164, 55.8659146], [37.3779453, 55.8658931], [37.3780165, 55.865860399999995], [37.3781454, 55.865832000000005], [37.3781544, 55.86577030000001], [37.3781216, 55.86571980000001], [37.3780412, 55.8656041], [37.3780027, 55.865487699999996], [37.3779789, 55.8654473], [37.3779317, 55.86530930000001], [37.3779287, 55.8652235], [37.3779317, 55.865191700000004], [37.37795139999999, 55.8651266], [37.3779627, 55.86511830000001], [37.37798339999999, 55.8650941], [37.3777425, 55.8650584], [37.37764049999999, 55.86501290000001], [37.3775554, 55.8649541], [37.377496099999995, 55.86488709999999], [37.3774557, 55.86480439999999], [37.37744959999999, 55.8647195], [37.37747139999999, 55.8646118], [37.3775126, 55.864532000000004], [37.3775621, 55.8644591], [37.377604899999994, 55.864399399999996], [37.37766249999999, 55.864366999999994], [37.377763099999996, 55.8643449], [37.37789639999999, 55.8643208], [37.3779706, 55.8642736], [37.378022, 55.86423], [37.3780319, 55.8641287], [37.3780915, 55.8640298], [37.378208900000004, 55.8639647], [37.378495, 55.8638827], [37.37871810000001, 55.8638043], [37.3790207, 55.8637073], [37.3791572, 55.8636269], [37.3792243, 55.8635631], [37.3793726, 55.863488], [37.3796981, 55.8633642], [37.3797707, 55.863294399999994], [37.379806499999994, 55.8632147], [37.3798116, 55.863117700000004], [37.3797747, 55.8630346], [37.3797066, 55.8629456], [37.3795956, 55.862821], [37.37948639999999, 55.8627295], [37.3793548, 55.8626564], [37.3791178, 55.86255890000001], [37.378765300000005, 55.8624311], [37.3786316, 55.86237390000001], [37.3784697, 55.862295100000004], [37.3783671, 55.8622164], [37.378273300000004, 55.862134000000005], [37.3782026, 55.8620667], [37.3781735, 55.8619917], [37.378184399999995, 55.8619423], [37.378191900000004, 55.86188659999999], [37.3782176, 55.8617633], [37.3782221, 55.861677699999994], [37.378207399999994, 55.861530800000004], [37.3782402, 55.8613873], [37.378296399999996, 55.861258], [37.3783291, 55.8611657], [37.3783478, 55.8610562], [37.378412600000004, 55.8609742], [37.3784965, 55.8608482], [37.3785915, 55.8607255], [37.3786453, 55.8606659], [37.378742700000004, 55.8606154], [37.3788758, 55.860556800000005], [37.3789843, 55.8604933], [37.379160999999996, 55.860382900000005], [37.3793443, 55.8603025], [37.3794992, 55.860236], [37.3796397, 55.8601411], [37.379748, 55.860056300000004], [37.379866899999996, 55.859973399999994], [37.3799498, 55.8599007], [37.3800003, 55.859842199999996], [37.380040099999995, 55.8597512], [37.380051699999996, 55.859617199999995], [37.3800303, 55.8594722], [37.3800089, 55.859377099999996], [37.3799336, 55.8593003], [37.379854699999996, 55.859259699999996], [37.379711, 55.85922109999999], [37.3795419, 55.8591967], [37.379391, 55.8591743], [37.379153800000005, 55.8591053], [37.3789402, 55.85902419999999], [37.3787518, 55.8589657], [37.3784925, 55.85888099999999], [37.378210800000005, 55.8587999], [37.378026399999996, 55.858736900000004], [37.37784619999999, 55.8586603], [37.3776781, 55.8585837], [37.3774758, 55.8585315], [37.377207999999996, 55.8584543], [37.37700339999999, 55.858388], [37.376758200000005, 55.858310100000004], [37.376631399999994, 55.85824949999999], [37.3765154, 55.8581766], [37.376448499999995, 55.85806939999999], [37.37640939999999, 55.857929799999994], [37.376399, 55.857832699999996], [37.3763849, 55.857739699999996], [37.3762739, 55.8575557], [37.376231, 55.85749699999999], [37.3761627, 55.857478699999994], [37.37608709999999, 55.85746859999999], [37.3760154, 55.85742389999999], [37.3759824, 55.85737639999999], [37.375972600000004, 55.857300599999995], [37.3759407, 55.85720549999999], [37.3758833, 55.85708209999999], [37.3758579, 55.856994099999994], [37.3758702, 55.856936999999995], [37.3759231, 55.8568733], [37.375998300000006, 55.856841399999986], [37.3760713, 55.8567992], [37.376122, 55.856712300000005], [37.376183399999995, 55.856623799999994], [37.376231499999996, 55.8565208], [37.3762317, 55.8564121], [37.3762193, 55.8563208], [37.3761554, 55.8561788], [37.37611270000001, 55.8561299], [37.3759911, 55.85606109999999], [37.37588739999999, 55.8559961], [37.375610300000005, 55.855862599999995], [37.37537330000001, 55.8557693], [37.3752009, 55.855704499999995], [37.3750716, 55.85564159999999], [37.3749541, 55.855548], [37.374840799999994, 55.8554452], [37.3748187, 55.8553699], [37.3748189, 55.855301399999995], [37.37484539999999, 55.8552513], [37.3749347, 55.8551704], [37.3750731, 55.8550827], [37.3755896, 55.85482659999999], [37.376044099999994, 55.854575], [37.3761822, 55.85450659999999], [37.376395200000005, 55.854434899999994], [37.3765354, 55.854402099999994], [37.3767581, 55.8543703], [37.37693290000001, 55.85434849999999], [37.3771499, 55.85434899999999], [37.3774379, 55.85434139999999], [37.3775393, 55.8543312], [37.377724099999995, 55.85429599999999], [37.377868299999996, 55.85425169999999], [37.3780237, 55.85421049999999], [37.3781425, 55.8541143], [37.378252100000005, 55.8540163], [37.37851020000001, 55.85387479999999], [37.3788165, 55.8537569], [37.378980399999996, 55.8536389], [37.37911330000001, 55.85356109999999], [37.379227799999995, 55.853519], [37.3794057, 55.853491999999996], [37.3795719, 55.85348689999999], [37.3798725, 55.8534722], [37.38010439999999, 55.85349299999999], [37.380352300000006, 55.8535469], [37.3805325, 55.85362249999999], [37.3808343, 55.8538052], [37.38104469999999, 55.853941199999994], [37.38124699999999, 55.85412149999999], [37.381360099999995, 55.85423339999999], [37.381527999999996, 55.854360199999995], [37.3817008, 55.85447459999999], [37.38180749999999, 55.8545362], [37.381971699999994, 55.85456799999999], [37.382634499999995, 55.854625799999994], [37.3827278, 55.85463169999999], [37.38286959999999, 55.85462959999999], [37.383039999999994, 55.85463419999999], [37.383244899999994, 55.85463339999999], [37.3834336, 55.8546152], [37.38408669999999, 55.8545702], [37.38418789999999, 55.8545703], [37.384303499999994, 55.85456479999999], [37.3847154, 55.854498899999996], [37.384802799999996, 55.854487599999985], [37.38496699999999, 55.85447069999999], [37.385088599999996, 55.85446509999999], [37.3851919, 55.85446629999999], [37.3853219, 55.854466399999986], [37.385400999999995, 55.85448019999999], [37.3855164, 55.85451], [37.385641899999996, 55.8545752], [37.3859175, 55.8547123], [37.385978, 55.85476939999999], [37.386022499999996, 55.85484929999999], [37.38604449999999, 55.85494169999999], [37.3861314, 55.855047799999994], [37.386187799999995, 55.8551654], [37.386296699999995, 55.8553411], [37.3864142, 55.855437699999996], [37.3865111, 55.8555592], [37.3865711, 55.8556333], [37.3866386, 55.8556939], [37.3867112, 55.8557501], [37.386800099999995, 55.8557942], [37.3869052, 55.85582599999999], [37.38700719999999, 55.8558489], [37.38716719999999, 55.855860899999996], [37.38724759999999, 55.8558598], [37.38736899999999, 55.855846199999995], [37.38749759999999, 55.855823199999996], [37.3875903, 55.8557979], [37.38768209999999, 55.85576459999999], [37.38775759999999, 55.8557298], [37.38784679999999, 55.855678399999995], [37.3879089, 55.8556269], [37.38796109999999, 55.855560499999996], [37.3884201, 55.855240499999994], [37.3886237, 55.855064999999996], [37.3888403, 55.854884599999984], [37.389122300000004, 55.854686399999984], [37.389358200000004, 55.85445369999999], [37.3895991, 55.854299299999994], [37.389815999999996, 55.85420299999999], [37.38996939999999, 55.85416419999999], [37.3900942, 55.85414469999999], [37.39021, 55.8541433], [37.3903606, 55.85416449999999], [37.390809499999996, 55.854433799999995], [37.391258900000004, 55.8547422], [37.3914227, 55.85485189999999], [37.3916537, 55.85494789999999], [37.39205510000001, 55.8550098], [37.39252210000001, 55.8550142], [37.392985800000005, 55.85498669999999], [37.3932658, 55.854949299999994], [37.3934837, 55.85491739999999], [37.3936425, 55.85486569999999], [37.393795600000004, 55.85478199999999], [37.393942, 55.854686399999984], [37.39406399999999, 55.85455999999999], [37.39411280000001, 55.85442649999999], [37.3945561, 55.8544023], [37.3946926, 55.8545259], [37.39534930000001, 55.85584059999999], [37.396103200000006, 55.8573506], [37.3976398, 55.859973499999995], [37.3995994, 55.86230230000001], [37.4016622, 55.864469799999995], [37.4050796, 55.8672401], [37.4068486, 55.8684287], [37.4093294, 55.86988639999999], [37.411427999999994, 55.8709576], [37.406324399999995, 55.8742552], [37.4039951, 55.8759713], [37.3999047, 55.8764499], [37.39557190000001, 55.8770189], [37.3954134, 55.877121599999995], [37.39537810000001, 55.8771209], [37.3944357, 55.877242499999994], [37.390598600000004, 55.8774429], [37.3863176, 55.87766249999999], [37.384873799999994, 55.877742], [37.383409699999994, 55.8778959], [37.38325149999999, 55.8779125], [37.383204899999996, 55.877833599999995], [37.38231290000001, 55.877882699999994], [37.3821655, 55.87786869999999], [37.3820186, 55.8779469], [37.38166579999999, 55.87809], [37.381588799999996, 55.878150500000004], [37.3813907, 55.878206], [37.381254899999995, 55.8781996], [37.3811651, 55.8782184], [37.381056799999996, 55.878283999999994], [37.3809422, 55.8784093], [37.380830399999994, 55.8786384], [37.3807802, 55.8787248], [37.380758, 55.8787741], [37.38074699999999, 55.878864799999995], [37.3807319, 55.87893270000001], [37.380705999999996, 55.8790007], [37.38067649999999, 55.879062499999996], [37.38064699999999, 55.879116100000005], [37.3806152, 55.879173], [37.3805593, 55.8792569], [37.3805307, 55.8792963], [37.3804198, 55.879403399999994], [37.3801951, 55.8795618], [37.38008789999999, 55.8796389], [37.38004539999999, 55.8797247], [37.3799924, 55.8798119], [37.3799186, 55.8798922], [37.3798326, 55.8799355], [37.3797165, 55.879974399999995], [37.379601199999996, 55.879989599999995], [37.3794227, 55.8799893], [37.379294699999996, 55.8799719], [37.37911880000001, 55.879953300000004], [37.378842999999996, 55.88008339999999], [37.3787477, 55.8801144], [37.3785607, 55.8801092], [37.3783516, 55.880113200000004], [37.378165, 55.8801579], [37.3780506, 55.8802118], [37.377940599999995, 55.880272399999996], [37.37788149999999, 55.8803332], [37.37784159999999, 55.880391499999995], [37.3777937, 55.88046449999999], [37.377602599999996, 55.88062109999999], [37.377367799999995, 55.8807527], [37.3770543, 55.8809299], [37.37686779999999, 55.8810162], [37.37666769999999, 55.8810753], [37.3762138, 55.881166099999994], [37.3759603, 55.881258499999994], [37.375846499999994, 55.88128929999999], [37.375730600000004, 55.8812728], [37.375582800000004, 55.881208699999995], [37.375454399999995, 55.8811797], [37.37531520000001, 55.881169299999996], [37.3751796, 55.881185099999996], [37.3750472, 55.8811979], [37.37487939999999, 55.88123149999999], [37.3745517, 55.881319], [37.374426799999995, 55.8813579], [37.374280199999994, 55.88137639999999], [37.3740185, 55.8813652], [37.37380039999999, 55.8813507], [37.3736126, 55.881356999999994], [37.3734126, 55.88140049999999], [37.37295580000001, 55.88150439999999], [37.372919, 55.881517099999996], [37.3728638, 55.8815439], [37.372816, 55.8815767], [37.372761, 55.88162409999999], [37.3727019, 55.88169409999999], [37.372646599999996, 55.881795], [37.372583999999996, 55.881895899999996], [37.3725479, 55.881968699999994], [37.3725285, 55.8820092], [37.372505000000004, 55.8820555], [37.3724542, 55.8821937], [37.3724398, 55.8822502], [37.3724142, 55.882330200000006], [37.3723467, 55.882493499999995], [37.3723079, 55.882565], [37.3722283, 55.88266049999999], [37.3721784, 55.8827062], [37.3721224, 55.882761099999996], [37.3720548, 55.8828039], [37.37198399999999, 55.8828319], [37.3719163, 55.88286469999999], [37.37185169999999, 55.882905900000004], [37.371751499999995, 55.8829785], [37.371578, 55.88306409999999], [37.371480899999995, 55.883153], [37.3713762, 55.88324399999999], [37.3713335, 55.883299699999995], [37.3713124, 55.8833732], [37.37129469999999, 55.8834227], [37.3712563, 55.8834853], [37.3712357, 55.8835249], [37.371226699999994, 55.883577599999995], [37.371220599999994, 55.88362539999999], [37.37122039999999, 55.88369469999999], [37.37121749999999, 55.883763099999996], [37.3712258, 55.883835], [37.37126359999999, 55.883940599999995], [37.371409699999994, 55.884167999999995], [37.3715498, 55.88434169999999], [37.37168169999999, 55.884462299999996], [37.3719281, 55.88459949999999], [37.3720685, 55.88474139999999], [37.3721855, 55.8849032], [37.3723816, 55.88508649999999], [37.3725604, 55.885177399999996], [37.3727774, 55.8852552], [37.372959, 55.885366], [37.3730438, 55.8855096], [37.3731812, 55.8856598], [37.3734127, 55.8858201], [37.3738086, 55.8859853], [37.3743067, 55.8863125], [37.37449099999999, 55.8865255], [37.37456699999999, 55.88664439999999], [37.37463449999999, 55.8866989], [37.3747222, 55.8867963], [37.3747338, 55.88682099999999], [37.374774699999996, 55.886926599999995], [37.3747626, 55.88698109999999], [37.37469469999999, 55.88708329999999], [37.37460939999999, 55.88718709999999], [37.3744503, 55.8873238], [37.3743299, 55.887355], [37.374209099999995, 55.88740419999999], [37.3741769, 55.88736659999999], [37.3739567, 55.887400799999995], [37.37360699999999, 55.88742789999999], [37.3732724, 55.88744129999999], [37.37288159999999, 55.88748719999999], [37.372676, 55.8875529], [37.372559200000005, 55.88764809999999], [37.372522100000005, 55.8877759], [37.372550100000005, 55.887921899999995], [37.37253320000001, 55.888093], [37.37259890000001, 55.8881995], [37.3727291, 55.8883234], [37.37277290000001, 55.8884125], [37.372787499999994, 55.888556300000005], [37.3727774, 55.8888331], [37.372685499999996, 55.8892582], [37.3727433, 55.889393999999996], [37.373003999999995, 55.8895773], [37.373194399999996, 55.88972759999999], [37.3733406, 55.889866299999994], [37.373393300000004, 55.8899356], [37.3734752, 55.8900743], [37.373412800000004, 55.890295200000004], [37.3731888, 55.890539200000006], [37.373029499999994, 55.89075510000001], [37.3729436, 55.8909794], [37.3729403, 55.8911014], [37.3730104, 55.8912318], [37.3732068, 55.891331], [37.3735061, 55.891394], [37.3738233, 55.8914372], [37.3740258, 55.8914588], [37.374228499999994, 55.8914733], [37.374746599999995, 55.891562900000004], [37.3749549, 55.8915821], [37.3751241, 55.8916043], [37.3755863, 55.8917234], [37.3762161, 55.891929399999995], [37.376640699999996, 55.892096300000006], [37.3769609, 55.892260900000004], [37.377183699999996, 55.89239560000001], [37.37728799999999, 55.892479], [37.3773534, 55.8925971], [37.377392300000004, 55.892722500000005], [37.3773918, 55.8928406], [37.37729959999999, 55.892977], [37.3771482, 55.893076300000004], [37.3767403, 55.893271399999996], [37.376426099999996, 55.893514100000004], [37.3762398, 55.8936491], [37.376034499999996, 55.8937965], [37.3758632, 55.8939685], [37.3755865, 55.8942282], [37.3751754, 55.8945472], [37.375030800000005, 55.894666099999995], [37.3749168, 55.8947511], [37.3747603, 55.8948251], [37.3743538, 55.894988999999995], [37.374135200000005, 55.8950696], [37.373983499999994, 55.89509580000001], [37.3737537, 55.89510680000001], [37.37351280000001, 55.895104100000005], [37.373253399999996, 55.8950836], [37.37284749999999, 55.895033100000006], [37.3723888, 55.8949572], [37.372179700000004, 55.8949398], [37.3720235, 55.894946], [37.371867399999985, 55.894978300000005], [37.37168659999999, 55.89503330000001], [37.3715192, 55.895051900000006], [37.3713519, 55.89504290000001], [37.37118469999999, 55.895022700000005], [37.3710353, 55.8949862], [37.370915200000006, 55.8949436], [37.3708081, 55.894897099999994], [37.370598900000005, 55.8948527], [37.3704081, 55.8948229], [37.3703148, 55.89480939999999], [37.37026399999999, 55.8948022], [37.3700339, 55.894789499999995], [37.3698587, 55.8947421], [37.36971890000001, 55.8946731], [37.3695015, 55.8945505], [37.3691976, 55.8944739], [37.368879, 55.8944342], [37.368497399999995, 55.8943885], [37.36816830000001, 55.894335100000006], [37.3678257, 55.8942988], [37.36754139999999, 55.8942852], [37.367412200000004, 55.8942747], [37.3672753, 55.894267299999996], [37.3671932, 55.89428469999999], [37.3671293, 55.8943232], [37.367043499999994, 55.894398800000005], [37.366966399999995, 55.894457599999996], [37.3668927, 55.8944969], [37.366829499999994, 55.8945165], [37.366738600000005, 55.8945204], [37.3666194, 55.8944966], [37.3665144, 55.894461199999995], [37.3663954, 55.8944531], [37.3662702, 55.894482999999994], [37.3661663, 55.894542300000005], [37.3659631, 55.8946333], [37.365859300000004, 55.89466749999999], [37.365717200000006, 55.8947026], [37.365638000000004, 55.894733300000006], [37.3655747, 55.8947755], [37.36553210000001, 55.894829099999995], [37.365501300000005, 55.8948986], [37.365493, 55.894972700000004], [37.365498800000005, 55.895035400000005], [37.3655449, 55.895177000000004], [37.3656115, 55.895347], [37.3656456, 55.8954577], [37.3656698, 55.895517000000005], [37.36570580000001, 55.8956437], [37.3657174, 55.8958296], [37.36571490000001, 55.8959664], [37.3656997, 55.8960477], [37.365649399999995, 55.896131800000006], [37.36553430000001, 55.8962638], [37.36546739999999, 55.8963994], [37.36552270000001, 55.8966179], [37.365611300000005, 55.896683599999996], [37.3657676, 55.896700200000005], [37.36626739999999, 55.8967245], [37.366445999999996, 55.896737300000005], [37.3666178, 55.896753700000005], [37.366709300000004, 55.8967639], [37.367012300000006, 55.896876999999996], [37.3672708, 55.8970003], [37.36740439999999, 55.8970732], [37.36748909999999, 55.897140900000004], [37.3675378, 55.8972212], [37.367553300000004, 55.8972602], [37.3675688, 55.897299], [37.367582, 55.8973567], [37.367555, 55.8974395], [37.3674923, 55.897499599999996], [37.36742949999999, 55.8975748], [37.36742939999999, 55.8976525], [37.367469299999996, 55.8977203], [37.367585, 55.8978006], [37.367642499999995, 55.89788539999999], [37.367662499999994, 55.8979407], [37.3676335, 55.89803860000001], [37.3675346, 55.89817930000001], [37.3672102, 55.898379600000005], [37.366885999999994, 55.89857980000001], [37.3666135, 55.8986625], [37.366019, 55.8988824], [37.3658468, 55.8990111], [37.365756700000006, 55.899114700000005], [37.36573200000001, 55.8992116], [37.365745800000006, 55.899347399999996], [37.365692800000005, 55.8994466], [37.36551550000001, 55.899601499999996], [37.365273200000004, 55.8997712], [37.3651694, 55.8998863], [37.3647991, 55.9000741], [37.3640089, 55.9002455], [37.363663499999994, 55.9002961], [37.3633691, 55.9003037], [37.3630341, 55.9002968], [37.3628543, 55.9002893], [37.362693, 55.900308800000005], [37.3625364, 55.9003591], [37.3624065, 55.9004113], [37.3623642, 55.9004421], [37.3622822, 55.900505900000006], [37.362104900000006, 55.90064949999999], [37.361966499999994, 55.900778200000005], [37.36188939999999, 55.90086779999999], [37.36184459999999, 55.9009716], [37.3618333, 55.901132800000006], [37.361777599999996, 55.901384699999994], [37.3617712, 55.9014555], [37.361789099999996, 55.9015456], [37.3618136, 55.9015719], [37.361868099999995, 55.9015602], [37.3620737, 55.9014737], [37.362245900000005, 55.90142169999999], [37.3623634, 55.901387299999996], [37.3624231, 55.901380499999995], [37.362507300000004, 55.9013825], [37.362553000000005, 55.901396399999996], [37.36259510000001, 55.9014221], [37.3626284, 55.90144179999999], [37.3626756, 55.9014526], [37.3627546, 55.9014508], [37.362808900000005, 55.9014568], [37.3628335, 55.90146959999999], [37.3628386, 55.901491299999996], [37.3628279, 55.9015524], [37.362830900000006, 55.901588999999994], [37.36283290000001, 55.9016058], [37.3628608, 55.9016559], [37.362909300000005, 55.90169749999999], [37.36293570000001, 55.9017168], [37.3629635, 55.901734399999995], [37.362995600000005, 55.901747699999994], [37.3630652, 55.9017736], [37.3631061, 55.901796999999995], [37.363146300000004, 55.90182649999999], [37.3631617, 55.901860799999994], [37.363233300000005, 55.9019031], [37.3632843, 55.9019368], [37.363322600000004, 55.901961799999995], [37.363373800000005, 55.90198939999999], [37.3635542, 55.90207530000001], [37.3636856, 55.902131600000004], [37.3637998, 55.902171100000004], [37.363848499999996, 55.9021774], [37.3638958, 55.902179700000005], [37.3639554, 55.90217820000001], [37.364139300000005, 55.9021664], [37.36418449999999, 55.9021676], [37.3642173, 55.902173600000005], [37.364248599999996, 55.9021861], [37.3643161, 55.90223030000001], [37.3643536, 55.9022473], [37.3643784, 55.9022575], [37.364611499999995, 55.902330600000006], [37.364727099999996, 55.9023692], [37.364796, 55.9023867], [37.364869299999995, 55.902402900000006], [37.3649622, 55.9024167], [37.3650805, 55.902416800000005], [37.36511540000001, 55.9024219], [37.36517280000001, 55.9024347], [37.3652094, 55.9024458], [37.3652516, 55.9024624], [37.365356600000005, 55.9025206], [37.3654092, 55.9025475], [37.3654335, 55.90255690000001], [37.3656704, 55.9026105], [37.3658037, 55.9026452], [37.365851, 55.902666999999994], [37.365908700000006, 55.9027005], [37.3659807, 55.9027292], [37.366078900000005, 55.902750000000005], [37.366248999999996, 55.902778700000006], [37.3664226, 55.9028134], [37.3666318, 55.9028493], [37.3668172, 55.9028838], [37.36688339999999, 55.9028905], [37.3669743, 55.902896], [37.3670452, 55.902900700000004], [37.3670828, 55.9029043], [37.367118700000006, 55.9029116], [37.36726099999999, 55.90295230000001], [37.3673457, 55.9029712], [37.3674281, 55.9029862], [37.36748409999999, 55.902995000000004], [37.3676099, 55.9030058], [37.367716900000005, 55.9030118], [37.3679082, 55.9030254], [37.3679977, 55.9030318], [37.36823270000001, 55.9030498], [37.36833270000001, 55.9030637], [37.368469399999995, 55.903091399999994], [37.3686097, 55.90311820000001], [37.3687642, 55.903133100000005], [37.369193900000006, 55.903172100000006], [37.36933330000001, 55.9031843], [37.3694519, 55.9031979], [37.369545, 55.9032148], [37.3696377, 55.9032365], [37.3697761, 55.903279], [37.3699277, 55.903334], [37.37006349999999, 55.9033986], [37.37013830000001, 55.9034321], [37.370195100000004, 55.903452800000004], [37.3702688, 55.903465399999995], [37.370215, 55.90355530000001], [37.3685896, 55.905577900000004], [37.367846099999994, 55.905343900000005], [37.366283599999996, 55.9067026], [37.36986139999999, 55.90819590000001], [37.372963399999996, 55.909637499999995], [37.376795200000004, 55.911243899999995], [37.377708999999996, 55.9114228], [37.37835020000001, 55.91148949999999], [37.379231399999995, 55.911491299999994], [37.38106479999999, 55.9113985], [37.38231630000001, 55.91134759999999], [37.3830057, 55.9113592], [37.383677299999995, 55.91140059999999], [37.3839973, 55.9114283], [37.3849908, 55.9115081], [37.386109, 55.9116113], [37.386723999999994, 55.91165699999999], [37.3870521, 55.9117312], [37.387326699999996, 55.91182909999999], [37.389345, 55.9125905], [37.3900178, 55.912844299999996], [37.390159700000005, 55.912720900000004], [37.3902377, 55.9126489], [37.390162700000005, 55.9125631], [37.39013020000001, 55.9124066], [37.3900948, 55.9109124], [37.3900942, 55.910795900000004], [37.3900164, 55.90835280000001], [37.3899912, 55.9074117], [37.3899552, 55.9062527], [37.389911, 55.90479739999999], [37.389907799999996, 55.90460469999999], [37.3899171, 55.9043205], [37.3899354, 55.9040539], [37.3899733, 55.903831399999994], [37.3901046, 55.903565300000004], [37.390227499999995, 55.9033576], [37.3904289, 55.903119200000006], [37.3908955, 55.902779800000005], [37.3913797, 55.902464499999994], [37.3919957, 55.902235100000006], [37.39239270000001, 55.902120800000006], [37.392854, 55.9020065], [37.3950441, 55.901700399999996], [37.39599380000001, 55.9015754], [37.3972208, 55.9014305], [37.398245, 55.90160759999999], [37.39839520000001, 55.901589599999994], [37.3992913, 55.9007554], [37.4003749, 55.898704300000006], [37.400568, 55.8983494], [37.4005917, 55.8982942], [37.4008019, 55.897897199999996], [37.4028761, 55.894212200000005], [37.403908900000005, 55.892684599999995], [37.4039771, 55.892496900000005], [37.40408759999999, 55.8922811], [37.404181599999994, 55.8920695], [37.404242499999995, 55.8918433], [37.4043041, 55.891620999999994], [37.4043932, 55.8912228], [37.4043979, 55.8911809], [37.404027799999994, 55.8886169], [37.404059999999994, 55.8881899], [37.404092999999996, 55.8879124], [37.4041625, 55.88768069999999], [37.4042239, 55.887521299999996], [37.404384799999995, 55.88729159999999], [37.404509499999996, 55.887103999999994], [37.404616, 55.8869621], [37.404727099999995, 55.88680339999999], [37.4048951, 55.8866559], [37.4050534, 55.8865162], [37.4052901, 55.8863863], [37.405577900000004, 55.8862348], [37.4062888, 55.8859318], [37.4069546, 55.885687999999995], [37.4093978, 55.8849173], [37.409420499999996, 55.88068759999999], [37.4104313, 55.880302], [37.414931599999996, 55.879310800000006], [37.4141258, 55.8790939], [37.414373499999996, 55.87886739999999], [37.415518500000005, 55.879189], [37.4156599, 55.8791436], [37.417163499999994, 55.8783095], [37.42115520000001, 55.8783224], [37.421162200000005, 55.8779213], [37.423722100000006, 55.877717399999995], [37.4240955, 55.8780005], [37.424293399999996, 55.877938300000004], [37.424519100000005, 55.877891999999996], [37.4247892, 55.87782419999999], [37.425034700000005, 55.8777581], [37.42537060000001, 55.87767439999999], [37.42559830000001, 55.8776108], [37.425834300000005, 55.8775513], [37.42599210000001, 55.8775194], [37.426191, 55.8774823], [37.426447499999995, 55.87746979999999], [37.4266635, 55.87746429999999], [37.4268608, 55.877482799999996], [37.4271857, 55.8775335], [37.427488499999995, 55.87758759999999], [37.427758600000004, 55.87763759999999], [37.428026900000006, 55.877693099999995], [37.428327, 55.8777561], [37.4286017, 55.8778089], [37.42885230000001, 55.8778702], [37.429101100000004, 55.8779347], [37.42939580000001, 55.8779913], [37.4296008, 55.8780165], [37.429795000000006, 55.8780201], [37.430082, 55.8779762], [37.4303564, 55.87792339999999], [37.4306567, 55.877879699999994], [37.4309505, 55.877851199999995], [37.435472100000005, 55.879263599999994], [37.436483499999994, 55.8795786], [37.437785, 55.878564499999996], [37.4378402, 55.878146], [37.437978300000005, 55.8772161], [37.4387242, 55.8765343], [37.440133200000005, 55.875852300000005], [37.4426198, 55.874410999999995], [37.4449403, 55.873419], [37.44762239999999, 55.8719788], [37.44893870000001, 55.871357399999994], [37.4514503, 55.870264799999994], [37.4528921, 55.8700626], [37.4539735, 55.870116], [37.454602699999995, 55.8684899], [37.45454939999999, 55.8671416], [37.454721899999996, 55.86613630000001], [37.455090999999996, 55.864689299999995], [37.4559372, 55.8628426], [37.456082599999995, 55.86188479999999], [37.45660139999999, 55.8608586], [37.4577068, 55.85983739999999], [37.4582562, 55.8585639], [37.458821099999994, 55.85763849999999], [37.459445699999996, 55.8563209], [37.459825599999995, 55.855296599999996], [37.4601813, 55.8541059], [37.460847199999996, 55.85300399999999], [37.4610061, 55.85180669999999], [37.4613263, 55.85104499999999], [37.4628942, 55.8500763], [37.4636035, 55.849086299999996], [37.4634933, 55.8481997], [37.4639345, 55.84768559999999], [37.464462499999996, 55.847118200000004], [37.46537980000001, 55.8462341], [37.466711700000005, 55.8456326], [37.4680678, 55.8446782], [37.468845300000005, 55.8435381], [37.469885399999995, 55.8431779], [37.4703495, 55.842725900000005], [37.471515600000004, 55.8423979], [37.4722678, 55.8417749], [37.47251230000001, 55.840982999999994], [37.4725865, 55.8403538], [37.4720609, 55.8393886], [37.471778900000004, 55.8385544], [37.471677799999995, 55.837785499999995], [37.472178500000005, 55.8371823], [37.474223499999994, 55.8359672], [37.4762079, 55.8342859], [37.4778166, 55.832852800000005], [37.478549900000004, 55.8319632], [37.478983, 55.8315541], [37.479122700000005, 55.830748], [37.4783235, 55.8304707], [37.47446779999999, 55.8300036], [37.4744188, 55.8298286], [37.4757717, 55.8286851], [37.4762377, 55.8282843], [37.476299399999995, 55.828231900000006], [37.4779908, 55.8267936], [37.4782013, 55.8266146], [37.4784938, 55.8265742], [37.4788291, 55.8266538], [37.4803853, 55.8270233], [37.4813937, 55.8270137], [37.4828335, 55.826914800000004], [37.4835307, 55.826837399999995], [37.48428489999999, 55.8267077], [37.4856033, 55.826517], [37.4859625, 55.8264992], [37.486376, 55.826478800000004], [37.4871593, 55.826484699999995], [37.488426999999994, 55.8265657], [37.489792900000005, 55.826931], [37.490292800000006, 55.827064699999994], [37.4906968, 55.827172700000006], [37.4909498, 55.8272398], [37.4910751, 55.8272718], [37.49332820000001, 55.824519], [37.493365700000005, 55.8244783], [37.492648100000004, 55.8242031], [37.4919622, 55.8238104], [37.490720200000005, 55.8230964], [37.4902612, 55.8227664], [37.4898587, 55.822439300000006], [37.4889712, 55.821681999999996], [37.488042, 55.8206297], [37.4875492, 55.81986709999999], [37.48706959999999, 55.8188513], [37.486803599999995, 55.81793449999999], [37.486701, 55.81742749999999], [37.4867197, 55.8171743], [37.486724599999995, 55.81687049999999], [37.4867584, 55.8161493], [37.48684419999999, 55.8153461], [37.4869086, 55.81502439999999], [37.48702779999999, 55.8139517], [37.4871006, 55.8136659], [37.48722399999999, 55.813278399999994], [37.487361899999996, 55.8129907], [37.48765959999999, 55.8124387], [37.48789789999999, 55.812102100000004], [37.4885824, 55.81126879999999], [37.48941, 55.8103134], [37.490987, 55.8084988], [37.493174, 55.8059574], [37.49614270000001, 55.8024742], [37.498478000000006, 55.79981890000001], [37.4995576, 55.79859400000001], [37.50055530000001, 55.79734260000001], [37.50257580000001, 55.794982100000006], [37.50324739999999, 55.7938611], [37.5038924, 55.79112070000001], [37.504044199999996, 55.79044530000001], [37.5043917, 55.788578400000006], [37.50488969999999, 55.7866344], [37.505233700000005, 55.7848542], [37.505761, 55.7826699], [37.5062857, 55.78032210000001], [37.5066488, 55.778409], [37.5068526, 55.7778633], [37.506981399999994, 55.7775711], [37.507051499999996, 55.7774334], [37.5074439, 55.7768213], [37.5077413, 55.776431200000005], [37.50807530000001, 55.77605560000001], [37.5086447, 55.7754461], [37.5092005, 55.7748795], [37.50943290000001, 55.77466149999999], [37.5096911, 55.774396], [37.51004, 55.7740431], [37.51025, 55.773828200000004], [37.51055230000001, 55.7735211], [37.5109932, 55.7730656], [37.511275399999995, 55.77275980000001], [37.5117056, 55.7722795], [37.51188839999999, 55.77208590000001], [37.512122700000006, 55.7718391], [37.5125247, 55.7714167], [37.512802900000004, 55.7711244], [37.51317280000001, 55.77073860000001], [37.5133405, 55.7705612], [37.5136763, 55.77021580000001], [37.513846599999994, 55.7700395], [37.5140063, 55.769874200000004], [37.514308, 55.76955800000001], [37.514664999999994, 55.769177600000006], [37.5147929, 55.769041300000005], [37.514926599999995, 55.76889890000001], [37.5150741, 55.768744500000004], [37.515241599999996, 55.76856910000001], [37.5155606, 55.76823260000001], [37.5159631, 55.767810600000004], [37.5163263, 55.7674284], [37.5171018, 55.7666244], [37.5179168, 55.76577080000001], [37.5187374, 55.764904300000005], [37.5195731, 55.764022800000006], [37.519849699999995, 55.76373630000001], [37.520135900000014, 55.763439600000005], [37.52051660000001, 55.763041], [37.5208286, 55.76271430000001], [37.521232700000006, 55.762271000000005], [37.5214748, 55.76201990000001], [37.5219435, 55.761509000000004], [37.521830900000005, 55.7614838]]]]}}, {"id": 226149, "osm_type": "relation", "type": "Feature", "name": "Западный административный округ", "properties": {"ref": "ЗАО", "name": "Западный административный округ", "name:be": "Заходняя адміністрацыйная акруга", "name:de": "Westlicher Verwaltungsbezirk", "name:en": "Western Administrative Okrug", "website": "http://www.zao.mos.ru/", "boundary": "administrative", "wikipedia": "ru:Западный административный округ", "addr:region": "Москва", "admin_level": "5", "addr:country": "RU"}, "geometry": {"type": "MultiPolygon", "coordinates": [[[[37.3850513, 55.8093072], [37.384948099999995, 55.8090119], [37.380721799999996, 55.809390900000004], [37.3806179, 55.8090092], [37.3797943, 55.8090609], [37.379392100000004, 55.8091485], [37.378641099999996, 55.8083657], [37.3780837, 55.80778459999999], [37.37784179999999, 55.80698699999999], [37.3791232, 55.8065438], [37.3785716, 55.805679999999995], [37.378233, 55.805678900000004], [37.37724649999999, 55.804192], [37.375329, 55.80322749999999], [37.374509399999994, 55.8037032], [37.3743479, 55.8037969], [37.37380139999999, 55.8035562], [37.373561699999996, 55.8029868], [37.3723377, 55.8031613], [37.372382900000005, 55.803293399999994], [37.3720936, 55.8033531], [37.3725457, 55.8056751], [37.372826999999994, 55.8064331], [37.3729591, 55.8074531], [37.372772700000006, 55.8079751], [37.37286759999999, 55.8086101], [37.372793, 55.808685], [37.371746599999994, 55.809241899999996], [37.3730748, 55.811276199999995], [37.3735856, 55.812141499999996], [37.3738627, 55.8125917], [37.37488469999999, 55.812424799999995], [37.375063399999995, 55.8123851], [37.376497699999994, 55.812066099999996], [37.377474199999995, 55.812675999999996], [37.377968599999996, 55.812371], [37.3782798, 55.812192700000004], [37.378300800000005, 55.8121806], [37.378438800000005, 55.812099599999996], [37.379207599999994, 55.81164819999999], [37.379704, 55.81149129999999], [37.3801967, 55.8113191], [37.38022099999999, 55.81126709999999], [37.3799909, 55.811015399999995], [37.3796639, 55.810670599999995], [37.3805733, 55.81065439999999], [37.38108079999999, 55.81064539999999], [37.3807281, 55.80965739999999], [37.3823725, 55.8095241], [37.3850513, 55.8093072]]], [[[37.303564099999996, 55.803558800000005], [37.3032652, 55.8031819], [37.3029227, 55.8024772], [37.302776900000005, 55.8012728], [37.30235390000001, 55.79863350000001], [37.29821730000001, 55.797628100000004], [37.2944673, 55.79671670000001], [37.2944097, 55.796787200000004], [37.294117400000005, 55.79671260000001], [37.294168400000004, 55.796634700000006], [37.293168400000006, 55.79639710000001], [37.2932645, 55.798064700000005], [37.29050200000001, 55.80198969999999], [37.29542210000001, 55.8029975], [37.29663210000001, 55.803202399999996], [37.297769200000005, 55.803354], [37.29863650000001, 55.8034501], [37.299686300000005, 55.8035219], [37.303564099999996, 55.803558800000005]]], [[[37.22058080000001, 55.6105164], [37.216819300000004, 55.609054], [37.214472900000004, 55.608038500000006], [37.2162115, 55.6062574], [37.218235400000005, 55.6040205], [37.21577320000001, 55.6019032], [37.21231270000001, 55.6024835], [37.21033590000001, 55.60482], [37.2085445, 55.6052024], [37.2078688, 55.6058442], [37.20721330000001, 55.6063978], [37.2067495, 55.606677399999995], [37.2066836, 55.6066933], [37.20612230000001, 55.60673880000001], [37.2038893, 55.6067807], [37.20271960000001, 55.60903690000001], [37.20061320000001, 55.609969], [37.19527300000001, 55.6069476], [37.200203300000005, 55.6037206], [37.2004742, 55.603442300000005], [37.200520600000004, 55.603252100000006], [37.20043220000001, 55.603087099999996], [37.199829900000005, 55.60270380000001], [37.19827680000001, 55.603540300000006], [37.197946900000005, 55.603697399999994], [37.19905910000001, 55.604329], [37.19797990000001, 55.6049442], [37.19549010000001, 55.603530500000005], [37.195133700000014, 55.60371210000001], [37.194028200000005, 55.603128700000006], [37.19495320000001, 55.60259070000001], [37.19212870000001, 55.6013665], [37.191728000000005, 55.6018909], [37.19099320000001, 55.6017778], [37.19097800000001, 55.6017842], [37.1908778, 55.601801599999995], [37.1908517, 55.6018377], [37.19059220000001, 55.601786399999995], [37.19030910000001, 55.6020849], [37.19018290000001, 55.6022261], [37.1902594, 55.6022468], [37.190118100000014, 55.602388700000006], [37.1899968, 55.60235090000001], [37.1897881, 55.602540100000006], [37.189494599999996, 55.6024374], [37.18932230000001, 55.60237280000001], [37.189105100000006, 55.602314500000006], [37.189237399999996, 55.60210880000001], [37.188176500000004, 55.601838], [37.188096800000004, 55.60188779999999], [37.1877603, 55.6017427], [37.187310100000005, 55.6016185], [37.1872233, 55.6016938], [37.186773300000006, 55.6015547], [37.186752500000004, 55.601547599999996], [37.1866048, 55.60170290000001], [37.1861857, 55.6019682], [37.184449699999995, 55.6014043], [37.1835234, 55.60235190000001], [37.185402100000005, 55.6029612], [37.186081099999996, 55.60320230000001], [37.1864995, 55.6033467], [37.1866499, 55.60339810000001], [37.185816100000004, 55.604213200000004], [37.185413000000004, 55.6040981], [37.1845349, 55.6047048], [37.1842421, 55.6049907], [37.1841566, 55.6049657], [37.1831699, 55.6056473], [37.184554, 55.6062608], [37.186052600000004, 55.606971900000005], [37.1861413, 55.60695880000001], [37.1862902, 55.60687], [37.1875999, 55.607475300000004], [37.1876354, 55.6075901], [37.1894868, 55.608344900000006], [37.1896379, 55.608476800000005], [37.1904065, 55.6088837], [37.1906344, 55.609095200000006], [37.193707, 55.610497599999995], [37.196051800000006, 55.6116092], [37.19616430000001, 55.6115501], [37.19673090000001, 55.6120696], [37.197821399999995, 55.6130165], [37.19960230000001, 55.61468349999999], [37.2017672, 55.615994300000004], [37.20711680000001, 55.617794399999994], [37.206813700000005, 55.618051200000004], [37.207337800000005, 55.618213700000005], [37.207467599999994, 55.61811200000001], [37.20994530000001, 55.619106], [37.2112733, 55.62010530000001], [37.21137530000001, 55.620161700000004], [37.2114751, 55.62017330000001], [37.2115913, 55.62015350000001], [37.21207230000001, 55.620570400000005], [37.2119824, 55.620591600000004], [37.2141215, 55.6222805], [37.2145561, 55.62275910000001], [37.216923900000005, 55.621861499999994], [37.2173867, 55.6216869], [37.2162354, 55.6208673], [37.2177305, 55.6184031], [37.21768339999999, 55.6183835], [37.2166937, 55.6180144], [37.214301, 55.617143], [37.21531510000001, 55.6159174], [37.218304, 55.6142366], [37.21845580000001, 55.61411090000001], [37.21803380000001, 55.61271210000001], [37.21815820000001, 55.6125813], [37.21865270000001, 55.61251250000001], [37.21893120000001, 55.6124171], [37.218994300000006, 55.6122076], [37.2191205, 55.6118322], [37.22058080000001, 55.6105164]]], [[[37.3705437, 55.78832260000001], [37.37060099999999, 55.78819190000001], [37.369195600000005, 55.7876769], [37.3677342, 55.78717210000001], [37.3670921, 55.7869869], [37.366542200000005, 55.78671430000001], [37.3647942, 55.786086399999995], [37.361634599999995, 55.78505810000001], [37.359386099999995, 55.78408639999999], [37.3602531, 55.783532400000006], [37.36046699999999, 55.783374], [37.36071230000001, 55.7832652], [37.3606997, 55.783139000000006], [37.3606052, 55.7830651], [37.359504099999995, 55.7824176], [37.359631699999994, 55.782332300000014], [37.35825139999999, 55.7814912], [37.3581451, 55.781575100000005], [37.358261999999996, 55.781699399999994], [37.358294199999996, 55.7817995], [37.3582366, 55.7818352], [37.3566283, 55.7808402], [37.3555297, 55.780143900000006], [37.35428569999999, 55.779347200000004], [37.3522319, 55.778027200000004], [37.3524529, 55.777815600000004], [37.3521939, 55.7776802], [37.35239, 55.77751000000001], [37.3522538, 55.7764698], [37.3524633, 55.7743212], [37.352478399999995, 55.7741673], [37.352439499999996, 55.7737624], [37.350630599999995, 55.77287870000001], [37.35020149999999, 55.7724094], [37.3486378, 55.77073270000001], [37.3487426, 55.770685300000004], [37.3484687, 55.7701745], [37.348105600000004, 55.7700806], [37.3477342, 55.770162400000004], [37.347392, 55.769817700000004], [37.34706709999999, 55.76955120000001], [37.346419, 55.76957000000001], [37.34591580000001, 55.76955720000001], [37.3457276, 55.769593500000006], [37.3450037, 55.76973360000001], [37.344514499999995, 55.76975650000001], [37.344501199999996, 55.76934670000001], [37.344496899999996, 55.76859810000001], [37.3398609, 55.76901970000001], [37.338343800000004, 55.769276600000005], [37.3403335, 55.7704036], [37.3392543, 55.77059880000001], [37.339516100000004, 55.770717700000006], [37.3382839, 55.771291399999996], [37.3366542, 55.7711801], [37.3323016, 55.7719341], [37.3320312, 55.7715445], [37.3319586, 55.77137530000001], [37.3320439, 55.76998280000001], [37.3320916, 55.76885730000001], [37.33211120000001, 55.768689], [37.33233830000001, 55.768688100000006], [37.332412000000005, 55.768296400000004], [37.3322456, 55.768248400000004], [37.332247499999994, 55.767984], [37.3305401, 55.7678458], [37.3296449, 55.7674265], [37.32871930000001, 55.7672931], [37.32854880000001, 55.7672942], [37.3273495, 55.7672245], [37.3271802, 55.7672065], [37.325541900000005, 55.76710560000001], [37.3240721, 55.7670194], [37.322954, 55.76695780000001], [37.32070230000001, 55.766820700000004], [37.3192726, 55.76897250000001], [37.318936900000004, 55.769506500000006], [37.3174229, 55.769290600000005], [37.3160351, 55.76914930000001], [37.3143587, 55.76912480000001], [37.3127565, 55.769081], [37.311442099999994, 55.7694495], [37.3099097, 55.76999980000001], [37.3084937, 55.77059130000001], [37.309290999999995, 55.77110090000001], [37.3093795, 55.7712046], [37.3098117, 55.771972100000006], [37.31085159999999, 55.77543610000001], [37.311632499999995, 55.77525520000001], [37.3153018, 55.7746034], [37.32241500000001, 55.7769447], [37.32297290000001, 55.776733500000006], [37.3240236, 55.7775334], [37.323466599999996, 55.7777055], [37.3243366, 55.778602500000005], [37.325135900000014, 55.7790494], [37.32537610000001, 55.77909880000001], [37.3268031, 55.77932810000001], [37.3278009, 55.780016], [37.3284094, 55.78108639999999], [37.3278161, 55.78124639999999], [37.3246985, 55.7824278], [37.32223520000001, 55.78335870000001], [37.317887599999985, 55.7847147], [37.31540759999999, 55.785536500000006], [37.31282709999999, 55.7863845], [37.3131458, 55.77975130000001], [37.3127202, 55.7798866], [37.31184329999999, 55.7801654], [37.3115518, 55.7841496], [37.31060599999999, 55.784464199999995], [37.3123888, 55.787057499999996], [37.312880099999994, 55.787790300000005], [37.3141156, 55.78805860000001], [37.31458979999999, 55.788064399999996], [37.314527899999995, 55.7882412], [37.315414399999995, 55.7882412], [37.315399, 55.7884035], [37.314842299999995, 55.78876280000001], [37.3145021, 55.789383], [37.3141156, 55.789835000000004], [37.313708399999996, 55.79011610000001], [37.31325999999999, 55.7903074], [37.312821899999996, 55.790811600000005], [37.312486799999995, 55.79097970000001], [37.31143539999999, 55.791234700000004], [37.31122919999999, 55.791234700000004], [37.3107138, 55.79151860000001], [37.3100592, 55.792086600000005], [37.310564299999996, 55.79230970000001], [37.3115333, 55.79258790000001], [37.316043199999996, 55.792666100000005], [37.3164453, 55.79277910000001], [37.3164556, 55.792877600000004], [37.3162288, 55.79291240000001], [37.3158938, 55.79300510000001], [37.314919599999996, 55.79339340000001], [37.314388699999995, 55.7936861], [37.317079199999995, 55.7947697], [37.317172, 55.79503920000001], [37.3181822, 55.79503920000001], [37.321310800000006, 55.79612860000001], [37.3213211, 55.79623580000001], [37.32315090000001, 55.7970297], [37.323295200000004, 55.79689930000001], [37.3233777, 55.7968935], [37.323393100000004, 55.797003600000004], [37.3243879, 55.79681240000001], [37.3246147, 55.7966965], [37.3247281, 55.79660090000001], [37.3244085, 55.796386500000004], [37.3245271, 55.796288000000004], [37.3250064, 55.79643000000001], [37.324970300000004, 55.79660090000001], [37.3247538, 55.79685590000001], [37.3240838, 55.79711660000001], [37.3235735, 55.79711660000001], [37.3225685, 55.79741500000001], [37.3216559, 55.7977624], [37.320955000000005, 55.797820300000005], [37.320295200000004, 55.7976697], [37.319284999999994, 55.7972699], [37.319284999999994, 55.79703230000001], [37.3195118, 55.79679470000001], [37.3195324, 55.79663240000001], [37.31848099999999, 55.7964065], [37.317924299999994, 55.796110900000016], [37.316821299999994, 55.79578060000001], [37.3166151, 55.79623260000001], [37.316378, 55.79635430000001], [37.3159348, 55.79634270000001], [37.3153472, 55.796093500000005], [37.31526469999999, 55.79616890000001], [37.3155946, 55.79656870000001], [37.315336900000005, 55.796858400000005], [37.313924699999994, 55.79630790000001], [37.3137185, 55.79609930000001], [37.3137597, 55.79597180000001], [37.3126773, 55.79567630000001], [37.31188359999999, 55.796858400000005], [37.311440299999994, 55.79679470000001], [37.31167739999999, 55.79639490000001], [37.3097394, 55.79601820000001], [37.3094199, 55.7958617], [37.3092269, 55.79677550000001], [37.309202, 55.796893600000004], [37.3091519, 55.79713080000001], [37.3080428, 55.79697430000001], [37.3079191, 55.797228200000006], [37.310296099999995, 55.797675500000004], [37.31189479999999, 55.7978565], [37.314306099999996, 55.79813320000002], [37.314769899999995, 55.79925730000001], [37.316367699999994, 55.799396400000006], [37.319440799999995, 55.800483799999995], [37.3195118, 55.800508900000004], [37.320377, 55.8003827], [37.3204547, 55.8003742], [37.3205736, 55.800555200000005], [37.3211611, 55.8006132], [37.32179, 55.800752200000005], [37.323161, 55.8007233], [37.32515050000001, 55.800549499999995], [37.3276039, 55.80029449999999], [37.33448599999999, 55.79961080000001], [37.3344983, 55.79996250000001], [37.3349988, 55.8010969], [37.3361042, 55.8020658], [37.342775800000005, 55.8051114], [37.3473758, 55.8065619], [37.351141299999995, 55.8058142], [37.3581286, 55.8037392], [37.359121099999996, 55.80128469999999], [37.357334599999994, 55.8003252], [37.3541188, 55.798919300000016], [37.35364239999999, 55.797223300000006], [37.34873290000001, 55.79638190000001], [37.3531093, 55.79436810000001], [37.35781739999999, 55.79256830000001], [37.3606125, 55.7916811], [37.3611837, 55.79161580000001], [37.36726469999999, 55.790358900000015], [37.36835620000001, 55.7899745], [37.3687664, 55.78973520000001], [37.36917390000001, 55.7894487], [37.3698721, 55.78891050000001], [37.370051499999995, 55.788777100000004], [37.3703118, 55.7885664], [37.3704513, 55.788433600000005], [37.3705437, 55.78832260000001]]], [[[37.3154753, 55.6129661], [37.3154505, 55.61293270000001], [37.3153795, 55.61290270000001], [37.3153056, 55.612877], [37.3152019, 55.6128808], [37.31496599999999, 55.6129145], [37.31488029999999, 55.612909300000005], [37.314813699999995, 55.6128803], [37.3147303, 55.612794], [37.314713499999996, 55.61273290000001], [37.31472649999999, 55.612690300000004], [37.3149131, 55.612585100000004], [37.3149259, 55.61243880000001], [37.31496979999999, 55.6120764], [37.314009199999994, 55.6115751], [37.31427699999999, 55.6114785], [37.3143502, 55.611022999999996], [37.31443349999999, 55.610776200000004], [37.314315900000004, 55.6103736], [37.3132303, 55.6098613], [37.313086299999995, 55.6098307], [37.311623899999994, 55.60871500000001], [37.312113700000005, 55.6085295], [37.31139339999999, 55.6079832], [37.309849199999995, 55.608666], [37.3097142, 55.60855220000001], [37.30962149999999, 55.608586100000004], [37.308278, 55.6074725], [37.308505100000005, 55.607386399999996], [37.3077325, 55.606664499999994], [37.307472, 55.6058632], [37.3070556, 55.6057004], [37.30774749999999, 55.605444], [37.307440899999996, 55.605083900000004], [37.307546699999996, 55.604656], [37.3073786, 55.604542300000006], [37.3075184, 55.604339800000005], [37.310517399999995, 55.603870900000004], [37.31045759999999, 55.6033491], [37.30989399999999, 55.602835600000006], [37.31008469999999, 55.602075500000005], [37.309605, 55.601243999999994], [37.30967999999999, 55.6011936], [37.3099721, 55.6013504], [37.3103367, 55.601150200000006], [37.311323699999996, 55.6012706], [37.3118183, 55.6012587], [37.3130339, 55.6009826], [37.3132269, 55.600811300000004], [37.3126301, 55.600447499999994], [37.3127154, 55.60013790000001], [37.3137507, 55.5992018], [37.31464559999999, 55.59903210000001], [37.31376169999999, 55.598784], [37.31283749999999, 55.598527100000005], [37.3107373, 55.5979267], [37.30678339999999, 55.596978400000005], [37.303423699999996, 55.596097900000004], [37.299228500000005, 55.59500010000001], [37.29515520000002, 55.59393310000001], [37.293068000000005, 55.593376000000006], [37.284026999999995, 55.59111330000001], [37.2808707, 55.59031800000001], [37.27821830000001, 55.5896061], [37.2775214, 55.589382], [37.2761614, 55.5890809], [37.2738238, 55.5884361], [37.27070080000001, 55.587579999999996], [37.2706013, 55.5874983], [37.268910800000015, 55.5870569], [37.26890420000001, 55.5870177], [37.26575230000002, 55.5862918], [37.263087, 55.5855438], [37.26012080000001, 55.58488059999999], [37.256475200000004, 55.584060799999996], [37.2526638, 55.5832149], [37.2496384, 55.582540300000005], [37.24393210000001, 55.583830999999996], [37.2419491, 55.5847732], [37.2309815, 55.583631], [37.230206800000005, 55.585321300000004], [37.23537330000001, 55.5865564], [37.23534860000001, 55.5891395], [37.234877399999995, 55.5934803], [37.236514400000004, 55.594053], [37.23905280000001, 55.5954879], [37.23916620000001, 55.59544030000001], [37.23973300000001, 55.59574090000001], [37.2398011, 55.59594020000001], [37.2418516, 55.5970491], [37.2456424, 55.601942300000005], [37.24655890000001, 55.6022498], [37.247379200000005, 55.60258290000001], [37.24833430000001, 55.6030376], [37.24843620000001, 55.6031245], [37.2490035, 55.6035917], [37.249142400000004, 55.6037643], [37.2492225, 55.603894], [37.249338400000006, 55.6040761], [37.249580800000004, 55.6049631], [37.250035800000006, 55.6067861], [37.2504056, 55.608293800000006], [37.2544191, 55.610126900000004], [37.2530984, 55.6110538], [37.248562500000006, 55.6142371], [37.248870600000004, 55.614471099999996], [37.2488851, 55.6145658], [37.2491435, 55.614752100000004], [37.2491441, 55.614981799999995], [37.2503672, 55.6149381], [37.250143200000004, 55.6148701], [37.2509955, 55.61444709999999], [37.2528613, 55.6154236], [37.254087999999996, 55.61601580000001], [37.255205200000006, 55.6164853], [37.25870690000001, 55.6172331], [37.258554700000005, 55.6173598], [37.25911120000001, 55.6174909], [37.2592167, 55.6173642], [37.2610395, 55.6177041], [37.2613514, 55.61783739999999], [37.261526, 55.61782749999999], [37.26151850000001, 55.6173191], [37.2615865, 55.6170912], [37.26290050000001, 55.615086999999995], [37.26313930000001, 55.61471], [37.26347560000001, 55.6144149], [37.267375400000006, 55.616159800000005], [37.26821600000001, 55.6166007], [37.26897300000001, 55.6169261], [37.269436400000004, 55.6171848], [37.2716524, 55.618802900000006], [37.2721804, 55.6191], [37.272863900000004, 55.6193347], [37.2737654, 55.619647699999994], [37.27393230000001, 55.6195497], [37.2792364, 55.6163868], [37.2799813, 55.6173713], [37.2805646, 55.617738800000005], [37.2805616, 55.617750300000004], [37.281135400000004, 55.618125400000004], [37.281402, 55.618522500000005], [37.2818339, 55.6188452], [37.28218590000001, 55.619313700000006], [37.28293630000001, 55.6191284], [37.282415500000006, 55.61843820000001], [37.28258580000001, 55.618363200000005], [37.2804408, 55.615833200000004], [37.2805295, 55.6157811], [37.2804462, 55.6156819], [37.2812394, 55.615207], [37.281361499999996, 55.615297], [37.2814239, 55.6152606], [37.2814257, 55.6152628], [37.2816293, 55.615145000000005], [37.2818521, 55.6152612], [37.282625200000005, 55.615363800000004], [37.2838035, 55.615189], [37.2870949, 55.616305700000005], [37.2875796, 55.616283499999994], [37.288157500000004, 55.61653930000001], [37.2881676, 55.6163965], [37.288638600000006, 55.6167271], [37.2886821, 55.6168669], [37.28933290000001, 55.6166826], [37.28971580000001, 55.616726], [37.290384, 55.6163776], [37.29041620000001, 55.6164009], [37.2918896, 55.6157448], [37.29191170000001, 55.6157606], [37.29260290000001, 55.615480999999996], [37.2939434, 55.614655], [37.29410590000001, 55.614696699999996], [37.294251900000006, 55.614863899999996], [37.294651200000004, 55.6150298], [37.294786900000005, 55.615037300000004], [37.294956000000006, 55.6152424], [37.29524590000001, 55.615341900000004], [37.2960475, 55.616945], [37.2970894, 55.61815810000001], [37.29714680000001, 55.618180300000006], [37.2972635, 55.6181896], [37.2974048, 55.61818530000001], [37.29773980000001, 55.61812880000001], [37.298052900000016, 55.6183666], [37.29809430000001, 55.61843280000001], [37.298251400000005, 55.61855280000001], [37.29827570000001, 55.61855290000001], [37.29832000000001, 55.61855870000001], [37.29836240000001, 55.6185747], [37.29841050000001, 55.6186055], [37.29845260000001, 55.6186524], [37.29850470000001, 55.6187072], [37.29855490000001, 55.6187496], [37.29861720000001, 55.618798700000006], [37.29867540000001, 55.6188148], [37.29873000000001, 55.61881030000001], [37.298772200000016, 55.6187966], [37.29882290000001, 55.618768200000005], [37.298861200000005, 55.61873870000001], [37.29894010000001, 55.6187114], [37.29897050000001, 55.6186692], [37.298998800000014, 55.6186624], [37.29905720000001, 55.6186625], [37.299079500000005, 55.6186592], [37.29910970000001, 55.618642], [37.29914610000001, 55.618633], [37.299208500000006, 55.618633200000005], [37.29924690000001, 55.61864], [37.299293000000006, 55.6186572], [37.2993475, 55.6186618], [37.29942210000001, 55.6186666], [37.299478400000005, 55.6186747], [37.29952890000001, 55.6186747], [37.29958130000001, 55.618660999999996], [37.2996217, 55.6186543], [37.299702300000014, 55.6186488], [37.29981730000001, 55.6186306], [37.29990610000001, 55.6186194], [37.29995050000001, 55.61859890000001], [37.29997670000001, 55.61857620000001], [37.300021199999996, 55.6185637], [37.300051499999995, 55.618549], [37.3000759, 55.618525000000005], [37.3001144, 55.6184784], [37.3001731, 55.618428300000005], [37.300229699999996, 55.61839870000001], [37.30027, 55.6183884], [37.3003104, 55.618385100000005], [37.30033280000001, 55.61837030000001], [37.3003609, 55.61834290000001], [37.3004518, 55.618334000000004], [37.300487999999994, 55.618323800000006], [37.3005346, 55.61831480000001], [37.3005608, 55.61831480000001], [37.3006109, 55.61833200000001], [37.30064719999999, 55.618337800000006], [37.30068949999999, 55.61833790000001], [37.300713800000004, 55.6183345], [37.3007299, 55.6183241], [37.3007502, 55.6182968], [37.3007887, 55.6182775], [37.300815, 55.618270800000005], [37.3008331, 55.6182548], [37.30086939999999, 55.6182491], [37.3009561, 55.6182378], [37.3010308, 55.6182299], [37.301085199999996, 55.6182256], [37.3011356, 55.6182279], [37.3011437, 55.6182347], [37.3011638, 55.6182461], [37.301179999999995, 55.6182462], [37.301196, 55.6182372], [37.3012183, 55.618222300000006], [37.30123439999999, 55.618215500000005], [37.3013149, 55.6182145], [37.3013736, 55.618200900000005], [37.3013998, 55.618200900000005], [37.301432, 55.618209], [37.3014522, 55.61821020000001], [37.3014763, 55.61821030000001], [37.301504599999994, 55.6181965], [37.301542999999995, 55.618183], [37.3015792, 55.6181807], [37.30160959999999, 55.618180800000005], [37.301665899999996, 55.61819680000001], [37.30169399999999, 55.618200200000004], [37.3017082, 55.618200300000005], [37.30172639999999, 55.618191200000005], [37.301740499999994, 55.61817980000001], [37.30176459999999, 55.61817530000001], [37.301805099999996, 55.618176500000004], [37.30186959999999, 55.618180100000004], [37.301912, 55.6181744], [37.30197439999999, 55.61815500000001], [37.3020068, 55.61815060000001], [37.302039, 55.61815060000001], [37.3020712, 55.61815880000001], [37.3021094, 55.61815880000001], [37.3021661, 55.618148500000004], [37.3022347, 55.61812580000001], [37.3022688, 55.618121300000006], [37.3023031, 55.618124900000005], [37.3023574, 55.61813980000001], [37.3023898, 55.618145500000004], [37.30242, 55.618145500000004], [37.3024423, 55.61813190000001], [37.30248459999999, 55.618124], [37.302528900000006, 55.61812290000001], [37.302621599999995, 55.618123000000004], [37.302673999999996, 55.61812200000001], [37.3027466, 55.61811520000001], [37.3027869, 55.61811540000001], [37.3028756, 55.618121200000004], [37.3029643, 55.618122500000005], [37.3030713, 55.61809530000001], [37.3030956, 55.61809530000001], [37.303176300000004, 55.6180886], [37.303220499999995, 55.6180796], [37.3032851, 55.618056800000005], [37.3033112, 55.6180546], [37.3033657, 55.6180546], [37.3034082, 55.618051300000005], [37.30342439999999, 55.618044499999996], [37.303454699999996, 55.6180091], [37.303484999999995, 55.61798639999999], [37.303523399999996, 55.617977399999994], [37.3035598, 55.6179763], [37.3036342, 55.617976399999996], [37.3037795, 55.6179686], [37.3039266, 55.617948399999996], [37.3041081, 55.6179349], [37.3041888, 55.617934], [37.30426139999999, 55.6179227], [37.3043461, 55.6179125], [37.30445099999999, 55.6179036], [37.3045638, 55.6179003], [37.3046928, 55.617912000000004], [37.304743099999996, 55.6179131], [37.30484379999999, 55.617913300000005], [37.3049326, 55.6179282], [37.3049689, 55.6179283], [37.305025300000004, 55.617917], [37.3051041, 55.617894299999996], [37.3051505, 55.617877299999996], [37.3051746, 55.61787739999999], [37.3052008, 55.617888799999996], [37.305208900000004, 55.617899099999995], [37.3052147, 55.6179207], [37.3052228, 55.6179356], [37.3052651, 55.617945999999996], [37.3052973, 55.6179506], [37.305315400000005, 55.61795], [37.3053639, 55.617948399999996], [37.305511100000004, 55.617907599999995], [37.3055434, 55.6179008], [37.3055596, 55.617890499999994], [37.305592000000004, 55.617846099999994], [37.305640499999996, 55.61782099999999], [37.3056771, 55.617809699999995], [37.305709300000004, 55.617809799999996], [37.305767599999996, 55.6178179], [37.305813900000004, 55.6178202], [37.3058483, 55.617806599999994], [37.3058907, 55.617777], [37.3059635, 55.6177543], [37.306015800000004, 55.6177452], [37.3060481, 55.617732700000005], [37.3060987, 55.6177019], [37.3061572, 55.61768159999999], [37.3062056, 55.617677099999995], [37.30625, 55.617669199999995], [37.3063167, 55.617642999999994], [37.3063794, 55.6176101], [37.30643, 55.617580399999994], [37.3065289, 55.617552100000005], [37.3066056, 55.6175248], [37.306678399999996, 55.61748959999999], [37.3067067, 55.617466799999995], [37.3067713, 55.6174191], [37.3068281, 55.6173827], [37.306941099999996, 55.6173463], [37.307009699999995, 55.6173282], [37.3070703, 55.6173032], [37.307151, 55.6172782], [37.30722759999999, 55.6172658], [37.3072721, 55.6172521], [37.3073084, 55.61723739999999], [37.3073426, 55.6172363], [37.307395, 55.6172363], [37.30743139999999, 55.6172341], [37.307491899999995, 55.6172171], [37.3075748, 55.6172001], [37.30760709999999, 55.617187599999994], [37.3076393, 55.6171592], [37.30764549999999, 55.617133], [37.30762939999999, 55.617108900000005], [37.3075913, 55.617076999999995], [37.3075754, 55.6170518], [37.3075735, 55.617008399999996], [37.307561699999994, 55.616963999999996], [37.307543599999995, 55.616933100000004], [37.30749739999999, 55.6168942], [37.30745939999999, 55.616854399999994], [37.30736709999999, 55.616788], [37.3073007, 55.6167548], [37.30726649999999, 55.6167354], [37.307250499999995, 55.616708], [37.30722239999999, 55.6166771], [37.3071702, 55.616649699999996], [37.3071603, 55.616630300000004], [37.30716439999999, 55.616592700000005], [37.3071851, 55.6165743], [37.3072782, 55.6164012], [37.307756, 55.616205], [37.307890799999996, 55.616161399999996], [37.307978999999996, 55.61611490000001], [37.3081346, 55.616021499999995], [37.3082754, 55.61595930000001], [37.308399800000004, 55.6159214], [37.308531200000004, 55.615917800000005], [37.30868939999999, 55.6159346], [37.3088758, 55.6159849], [37.308936200000005, 55.6159974], [37.3089936, 55.6159965], [37.3090408, 55.61597270000001], [37.3090663, 55.615936600000005], [37.3091055, 55.6158035], [37.3091511, 55.615775000000006], [37.3092269, 55.6157665], [37.3092588, 55.615739000000005], [37.3092608, 55.615710400000005], [37.3092104, 55.6156827], [37.309130100000004, 55.6156661], [37.3090524, 55.6156578], [37.3089449, 55.615632700000006], [37.3088997, 55.6155995], [37.308914800000004, 55.615571900000006], [37.308983999999995, 55.61555580000001], [37.3090949, 55.6155474], [37.3092858, 55.615543100000004], [37.3094147, 55.6155412], [37.3095881, 55.6155254], [37.309727599999995, 55.6155016], [37.30982039999999, 55.615473200000004], [37.30986939999999, 55.615442], [37.309888199999996, 55.6154012], [37.309858399999996, 55.61530590000001], [37.3098117, 55.615169800000004], [37.309833999999995, 55.61513070000001], [37.3098913, 55.615109000000004], [37.3099703, 55.6151044], [37.310042599999996, 55.61511780000001], [37.310131399999996, 55.6151846], [37.3102133, 55.6152177], [37.31042399999999, 55.6152269], [37.3105567, 55.61525280000001], [37.310649299999994, 55.6152405], [37.3107506, 55.6152025], [37.31081639999999, 55.615150400000005], [37.310863899999994, 55.6150743], [37.3109719, 55.6150041], [37.311070599999994, 55.6149368], [37.3111051, 55.61488539999999], [37.3111023, 55.6148519], [37.31107539999999, 55.614817699999996], [37.31094099999999, 55.6147956], [37.31082149999999, 55.6147538], [37.310767999999996, 55.6147106], [37.3107957, 55.6146706], [37.310860899999994, 55.6146508], [37.310963599999994, 55.61464899999999], [37.311104799999995, 55.614657799999996], [37.311232499999996, 55.61468369999999], [37.311344999999996, 55.6147125], [37.311469399999986, 55.6147498], [37.3115309, 55.6147858], [37.311568199999996, 55.6148337], [37.31162039999999, 55.614849899999996], [37.311689499999986, 55.61484139999999], [37.311751799999996, 55.614812900000004], [37.31186469999999, 55.6147627], [37.31198779999999, 55.6147296], [37.3120703, 55.6147287], [37.3121375, 55.6147479], [37.3122146, 55.61480409999999], [37.3122766, 55.614856599999996], [37.3123653, 55.614927099999996], [37.3124527, 55.614960599999996], [37.3125318, 55.6149655], [37.312604099999994, 55.6149561], [37.3126767, 55.614927699999996], [37.3127913, 55.61486699999999], [37.3129279, 55.61480039999999], [37.312968399999995, 55.6147663], [37.3129771, 55.6147206], [37.312947099999995, 55.614673999999994], [37.312869899999995, 55.614622499999996], [37.3127776, 55.6145623], [37.3127325, 55.6144928], [37.312751399999996, 55.6144338], [37.312820499999994, 55.6143948], [37.3129114, 55.6143808], [37.31302409999999, 55.6143857], [37.313123399999995, 55.614358200000005], [37.313207799999994, 55.6143242], [37.3132853, 55.6142786], [37.313366499999994, 55.6141911], [37.3133785, 55.614139800000004], [37.3133722, 55.614075], [37.3133506, 55.6140036], [37.31336439999999, 55.6139256], [37.3134103, 55.6138229], [37.31346939999999, 55.6137611], [37.3135252, 55.613722100000004], [37.3135893, 55.613713700000005], [37.31366159999999, 55.613731900000005], [37.313742, 55.6137749], [37.31384949999999, 55.6138226], [37.313921799999996, 55.6138332], [37.31399749999999, 55.613813300000004], [37.314078599999995, 55.61375820000001], [37.31417999999999, 55.6136756], [37.31422419999999, 55.613581499999995], [37.314273099999994, 55.613526300000004], [37.31438099999999, 55.6134903], [37.3146151, 55.613438300000006], [37.3147179, 55.613391], [37.3148108, 55.613342100000004], [37.314923699999994, 55.6132978], [37.3150489, 55.6132762], [37.315225, 55.6132623], [37.31529749999999, 55.613240399999995], [37.31533280000001, 55.6132062], [37.31535830000001, 55.613156800000006], [37.3154328, 55.613083599999996], [37.3154566, 55.6130265], [37.3154753, 55.6129661]]], [[[37.5744922, 55.7488635], [37.5744493, 55.746327300000004], [37.574133800000006, 55.745453600000005], [37.573891399999994, 55.744708900000006], [37.5730331, 55.7436943], [37.56832670000001, 55.73855250000001], [37.56575030000001, 55.736401], [37.563632600000005, 55.735095400000006], [37.559062499999996, 55.733068700000004], [37.553034499999995, 55.729946600000005], [37.5488288, 55.728424200000006], [37.5477856, 55.72806810000001], [37.545220300000004, 55.72719130000001], [37.5449026, 55.72705570000001], [37.5430747, 55.72556630000001], [37.54186349999999, 55.724039600000005], [37.54118149999999, 55.722055800000014], [37.541081199999994, 55.72012510000001], [37.5418853, 55.7175946], [37.543330700000006, 55.715617200000004], [37.5459418, 55.71368699999999], [37.54851590000001, 55.712262800000005], [37.552896999999994, 55.710972600000005], [37.5568729, 55.710342600000004], [37.5592321, 55.7102802], [37.55702469999999, 55.70861480000001], [37.55414939999999, 55.70653060000001], [37.546313000000005, 55.700746300000006], [37.536571200000004, 55.69356320000001], [37.535747300000004, 55.69309880000001], [37.530053300000006, 55.689929], [37.51166239999999, 55.679730600000006], [37.5121291, 55.679442800000004], [37.514263699999994, 55.678286], [37.5188513, 55.676134100000006], [37.5236985, 55.673846999999995], [37.524002700000004, 55.67372030000001], [37.52413820000001, 55.6736653], [37.520093700000004, 55.670884599999994], [37.5089576, 55.663380800000006], [37.506542800000005, 55.6617784], [37.501653399999995, 55.6585246], [37.4956144, 55.6556312], [37.4826333, 55.649537], [37.4824662, 55.649460499999996], [37.4782007, 55.6475145], [37.4637211, 55.6407043], [37.455718700000006, 55.6370488], [37.4554342, 55.6372228], [37.455621799999996, 55.6373216], [37.455829599999994, 55.63744749999999], [37.45596739999999, 55.6375575], [37.4561515, 55.6376911], [37.45622699999999, 55.6378497], [37.456282699999996, 55.637968300000004], [37.4563368, 55.63814360000001], [37.456388999999994, 55.638306400000005], [37.4564172, 55.638473000000005], [37.45648549999999, 55.638706600000006], [37.4565492, 55.63898090000001], [37.456601899999995, 55.6392249], [37.4566379, 55.63935190000001], [37.4567373, 55.6396918], [37.45678749999999, 55.63991820000001], [37.456823899999996, 55.640053800000004], [37.45684779999999, 55.640172400000004], [37.456838, 55.64031870000001], [37.45682439999999, 55.6404324], [37.4567711, 55.6405261], [37.452481199999994, 55.64419590000001], [37.448126300000006, 55.6479161], [37.4433196, 55.652025], [37.438858800000006, 55.655633900000005], [37.436554, 55.6575984], [37.435324900000005, 55.658661599999995], [37.4342086, 55.659627199999996], [37.433923300000004, 55.6597201], [37.433649499999994, 55.6598112], [37.433313000000005, 55.6599099], [37.4330011, 55.6599748], [37.4326465, 55.66005290000001], [37.4322994, 55.66013610000001], [37.429005800000006, 55.661090300000005], [37.4270025, 55.66096520000001], [37.4266977, 55.660983800000004], [37.42511840000001, 55.6608651], [37.4233846, 55.6607476], [37.4188082, 55.660408700000005], [37.415198600000004, 55.66015660000001], [37.41531880000001, 55.657984199999994], [37.415198100000005, 55.657789699999995], [37.4150833, 55.6577979], [37.4133726, 55.6577257], [37.413219399999996, 55.6576738], [37.414586299999996, 55.6556724], [37.416413, 55.6558027], [37.417448199999995, 55.6530212], [37.414743099999995, 55.65223280000001], [37.415013200000004, 55.65178709999999], [37.4146053, 55.6517057], [37.41468499999999, 55.651495499999996], [37.41368979999999, 55.6513248], [37.4136053, 55.651156900000004], [37.4154909, 55.6477488], [37.4170629, 55.6480663], [37.4171099, 55.6474951], [37.41708399999999, 55.647355000000005], [37.417055, 55.6468167], [37.41708159999999, 55.646738000000006], [37.417165, 55.6463924], [37.417492499999994, 55.6449072], [37.4173933, 55.642520000000005], [37.416916300000004, 55.6406218], [37.416480099999994, 55.639119400000006], [37.41652439999999, 55.638250500000005], [37.415171300000004, 55.63833470000001], [37.415162800000004, 55.638184300000006], [37.415098300000004, 55.63592080000001], [37.415092, 55.635700500000006], [37.4147728, 55.635688800000004], [37.41394, 55.635726600000005], [37.4122821, 55.63590490000001], [37.4115299, 55.6338668], [37.410851799999996, 55.63197], [37.410195200000004, 55.629849], [37.4101272, 55.629600100000005], [37.410071499999994, 55.629493200000006], [37.4099708, 55.62951720000001], [37.4099057, 55.62954230000001], [37.409863599999994, 55.62957180000001], [37.40982149999999, 55.6296014], [37.409773300000005, 55.6296284], [37.40973230000001, 55.629642000000004], [37.4096755, 55.629651700000004], [37.409612100000004, 55.629645800000006], [37.4095641, 55.6296273], [37.409548900000004, 55.6295914], [37.4095043, 55.62957300000001], [37.4094426, 55.62958270000001], [37.40937220000001, 55.6296079], [37.409156100000004, 55.629636700000006], [37.4089948, 55.6296241], [37.4088886, 55.6296114], [37.4088047, 55.62961520000001], [37.40871370000001, 55.62962280000001], [37.4084856, 55.6296605], [37.40839280000001, 55.6296672], [37.4082986, 55.629653600000005], [37.4081734, 55.6296496], [37.408113500000006, 55.62967090000001], [37.4079949, 55.629720600000006], [37.407874799999995, 55.629764800000004], [37.407765, 55.62979270000001], [37.4077033, 55.629796600000006], [37.40762599999999, 55.629794700000005], [37.4075507, 55.629774100000006], [37.4074359, 55.629718900000015], [37.407357, 55.62971300000001], [37.40728779999999, 55.62973730000001], [37.40722149999999, 55.629769100000004], [37.407154399999996, 55.629836000000005], [37.407068599999995, 55.629878500000004], [37.407001799999996, 55.629885200000004], [37.406795800000005, 55.6298744], [37.40673590000001, 55.62987530000001], [37.4065454, 55.62991010000001], [37.4064597, 55.62991980000001], [37.4063603, 55.62992070000001], [37.40628139999999, 55.62993220000001], [37.4061747, 55.629968000000005], [37.406096, 55.6299873], [37.40602749999999, 55.62999500000001], [37.405969, 55.629997900000006], [37.4057873, 55.6300017], [37.4057, 55.63001890000001], [37.40559520000001, 55.6300577], [37.40551800000001, 55.6300848], [37.40543220000001, 55.630104100000004], [37.4052537, 55.63013300000001], [37.4051714, 55.63013120000001], [37.4049929, 55.63012500000001], [37.40482709999999, 55.6301446], [37.404668199999996, 55.63019520000001], [37.404478, 55.630282900000005], [37.4043155, 55.63034330000001], [37.4040736, 55.6303665], [37.4037164, 55.6303478], [37.4034779, 55.630363100000004], [37.4033942, 55.63037260000001], [37.4033217, 55.6303794], [37.403257399999994, 55.6304005], [37.403211399999996, 55.630445], [37.4031749, 55.63045520000001], [37.4031206, 55.6304566], [37.4030468, 55.6304497], [37.402990200000005, 55.630447399999994], [37.402944, 55.630447], [37.4029018, 55.63045], [37.4028407, 55.630445], [37.402777, 55.630432500000005], [37.402692800000004, 55.630407399999996], [37.402609399999996, 55.630385100000005], [37.402563, 55.6303819], [37.40251020000001, 55.6303825], [37.4024286, 55.630394800000005], [37.402353500000004, 55.6304055], [37.402295900000006, 55.630406], [37.4021875, 55.63039080000001], [37.4020826, 55.63037520000001], [37.40203290000001, 55.6303746], [37.4019255, 55.630380200000005], [37.401843199999995, 55.63037890000001], [37.4017623, 55.630369900000005], [37.4015832, 55.6303404], [37.4013858, 55.630295700000005], [37.40129739999999, 55.630282900000005], [37.4011777, 55.630278000000004], [37.401097199999995, 55.6302656], [37.4009843, 55.630231], [37.4009364, 55.6302236], [37.4008669, 55.6302285], [37.40064709999999, 55.6302418], [37.4004948, 55.6302479], [37.400373, 55.6302441], [37.40031210000001, 55.630240300000004], [37.4002588, 55.630228], [37.4001991, 55.63021560000001], [37.400140300000004, 55.630213100000006], [37.4000577, 55.6302278], [37.399985900000004, 55.6302265], [37.3998967, 55.630215400000004], [37.399798800000006, 55.6302054], [37.3997271, 55.63020530000001], [37.3996335, 55.6302176], [37.399544399999996, 55.6302104], [37.399457399999996, 55.6302076], [37.3993964, 55.630210000000005], [37.399278900000006, 55.630222100000005], [37.39912230000001, 55.6302406], [37.399033100000004, 55.63025030000001], [37.39893300000001, 55.6302601], [37.3988677, 55.6302724], [37.398800200000004, 55.630289499999996], [37.39873480000001, 55.63033000000001], [37.398658700000006, 55.630348500000004], [37.3984347, 55.63041220000001], [37.3983214, 55.630431800000004], [37.39825930000001, 55.63045030000001], [37.39819730000001, 55.630468900000004], [37.3981274, 55.6302862], [37.3980878, 55.6300705], [37.39801230000001, 55.62955270000001], [37.3979493, 55.6290472], [37.397905200000004, 55.628781000000004], [37.3975485, 55.62872070000001], [37.3946451, 55.62887230000001], [37.3945286, 55.62878390000001], [37.3937195, 55.627831], [37.3911967, 55.628113100000014], [37.387695199999996, 55.628497200000005], [37.3879156, 55.62941630000001], [37.388406399999994, 55.6311744], [37.38845739999999, 55.63133290000001], [37.3885536, 55.631567399999994], [37.3886019, 55.6316954], [37.3885514, 55.6317012], [37.38849939999999, 55.6317098], [37.388463099999996, 55.631719800000006], [37.3883794, 55.6317438], [37.388238, 55.6317748], [37.388126, 55.631804599999995], [37.388006, 55.6318406], [37.38787759999999, 55.63188099999999], [37.38776789999999, 55.6319116], [37.387651299999995, 55.631958000000004], [37.38756759999999, 55.632008500000005], [37.38744499999999, 55.63207230000001], [37.38726729999999, 55.63217120000001], [37.3871166, 55.632255400000005], [37.38707449999999, 55.632219500000005], [37.377874299999995, 55.62633710000001], [37.375641599999994, 55.62493810000001], [37.377568399999994, 55.62393540000001], [37.3764027, 55.62323010000001], [37.37380399999999, 55.624570500000004], [37.373342300000004, 55.624817300000004], [37.37068399999999, 55.62538000000001], [37.367912100000005, 55.62791390000001], [37.3661084, 55.630546700000004], [37.362382000000004, 55.629788100000006], [37.3598593, 55.6313805], [37.359825699999995, 55.6313936], [37.3601468, 55.6332724], [37.3597308, 55.6338597], [37.35884049999999, 55.63377510000001], [37.3583565, 55.634075800000005], [37.3585032, 55.634565300000006], [37.3582507, 55.6347584], [37.3555985, 55.63523590000001], [37.3552828, 55.63535920000001], [37.352990999999996, 55.635432400000006], [37.3515508, 55.6360771], [37.35063949999999, 55.6362374], [37.3473923, 55.634432600000004], [37.347006199999996, 55.6342972], [37.3464653, 55.6341085], [37.345505100000004, 55.633888999999996], [37.3425517, 55.633160100000005], [37.3421195, 55.6337877], [37.3388586, 55.63539420000001], [37.3385496, 55.635488], [37.3360563, 55.63517900000001], [37.3359621, 55.6354295], [37.33561580000001, 55.636108400000005], [37.335484199999996, 55.6360955], [37.335274, 55.6366417], [37.3344062, 55.63847990000001], [37.3324398, 55.6395477], [37.3315369, 55.639459200000005], [37.3303472, 55.63932390000001], [37.329638700000004, 55.6399692], [37.330407199999996, 55.640859999999996], [37.329864099999995, 55.6418586], [37.3305008, 55.642189900000005], [37.33058139999999, 55.64221930000001], [37.3306524, 55.64225030000001], [37.3317032, 55.644527], [37.3320472, 55.645937800000006], [37.330896599999996, 55.6472771], [37.33089939999999, 55.6473055], [37.331116200000004, 55.6473917], [37.3328449, 55.6483677], [37.3342189, 55.6497934], [37.3346191, 55.6503665], [37.335004399999995, 55.65091830000001], [37.3360925, 55.651878499999995], [37.33785999999999, 55.652823999999995], [37.340514399999996, 55.653522900000006], [37.3429343, 55.65402949999999], [37.3429996, 55.6540457], [37.343057099999996, 55.6540578], [37.3429658, 55.654090499999995], [37.3428723, 55.6541425], [37.342829099999996, 55.6541916], [37.3427767, 55.6543266], [37.3427299, 55.6544343], [37.3426937, 55.6545087], [37.3426365, 55.6545917], [37.3425746, 55.6546762], [37.3425405, 55.6547513], [37.3425024, 55.6548082], [37.3423246, 55.65488779999999], [37.3422, 55.65496939999999], [37.3421265, 55.6550268], [37.342109900000004, 55.6550632], [37.342125900000006, 55.65511580000001], [37.3422161, 55.6552078], [37.3423454, 55.65531310000001], [37.342382300000004, 55.65537880000001], [37.342382900000004, 55.655412600000005], [37.3423819, 55.6554514], [37.342366399999996, 55.655497], [37.3422981, 55.6555616], [37.342224699999996, 55.655613100000004], [37.34187299999999, 55.655779300000006], [37.3417759, 55.6558453], [37.34169659999999, 55.65595510000001], [37.341605699999995, 55.656006999999995], [37.3415289, 55.6560662], [37.341500499999995, 55.6561278], [37.34148349999999, 55.6563012], [37.341462899999996, 55.6563856], [37.3413578, 55.6564722], [37.341345999999994, 55.656516100000005], [37.3413533, 55.656558800000006], [37.34136469999999, 55.6566116], [37.3413968, 55.6566829], [37.34168059999999, 55.656779900000004], [37.342656399999996, 55.6559971], [37.343460099999994, 55.65557590000001], [37.34406719999999, 55.655376200000006], [37.3449789, 55.655537300000006], [37.3462773, 55.656293399999996], [37.34602739999999, 55.6564398], [37.346110200000005, 55.656478], [37.346041699999994, 55.6565263], [37.344389099999994, 55.6574323], [37.34515220000001, 55.657996999999995], [37.3454227, 55.658295100000004], [37.3463961, 55.659128300000006], [37.34701939999999, 55.659457599999996], [37.347141199999996, 55.659492900000004], [37.3471348, 55.6595635], [37.3460669, 55.6597055], [37.34409439999999, 55.660127700000004], [37.34388849999999, 55.6600897], [37.3430252, 55.66015120000001], [37.34203, 55.660129100000006], [37.3422433, 55.660225100000005], [37.3422754, 55.6602687], [37.342355500000004, 55.66033560000001], [37.3424307, 55.66040830000001], [37.342513100000005, 55.6604974], [37.342579300000004, 55.660582700000006], [37.34262, 55.6606316], [37.3426923, 55.660690800000005], [37.3427485, 55.6607477], [37.342864799999994, 55.660842200000005], [37.3429892, 55.66093800000001], [37.34306539999999, 55.6610017], [37.3431217, 55.661050700000004], [37.3431556, 55.661103100000005], [37.3431756, 55.66115880000001], [37.343197499999995, 55.661208800000004], [37.34322739999999, 55.6612669], [37.3432755, 55.661334100000005], [37.3433334, 55.66141820000001], [37.343357499999996, 55.6614831], [37.34338749999999, 55.66151610000001], [37.34344159999999, 55.661566300000004], [37.343485699999995, 55.6616027], [37.34353, 55.6616243], [37.3435863, 55.661641499999995], [37.343622499999995, 55.6616484], [37.3437089, 55.6616633], [37.3437996, 55.6616781], [37.343845599999995, 55.661705500000004], [37.343871699999994, 55.661731700000004], [37.343879699999995, 55.6617624], [37.34386149999999, 55.6617991], [37.3438392, 55.661819200000004], [37.3438029, 55.6618373], [37.3437585, 55.6618567], [37.3437141, 55.6618918], [37.34366759999999, 55.6619611], [37.3436351, 55.662022500000006], [37.3436148, 55.6620611], [37.34360449999999, 55.66210090000001], [37.343608399999994, 55.662144100000006], [37.3436458, 55.66219660000001], [37.34366249999999, 55.66223520000001], [37.343692499999996, 55.6622684], [37.343729599999996, 55.66230240000001], [37.3437687, 55.662330900000015], [37.3438128, 55.66235360000001], [37.3438532, 55.66237070000001], [37.3439029, 55.662386000000005], [37.34397439999999, 55.66239990000001], [37.34404419999999, 55.662409100000005], [37.344112200000005, 55.66241840000001], [37.3441658, 55.66243500000001], [37.3441803, 55.6624606], [37.34458949999999, 55.6624264], [37.3476527, 55.662031400000004], [37.3481067, 55.66282220000001], [37.3482962, 55.66279130000001], [37.3484908, 55.662906500000005], [37.3482288, 55.66398290000001], [37.3481316, 55.664193100000006], [37.347963199999995, 55.66570210000001], [37.348046599999996, 55.66582880000001], [37.349778, 55.665564800000006], [37.350155300000004, 55.665428500000004], [37.35149649999999, 55.6648907], [37.351701999999996, 55.6648773], [37.352290999999994, 55.6646039], [37.3529643, 55.6641714], [37.35358239999999, 55.663724300000005], [37.3505088, 55.66241020000001], [37.350508999999995, 55.66202890000001], [37.3505549, 55.6618095], [37.350431199999996, 55.661795600000005], [37.35023759999999, 55.661198500000005], [37.35158649999999, 55.660820900000004], [37.35288759999999, 55.66033770000001], [37.3550293, 55.661146], [37.3584524, 55.66257610000001], [37.35824399999999, 55.6660449], [37.3633638, 55.66866230000001], [37.3639045, 55.66891850000001], [37.36461739999999, 55.6691244], [37.369041499999994, 55.66891910000001], [37.369998800000005, 55.667996800000004], [37.3699412, 55.666924200000004], [37.3698343, 55.66671840000001], [37.3699172, 55.666202600000005], [37.3697995, 55.6642071], [37.3696052, 55.66103890000001], [37.3699714, 55.660543700000005], [37.369765300000005, 55.6595194], [37.370952, 55.6590578], [37.372619, 55.65906], [37.3750564, 55.6590643], [37.376991399999994, 55.659102000000004], [37.3780033, 55.6594828], [37.37831800000001, 55.6598282], [37.37851800000001, 55.660479900000006], [37.379096, 55.66252540000001], [37.379712000000005, 55.6640279], [37.3798883, 55.6642691], [37.38006599999999, 55.6644295], [37.380582, 55.6644794], [37.3822024, 55.6645672], [37.385261799999995, 55.6645431], [37.3862366, 55.664514200000006], [37.38648609999999, 55.6644488], [37.3867928, 55.664190000000005], [37.3880708, 55.66283890000001], [37.3890513, 55.661805900000004], [37.389485699999994, 55.6616991], [37.3939277, 55.6608827], [37.39724139999999, 55.6610404], [37.399916100000006, 55.6615243], [37.400817399999994, 55.6616296], [37.401202, 55.6616043], [37.4021647, 55.66152290000001], [37.40466099999999, 55.66193620000001], [37.409480099999996, 55.66296390000001], [37.41198339999999, 55.663617800000004], [37.413945399999996, 55.664276900000004], [37.4154573, 55.6647647], [37.4130736, 55.6674098], [37.407338100000004, 55.6696825], [37.407535700000004, 55.669762600000006], [37.406731900000004, 55.67037290000001], [37.40594290000001, 55.67010390000001], [37.40488149999999, 55.6704097], [37.40436739999999, 55.67070290000001], [37.4042452, 55.6707015], [37.4040325, 55.6710433], [37.4044388, 55.67171820000001], [37.4045258, 55.671985], [37.4048008, 55.6728286], [37.4057073, 55.673280999999996], [37.4059717, 55.6744578], [37.4078106, 55.67561990000001], [37.40892530000001, 55.6763247], [37.4098154, 55.676697], [37.41031280000001, 55.6769594], [37.410213999999996, 55.6770209], [37.41129049999999, 55.6774909], [37.410585, 55.67804830000001], [37.411768699999996, 55.678501100000005], [37.4133272, 55.6790955], [37.4133889, 55.67918590000001], [37.415272900000005, 55.679908000000005], [37.41748099999999, 55.680776200000004], [37.4173186, 55.6808901], [37.4172142, 55.68095230000001], [37.41729439999999, 55.680985], [37.4161436, 55.6816553], [37.4154479, 55.682043300000004], [37.415334900000005, 55.6820779], [37.415196300000005, 55.6821004], [37.4151035, 55.682109800000006], [37.41484559999999, 55.68201830000001], [37.41460119999999, 55.681932], [37.414376, 55.6818551], [37.414209299999996, 55.682028100000004], [37.4143513, 55.682078600000004], [37.4146758, 55.6822001], [37.41487939999999, 55.6822889], [37.415160300000004, 55.6824256], [37.415174900000004, 55.682508600000006], [37.41515020000001, 55.68261210000001], [37.4151246, 55.6826945], [37.4150661, 55.682833800000004], [37.414996599999995, 55.682983], [37.414937099999996, 55.6831225], [37.41486339999999, 55.6832548], [37.41482189999999, 55.6833438], [37.41477139999999, 55.6834795], [37.4147409, 55.6835843], [37.414714, 55.6836829], [37.4146952, 55.683798], [37.414682899999995, 55.6839548], [37.41467659999999, 55.6841047], [37.41470399999999, 55.684133300000006], [37.414859299999996, 55.6848161], [37.41489949999999, 55.68488609999999], [37.4149591, 55.6849736], [37.414959999999994, 55.685266999999996], [37.414733999999996, 55.6859516], [37.414606899999995, 55.685931700000005], [37.41385449999999, 55.6879926], [37.41378339999999, 55.688123600000004], [37.4133068, 55.688900200000006], [37.4125257, 55.69023130000001], [37.412402300000004, 55.69041920000001], [37.4121665, 55.69070850000001], [37.411693099999994, 55.6912861], [37.4103742, 55.692629200000006], [37.408393200000006, 55.6942243], [37.4040926, 55.6974067], [37.4021617, 55.69883890000001], [37.401418, 55.69830770000001], [37.400832300000005, 55.697939100000006], [37.399245900000004, 55.6975865], [37.398366100000004, 55.69743530000001], [37.3979048, 55.697205600000004], [37.3974549, 55.696688], [37.397023399999995, 55.6965664], [37.39635210000001, 55.696607], [37.3956625, 55.69665530000001], [37.395072400000004, 55.69655260000001], [37.3945912, 55.696511400000006], [37.3941896, 55.696310900000014], [37.3938135, 55.69612310000001], [37.393405800000004, 55.696033500000006], [37.393872300000005, 55.695065400000004], [37.39355880000001, 55.694831900000004], [37.39019590000001, 55.69677590000001], [37.3841169, 55.69393720000001], [37.38388899999999, 55.6937045], [37.383884499999986, 55.69336270000001], [37.3835089, 55.69325820000001], [37.38308169999999, 55.69331900000001], [37.3827859, 55.693256500000004], [37.38127699999999, 55.69252730000001], [37.3810338, 55.69259180000001], [37.37828139999999, 55.69099890000001], [37.3771988, 55.6906146], [37.374868899999996, 55.6888372], [37.371433499999995, 55.6899575], [37.372803499999996, 55.69101570000001], [37.3677436, 55.6916546], [37.3660863, 55.6900234], [37.365308600000006, 55.69014870000001], [37.3642134, 55.690596000000006], [37.363229399999994, 55.6898534], [37.3626104, 55.688753000000005], [37.3641976, 55.68813570000001], [37.363896, 55.68771520000001], [37.35962659999999, 55.6889677], [37.3610709, 55.690014500000004], [37.3592139, 55.6908017], [37.359237199999995, 55.69131170000001], [37.3583092, 55.691633700000004], [37.35789659999999, 55.691669499999996], [37.35726169999999, 55.690408100000006], [37.3567538, 55.6899608], [37.3567062, 55.6893346], [37.3562459, 55.6886278], [37.35580149999999, 55.6874558], [37.356658599999996, 55.6877063], [37.35567459999999, 55.6861406], [37.355071499999994, 55.685523200000006], [37.3611, 55.6820978], [37.3589283, 55.6798956], [37.358627299999995, 55.679595000000006], [37.3580956, 55.6790776], [37.357484499999984, 55.6792432], [37.35648869999999, 55.678315900000015], [37.354438599999995, 55.6764784], [37.34902639999999, 55.67867090000001], [37.3460384, 55.6762631], [37.3341068, 55.6804232], [37.333637599999996, 55.680588300000004], [37.333310000000004, 55.680714200000004], [37.3311719, 55.681447299999995], [37.3310529, 55.6813421], [37.3305172, 55.6814853], [37.3298546, 55.68164409999999], [37.32953320000001, 55.681901399999994], [37.3291245, 55.6819282], [37.3260965, 55.6828568], [37.3290907, 55.6854965], [37.3292442, 55.68561630000001], [37.329705800000006, 55.6854456], [37.32873510000001, 55.684607299999996], [37.328707, 55.68447449999999], [37.326849599999996, 55.6829465], [37.330946, 55.681538700000004], [37.332472300000006, 55.68291490000001], [37.334049099999994, 55.682025900000006], [37.3348683, 55.682475100000005], [37.33355530000001, 55.6832534], [37.3339537, 55.683936700000004], [37.3339986, 55.684085399999994], [37.3339256, 55.6842151], [37.3337236, 55.6843258], [37.329427599999995, 55.6857865], [37.3307451, 55.6870408], [37.330653, 55.6870726], [37.33348749999999, 55.6896833], [37.3338526, 55.689558100000006], [37.335463499999996, 55.69102530000001], [37.337955300000004, 55.693306400000004], [37.338626999999995, 55.69251750000001], [37.338654399999996, 55.69131820000001], [37.33788939999999, 55.6900047], [37.338019300000006, 55.6896381], [37.338734800000005, 55.688757700000004], [37.33873520000001, 55.6887015], [37.3386965, 55.6886967], [37.338711700000005, 55.688670200000004], [37.3387642, 55.687735700000005], [37.338914100000004, 55.68765439999999], [37.3389175, 55.6873057], [37.3392587, 55.687337], [37.3392587, 55.6877486], [37.3397111, 55.6879499], [37.339869799999995, 55.6881825], [37.34198859999999, 55.688549300000005], [37.34198859999999, 55.6886254], [37.3424568, 55.6886746], [37.3423775, 55.6890145], [37.3426393, 55.6890906], [37.3433456, 55.6891264], [37.34386939999999, 55.689175600000006], [37.343917, 55.689350000000005], [37.3437481, 55.68953810000001], [37.343877299999996, 55.690591000000005], [37.342440399999994, 55.69237490000001], [37.342441599999994, 55.69303860000001], [37.342555700000005, 55.6938934], [37.342781099999996, 55.6944837], [37.3431517, 55.695685700000006], [37.3447258, 55.69837300000001], [37.3450296, 55.69851180000001], [37.345094399999994, 55.69827130000001], [37.347327699999994, 55.697600900000005], [37.35180199999999, 55.700055400000004], [37.35165119999999, 55.701786], [37.351524299999994, 55.7018486], [37.35156399999999, 55.70224220000001], [37.3560531, 55.7046831], [37.356367299999995, 55.7045314], [37.353988099999995, 55.7030896], [37.3541003, 55.7022801], [37.353135200000004, 55.7017236], [37.353344699999994, 55.70035320000001], [37.3556342, 55.7004417], [37.355712700000005, 55.69937920000001], [37.35749719999999, 55.699429800000004], [37.35764309999999, 55.69850010000001], [37.361660799999996, 55.69865190000001], [37.3614299, 55.70050930000001], [37.363248, 55.700566200000004], [37.363315400000005, 55.701729900000004], [37.363483699999996, 55.701729900000004], [37.363483699999996, 55.7014453], [37.364437699999996, 55.70075590000001], [37.3656273, 55.7008065], [37.365616100000004, 55.70117330000001], [37.365402800000005, 55.7013694], [37.365223300000004, 55.701382], [37.3648305, 55.701736200000006], [37.3653467, 55.701748800000004], [37.3656048, 55.701888], [37.365919100000006, 55.70240020000001], [37.3659864, 55.70279230000001], [37.366446499999995, 55.70293770000001], [37.366693399999996, 55.7019891], [37.369122000000004, 55.70235110000001], [37.36897280000001, 55.702761200000005], [37.3679112, 55.702692400000004], [37.3676622, 55.70327210000001], [37.3685876, 55.7034838], [37.3687594, 55.7031475], [37.3708919, 55.703690300000005], [37.370360399999996, 55.7041096], [37.3685867, 55.70370530000001], [37.3683947, 55.704159700000005], [37.36615510000001, 55.7070035], [37.368935500000006, 55.7074092], [37.3691979, 55.7084045], [37.3684404, 55.7084515], [37.368351700000005, 55.708223000000004], [37.3675534, 55.70820880000001], [37.367408499999996, 55.70801680000001], [37.3650394, 55.7080484], [37.3641316, 55.7088216], [37.36944449999999, 55.710363300000004], [37.37192149999999, 55.7108317], [37.3755621, 55.7114199], [37.3761056, 55.7106219], [37.3766162, 55.7106033], [37.37745139999999, 55.7092944], [37.377469899999994, 55.708748500000006], [37.37762969999999, 55.7040204], [37.377900999999994, 55.69692920000001], [37.382014, 55.69853670000001], [37.38544709999999, 55.696969100000004], [37.38788579999999, 55.69810450000001], [37.389829799999994, 55.696949200000006], [37.392162500000005, 55.69842320000001], [37.3886458, 55.7007934], [37.3904837, 55.702436500000005], [37.3882393, 55.70323320000001], [37.3885622, 55.70355620000001], [37.387941299999994, 55.704320100000004], [37.3924774, 55.70591930000001], [37.3919978, 55.706374800000006], [37.3897062, 55.70812280000001], [37.38787799999999, 55.70993580000001], [37.387033699999996, 55.710773], [37.38666099999999, 55.711147499999996], [37.3864367, 55.71126459999999], [37.38624479999999, 55.7113566], [37.386037599999995, 55.7114591], [37.385824899999996, 55.7115561], [37.385597399999995, 55.711661899999996], [37.3854092, 55.7117403], [37.385102, 55.7118528], [37.384836299999996, 55.7119348], [37.3845399, 55.71203590000001], [37.3843098, 55.71211060000001], [37.3840359, 55.71218530000001], [37.383749699999996, 55.7122778], [37.383477799999994, 55.712364900000004], [37.3831988, 55.712458600000005], [37.382961599999994, 55.712532900000014], [37.3827668, 55.71259810000001], [37.3826351, 55.712639200000005], [37.382300300000004, 55.7126822], [37.3820115, 55.71265270000001], [37.3815623, 55.712603300000005], [37.381352, 55.7130943], [37.381492099999996, 55.7131248], [37.381675699999995, 55.71317210000001], [37.38183769999999, 55.7132317], [37.3820207, 55.713321900000004], [37.382223399999994, 55.713433900000005], [37.382395200000005, 55.7135498], [37.3825374, 55.7136545], [37.382718000000004, 55.713784499999996], [37.3828791, 55.713897599999996], [37.3830521, 55.714016300000004], [37.383201099999994, 55.71411500000001], [37.3834063, 55.7142463], [37.3835493, 55.71433590000001], [37.3837149, 55.71444749999999], [37.383845199999996, 55.7145471], [37.383986799999995, 55.7146706], [37.38406599999999, 55.7147792], [37.38409119999999, 55.714812900000005], [37.3841377, 55.714878399999996], [37.3842333, 55.71502530000001], [37.3843099, 55.71516590000001], [37.3834397, 55.7168565], [37.382480699999995, 55.718719500000006], [37.3824119, 55.718853200000005], [37.38240939999999, 55.718858100000006], [37.381123499999994, 55.7213834], [37.380938900000004, 55.7215274], [37.380755300000004, 55.721662800000004], [37.3805754, 55.721805100000005], [37.3804383, 55.72194830000001], [37.3803066, 55.722099500000006], [37.38018699999999, 55.7222445], [37.3800325, 55.72239530000002], [37.37986709999999, 55.722533300000016], [37.37968959999999, 55.722664300000005], [37.37951220000001, 55.72281240000001], [37.3793277, 55.72296190000001], [37.3791054, 55.723107000000006], [37.3788893, 55.7232244], [37.378719800000006, 55.7232884], [37.378454, 55.72333840000001], [37.378478300000005, 55.72375250000001], [37.37866139999999, 55.72376570000001], [37.3788459, 55.72381500000001], [37.3789767, 55.72392220000001], [37.379090999999995, 55.72402290000001], [37.3792148, 55.72419490000001], [37.3792452, 55.7242945], [37.379214399999995, 55.7246766], [37.379268399999994, 55.72501860000001], [37.378368800000004, 55.72679420000001], [37.377204199999994, 55.72907980000001], [37.3771112, 55.72926220000001], [37.3766308, 55.730279100000004], [37.3757427, 55.73188749999999], [37.3747956, 55.7318736], [37.374180599999995, 55.732150800000014], [37.373982399999996, 55.73251290000002], [37.3739571, 55.73271480000001], [37.373984199999995, 55.73293210000001], [37.374135300000006, 55.7332714], [37.374368499999996, 55.73381030000001], [37.37444359999999, 55.7340883], [37.3745176, 55.7343246], [37.3741332, 55.735085000000005], [37.3739401, 55.73561870000001], [37.3735547, 55.736493800000005], [37.3713481, 55.7408036], [37.370408999999995, 55.7425274], [37.370015800000004, 55.74339580000001], [37.3689477, 55.745982000000005], [37.368577, 55.74786769999999], [37.36831190000001, 55.750130000000006], [37.368302400000005, 55.7519426], [37.3684666, 55.7559802], [37.368565100000005, 55.7568756], [37.3685442, 55.757775200000005], [37.3685414, 55.758676300000005], [37.3684912, 55.75957280000001], [37.3685911, 55.7604636], [37.36845590000001, 55.7612601], [37.368489, 55.76255650000001], [37.3683374, 55.76263990000001], [37.3681545, 55.76273310000001], [37.367872, 55.763037100000005], [37.3679288, 55.763206200000006], [37.36800830000001, 55.76334560000001], [37.36807590000001, 55.763484], [37.368128500000005, 55.763622000000005], [37.36815630000001, 55.76377600000001], [37.36814290000001, 55.76383870000001], [37.3680775, 55.76395070000001], [37.368026900000004, 55.764050700000006], [37.367905, 55.76413550000001], [37.3676723, 55.76419890000001], [37.3674968, 55.7642344], [37.36728539999999, 55.7642634], [37.3670106, 55.7642917], [37.3667278, 55.76431880000001], [37.3665472, 55.7642924], [37.3662853, 55.764289], [37.3657364, 55.7642046], [37.3656124, 55.764412400000005], [37.3656347, 55.76441530000001], [37.3658077, 55.7644374], [37.366306, 55.7646072], [37.3665194, 55.764880999999995], [37.3665436, 55.7649435], [37.3664092, 55.764925100000006], [37.366413800000004, 55.7649364], [37.3664961, 55.765096400000004], [37.366554, 55.76525820000001], [37.366581499999995, 55.76536880000001], [37.366637399999995, 55.76547510000001], [37.366730200000006, 55.76562080000001], [37.3668393, 55.76573640000001], [37.3669011, 55.765797600000006], [37.367102700000004, 55.765927000000005], [37.367222, 55.766020700000006], [37.3673967, 55.76615610000001], [37.3675796, 55.76627880000001], [37.3677668, 55.76638570000001], [37.3679493, 55.766499], [37.368154800000006, 55.766640200000005], [37.36835080000001, 55.76675470000001], [37.3685084, 55.766867399999995], [37.3686078, 55.76694090000001], [37.3686545, 55.76850380000001], [37.368644399999994, 55.76869000000001], [37.368537800000006, 55.768857800000006], [37.368433700000004, 55.76893040000001], [37.3682978, 55.7690294], [37.36813240000001, 55.76914120000001], [37.367958, 55.76925130000001], [37.3677609, 55.76937920000001], [37.3675624, 55.76949530000001], [37.367373, 55.7696215], [37.3671619, 55.76975070000001], [37.36702749999999, 55.769772900000014], [37.366883699999995, 55.7697945], [37.3667072, 55.7698806], [37.3665267, 55.7700084], [37.3664555, 55.770103000000006], [37.36639890000001, 55.77025220000001], [37.366409499999996, 55.7703678], [37.3665276, 55.77053540000001], [37.3666203, 55.77068439999999], [37.366769399999995, 55.770836300000006], [37.3667564, 55.770903100000005], [37.366687899999995, 55.7709677], [37.3665425, 55.7710439], [37.366357300000004, 55.7711444], [37.3661079, 55.7712637], [37.3658606, 55.7713812], [37.3656471, 55.771501900000004], [37.3654184, 55.7716361], [37.365259900000005, 55.771728], [37.365388200000005, 55.771812100000005], [37.36551680000001, 55.7718963], [37.3657866, 55.7717839], [37.36601520000001, 55.7717456], [37.3661966, 55.771723300000005], [37.36631510000001, 55.77173080000001], [37.366516100000005, 55.7717594], [37.366610300000005, 55.7717806], [37.366995300000006, 55.7718889], [37.3672541, 55.771953200000006], [37.3675417, 55.772017500000004], [37.3677005, 55.7720618], [37.3678722, 55.77212080000001], [37.3682455, 55.77231180000001], [37.3684736, 55.772405000000006], [37.368743300000006, 55.772498600000006], [37.36874890000001, 55.77261360000001], [37.3688249, 55.772724600000004], [37.3688853, 55.77303830000001], [37.37026159999999, 55.773026900000005], [37.3702608, 55.77136230000001], [37.37108049999999, 55.770896300000004], [37.380406099999995, 55.771578100000006], [37.383374499999995, 55.7716755], [37.386765999999994, 55.7708554], [37.390933600000004, 55.7710465], [37.394868499999994, 55.771203], [37.397342200000004, 55.771095900000006], [37.3982596, 55.77117690000001], [37.3997447, 55.7712515], [37.4001204, 55.771272200000006], [37.4085801, 55.77576220000001], [37.4100321, 55.775665000000004], [37.412185, 55.77552090000001], [37.41429169999999, 55.77543550000001], [37.4169486, 55.77532780000001], [37.4210255, 55.7749416], [37.4256268, 55.7745234], [37.428843300000004, 55.7742825], [37.4307464, 55.774173000000005], [37.4341209, 55.7741996], [37.4362176, 55.7744065], [37.439357900000005, 55.775217600000005], [37.443640099999996, 55.776332300000014], [37.4454867, 55.7768773], [37.4473534, 55.7772534], [37.44811970000001, 55.777308000000005], [37.448829399999994, 55.7772765], [37.449683799999995, 55.77714], [37.45064309999999, 55.7768688], [37.45303, 55.775693700000005], [37.4552656, 55.7741771], [37.46037890000001, 55.76907570000001], [37.46293970000001, 55.76695050000001], [37.463990100000004, 55.76577130000001], [37.4642718, 55.765227900000006], [37.464561499999995, 55.76430680000001], [37.4646628, 55.76329530000001], [37.464584599999995, 55.76279400000001], [37.4645693, 55.76269580000001], [37.4645205, 55.762383400000004], [37.463425900000004, 55.76019070000001], [37.461838, 55.7588385], [37.45960639999999, 55.7571482], [37.4576323, 55.75582], [37.455443599999995, 55.75478149999999], [37.453083299999996, 55.753887999999996], [37.4488347, 55.7528978], [37.4455712, 55.752098800000006], [37.442182800000005, 55.7513038], [37.439221599999996, 55.75053090000001], [37.437376300000004, 55.7496855], [37.436979, 55.749251900000004], [37.4366052, 55.74871860000001], [37.4363477, 55.7478732], [37.436690999999996, 55.74710030000001], [37.4373777, 55.7464239], [37.439738000000006, 55.74521610000001], [37.44248459999999, 55.743573500000004], [37.4444587, 55.7426072], [37.446518600000005, 55.741858300000004], [37.4492652, 55.741133600000005], [37.4525268, 55.740602100000004], [37.45531630000001, 55.740602100000004], [37.459135700000004, 55.7412061], [37.4617965, 55.741858300000004], [37.4648006, 55.7428971], [37.4673755, 55.7440325], [37.4710233, 55.74610990000001], [37.472782800000004, 55.7472693], [37.4741561, 55.74850120000001], [37.475143200000005, 55.749878], [37.4757869, 55.7512305], [37.476173100000004, 55.752293200000004], [37.4765165, 55.75458749999999], [37.476731, 55.7559641], [37.476773900000005, 55.75690590000001], [37.476173100000004, 55.76171120000001], [37.476173100000004, 55.76299090000001], [37.476388, 55.764510400000006], [37.47708699999999, 55.76552560000001], [37.4780555, 55.76669230000001], [37.4784216, 55.7670545], [37.4788659, 55.7673434], [37.4794184, 55.7675454], [37.4800361, 55.76771280000001], [37.481918900000004, 55.76797690000001], [37.4845108, 55.76817000000001], [37.487180599999995, 55.76819410000001], [37.489715800000006, 55.767959600000005], [37.492051800000006, 55.767360800000006], [37.4960858, 55.76610540000001], [37.49751620000001, 55.7656864], [37.49814580000001, 55.76550190000001], [37.50106399999999, 55.7643671], [37.50295230000001, 55.763401300000005], [37.5042827, 55.762532100000016], [37.505827599999996, 55.7617836], [37.51166409999999, 55.7596587], [37.5139298, 55.7584219], [37.5145394, 55.7580891], [37.516299, 55.7568334], [37.5176723, 55.7546358], [37.5181443, 55.753210900000006], [37.518502700000006, 55.7525846], [37.5202286, 55.750022200000004], [37.52036030000001, 55.7498517], [37.5220496, 55.747583399999996], [37.52252080000001, 55.7472106], [37.5236375, 55.746327300000004], [37.52556870000001, 55.74533690000001], [37.527972000000005, 55.744612200000006], [37.5324042, 55.744396300000005], [37.5367267, 55.7446364], [37.5403745, 55.7454577], [37.543550200000006, 55.7465205], [37.549043399999995, 55.748984300000004], [37.554535200000004, 55.751436399999996], [37.557561699999994, 55.7523904], [37.56017830000001, 55.7530784], [37.5640208, 55.7535974], [37.5678832, 55.75335580000001], [37.570801499999995, 55.752727900000004], [37.572059900000006, 55.752019700000005], [37.5730331, 55.751472], [37.5740201, 55.75033690000001], [37.5744922, 55.7488635]]]]}}]}')

In [14]:
district_boundaries

{'type': 'FeatureCollection',
 'geocoding': {'creation_date': '2016-01-09',
  'generator': {'author': {'name': 'Mapzen'},
   'package': 'fences-builder',
   'version': '0.1.2'},
  'license': 'ODbL (see http://www.openstreetmap.org/copyright)'},
 'features': [{'id': 1320234,
   'osm_type': 'relation',
   'type': 'Feature',
   'name': 'Восточный административный округ',
   'properties': {'ref': 'ВАО',
    'name': 'Восточный административный округ',
    'name:be': 'Усходняя адміністрацыйная акруга',
    'name:de': 'Östlicher Verwaltungsbezirk',
    'name:en': 'Eastern Administrative Okrug',
    'name:ru': 'Восточный административный округ',
    'website': 'http://www.vao.mos.ru',
    'boundary': 'administrative',
    'wikipedia': 'ru:Восточный административный округ',
    'addr:region': 'Москва',
    'admin_level': '5',
    'addr:country': 'RU'},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[37.8756653, 55.825342400000004],
       [37.876001599999995, 55.8249027],
       

In [15]:
# создаём карту Москвы
m = folium.Map(location=[moscow_lat, moscow_lng], zoom_start=10)

# создаём хороплет с помощью конструктора Choropleth и добавляем его на карту
folium.Choropleth(
    geo_data=district_boundaries,
    data=rating_df,
    columns=['district', 'rating'],
    key_on='feature.name',
    fill_color='YlGn',
    fill_opacity=0.8,
    legend_name='Медианный рейтинг заведений по районам',
).add_to(m)

# выводим карту
m

У конструктора `Choropleth()` много параметров:

- `geo_data` — строка, которая содержит путь к GeoJSON-файлу с информацией о границах регионов. Обратите внимание: читать или обрабатывать файл для построения хороплета не требуется.
- `data` — датафрейм, который, помимо прочего, содержит геоданные — информацию о широте и долготе точек.
- `columns` — список столбцов датафрейма из `data`, которые нужно использовать при построении фоновой картограммы.
- `key_on` — строка, которая содержит название нужного ключа в JSON, например с названием региона. В начале строки указывают `feature.`, а затем название ключа. В GeoJSON-файле с данными Москвы названия округов хранятся в ключе `name`, поэтому достаточно передать параметру `key_on` строку `'feature.name'`. Библиотека найдёт ключ в JSON, достанет соответствующее ему значение и сопоставит его со строками датафрейма `data`.
- `fill_color` — строка, которая задаёт цветовую схему хороплета. Мы использовали схему `YlGn`, которая содержит жёлтые (англ. yellow) и зелёные (англ. green) цвета и их оттенки. Цветовая схема может быть следующей:
![fillcolors_image](https://code.s3.yandex.net/data-analyst/new_images/sphx_glr_colormap_reference_002_2_0x%20(1).webp)
- `fill_opacity` — дробное число от `0` до `1`, которое задаёт прозрачность заливки хороплета. Чем меньше число, тем более прозрачной будет фоновая картограмма.
- `legend_name` — строка с подписью к цветовой легенде графика.